LSE Data Science Institute | ME204 (2023/24) | Week 02 Day 03

# 💻 Week 02 – Day 03: Collecting data from social media APIs (Reddit)

<span style="display: inline-block; padding: 0 10px; font-size: 1.15em;line-height: 1.5em; white-space: nowrap; border: 1px solid #E69F25; border-radius: .5em; color: #fcfcfc; background-color: #E69F25; vertical-align: middle;font-weight: 600 !important;">AFTERNOON NOTEBOOK</span>

**DATE:** 17 July 2024

**AUTHOR:** Dr [Jon Cardoso-Silva](https://jonjoncardoso.github.io)

-----


## ⚙️ Setup


In [1]:
import os
import json
import requests

import pandas as pd
import matplotlib.pyplot as plt

from scrapy import Selector
from tqdm.notebook import tqdm

# Context

So far, we have spent a reasonable amount of time gathering data via web scraping. We send requests to a web server, pretending to be a browser operating at the request of a human user, and then we reverse engineer the HTML code to extract the information we need. You are probably experts at this by now!

**However, web scraping is not the only way to obtain data from the web; sometimes, it isn't even the best way!**

Many websites, platforms and organisations offer **direct access** to their data via an API (**A**pplication **P**rogramming **I**nterface). I will illustrate the process by using the Reddit API.

# 1. Setting up your (secret) credentials 

This assumes you have completed this morning's 📚 [Prep](https://lse-dsi.github.io/ME204/2024/weeks/week02/day03/page.html#part-ii-preparation-for-collecting-data-from-reddit-api).

👨‍🏫 **TEACHING MOMENT**

- The entire section 1 is a teaching moment. Follow the instructions alongside your class teacher.

To use the API, we need to provide several sensitive pieces of information:

- your Reddit username (_do you want people to know it?_)
- your Reddit password, in plain text (_do you want people to know it?_)
- your Reddit app's client ID (_do you want anyone to send requests on your behalf?_)
- your Reddit app's client secret (_do you want anyone to send requests on your behalf?_)

If I leave this information in the notebook (on GitHub, especially), anyone reading it can impersonate me and send requests to Reddit on my behalf - a **serious security risk**.

**NEVER leave your credentials anywhere in your GitHub repository or notebook!**

--- 

🔊 Louder for those in the back:

<div style="font-size:2em">

☣️ **NEVER leave your credentials anywhere in your GitHub repository or notebook!** ☣️

Even if you delete it afterwards, it will still be in the repository's history, and ANYONE can access it.

</div>

---

Therefore, I saved my credentials in a file called `credentials.json` with everything I will need. It looks like this:

```json
{
    "reddit_username": "<your Reddit username>",
    "reddit_password": "<your Reddit password>",
    "app_client_id": "<your Reddit app's client ID>",
    "app_client_secret": "<your Reddit app's client secret>"
}
```

Then, I added `credentials.json` to my `.gitignore` file so that it is not tracked by GitHub. This way, I can read it from the notebook without exposing my credentials to the world:

In [ ]:
credentials_file_path = "./credentials.json"

# open the file and load the data into a variable
with open(credentials_file_path, "r") as f:
    credentials = json.load(f)

OK, now I took that out of the way, let's access the API!

## 1.1 Obtain a Token

The Reddit API requires, probably for security reasons, that we obtain an **access token** every time we access it via a script. We send a first request to a specific **API endpoint**[^1] in our credentials and get a string of characters, a token, that we can use to access the API for a limited amount of time. The code below shows how to do this in Python[^2].


[^1]: An endpoint is like a URL that we can use to access a specific part of the API. You must always read the documentation to find out which endpoints are available and what they do.
[^2]: The code in this section was adapted from Reddit's own [Python example code](https://github.com/reddit-archive/reddit/wiki/OAuth2-Quick-Start-Example#python-example)

**Setup the credentials before sending the request**


In [3]:
# We will still use the requests library, only this time we have to set up authentication parameters first
client_auth = requests.auth.HTTPBasicAuth(credentials["app_client_id"], credentials["app_client_secret"])

# You also need to send, via HTTP POST, your Reddit username and password.
post_data = {"grant_type": "password", 
             "username": credentials["reddit_username"], 
             "password": credentials["reddit_password"]}

# Just like Wikimedia, Reddit API also requests that we self-identify ourselves in the User-Agent.
headers = {"User-Agent": f"LSE ME204 (2024) API practice by {credentials['reddit_username']}"}


**Actually send the request**


In [ ]:
# From their documentation, I learned this is the endpoint I need
ACCESS_TOKEN_ENDPOINT = "https://www.reddit.com/api/v1/access_token"

# This time we are sending a HTTP POST instead of a HTTP GET
response = requests.post(ACCESS_TOKEN_ENDPOINT, auth=client_auth, data=post_data, headers=headers)
response.json()

If you configured everything correctly, you should get a response like this:

```json
{
    "access_token": "a_long_string_of_characters",
    "token_type": "bearer",
    "expires_in": 86400, // in seconds
    "scope": "*"
}
```

Double-check: how long is that in hours?

In [5]:
86400 / (60 * 60)

24.0

Let's save our token:

In [8]:
my_token = response.json()['access_token']

From now on, all my requests need to be followed by these HTTP HEADERS:

In [9]:
headers = {"Authorization": f"bearer {my_token}", 
           "User-Agent": f"LSE ME204 (2024) API practice by {credentials['reddit_username']}"}

## 1.2 Send our first request with the token 

In [14]:
BASE_ENDPOINT = "https://oauth.reddit.com"
f"{BASE_ENDPOINT}/top?limit=100"

'https://oauth.reddit.com/top?limit=100'

In [15]:
BASE_ENDPOINT = "https://oauth.reddit.com"

response = requests.get(f"{BASE_ENDPOINT}/top?limit=100", headers=headers)

## 1.3 How do we paginate?

From reading the [Reddit API documentation](https://www.reddit.com/dev/api), I learned that we have to use the `after` parameter to paginate. That is, after sending a request, I have to retrieve the `after` value from the response and use it in the next request. The code below shows how to do this.

In [24]:
# Obtain the data from the response
data = response.json()

type(data)

dict

In [48]:
# Obtain the data from the response
data_page01 = response.json()

# Get the ID of the last post
after_id = data_page01['data']['after']
after_id

't3_1b8qgke'

In [51]:
data_page01['data']['after']

't3_1b8qgke'

Now, I can send a new request to get the next 100 top posts (as of 7 November 2023):

In [52]:
f"{BASE_ENDPOINT}/top?limit=100&after={after_id}"

'https://oauth.reddit.com/top?limit=100&after=t3_1b8qgke'

In [53]:
data_page02 = requests.get(f"{BASE_ENDPOINT}/top?limit=100&after={after_id}", headers=headers).json()

In [54]:
data_page01 == data_page02

False

I could keep doing this:

In [55]:
data_page02['data']['after']

't3_1b8jzpo'

<div style="width:70%;border: 1px solid #aaa; border-radius:1em; padding: 1em; margin: 1em 0;">

⚠️ **BIG WARNING!**

As mentioned in the past, creating these variables 'by hand' (`data_page01`, `data_page02`, `data_page03`, ...) is a very bad practice in this context. We should use a loop instead, ideally combined with a custom function.

</div>

But let's stop here! Let me save those two JSON files and send them to you so that you can use them in the next section.

In [56]:
os.makedirs("data", exist_ok=True)

# Saving `data` to file called `reddit_page1.json`
with open("data/reddit_page1.json", "w") as f:
    json.dump(data_page01, f)

# Saving `data` to file called `reddit_page2.json`
with open("data/reddit_page2.json", "w") as f:
    json.dump(data_page02, f)

# 2. Data Manipulation

You've experimented with cleaning up Data Frames in the past. Now, let's add another layer of complexity: cleaning up JSON files (nested Python dictionaries) before converting them into Data Frames.

🎯 **ACTION POINTS:**

Here is what I want from you:

1. Load the two JSON file as Python dictionaries using the `json` package. Call them `data_page01` and `data_page02`.

2. Instead of navigating the dictionaries manually, use the [`pd.json_normalize()` function](https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.json_normalize.html) to convert the `[data][children]` list of each JSON into a 🐼 pandas DataFrame. Call them `df_page01` and `df_page02`. 

    💡 Tip: Check out the parameter `max_level` of the `pd.json_normalize()` function in the documentation.

3. Concatenate the two DataFrames into a single one using the [`pd.concat()` function](https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.concat.html). Call this `df_reddit`. Check that it has 200 rows.

4. Let's not be wasteful! Delete the previous objects to clear up memory in your computer!

    ```python
    del data_page01, data_page02, df_page01, df_page02
    ```

**🥇 THE REAL CHALLENGE:**

5. Preprocess `df_reddit` such that you end up with a DataFrame that has these exact columns:

    ```python
    ['id', 'title', 'permalink', 'post_hint',  'url', 'created_utc',            # Identifiers 
     'ups', 'downs', 'upvote_ratio', 'score',                                   # Votes
     'subreddit_id', 'subreddit_name_prefixed', 'subreddit_subscribers',        # Which subreddit?
     'over_18', 'num_comments', 'is_original_content', 'is_self', 'is_video',   # Post metadata
     'author', 'author_fullname', 'author_premium',                             # Author metadata
     'content_categories', 'edited', 'domain']                                  # Misc metadata
    ```


<details style="background-color:transparent;color:transparent"><summary>🤫 Here's the solution</summary>

```python
def normalise_page(page):
    first_round = pd.DataFrame.from_dict(page['data']['children'])
    second_round = pd.json_normalize(first_round['data'], max_level=1)
    return second_round

all_pages = [data_page01, data_page02]
df_reddit = pd.concat([normalise_page(page) for page in all_pages])

selected_cols = ['id', 'title', 'post_hint', 'created_utc',
     'ups', 'downs', 'upvote_ratio', 'score', 
     'subreddit_id', 'subreddit_name_prefixed', 'subreddit_subscribers', 
     'over_18', 'num_comments', 'is_original_content', 'is_self', 'is_video', 
     'author', 'author_fullname', 'author_premium', 
     'content_categories', 'edited', 'domain']

df_reddit = df_reddit[selected_cols].copy()

df_reddit
```

</details>

**YOUR SOLUTIONS**

Create new Python cells below and write your code there.

# 3. Exploratory Data Analysis

Once we have collected data, putting it into a nice and tidy tabular structure like the one we have now allows us to explore it more efficiently.

### Question 01: How many subreddits are represented in the Top 200 today? 


In [ ]:
# You already know the `nunique()` function from the previous notebook. Use it to answer this question.

### Question 02: How many top posts are there in each subreddit?

In [3]:
#

<details><summary>Spoilers: click here for a fancy solution</summary>


The [pandas Styler](https://pandas.pydata.org/pandas-docs/stable/user_guide/style.html) is a potent tool to format DataFrames for printing on the screen or exporting to HTML.

```python
# I am using these parenthesis to give my code some breathing space
(
    df_reddit['subreddit_name_prefixed'].value_counts(normalize=True)
        .to_frame()             # Styler is a DataFrame method, so I have to convert this Series into a DataFrame
        .style.format("{:.2%}") # This formats the values as percentages
        .background_gradient(cmap='Blues') # I can keep on compounding (piping) styling methods!
)
```
</details>


### Question 03: how many upvotes did these top posts get on average?


In [ ]:
# Try to answer it with pandas functions, as opposed to using a for loop

---------------

# All of this is too easy? Here's a 🏆 Challenge for you:

Try to recreate the following plot using the `lets-plot` library with your up-to-date data.

- The x-axis represents the time when the post was created.
- The y-axis indicates the subreddit where the post was published.
- Each dot represents a post, and its size is proportional to the number of upvotes it received up until the time of data collection.
- The vertical line separates a day from another.

<?xml version="1.0" encoding="utf-8" standalone="no"?>
<!DOCTYPE svg PUBLIC "-//W3C//DTD SVG 1.1//EN"
  "http://www.w3.org/Graphics/SVG/1.1/DTD/svg11.dtd">
<svg xmlns:xlink="http://www.w3.org/1999/xlink" width="1152pt" height="576pt" viewBox="0 0 1152 576" xmlns="http://www.w3.org/2000/svg" version="1.1">
 <metadata>
  <rdf:RDF xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:cc="http://creativecommons.org/ns#" xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#">
   <cc:Work>
    <dc:type rdf:resource="http://purl.org/dc/dcmitype/StillImage"/>
    <dc:date>2024-03-01T18:09:34.920624</dc:date>
    <dc:format>image/svg+xml</dc:format>
    <dc:creator>
     <cc:Agent>
      <dc:title>Matplotlib v3.7.0, https://matplotlib.org/</dc:title>
     </cc:Agent>
    </dc:creator>
   </cc:Work>
  </rdf:RDF>
 </metadata>
 <defs>
  <style type="text/css">*{stroke-linejoin: round; stroke-linecap: butt}</style>
 </defs>
 <g id="figure_1">
  <g id="patch_1">
   <path d="M 0 576 
L 1152 576 
L 1152 0 
L 0 0 
L 0 576 
z
" style="fill: none"/>
  </g>
  <g id="axes_1">
   <g id="patch_2">
    <path d="M 155.711875 511.526875 
L 985.745469 511.526875 
L 985.745469 66.497813 
L 155.711875 66.497813 
L 155.711875 511.526875 
z
" style="fill: none"/>
   </g>
   <g id="matplotlib.axis_1">
    <g id="xtick_1">
     <g id="line2d_1">
      <path d="M 241.849682 511.526875 
L 241.849682 66.497813 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_1">
      <!-- 18:00 -->
      <g style="fill: #4d4d4d" transform="translate(224.558432 525.395) scale(0.12 -0.12)">
       <defs>
        <path id="DejaVuSans-31" d="M 794 531 
L 1825 531 
L 1825 4091 
L 703 3866 
L 703 4441 
L 1819 4666 
L 2450 4666 
L 2450 531 
L 3481 531 
L 3481 0 
L 794 0 
L 794 531 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-38" d="M 2034 2216 
Q 1584 2216 1326 1975 
Q 1069 1734 1069 1313 
Q 1069 891 1326 650 
Q 1584 409 2034 409 
Q 2484 409 2743 651 
Q 3003 894 3003 1313 
Q 3003 1734 2745 1975 
Q 2488 2216 2034 2216 
z
M 1403 2484 
Q 997 2584 770 2862 
Q 544 3141 544 3541 
Q 544 4100 942 4425 
Q 1341 4750 2034 4750 
Q 2731 4750 3128 4425 
Q 3525 4100 3525 3541 
Q 3525 3141 3298 2862 
Q 3072 2584 2669 2484 
Q 3125 2378 3379 2068 
Q 3634 1759 3634 1313 
Q 3634 634 3220 271 
Q 2806 -91 2034 -91 
Q 1263 -91 848 271 
Q 434 634 434 1313 
Q 434 1759 690 2068 
Q 947 2378 1403 2484 
z
M 1172 3481 
Q 1172 3119 1398 2916 
Q 1625 2713 2034 2713 
Q 2441 2713 2670 2916 
Q 2900 3119 2900 3481 
Q 2900 3844 2670 4047 
Q 2441 4250 2034 4250 
Q 1625 4250 1398 4047 
Q 1172 3844 1172 3481 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-3a" d="M 750 794 
L 1409 794 
L 1409 0 
L 750 0 
L 750 794 
z
M 750 3309 
L 1409 3309 
L 1409 2516 
L 750 2516 
L 750 3309 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-30" d="M 2034 4250 
Q 1547 4250 1301 3770 
Q 1056 3291 1056 2328 
Q 1056 1369 1301 889 
Q 1547 409 2034 409 
Q 2525 409 2770 889 
Q 3016 1369 3016 2328 
Q 3016 3291 2770 3770 
Q 2525 4250 2034 4250 
z
M 2034 4750 
Q 2819 4750 3233 4129 
Q 3647 3509 3647 2328 
Q 3647 1150 3233 529 
Q 2819 -91 2034 -91 
Q 1250 -91 836 529 
Q 422 1150 422 2328 
Q 422 3509 836 4129 
Q 1250 4750 2034 4750 
z
" transform="scale(0.015625)"/>
       </defs>
       <use xlink:href="#DejaVuSans-31"/>
       <use xlink:href="#DejaVuSans-38" x="63.623047"/>
       <use xlink:href="#DejaVuSans-3a" x="127.246094"/>
       <use xlink:href="#DejaVuSans-30" x="160.9375"/>
       <use xlink:href="#DejaVuSans-30" x="224.560547"/>
      </g>
     </g>
    </g>
    <g id="xtick_2">
     <g id="line2d_2">
      <path d="M 343.86281 511.526875 
L 343.86281 66.497813 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_2">
      <!-- 21:00 -->
      <g style="fill: #4d4d4d" transform="translate(326.57156 525.395) scale(0.12 -0.12)">
       <defs>
        <path id="DejaVuSans-32" d="M 1228 531 
L 3431 531 
L 3431 0 
L 469 0 
L 469 531 
Q 828 903 1448 1529 
Q 2069 2156 2228 2338 
Q 2531 2678 2651 2914 
Q 2772 3150 2772 3378 
Q 2772 3750 2511 3984 
Q 2250 4219 1831 4219 
Q 1534 4219 1204 4116 
Q 875 4013 500 3803 
L 500 4441 
Q 881 4594 1212 4672 
Q 1544 4750 1819 4750 
Q 2544 4750 2975 4387 
Q 3406 4025 3406 3419 
Q 3406 3131 3298 2873 
Q 3191 2616 2906 2266 
Q 2828 2175 2409 1742 
Q 1991 1309 1228 531 
z
" transform="scale(0.015625)"/>
       </defs>
       <use xlink:href="#DejaVuSans-32"/>
       <use xlink:href="#DejaVuSans-31" x="63.623047"/>
       <use xlink:href="#DejaVuSans-3a" x="127.246094"/>
       <use xlink:href="#DejaVuSans-30" x="160.9375"/>
       <use xlink:href="#DejaVuSans-30" x="224.560547"/>
      </g>
     </g>
    </g>
    <g id="xtick_3">
     <g id="line2d_3">
      <path d="M 445.875938 511.526875 
L 445.875938 66.497813 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_3">
      <!-- 00:00 -->
      <g style="fill: #4d4d4d" transform="translate(428.584688 525.395) scale(0.12 -0.12)">
       <use xlink:href="#DejaVuSans-30"/>
       <use xlink:href="#DejaVuSans-30" x="63.623047"/>
       <use xlink:href="#DejaVuSans-3a" x="127.246094"/>
       <use xlink:href="#DejaVuSans-30" x="160.9375"/>
       <use xlink:href="#DejaVuSans-30" x="224.560547"/>
      </g>
     </g>
    </g>
    <g id="xtick_4">
     <g id="line2d_4">
      <path d="M 547.889066 511.526875 
L 547.889066 66.497813 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_4">
      <!-- 03:00 -->
      <g style="fill: #4d4d4d" transform="translate(530.597816 525.395) scale(0.12 -0.12)">
       <defs>
        <path id="DejaVuSans-33" d="M 2597 2516 
Q 3050 2419 3304 2112 
Q 3559 1806 3559 1356 
Q 3559 666 3084 287 
Q 2609 -91 1734 -91 
Q 1441 -91 1130 -33 
Q 819 25 488 141 
L 488 750 
Q 750 597 1062 519 
Q 1375 441 1716 441 
Q 2309 441 2620 675 
Q 2931 909 2931 1356 
Q 2931 1769 2642 2001 
Q 2353 2234 1838 2234 
L 1294 2234 
L 1294 2753 
L 1863 2753 
Q 2328 2753 2575 2939 
Q 2822 3125 2822 3475 
Q 2822 3834 2567 4026 
Q 2313 4219 1838 4219 
Q 1578 4219 1281 4162 
Q 984 4106 628 3988 
L 628 4550 
Q 988 4650 1302 4700 
Q 1616 4750 1894 4750 
Q 2613 4750 3031 4423 
Q 3450 4097 3450 3541 
Q 3450 3153 3228 2886 
Q 3006 2619 2597 2516 
z
" transform="scale(0.015625)"/>
       </defs>
       <use xlink:href="#DejaVuSans-30"/>
       <use xlink:href="#DejaVuSans-33" x="63.623047"/>
       <use xlink:href="#DejaVuSans-3a" x="127.246094"/>
       <use xlink:href="#DejaVuSans-30" x="160.9375"/>
       <use xlink:href="#DejaVuSans-30" x="224.560547"/>
      </g>
     </g>
    </g>
    <g id="xtick_5">
     <g id="line2d_5">
      <path d="M 649.902194 511.526875 
L 649.902194 66.497813 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_5">
      <!-- 06:00 -->
      <g style="fill: #4d4d4d" transform="translate(632.610944 525.395) scale(0.12 -0.12)">
       <defs>
        <path id="DejaVuSans-36" d="M 2113 2584 
Q 1688 2584 1439 2293 
Q 1191 2003 1191 1497 
Q 1191 994 1439 701 
Q 1688 409 2113 409 
Q 2538 409 2786 701 
Q 3034 994 3034 1497 
Q 3034 2003 2786 2293 
Q 2538 2584 2113 2584 
z
M 3366 4563 
L 3366 3988 
Q 3128 4100 2886 4159 
Q 2644 4219 2406 4219 
Q 1781 4219 1451 3797 
Q 1122 3375 1075 2522 
Q 1259 2794 1537 2939 
Q 1816 3084 2150 3084 
Q 2853 3084 3261 2657 
Q 3669 2231 3669 1497 
Q 3669 778 3244 343 
Q 2819 -91 2113 -91 
Q 1303 -91 875 529 
Q 447 1150 447 2328 
Q 447 3434 972 4092 
Q 1497 4750 2381 4750 
Q 2619 4750 2861 4703 
Q 3103 4656 3366 4563 
z
" transform="scale(0.015625)"/>
       </defs>
       <use xlink:href="#DejaVuSans-30"/>
       <use xlink:href="#DejaVuSans-36" x="63.623047"/>
       <use xlink:href="#DejaVuSans-3a" x="127.246094"/>
       <use xlink:href="#DejaVuSans-30" x="160.9375"/>
       <use xlink:href="#DejaVuSans-30" x="224.560547"/>
      </g>
     </g>
    </g>
    <g id="xtick_6">
     <g id="line2d_6">
      <path d="M 751.915322 511.526875 
L 751.915322 66.497813 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_6">
      <!-- 09:00 -->
      <g style="fill: #4d4d4d" transform="translate(734.624072 525.395) scale(0.12 -0.12)">
       <defs>
        <path id="DejaVuSans-39" d="M 703 97 
L 703 672 
Q 941 559 1184 500 
Q 1428 441 1663 441 
Q 2288 441 2617 861 
Q 2947 1281 2994 2138 
Q 2813 1869 2534 1725 
Q 2256 1581 1919 1581 
Q 1219 1581 811 2004 
Q 403 2428 403 3163 
Q 403 3881 828 4315 
Q 1253 4750 1959 4750 
Q 2769 4750 3195 4129 
Q 3622 3509 3622 2328 
Q 3622 1225 3098 567 
Q 2575 -91 1691 -91 
Q 1453 -91 1209 -44 
Q 966 3 703 97 
z
M 1959 2075 
Q 2384 2075 2632 2365 
Q 2881 2656 2881 3163 
Q 2881 3666 2632 3958 
Q 2384 4250 1959 4250 
Q 1534 4250 1286 3958 
Q 1038 3666 1038 3163 
Q 1038 2656 1286 2365 
Q 1534 2075 1959 2075 
z
" transform="scale(0.015625)"/>
       </defs>
       <use xlink:href="#DejaVuSans-30"/>
       <use xlink:href="#DejaVuSans-39" x="63.623047"/>
       <use xlink:href="#DejaVuSans-3a" x="127.246094"/>
       <use xlink:href="#DejaVuSans-30" x="160.9375"/>
       <use xlink:href="#DejaVuSans-30" x="224.560547"/>
      </g>
     </g>
    </g>
    <g id="xtick_7">
     <g id="line2d_7">
      <path d="M 853.92845 511.526875 
L 853.92845 66.497813 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_7">
      <!-- 12:00 -->
      <g style="fill: #4d4d4d" transform="translate(836.6372 525.395) scale(0.12 -0.12)">
       <use xlink:href="#DejaVuSans-31"/>
       <use xlink:href="#DejaVuSans-32" x="63.623047"/>
       <use xlink:href="#DejaVuSans-3a" x="127.246094"/>
       <use xlink:href="#DejaVuSans-30" x="160.9375"/>
       <use xlink:href="#DejaVuSans-30" x="224.560547"/>
      </g>
     </g>
    </g>
    <g id="xtick_8">
     <g id="line2d_8">
      <path d="M 955.941578 511.526875 
L 955.941578 66.497813 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_8">
      <!-- 15:00 -->
      <g style="fill: #4d4d4d" transform="translate(938.650328 525.395) scale(0.12 -0.12)">
       <defs>
        <path id="DejaVuSans-35" d="M 691 4666 
L 3169 4666 
L 3169 4134 
L 1269 4134 
L 1269 2991 
Q 1406 3038 1543 3061 
Q 1681 3084 1819 3084 
Q 2600 3084 3056 2656 
Q 3513 2228 3513 1497 
Q 3513 744 3044 326 
Q 2575 -91 1722 -91 
Q 1428 -91 1123 -41 
Q 819 9 494 109 
L 494 744 
Q 775 591 1075 516 
Q 1375 441 1709 441 
Q 2250 441 2565 725 
Q 2881 1009 2881 1497 
Q 2881 1984 2565 2268 
Q 2250 2553 1709 2553 
Q 1456 2553 1204 2497 
Q 953 2441 691 2322 
L 691 4666 
z
" transform="scale(0.015625)"/>
       </defs>
       <use xlink:href="#DejaVuSans-31"/>
       <use xlink:href="#DejaVuSans-35" x="63.623047"/>
       <use xlink:href="#DejaVuSans-3a" x="127.246094"/>
       <use xlink:href="#DejaVuSans-30" x="160.9375"/>
       <use xlink:href="#DejaVuSans-30" x="224.560547"/>
      </g>
     </g>
    </g>
    <g id="xtick_9">
     <g id="line2d_9">
      <path d="M 190.843118 511.526875 
L 190.843118 66.497813 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #fafafa"/>
     </g>
    </g>
    <g id="xtick_10">
     <g id="line2d_10">
      <path d="M 292.856246 511.526875 
L 292.856246 66.497813 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #fafafa"/>
     </g>
    </g>
    <g id="xtick_11">
     <g id="line2d_11">
      <path d="M 394.869374 511.526875 
L 394.869374 66.497813 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #fafafa"/>
     </g>
    </g>
    <g id="xtick_12">
     <g id="line2d_12">
      <path d="M 496.882502 511.526875 
L 496.882502 66.497813 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #fafafa"/>
     </g>
    </g>
    <g id="xtick_13">
     <g id="line2d_13">
      <path d="M 598.89563 511.526875 
L 598.89563 66.497813 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #fafafa"/>
     </g>
    </g>
    <g id="xtick_14">
     <g id="line2d_14">
      <path d="M 700.908758 511.526875 
L 700.908758 66.497813 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #fafafa"/>
     </g>
    </g>
    <g id="xtick_15">
     <g id="line2d_15">
      <path d="M 802.921886 511.526875 
L 802.921886 66.497813 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #fafafa"/>
     </g>
    </g>
    <g id="xtick_16">
     <g id="line2d_16">
      <path d="M 904.935014 511.526875 
L 904.935014 66.497813 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #fafafa"/>
     </g>
    </g>
   </g>
   <g id="matplotlib.axis_2">
    <g id="ytick_1">
     <g id="line2d_17">
      <path d="M 155.711875 502.382442 
L 985.745469 502.382442 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_9">
      <!-- r/books -->
      <g style="fill: #4d4d4d" transform="translate(110.189688 505.417755) scale(0.11 -0.11)">
       <defs>
        <path id="DejaVuSans-72" d="M 2631 2963 
Q 2534 3019 2420 3045 
Q 2306 3072 2169 3072 
Q 1681 3072 1420 2755 
Q 1159 2438 1159 1844 
L 1159 0 
L 581 0 
L 581 3500 
L 1159 3500 
L 1159 2956 
Q 1341 3275 1631 3429 
Q 1922 3584 2338 3584 
Q 2397 3584 2469 3576 
Q 2541 3569 2628 3553 
L 2631 2963 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-2f" d="M 1625 4666 
L 2156 4666 
L 531 -594 
L 0 -594 
L 1625 4666 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-62" d="M 3116 1747 
Q 3116 2381 2855 2742 
Q 2594 3103 2138 3103 
Q 1681 3103 1420 2742 
Q 1159 2381 1159 1747 
Q 1159 1113 1420 752 
Q 1681 391 2138 391 
Q 2594 391 2855 752 
Q 3116 1113 3116 1747 
z
M 1159 2969 
Q 1341 3281 1617 3432 
Q 1894 3584 2278 3584 
Q 2916 3584 3314 3078 
Q 3713 2572 3713 1747 
Q 3713 922 3314 415 
Q 2916 -91 2278 -91 
Q 1894 -91 1617 61 
Q 1341 213 1159 525 
L 1159 0 
L 581 0 
L 581 4863 
L 1159 4863 
L 1159 2969 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-6f" d="M 1959 3097 
Q 1497 3097 1228 2736 
Q 959 2375 959 1747 
Q 959 1119 1226 758 
Q 1494 397 1959 397 
Q 2419 397 2687 759 
Q 2956 1122 2956 1747 
Q 2956 2369 2687 2733 
Q 2419 3097 1959 3097 
z
M 1959 3584 
Q 2709 3584 3137 3096 
Q 3566 2609 3566 1747 
Q 3566 888 3137 398 
Q 2709 -91 1959 -91 
Q 1206 -91 779 398 
Q 353 888 353 1747 
Q 353 2609 779 3096 
Q 1206 3584 1959 3584 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-6b" d="M 581 4863 
L 1159 4863 
L 1159 1991 
L 2875 3500 
L 3609 3500 
L 1753 1863 
L 3688 0 
L 2938 0 
L 1159 1709 
L 1159 0 
L 581 0 
L 581 4863 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-73" d="M 2834 3397 
L 2834 2853 
Q 2591 2978 2328 3040 
Q 2066 3103 1784 3103 
Q 1356 3103 1142 2972 
Q 928 2841 928 2578 
Q 928 2378 1081 2264 
Q 1234 2150 1697 2047 
L 1894 2003 
Q 2506 1872 2764 1633 
Q 3022 1394 3022 966 
Q 3022 478 2636 193 
Q 2250 -91 1575 -91 
Q 1294 -91 989 -36 
Q 684 19 347 128 
L 347 722 
Q 666 556 975 473 
Q 1284 391 1588 391 
Q 1994 391 2212 530 
Q 2431 669 2431 922 
Q 2431 1156 2273 1281 
Q 2116 1406 1581 1522 
L 1381 1569 
Q 847 1681 609 1914 
Q 372 2147 372 2553 
Q 372 3047 722 3315 
Q 1072 3584 1716 3584 
Q 2034 3584 2315 3537 
Q 2597 3491 2834 3397 
z
" transform="scale(0.015625)"/>
       </defs>
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-62" x="74.804688"/>
       <use xlink:href="#DejaVuSans-6f" x="138.28125"/>
       <use xlink:href="#DejaVuSans-6f" x="199.462891"/>
       <use xlink:href="#DejaVuSans-6b" x="260.644531"/>
       <use xlink:href="#DejaVuSans-73" x="318.554688"/>
      </g>
     </g>
    </g>
    <g id="ytick_2">
     <g id="line2d_18">
      <path d="M 155.711875 487.141721 
L 985.745469 487.141721 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_10">
      <!-- r/UpliftingNews -->
      <g style="fill: #4d4d4d" transform="translate(66.861719 490.177033) scale(0.11 -0.11)">
       <defs>
        <path id="DejaVuSans-55" d="M 556 4666 
L 1191 4666 
L 1191 1831 
Q 1191 1081 1462 751 
Q 1734 422 2344 422 
Q 2950 422 3222 751 
Q 3494 1081 3494 1831 
L 3494 4666 
L 4128 4666 
L 4128 1753 
Q 4128 841 3676 375 
Q 3225 -91 2344 -91 
Q 1459 -91 1007 375 
Q 556 841 556 1753 
L 556 4666 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-70" d="M 1159 525 
L 1159 -1331 
L 581 -1331 
L 581 3500 
L 1159 3500 
L 1159 2969 
Q 1341 3281 1617 3432 
Q 1894 3584 2278 3584 
Q 2916 3584 3314 3078 
Q 3713 2572 3713 1747 
Q 3713 922 3314 415 
Q 2916 -91 2278 -91 
Q 1894 -91 1617 61 
Q 1341 213 1159 525 
z
M 3116 1747 
Q 3116 2381 2855 2742 
Q 2594 3103 2138 3103 
Q 1681 3103 1420 2742 
Q 1159 2381 1159 1747 
Q 1159 1113 1420 752 
Q 1681 391 2138 391 
Q 2594 391 2855 752 
Q 3116 1113 3116 1747 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-6c" d="M 603 4863 
L 1178 4863 
L 1178 0 
L 603 0 
L 603 4863 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-69" d="M 603 3500 
L 1178 3500 
L 1178 0 
L 603 0 
L 603 3500 
z
M 603 4863 
L 1178 4863 
L 1178 4134 
L 603 4134 
L 603 4863 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-66" d="M 2375 4863 
L 2375 4384 
L 1825 4384 
Q 1516 4384 1395 4259 
Q 1275 4134 1275 3809 
L 1275 3500 
L 2222 3500 
L 2222 3053 
L 1275 3053 
L 1275 0 
L 697 0 
L 697 3053 
L 147 3053 
L 147 3500 
L 697 3500 
L 697 3744 
Q 697 4328 969 4595 
Q 1241 4863 1831 4863 
L 2375 4863 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-74" d="M 1172 4494 
L 1172 3500 
L 2356 3500 
L 2356 3053 
L 1172 3053 
L 1172 1153 
Q 1172 725 1289 603 
Q 1406 481 1766 481 
L 2356 481 
L 2356 0 
L 1766 0 
Q 1100 0 847 248 
Q 594 497 594 1153 
L 594 3053 
L 172 3053 
L 172 3500 
L 594 3500 
L 594 4494 
L 1172 4494 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-6e" d="M 3513 2113 
L 3513 0 
L 2938 0 
L 2938 2094 
Q 2938 2591 2744 2837 
Q 2550 3084 2163 3084 
Q 1697 3084 1428 2787 
Q 1159 2491 1159 1978 
L 1159 0 
L 581 0 
L 581 3500 
L 1159 3500 
L 1159 2956 
Q 1366 3272 1645 3428 
Q 1925 3584 2291 3584 
Q 2894 3584 3203 3211 
Q 3513 2838 3513 2113 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-67" d="M 2906 1791 
Q 2906 2416 2648 2759 
Q 2391 3103 1925 3103 
Q 1463 3103 1205 2759 
Q 947 2416 947 1791 
Q 947 1169 1205 825 
Q 1463 481 1925 481 
Q 2391 481 2648 825 
Q 2906 1169 2906 1791 
z
M 3481 434 
Q 3481 -459 3084 -895 
Q 2688 -1331 1869 -1331 
Q 1566 -1331 1297 -1286 
Q 1028 -1241 775 -1147 
L 775 -588 
Q 1028 -725 1275 -790 
Q 1522 -856 1778 -856 
Q 2344 -856 2625 -561 
Q 2906 -266 2906 331 
L 2906 616 
Q 2728 306 2450 153 
Q 2172 0 1784 0 
Q 1141 0 747 490 
Q 353 981 353 1791 
Q 353 2603 747 3093 
Q 1141 3584 1784 3584 
Q 2172 3584 2450 3431 
Q 2728 3278 2906 2969 
L 2906 3500 
L 3481 3500 
L 3481 434 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-4e" d="M 628 4666 
L 1478 4666 
L 3547 763 
L 3547 4666 
L 4159 4666 
L 4159 0 
L 3309 0 
L 1241 3903 
L 1241 0 
L 628 0 
L 628 4666 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-65" d="M 3597 1894 
L 3597 1613 
L 953 1613 
Q 991 1019 1311 708 
Q 1631 397 2203 397 
Q 2534 397 2845 478 
Q 3156 559 3463 722 
L 3463 178 
Q 3153 47 2828 -22 
Q 2503 -91 2169 -91 
Q 1331 -91 842 396 
Q 353 884 353 1716 
Q 353 2575 817 3079 
Q 1281 3584 2069 3584 
Q 2775 3584 3186 3129 
Q 3597 2675 3597 1894 
z
M 3022 2063 
Q 3016 2534 2758 2815 
Q 2500 3097 2075 3097 
Q 1594 3097 1305 2825 
Q 1016 2553 972 2059 
L 3022 2063 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-77" d="M 269 3500 
L 844 3500 
L 1563 769 
L 2278 3500 
L 2956 3500 
L 3675 769 
L 4391 3500 
L 4966 3500 
L 4050 0 
L 3372 0 
L 2619 2869 
L 1863 0 
L 1184 0 
L 269 3500 
z
" transform="scale(0.015625)"/>
       </defs>
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-55" x="74.804688"/>
       <use xlink:href="#DejaVuSans-70" x="147.998047"/>
       <use xlink:href="#DejaVuSans-6c" x="211.474609"/>
       <use xlink:href="#DejaVuSans-69" x="239.257812"/>
       <use xlink:href="#DejaVuSans-66" x="267.041016"/>
       <use xlink:href="#DejaVuSans-74" x="300.496094"/>
       <use xlink:href="#DejaVuSans-69" x="339.705078"/>
       <use xlink:href="#DejaVuSans-6e" x="367.488281"/>
       <use xlink:href="#DejaVuSans-67" x="430.867188"/>
       <use xlink:href="#DejaVuSans-4e" x="494.34375"/>
       <use xlink:href="#DejaVuSans-65" x="569.148438"/>
       <use xlink:href="#DejaVuSans-77" x="630.671875"/>
       <use xlink:href="#DejaVuSans-73" x="712.458984"/>
      </g>
     </g>
    </g>
    <g id="ytick_3">
     <g id="line2d_19">
      <path d="M 155.711875 471.901 
L 985.745469 471.901 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_11">
      <!-- r/EarthPorn -->
      <g style="fill: #4d4d4d" transform="translate(88.971719 474.936312) scale(0.11 -0.11)">
       <defs>
        <path id="DejaVuSans-45" d="M 628 4666 
L 3578 4666 
L 3578 4134 
L 1259 4134 
L 1259 2753 
L 3481 2753 
L 3481 2222 
L 1259 2222 
L 1259 531 
L 3634 531 
L 3634 0 
L 628 0 
L 628 4666 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-61" d="M 2194 1759 
Q 1497 1759 1228 1600 
Q 959 1441 959 1056 
Q 959 750 1161 570 
Q 1363 391 1709 391 
Q 2188 391 2477 730 
Q 2766 1069 2766 1631 
L 2766 1759 
L 2194 1759 
z
M 3341 1997 
L 3341 0 
L 2766 0 
L 2766 531 
Q 2569 213 2275 61 
Q 1981 -91 1556 -91 
Q 1019 -91 701 211 
Q 384 513 384 1019 
Q 384 1609 779 1909 
Q 1175 2209 1959 2209 
L 2766 2209 
L 2766 2266 
Q 2766 2663 2505 2880 
Q 2244 3097 1772 3097 
Q 1472 3097 1187 3025 
Q 903 2953 641 2809 
L 641 3341 
Q 956 3463 1253 3523 
Q 1550 3584 1831 3584 
Q 2591 3584 2966 3190 
Q 3341 2797 3341 1997 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-68" d="M 3513 2113 
L 3513 0 
L 2938 0 
L 2938 2094 
Q 2938 2591 2744 2837 
Q 2550 3084 2163 3084 
Q 1697 3084 1428 2787 
Q 1159 2491 1159 1978 
L 1159 0 
L 581 0 
L 581 4863 
L 1159 4863 
L 1159 2956 
Q 1366 3272 1645 3428 
Q 1925 3584 2291 3584 
Q 2894 3584 3203 3211 
Q 3513 2838 3513 2113 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-50" d="M 1259 4147 
L 1259 2394 
L 2053 2394 
Q 2494 2394 2734 2622 
Q 2975 2850 2975 3272 
Q 2975 3691 2734 3919 
Q 2494 4147 2053 4147 
L 1259 4147 
z
M 628 4666 
L 2053 4666 
Q 2838 4666 3239 4311 
Q 3641 3956 3641 3272 
Q 3641 2581 3239 2228 
Q 2838 1875 2053 1875 
L 1259 1875 
L 1259 0 
L 628 0 
L 628 4666 
z
" transform="scale(0.015625)"/>
       </defs>
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-45" x="74.804688"/>
       <use xlink:href="#DejaVuSans-61" x="137.988281"/>
       <use xlink:href="#DejaVuSans-72" x="199.267578"/>
       <use xlink:href="#DejaVuSans-74" x="240.380859"/>
       <use xlink:href="#DejaVuSans-68" x="279.589844"/>
       <use xlink:href="#DejaVuSans-50" x="342.96875"/>
       <use xlink:href="#DejaVuSans-6f" x="399.646484"/>
       <use xlink:href="#DejaVuSans-72" x="460.828125"/>
       <use xlink:href="#DejaVuSans-6e" x="500.191406"/>
      </g>
     </g>
    </g>
    <g id="ytick_4">
     <g id="line2d_20">
      <path d="M 155.711875 456.660278 
L 985.745469 456.660278 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_12">
      <!-- r/TwoXChromosomes -->
      <g style="fill: #4d4d4d" transform="translate(36.589375 459.695591) scale(0.11 -0.11)">
       <defs>
        <path id="DejaVuSans-54" d="M -19 4666 
L 3928 4666 
L 3928 4134 
L 2272 4134 
L 2272 0 
L 1638 0 
L 1638 4134 
L -19 4134 
L -19 4666 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-58" d="M 403 4666 
L 1081 4666 
L 2241 2931 
L 3406 4666 
L 4084 4666 
L 2584 2425 
L 4184 0 
L 3506 0 
L 2194 1984 
L 872 0 
L 191 0 
L 1856 2491 
L 403 4666 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-43" d="M 4122 4306 
L 4122 3641 
Q 3803 3938 3442 4084 
Q 3081 4231 2675 4231 
Q 1875 4231 1450 3742 
Q 1025 3253 1025 2328 
Q 1025 1406 1450 917 
Q 1875 428 2675 428 
Q 3081 428 3442 575 
Q 3803 722 4122 1019 
L 4122 359 
Q 3791 134 3420 21 
Q 3050 -91 2638 -91 
Q 1578 -91 968 557 
Q 359 1206 359 2328 
Q 359 3453 968 4101 
Q 1578 4750 2638 4750 
Q 3056 4750 3426 4639 
Q 3797 4528 4122 4306 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-6d" d="M 3328 2828 
Q 3544 3216 3844 3400 
Q 4144 3584 4550 3584 
Q 5097 3584 5394 3201 
Q 5691 2819 5691 2113 
L 5691 0 
L 5113 0 
L 5113 2094 
Q 5113 2597 4934 2840 
Q 4756 3084 4391 3084 
Q 3944 3084 3684 2787 
Q 3425 2491 3425 1978 
L 3425 0 
L 2847 0 
L 2847 2094 
Q 2847 2600 2669 2842 
Q 2491 3084 2119 3084 
Q 1678 3084 1418 2786 
Q 1159 2488 1159 1978 
L 1159 0 
L 581 0 
L 581 3500 
L 1159 3500 
L 1159 2956 
Q 1356 3278 1631 3431 
Q 1906 3584 2284 3584 
Q 2666 3584 2933 3390 
Q 3200 3197 3328 2828 
z
" transform="scale(0.015625)"/>
       </defs>
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-54" x="74.804688"/>
       <use xlink:href="#DejaVuSans-77" x="119.388672"/>
       <use xlink:href="#DejaVuSans-6f" x="201.175781"/>
       <use xlink:href="#DejaVuSans-58" x="262.357422"/>
       <use xlink:href="#DejaVuSans-43" x="323.613281"/>
       <use xlink:href="#DejaVuSans-68" x="393.4375"/>
       <use xlink:href="#DejaVuSans-72" x="456.816406"/>
       <use xlink:href="#DejaVuSans-6f" x="495.679688"/>
       <use xlink:href="#DejaVuSans-6d" x="556.861328"/>
       <use xlink:href="#DejaVuSans-6f" x="654.273438"/>
       <use xlink:href="#DejaVuSans-73" x="715.455078"/>
       <use xlink:href="#DejaVuSans-6f" x="767.554688"/>
       <use xlink:href="#DejaVuSans-6d" x="828.736328"/>
       <use xlink:href="#DejaVuSans-65" x="926.148438"/>
       <use xlink:href="#DejaVuSans-73" x="987.671875"/>
      </g>
     </g>
    </g>
    <g id="ytick_5">
     <g id="line2d_21">
      <path d="M 155.711875 441.419557 
L 985.745469 441.419557 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_13">
      <!-- r/LifeProTips -->
      <g style="fill: #4d4d4d" transform="translate(83.31875 444.454869) scale(0.11 -0.11)">
       <defs>
        <path id="DejaVuSans-4c" d="M 628 4666 
L 1259 4666 
L 1259 531 
L 3531 531 
L 3531 0 
L 628 0 
L 628 4666 
z
" transform="scale(0.015625)"/>
       </defs>
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-4c" x="74.804688"/>
       <use xlink:href="#DejaVuSans-69" x="130.517578"/>
       <use xlink:href="#DejaVuSans-66" x="158.300781"/>
       <use xlink:href="#DejaVuSans-65" x="193.505859"/>
       <use xlink:href="#DejaVuSans-50" x="255.029297"/>
       <use xlink:href="#DejaVuSans-72" x="313.582031"/>
       <use xlink:href="#DejaVuSans-6f" x="352.445312"/>
       <use xlink:href="#DejaVuSans-54" x="413.626953"/>
       <use xlink:href="#DejaVuSans-69" x="471.585938"/>
       <use xlink:href="#DejaVuSans-70" x="499.369141"/>
       <use xlink:href="#DejaVuSans-73" x="562.845703"/>
      </g>
     </g>
    </g>
    <g id="ytick_6">
     <g id="line2d_22">
      <path d="M 155.711875 426.178836 
L 985.745469 426.178836 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_14">
      <!-- r/gadgets -->
      <g style="fill: #4d4d4d" transform="translate(98.232344 429.214148) scale(0.11 -0.11)">
       <defs>
        <path id="DejaVuSans-64" d="M 2906 2969 
L 2906 4863 
L 3481 4863 
L 3481 0 
L 2906 0 
L 2906 525 
Q 2725 213 2448 61 
Q 2172 -91 1784 -91 
Q 1150 -91 751 415 
Q 353 922 353 1747 
Q 353 2572 751 3078 
Q 1150 3584 1784 3584 
Q 2172 3584 2448 3432 
Q 2725 3281 2906 2969 
z
M 947 1747 
Q 947 1113 1208 752 
Q 1469 391 1925 391 
Q 2381 391 2643 752 
Q 2906 1113 2906 1747 
Q 2906 2381 2643 2742 
Q 2381 3103 1925 3103 
Q 1469 3103 1208 2742 
Q 947 2381 947 1747 
z
" transform="scale(0.015625)"/>
       </defs>
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-67" x="74.804688"/>
       <use xlink:href="#DejaVuSans-61" x="138.28125"/>
       <use xlink:href="#DejaVuSans-64" x="199.560547"/>
       <use xlink:href="#DejaVuSans-67" x="263.037109"/>
       <use xlink:href="#DejaVuSans-65" x="326.513672"/>
       <use xlink:href="#DejaVuSans-74" x="388.037109"/>
       <use xlink:href="#DejaVuSans-73" x="427.246094"/>
      </g>
     </g>
    </g>
    <g id="ytick_7">
     <g id="line2d_23">
      <path d="M 155.711875 410.938114 
L 985.745469 410.938114 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_15">
      <!-- r/Jokes -->
      <g style="fill: #4d4d4d" transform="translate(114.288906 413.973427) scale(0.11 -0.11)">
       <defs>
        <path id="DejaVuSans-4a" d="M 628 4666 
L 1259 4666 
L 1259 325 
Q 1259 -519 939 -900 
Q 619 -1281 -91 -1281 
L -331 -1281 
L -331 -750 
L -134 -750 
Q 284 -750 456 -515 
Q 628 -281 628 325 
L 628 4666 
z
" transform="scale(0.015625)"/>
       </defs>
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-4a" x="74.804688"/>
       <use xlink:href="#DejaVuSans-6f" x="104.296875"/>
       <use xlink:href="#DejaVuSans-6b" x="165.478516"/>
       <use xlink:href="#DejaVuSans-65" x="219.763672"/>
       <use xlink:href="#DejaVuSans-73" x="281.287109"/>
      </g>
     </g>
    </g>
    <g id="ytick_8">
     <g id="line2d_24">
      <path d="M 155.711875 395.697393 
L 985.745469 395.697393 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_16">
      <!-- r/food -->
      <g style="fill: #4d4d4d" transform="translate(118.417344 398.732705) scale(0.11 -0.11)">
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-66" x="74.804688"/>
       <use xlink:href="#DejaVuSans-6f" x="110.009766"/>
       <use xlink:href="#DejaVuSans-6f" x="171.191406"/>
       <use xlink:href="#DejaVuSans-64" x="232.373047"/>
      </g>
     </g>
    </g>
    <g id="ytick_9">
     <g id="line2d_25">
      <path d="M 155.711875 380.456672 
L 985.745469 380.456672 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_17">
      <!-- r/IAmA -->
      <g style="fill: #4d4d4d" transform="translate(113.725156 383.491984) scale(0.11 -0.11)">
       <defs>
        <path id="DejaVuSans-49" d="M 628 4666 
L 1259 4666 
L 1259 0 
L 628 0 
L 628 4666 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-41" d="M 2188 4044 
L 1331 1722 
L 3047 1722 
L 2188 4044 
z
M 1831 4666 
L 2547 4666 
L 4325 0 
L 3669 0 
L 3244 1197 
L 1141 1197 
L 716 0 
L 50 0 
L 1831 4666 
z
" transform="scale(0.015625)"/>
       </defs>
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-49" x="74.804688"/>
       <use xlink:href="#DejaVuSans-41" x="104.296875"/>
       <use xlink:href="#DejaVuSans-6d" x="172.705078"/>
       <use xlink:href="#DejaVuSans-41" x="270.117188"/>
      </g>
     </g>
    </g>
    <g id="ytick_10">
     <g id="line2d_26">
      <path d="M 155.711875 365.21595 
L 985.745469 365.21595 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_18">
      <!-- r/videos -->
      <g style="fill: #4d4d4d" transform="translate(106.955 368.251263) scale(0.11 -0.11)">
       <defs>
        <path id="DejaVuSans-76" d="M 191 3500 
L 800 3500 
L 1894 563 
L 2988 3500 
L 3597 3500 
L 2284 0 
L 1503 0 
L 191 3500 
z
" transform="scale(0.015625)"/>
       </defs>
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-76" x="74.804688"/>
       <use xlink:href="#DejaVuSans-69" x="133.984375"/>
       <use xlink:href="#DejaVuSans-64" x="161.767578"/>
       <use xlink:href="#DejaVuSans-65" x="225.244141"/>
       <use xlink:href="#DejaVuSans-6f" x="286.767578"/>
       <use xlink:href="#DejaVuSans-73" x="347.949219"/>
      </g>
     </g>
    </g>
    <g id="ytick_11">
     <g id="line2d_27">
      <path d="M 155.711875 349.975229 
L 985.745469 349.975229 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_19">
      <!-- r/science -->
      <g style="fill: #4d4d4d" transform="translate(101.343281 353.010542) scale(0.11 -0.11)">
       <defs>
        <path id="DejaVuSans-63" d="M 3122 3366 
L 3122 2828 
Q 2878 2963 2633 3030 
Q 2388 3097 2138 3097 
Q 1578 3097 1268 2742 
Q 959 2388 959 1747 
Q 959 1106 1268 751 
Q 1578 397 2138 397 
Q 2388 397 2633 464 
Q 2878 531 3122 666 
L 3122 134 
Q 2881 22 2623 -34 
Q 2366 -91 2075 -91 
Q 1284 -91 818 406 
Q 353 903 353 1747 
Q 353 2603 823 3093 
Q 1294 3584 2113 3584 
Q 2378 3584 2631 3529 
Q 2884 3475 3122 3366 
z
" transform="scale(0.015625)"/>
       </defs>
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-73" x="74.804688"/>
       <use xlink:href="#DejaVuSans-63" x="126.904297"/>
       <use xlink:href="#DejaVuSans-69" x="181.884766"/>
       <use xlink:href="#DejaVuSans-65" x="209.667969"/>
       <use xlink:href="#DejaVuSans-6e" x="271.191406"/>
       <use xlink:href="#DejaVuSans-63" x="334.570312"/>
       <use xlink:href="#DejaVuSans-65" x="389.550781"/>
      </g>
     </g>
    </g>
    <g id="ytick_12">
     <g id="line2d_28">
      <path d="M 155.711875 334.734508 
L 985.745469 334.734508 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_20">
      <!-- r/Music -->
      <g style="fill: #4d4d4d" transform="translate(111.4375 337.76982) scale(0.11 -0.11)">
       <defs>
        <path id="DejaVuSans-4d" d="M 628 4666 
L 1569 4666 
L 2759 1491 
L 3956 4666 
L 4897 4666 
L 4897 0 
L 4281 0 
L 4281 4097 
L 3078 897 
L 2444 897 
L 1241 4097 
L 1241 0 
L 628 0 
L 628 4666 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-75" d="M 544 1381 
L 544 3500 
L 1119 3500 
L 1119 1403 
Q 1119 906 1312 657 
Q 1506 409 1894 409 
Q 2359 409 2629 706 
Q 2900 1003 2900 1516 
L 2900 3500 
L 3475 3500 
L 3475 0 
L 2900 0 
L 2900 538 
Q 2691 219 2414 64 
Q 2138 -91 1772 -91 
Q 1169 -91 856 284 
Q 544 659 544 1381 
z
M 1991 3584 
L 1991 3584 
z
" transform="scale(0.015625)"/>
       </defs>
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-4d" x="74.804688"/>
       <use xlink:href="#DejaVuSans-75" x="161.083984"/>
       <use xlink:href="#DejaVuSans-73" x="224.462891"/>
       <use xlink:href="#DejaVuSans-69" x="276.5625"/>
       <use xlink:href="#DejaVuSans-63" x="304.345703"/>
      </g>
     </g>
    </g>
    <g id="ytick_13">
     <g id="line2d_29">
      <path d="M 155.711875 319.493786 
L 985.745469 319.493786 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_21">
      <!-- r/DIY -->
      <g style="fill: #4d4d4d" transform="translate(124.300625 322.529099) scale(0.11 -0.11)">
       <defs>
        <path id="DejaVuSans-44" d="M 1259 4147 
L 1259 519 
L 2022 519 
Q 2988 519 3436 956 
Q 3884 1394 3884 2338 
Q 3884 3275 3436 3711 
Q 2988 4147 2022 4147 
L 1259 4147 
z
M 628 4666 
L 1925 4666 
Q 3281 4666 3915 4102 
Q 4550 3538 4550 2338 
Q 4550 1131 3912 565 
Q 3275 0 1925 0 
L 628 0 
L 628 4666 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-59" d="M -13 4666 
L 666 4666 
L 1959 2747 
L 3244 4666 
L 3922 4666 
L 2272 2222 
L 2272 0 
L 1638 0 
L 1638 2222 
L -13 4666 
z
" transform="scale(0.015625)"/>
       </defs>
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-44" x="74.804688"/>
       <use xlink:href="#DejaVuSans-49" x="151.806641"/>
       <use xlink:href="#DejaVuSans-59" x="181.298828"/>
      </g>
     </g>
    </g>
    <g id="ytick_14">
     <g id="line2d_30">
      <path d="M 155.711875 304.253065 
L 985.745469 304.253065 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_22">
      <!-- r/Futurology -->
      <g style="fill: #4d4d4d" transform="translate(84.472031 307.288378) scale(0.11 -0.11)">
       <defs>
        <path id="DejaVuSans-46" d="M 628 4666 
L 3309 4666 
L 3309 4134 
L 1259 4134 
L 1259 2759 
L 3109 2759 
L 3109 2228 
L 1259 2228 
L 1259 0 
L 628 0 
L 628 4666 
z
" transform="scale(0.015625)"/>
        <path id="DejaVuSans-79" d="M 2059 -325 
Q 1816 -950 1584 -1140 
Q 1353 -1331 966 -1331 
L 506 -1331 
L 506 -850 
L 844 -850 
Q 1081 -850 1212 -737 
Q 1344 -625 1503 -206 
L 1606 56 
L 191 3500 
L 800 3500 
L 1894 763 
L 2988 3500 
L 3597 3500 
L 2059 -325 
z
" transform="scale(0.015625)"/>
       </defs>
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-46" x="74.804688"/>
       <use xlink:href="#DejaVuSans-75" x="126.824219"/>
       <use xlink:href="#DejaVuSans-74" x="190.203125"/>
       <use xlink:href="#DejaVuSans-75" x="229.412109"/>
       <use xlink:href="#DejaVuSans-72" x="292.791016"/>
       <use xlink:href="#DejaVuSans-6f" x="331.654297"/>
       <use xlink:href="#DejaVuSans-6c" x="392.835938"/>
       <use xlink:href="#DejaVuSans-6f" x="420.619141"/>
       <use xlink:href="#DejaVuSans-67" x="481.800781"/>
       <use xlink:href="#DejaVuSans-79" x="545.277344"/>
      </g>
     </g>
    </g>
    <g id="ytick_15">
     <g id="line2d_31">
      <path d="M 155.711875 289.012344 
L 985.745469 289.012344 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_23">
      <!-- r/sports -->
      <g style="fill: #4d4d4d" transform="translate(108.725313 292.047656) scale(0.11 -0.11)">
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-73" x="74.804688"/>
       <use xlink:href="#DejaVuSans-70" x="126.904297"/>
       <use xlink:href="#DejaVuSans-6f" x="190.380859"/>
       <use xlink:href="#DejaVuSans-72" x="251.5625"/>
       <use xlink:href="#DejaVuSans-74" x="292.675781"/>
       <use xlink:href="#DejaVuSans-73" x="331.884766"/>
      </g>
     </g>
    </g>
    <g id="ytick_16">
     <g id="line2d_32">
      <path d="M 155.711875 273.771622 
L 985.745469 273.771622 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_24">
      <!-- r/tifu -->
      <g style="fill: #4d4d4d" transform="translate(124.522344 276.806935) scale(0.11 -0.11)">
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-74" x="74.804688"/>
       <use xlink:href="#DejaVuSans-69" x="114.013672"/>
       <use xlink:href="#DejaVuSans-66" x="141.796875"/>
       <use xlink:href="#DejaVuSans-75" x="177.001953"/>
      </g>
     </g>
    </g>
    <g id="ytick_17">
     <g id="line2d_33">
      <path d="M 155.711875 258.530901 
L 985.745469 258.530901 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_25">
      <!-- r/Showerthoughts -->
      <g style="fill: #4d4d4d" transform="translate(52.78 261.566214) scale(0.11 -0.11)">
       <defs>
        <path id="DejaVuSans-53" d="M 3425 4513 
L 3425 3897 
Q 3066 4069 2747 4153 
Q 2428 4238 2131 4238 
Q 1616 4238 1336 4038 
Q 1056 3838 1056 3469 
Q 1056 3159 1242 3001 
Q 1428 2844 1947 2747 
L 2328 2669 
Q 3034 2534 3370 2195 
Q 3706 1856 3706 1288 
Q 3706 609 3251 259 
Q 2797 -91 1919 -91 
Q 1588 -91 1214 -16 
Q 841 59 441 206 
L 441 856 
Q 825 641 1194 531 
Q 1563 422 1919 422 
Q 2459 422 2753 634 
Q 3047 847 3047 1241 
Q 3047 1584 2836 1778 
Q 2625 1972 2144 2069 
L 1759 2144 
Q 1053 2284 737 2584 
Q 422 2884 422 3419 
Q 422 4038 858 4394 
Q 1294 4750 2059 4750 
Q 2388 4750 2728 4690 
Q 3069 4631 3425 4513 
z
" transform="scale(0.015625)"/>
       </defs>
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-53" x="74.804688"/>
       <use xlink:href="#DejaVuSans-68" x="138.28125"/>
       <use xlink:href="#DejaVuSans-6f" x="201.660156"/>
       <use xlink:href="#DejaVuSans-77" x="262.841797"/>
       <use xlink:href="#DejaVuSans-65" x="344.628906"/>
       <use xlink:href="#DejaVuSans-72" x="406.152344"/>
       <use xlink:href="#DejaVuSans-74" x="447.265625"/>
       <use xlink:href="#DejaVuSans-68" x="486.474609"/>
       <use xlink:href="#DejaVuSans-6f" x="549.853516"/>
       <use xlink:href="#DejaVuSans-75" x="611.035156"/>
       <use xlink:href="#DejaVuSans-67" x="674.414062"/>
       <use xlink:href="#DejaVuSans-68" x="737.890625"/>
       <use xlink:href="#DejaVuSans-74" x="801.269531"/>
       <use xlink:href="#DejaVuSans-73" x="840.478516"/>
      </g>
     </g>
    </g>
    <g id="ytick_18">
     <g id="line2d_34">
      <path d="M 155.711875 243.29018 
L 985.745469 243.29018 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_26">
      <!-- r/movies -->
      <g style="fill: #4d4d4d" transform="translate(103.223594 246.325492) scale(0.11 -0.11)">
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-6d" x="74.804688"/>
       <use xlink:href="#DejaVuSans-6f" x="172.216797"/>
       <use xlink:href="#DejaVuSans-76" x="233.398438"/>
       <use xlink:href="#DejaVuSans-69" x="292.578125"/>
       <use xlink:href="#DejaVuSans-65" x="320.361328"/>
       <use xlink:href="#DejaVuSans-73" x="381.884766"/>
      </g>
     </g>
    </g>
    <g id="ytick_19">
     <g id="line2d_35">
      <path d="M 155.711875 228.049458 
L 985.745469 228.049458 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_27">
      <!-- r/gaming -->
      <g style="fill: #4d4d4d" transform="translate(101.284844 231.084771) scale(0.11 -0.11)">
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-67" x="74.804688"/>
       <use xlink:href="#DejaVuSans-61" x="138.28125"/>
       <use xlink:href="#DejaVuSans-6d" x="199.560547"/>
       <use xlink:href="#DejaVuSans-69" x="296.972656"/>
       <use xlink:href="#DejaVuSans-6e" x="324.755859"/>
       <use xlink:href="#DejaVuSans-67" x="388.134766"/>
      </g>
     </g>
    </g>
    <g id="ytick_20">
     <g id="line2d_36">
      <path d="M 155.711875 212.808737 
L 985.745469 212.808737 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_28">
      <!-- r/OldSchoolCool -->
      <g style="fill: #4d4d4d" transform="translate(63.317656 215.84405) scale(0.11 -0.11)">
       <defs>
        <path id="DejaVuSans-4f" d="M 2522 4238 
Q 1834 4238 1429 3725 
Q 1025 3213 1025 2328 
Q 1025 1447 1429 934 
Q 1834 422 2522 422 
Q 3209 422 3611 934 
Q 4013 1447 4013 2328 
Q 4013 3213 3611 3725 
Q 3209 4238 2522 4238 
z
M 2522 4750 
Q 3503 4750 4090 4092 
Q 4678 3434 4678 2328 
Q 4678 1225 4090 567 
Q 3503 -91 2522 -91 
Q 1538 -91 948 565 
Q 359 1222 359 2328 
Q 359 3434 948 4092 
Q 1538 4750 2522 4750 
z
" transform="scale(0.015625)"/>
       </defs>
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-4f" x="74.804688"/>
       <use xlink:href="#DejaVuSans-6c" x="153.515625"/>
       <use xlink:href="#DejaVuSans-64" x="181.298828"/>
       <use xlink:href="#DejaVuSans-53" x="244.775391"/>
       <use xlink:href="#DejaVuSans-63" x="308.251953"/>
       <use xlink:href="#DejaVuSans-68" x="363.232422"/>
       <use xlink:href="#DejaVuSans-6f" x="426.611328"/>
       <use xlink:href="#DejaVuSans-6f" x="487.792969"/>
       <use xlink:href="#DejaVuSans-6c" x="548.974609"/>
       <use xlink:href="#DejaVuSans-43" x="576.757812"/>
       <use xlink:href="#DejaVuSans-6f" x="646.582031"/>
       <use xlink:href="#DejaVuSans-6f" x="707.763672"/>
       <use xlink:href="#DejaVuSans-6c" x="768.945312"/>
      </g>
     </g>
    </g>
    <g id="ytick_21">
     <g id="line2d_37">
      <path d="M 155.711875 197.568016 
L 985.745469 197.568016 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_29">
      <!-- r/AskReddit -->
      <g style="fill: #4d4d4d" transform="translate(87.857969 200.603328) scale(0.11 -0.11)">
       <defs>
        <path id="DejaVuSans-52" d="M 2841 2188 
Q 3044 2119 3236 1894 
Q 3428 1669 3622 1275 
L 4263 0 
L 3584 0 
L 2988 1197 
Q 2756 1666 2539 1819 
Q 2322 1972 1947 1972 
L 1259 1972 
L 1259 0 
L 628 0 
L 628 4666 
L 2053 4666 
Q 2853 4666 3247 4331 
Q 3641 3997 3641 3322 
Q 3641 2881 3436 2590 
Q 3231 2300 2841 2188 
z
M 1259 4147 
L 1259 2491 
L 2053 2491 
Q 2509 2491 2742 2702 
Q 2975 2913 2975 3322 
Q 2975 3731 2742 3939 
Q 2509 4147 2053 4147 
L 1259 4147 
z
" transform="scale(0.015625)"/>
       </defs>
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-41" x="74.804688"/>
       <use xlink:href="#DejaVuSans-73" x="143.212891"/>
       <use xlink:href="#DejaVuSans-6b" x="195.3125"/>
       <use xlink:href="#DejaVuSans-52" x="253.222656"/>
       <use xlink:href="#DejaVuSans-65" x="318.205078"/>
       <use xlink:href="#DejaVuSans-64" x="379.728516"/>
       <use xlink:href="#DejaVuSans-64" x="443.205078"/>
       <use xlink:href="#DejaVuSans-69" x="506.681641"/>
       <use xlink:href="#DejaVuSans-74" x="534.464844"/>
      </g>
     </g>
    </g>
    <g id="ytick_22">
     <g id="line2d_38">
      <path d="M 155.711875 182.327295 
L 985.745469 182.327295 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_30">
      <!-- r/aww -->
      <g style="fill: #4d4d4d" transform="translate(118.001406 185.362607) scale(0.11 -0.11)">
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-61" x="74.804688"/>
       <use xlink:href="#DejaVuSans-77" x="136.083984"/>
       <use xlink:href="#DejaVuSans-77" x="217.871094"/>
      </g>
     </g>
    </g>
    <g id="ytick_23">
     <g id="line2d_39">
      <path d="M 155.711875 167.086573 
L 985.745469 167.086573 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_31">
      <!-- r/nottheonion -->
      <g style="fill: #4d4d4d" transform="translate(76.208281 170.121886) scale(0.11 -0.11)">
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-6e" x="74.804688"/>
       <use xlink:href="#DejaVuSans-6f" x="138.183594"/>
       <use xlink:href="#DejaVuSans-74" x="199.365234"/>
       <use xlink:href="#DejaVuSans-74" x="238.574219"/>
       <use xlink:href="#DejaVuSans-68" x="277.783203"/>
       <use xlink:href="#DejaVuSans-65" x="341.162109"/>
       <use xlink:href="#DejaVuSans-6f" x="402.685547"/>
       <use xlink:href="#DejaVuSans-6e" x="463.867188"/>
       <use xlink:href="#DejaVuSans-69" x="527.246094"/>
       <use xlink:href="#DejaVuSans-6f" x="555.029297"/>
       <use xlink:href="#DejaVuSans-6e" x="616.210938"/>
      </g>
     </g>
    </g>
    <g id="ytick_24">
     <g id="line2d_40">
      <path d="M 155.711875 151.845852 
L 985.745469 151.845852 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_32">
      <!-- r/mildlyinteresting -->
      <g style="fill: #4d4d4d" transform="translate(50.15375 154.881164) scale(0.11 -0.11)">
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-6d" x="74.804688"/>
       <use xlink:href="#DejaVuSans-69" x="172.216797"/>
       <use xlink:href="#DejaVuSans-6c" x="200"/>
       <use xlink:href="#DejaVuSans-64" x="227.783203"/>
       <use xlink:href="#DejaVuSans-6c" x="291.259766"/>
       <use xlink:href="#DejaVuSans-79" x="319.042969"/>
       <use xlink:href="#DejaVuSans-69" x="378.222656"/>
       <use xlink:href="#DejaVuSans-6e" x="406.005859"/>
       <use xlink:href="#DejaVuSans-74" x="469.384766"/>
       <use xlink:href="#DejaVuSans-65" x="508.59375"/>
       <use xlink:href="#DejaVuSans-72" x="570.117188"/>
       <use xlink:href="#DejaVuSans-65" x="608.980469"/>
       <use xlink:href="#DejaVuSans-73" x="670.503906"/>
       <use xlink:href="#DejaVuSans-74" x="722.603516"/>
       <use xlink:href="#DejaVuSans-69" x="761.8125"/>
       <use xlink:href="#DejaVuSans-6e" x="789.595703"/>
       <use xlink:href="#DejaVuSans-67" x="852.974609"/>
      </g>
     </g>
    </g>
    <g id="ytick_25">
     <g id="line2d_41">
      <path d="M 155.711875 136.605131 
L 985.745469 136.605131 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_33">
      <!-- r/news -->
      <g style="fill: #4d4d4d" transform="translate(114.268281 139.640443) scale(0.11 -0.11)">
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-6e" x="74.804688"/>
       <use xlink:href="#DejaVuSans-65" x="138.183594"/>
       <use xlink:href="#DejaVuSans-77" x="199.707031"/>
       <use xlink:href="#DejaVuSans-73" x="281.494141"/>
      </g>
     </g>
    </g>
    <g id="ytick_26">
     <g id="line2d_42">
      <path d="M 155.711875 121.364409 
L 985.745469 121.364409 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_34">
      <!-- r/funny -->
      <g style="fill: #4d4d4d" transform="translate(111.4375 124.399722) scale(0.11 -0.11)">
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-66" x="74.804688"/>
       <use xlink:href="#DejaVuSans-75" x="110.009766"/>
       <use xlink:href="#DejaVuSans-6e" x="173.388672"/>
       <use xlink:href="#DejaVuSans-6e" x="236.767578"/>
       <use xlink:href="#DejaVuSans-79" x="300.146484"/>
      </g>
     </g>
    </g>
    <g id="ytick_27">
     <g id="line2d_43">
      <path d="M 155.711875 106.123688 
L 985.745469 106.123688 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_35">
      <!-- r/todayilearned -->
      <g style="fill: #4d4d4d" transform="translate(66.782656 109.159) scale(0.11 -0.11)">
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-74" x="74.804688"/>
       <use xlink:href="#DejaVuSans-6f" x="114.013672"/>
       <use xlink:href="#DejaVuSans-64" x="175.195312"/>
       <use xlink:href="#DejaVuSans-61" x="238.671875"/>
       <use xlink:href="#DejaVuSans-79" x="299.951172"/>
       <use xlink:href="#DejaVuSans-69" x="359.130859"/>
       <use xlink:href="#DejaVuSans-6c" x="386.914062"/>
       <use xlink:href="#DejaVuSans-65" x="414.697266"/>
       <use xlink:href="#DejaVuSans-61" x="476.220703"/>
       <use xlink:href="#DejaVuSans-72" x="537.5"/>
       <use xlink:href="#DejaVuSans-6e" x="576.863281"/>
       <use xlink:href="#DejaVuSans-65" x="640.242188"/>
       <use xlink:href="#DejaVuSans-64" x="701.765625"/>
      </g>
     </g>
    </g>
    <g id="ytick_28">
     <g id="line2d_44">
      <path d="M 155.711875 90.882967 
L 985.745469 90.882967 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_36">
      <!-- r/pics -->
      <g style="fill: #4d4d4d" transform="translate(120.916406 93.918279) scale(0.11 -0.11)">
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-70" x="74.804688"/>
       <use xlink:href="#DejaVuSans-69" x="138.28125"/>
       <use xlink:href="#DejaVuSans-63" x="166.064453"/>
       <use xlink:href="#DejaVuSans-73" x="221.044922"/>
      </g>
     </g>
    </g>
    <g id="ytick_29">
     <g id="line2d_45">
      <path d="M 155.711875 75.642245 
L 985.745469 75.642245 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke: #e5e5e5; stroke-width: 0.8"/>
     </g>
     <g id="text_37">
      <!-- r/worldnews -->
      <g style="fill: #4d4d4d" transform="translate(83.980469 78.677558) scale(0.11 -0.11)">
       <use xlink:href="#DejaVuSans-72"/>
       <use xlink:href="#DejaVuSans-2f" x="41.113281"/>
       <use xlink:href="#DejaVuSans-77" x="74.804688"/>
       <use xlink:href="#DejaVuSans-6f" x="156.591797"/>
       <use xlink:href="#DejaVuSans-72" x="217.773438"/>
       <use xlink:href="#DejaVuSans-6c" x="258.886719"/>
       <use xlink:href="#DejaVuSans-64" x="286.669922"/>
       <use xlink:href="#DejaVuSans-6e" x="350.146484"/>
       <use xlink:href="#DejaVuSans-65" x="413.525391"/>
       <use xlink:href="#DejaVuSans-77" x="475.048828"/>
       <use xlink:href="#DejaVuSans-73" x="556.835938"/>
      </g>
     </g>
    </g>
   </g>
   <g id="PathCollection_1">
    <path d="M 364.699936 97.415801 
C 366.432464 97.415801 368.094265 96.72746 369.319347 95.502378 
C 370.54443 94.277296 371.23277 92.615494 371.23277 90.882967 
C 371.23277 89.150439 370.54443 87.488637 369.319347 86.263555 
C 368.094265 85.038473 366.432464 84.350132 364.699936 84.350132 
C 362.967408 84.350132 361.305607 85.038473 360.080525 86.263555 
C 358.855443 87.488637 358.167102 89.150439 358.167102 90.882967 
C 358.167102 92.615494 358.855443 94.277296 360.080525 95.502378 
C 361.305607 96.72746 362.967408 97.415801 364.699936 97.415801 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481b6d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 219.964088 128.632228 
C 221.891536 128.632228 223.740301 127.866445 225.103212 126.503534 
C 226.466124 125.140622 227.231907 123.291857 227.231907 121.364409 
C 227.231907 119.436961 226.466124 117.588197 225.103212 116.225285 
C 223.740301 114.862373 221.891536 114.09659 219.964088 114.09659 
C 218.03664 114.09659 216.187875 114.862373 214.824964 116.225285 
C 213.462052 117.588197 212.696269 119.436961 212.696269 121.364409 
C 212.696269 123.291857 213.462052 125.140622 214.824964 126.503534 
C 216.187875 127.866445 218.03664 128.632228 219.964088 128.632228 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482475; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 815.626299 97.873851 
C 817.480303 97.873851 819.258621 97.137248 820.5696 95.826269 
C 821.88058 94.51529 822.617183 92.736971 822.617183 90.882967 
C 822.617183 89.028962 821.88058 87.250644 820.5696 85.939665 
C 819.258621 84.628686 817.480303 83.892082 815.626299 83.892082 
C 813.772294 83.892082 811.993976 84.628686 810.682997 85.939665 
C 809.372018 87.250644 808.635414 89.028962 808.635414 90.882967 
C 808.635414 92.736971 809.372018 94.51529 810.682997 95.826269 
C 811.993976 97.137248 813.772294 97.873851 815.626299 97.873851 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482071; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 778.174257 127.825003 
C 779.887626 127.825003 781.531051 127.144274 782.742586 125.932739 
C 783.954121 124.721204 784.63485 123.077779 784.63485 121.364409 
C 784.63485 119.65104 783.954121 118.007615 782.742586 116.79608 
C 781.531051 115.584544 779.887626 114.903816 778.174257 114.903816 
C 776.460887 114.903816 774.817462 115.584544 773.605927 116.79608 
C 772.394392 118.007615 771.713663 119.65104 771.713663 121.364409 
C 771.713663 123.077779 772.394392 124.721204 773.605927 125.932739 
C 774.817462 127.144274 776.460887 127.825003 778.174257 127.825003 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481b6d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 338.837719 99.582389 
C 341.144833 99.582389 343.357764 98.665763 344.989139 97.034387 
C 346.620515 95.403011 347.537141 93.19008 347.537141 90.882967 
C 347.537141 88.575853 346.620515 86.362922 344.989139 84.731546 
C 343.357764 83.10017 341.144833 82.183544 338.837719 82.183544 
C 336.530605 82.183544 334.317674 83.10017 332.686299 84.731546 
C 331.054923 86.362922 330.138297 88.575853 330.138297 90.882967 
C 330.138297 93.19008 331.054923 95.403011 332.686299 97.034387 
C 334.317674 98.665763 336.530605 99.582389 338.837719 99.582389 
z
" clip-path="url(#p8a32aafd77)" style="fill: #443983; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 257.13276 129.051496 
C 259.171399 129.051496 261.126816 128.241536 262.568352 126.800001 
C 264.009887 125.358465 264.819847 123.403049 264.819847 121.364409 
C 264.819847 119.32577 264.009887 117.370353 262.568352 115.928818 
C 261.126816 114.487282 259.171399 113.677322 257.13276 113.677322 
C 255.094121 113.677322 253.138704 114.487282 251.697169 115.928818 
C 250.255633 117.370353 249.445673 119.32577 249.445673 121.364409 
C 249.445673 123.403049 250.255633 125.358465 251.697169 126.800001 
C 253.138704 128.241536 255.094121 129.051496 257.13276 129.051496 
z
" clip-path="url(#p8a32aafd77)" style="fill: #472a7a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 328.91033 112.654134 
C 330.642225 112.654134 332.303418 111.966045 333.528053 110.74141 
C 334.752687 109.516776 335.440776 107.855582 335.440776 106.123688 
C 335.440776 104.391794 334.752687 102.7306 333.528053 101.505966 
C 332.303418 100.281331 330.642225 99.593242 328.91033 99.593242 
C 327.178436 99.593242 325.517242 100.281331 324.292608 101.505966 
C 323.067974 102.7306 322.379885 104.391794 322.379885 106.123688 
C 322.379885 107.855582 323.067974 109.516776 324.292608 110.74141 
C 325.517242 111.966045 327.178436 112.654134 328.91033 112.654134 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481b6d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 374.891803 161.528107 
C 377.459567 161.528107 379.922508 160.507924 381.738192 158.69224 
C 383.553875 156.876557 384.574059 154.413616 384.574059 151.845852 
C 384.574059 149.278088 383.553875 146.815147 381.738192 144.999463 
C 379.922508 143.18378 377.459567 142.163596 374.891803 142.163596 
C 372.324039 142.163596 369.861098 143.18378 368.045415 144.999463 
C 366.229731 146.815147 365.209548 149.278088 365.209548 151.845852 
C 365.209548 154.413616 366.229731 156.876557 368.045415 158.69224 
C 369.861098 160.507924 372.324039 161.528107 374.891803 161.528107 
z
" clip-path="url(#p8a32aafd77)" style="fill: #3e4989; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 424.160366 97.051829 
C 425.796367 97.051829 427.365583 96.401839 428.52241 95.245011 
C 429.679238 94.088184 430.329229 92.518968 430.329229 90.882967 
C 430.329229 89.246965 429.679238 87.67775 428.52241 86.520922 
C 427.365583 85.364094 425.796367 84.714104 424.160366 84.714104 
C 422.524364 84.714104 420.955149 85.364094 419.798321 86.520922 
C 418.641493 87.67775 417.991503 89.246965 417.991503 90.882967 
C 417.991503 92.518968 418.641493 94.088184 419.798321 95.245011 
C 420.955149 96.401839 422.524364 97.051829 424.160366 97.051829 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481769; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 363.150848 96.051748 
C 364.521625 96.051748 365.836442 95.507132 366.805728 94.537847 
C 367.775013 93.568561 368.319629 92.253743 368.319629 90.882967 
C 368.319629 89.51219 367.775013 88.197372 366.805728 87.228087 
C 365.836442 86.258801 364.521625 85.714186 363.150848 85.714186 
C 361.780071 85.714186 360.465253 86.258801 359.495968 87.228087 
C 358.526682 88.197372 357.982067 89.51219 357.982067 90.882967 
C 357.982067 92.253743 358.526682 93.568561 359.495968 94.537847 
C 360.465253 95.507132 361.780071 96.051748 363.150848 96.051748 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 258.587392 143.384065 
C 260.385186 143.384065 262.109589 142.669793 263.380822 141.398561 
C 264.652054 140.127328 265.366326 138.402925 265.366326 136.605131 
C 265.366326 134.807336 264.652054 133.082933 263.380822 131.8117 
C 262.109589 130.540468 260.385186 129.826197 258.587392 129.826197 
C 256.789597 129.826197 255.065194 130.540468 253.793962 131.8117 
C 252.522729 133.082933 251.808458 134.807336 251.808458 136.605131 
C 251.808458 138.402925 252.522729 140.127328 253.793962 141.398561 
C 255.065194 142.669793 256.789597 143.384065 258.587392 143.384065 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481d6f; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 870.477246 98.219693 
C 872.422969 98.219693 874.289261 97.446649 875.665095 96.070815 
C 877.040928 94.694982 877.813972 92.828689 877.813972 90.882967 
C 877.813972 88.937244 877.040928 87.070951 875.665095 85.695118 
C 874.289261 84.319284 872.422969 83.546241 870.477246 83.546241 
C 868.531524 83.546241 866.665231 84.319284 865.289397 85.695118 
C 863.913564 87.070951 863.14052 88.937244 863.14052 90.882967 
C 863.14052 92.828689 863.913564 94.694982 865.289397 96.070815 
C 866.665231 97.446649 868.531524 98.219693 870.477246 98.219693 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482576; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 449.663648 98.219693 
C 451.60937 98.219693 453.475663 97.446649 454.851496 96.070815 
C 456.22733 94.694982 457.000374 92.828689 457.000374 90.882967 
C 457.000374 88.937244 456.22733 87.070951 454.851496 85.695118 
C 453.475663 84.319284 451.60937 83.546241 449.663648 83.546241 
C 447.717925 83.546241 445.851633 84.319284 444.475799 85.695118 
C 443.099965 87.070951 442.326922 88.937244 442.326922 90.882967 
C 442.326922 92.828689 443.099965 94.694982 444.475799 96.070815 
C 445.851633 97.446649 447.717925 98.219693 449.663648 98.219693 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482576; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 326.284437 251.928899 
C 328.575452 251.928899 330.772942 251.018669 332.392934 249.398677 
C 334.012926 247.778685 334.923156 245.581195 334.923156 243.29018 
C 334.923156 240.999165 334.012926 238.801675 332.392934 237.181683 
C 330.772942 235.56169 328.575452 234.65146 326.284437 234.65146 
C 323.993422 234.65146 321.795932 235.56169 320.17594 237.181683 
C 318.555947 238.801675 317.645717 240.999165 317.645717 243.29018 
C 317.645717 245.581195 318.555947 247.778685 320.17594 249.398677 
C 321.795932 251.018669 323.993422 251.928899 326.284437 251.928899 
z
" clip-path="url(#p8a32aafd77)" style="fill: #453882; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 220.502491 81.459035 
C 222.045121 81.459035 223.524778 80.846142 224.615582 79.755337 
C 225.706387 78.664532 226.319281 77.184876 226.319281 75.642245 
C 226.319281 74.099615 225.706387 72.619958 224.615582 71.529154 
C 223.524778 70.438349 222.045121 69.825455 220.502491 69.825455 
C 218.95986 69.825455 217.480204 70.438349 216.389399 71.529154 
C 215.298594 72.619958 214.6857 74.099615 214.6857 75.642245 
C 214.6857 77.184876 215.298594 78.664532 216.389399 79.755337 
C 217.480204 80.846142 218.95986 81.459035 220.502491 81.459035 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481467; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 587.334142 142.967446 
C 589.021448 142.967446 590.639873 142.297073 591.832979 141.103967 
C 593.026084 139.910862 593.696458 138.292436 593.696458 136.605131 
C 593.696458 134.917825 593.026084 133.299399 591.832979 132.106294 
C 590.639873 130.913188 589.021448 130.242815 587.334142 130.242815 
C 585.646836 130.242815 584.028411 130.913188 582.835305 132.106294 
C 581.6422 133.299399 580.971826 134.917825 580.971826 136.605131 
C 580.971826 138.292436 581.6422 139.910862 582.835305 141.103967 
C 584.028411 142.297073 585.646836 142.967446 587.334142 142.967446 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481a6c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 290.570396 81.855193 
C 292.21809 81.855193 293.798519 81.200558 294.963614 80.035463 
C 296.128709 78.870368 296.783345 77.289938 296.783345 75.642245 
C 296.783345 73.994552 296.128709 72.414122 294.963614 71.249028 
C 293.798519 70.083933 292.21809 69.429297 290.570396 69.429297 
C 288.922703 69.429297 287.342274 70.083933 286.177179 71.249028 
C 285.012084 72.414122 284.357448 73.994552 284.357448 75.642245 
C 284.357448 77.289938 285.012084 78.870368 286.177179 80.035463 
C 287.342274 81.200558 288.922703 81.855193 290.570396 81.855193 
z
" clip-path="url(#p8a32aafd77)" style="fill: #48186a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 607.991801 111.553238 
C 609.431734 111.553238 610.812885 110.981146 611.831072 109.96296 
C 612.849259 108.944773 613.421351 107.563621 613.421351 106.123688 
C 613.421351 104.683754 612.849259 103.302603 611.831072 102.284416 
C 610.812885 101.26623 609.431734 100.694138 607.991801 100.694138 
C 606.551867 100.694138 605.170716 101.26623 604.152529 102.284416 
C 603.134342 103.302603 602.562251 104.683754 602.562251 106.123688 
C 602.562251 107.563621 603.134342 108.944773 604.152529 109.96296 
C 605.170716 110.981146 606.551867 111.553238 607.991801 111.553238 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471063; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 541.28655 176.144931 
C 543.688854 176.144931 545.99309 175.190485 547.691776 173.491799 
C 549.390462 171.793114 550.344907 169.488878 550.344907 167.086573 
C 550.344907 164.684269 549.390462 162.380033 547.691776 160.681347 
C 545.99309 158.982661 543.688854 158.028215 541.28655 158.028215 
C 538.884245 158.028215 536.580009 158.982661 534.881323 160.681347 
C 533.182638 162.380033 532.228192 164.684269 532.228192 167.086573 
C 532.228192 169.488878 533.182638 171.793114 534.881323 173.491799 
C 536.580009 175.190485 538.884245 176.144931 541.28655 176.144931 
z
" clip-path="url(#p8a32aafd77)" style="fill: #423f85; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 374.410075 82.729308 
C 376.289586 82.729308 378.09237 81.982571 379.421385 80.653556 
C 380.7504 79.324541 381.497138 77.521756 381.497138 75.642245 
C 381.497138 73.762734 380.7504 71.95995 379.421385 70.630935 
C 378.09237 69.30192 376.289586 68.555182 374.410075 68.555182 
C 372.530563 68.555182 370.727779 69.30192 369.398764 70.630935 
C 368.069749 71.95995 367.323011 73.762734 367.323011 75.642245 
C 367.323011 77.521756 368.069749 79.324541 369.398764 80.653556 
C 370.727779 81.982571 372.530563 82.729308 374.410075 82.729308 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482173; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 434.134983 325.401045 
C 435.701606 325.401045 437.204275 324.778619 438.312045 323.670849 
C 439.419815 322.563079 440.042242 321.06041 440.042242 319.493786 
C 440.042242 317.927163 439.419815 316.424494 438.312045 315.316724 
C 437.204275 314.208954 435.701606 313.586528 434.134983 313.586528 
C 432.568359 313.586528 431.06569 314.208954 429.95792 315.316724 
C 428.85015 316.424494 428.227724 317.927163 428.227724 319.493786 
C 428.227724 321.06041 428.85015 322.563079 429.95792 323.670849 
C 431.06569 324.778619 432.568359 325.401045 434.134983 325.401045 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481467; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 380.729221 110.132696 
C 381.792422 110.132696 382.812221 109.710281 383.564018 108.958485 
C 384.315815 108.206688 384.738229 107.186889 384.738229 106.123688 
C 384.738229 105.060487 384.315815 104.040688 383.564018 103.288891 
C 382.812221 102.537094 381.792422 102.11468 380.729221 102.11468 
C 379.66602 102.11468 378.646221 102.537094 377.894424 103.288891 
C 377.142628 104.040688 376.720213 105.060487 376.720213 106.123688 
C 376.720213 107.186889 377.142628 108.206688 377.894424 108.958485 
C 378.646221 109.710281 379.66602 110.132696 380.729221 110.132696 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 768.473564 157.217138 
C 769.898045 157.217138 771.264376 156.651185 772.271636 155.643924 
C 773.278897 154.636664 773.84485 153.270334 773.84485 151.845852 
C 773.84485 150.42137 773.278897 149.05504 772.271636 148.047779 
C 771.264376 147.040519 769.898045 146.474566 768.473564 146.474566 
C 767.049082 146.474566 765.682752 147.040519 764.675491 148.047779 
C 763.668231 149.05504 763.102278 150.42137 763.102278 151.845852 
C 763.102278 153.270334 763.668231 154.636664 764.675491 155.643924 
C 765.682752 156.651185 767.049082 157.217138 768.473564 157.217138 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471063; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 246.978676 103.408067 
C 250.300371 103.408067 253.486466 102.088344 255.835259 99.73955 
C 258.184053 97.390757 259.503776 94.204662 259.503776 90.882967 
C 259.503776 87.561271 258.184053 84.375176 255.835259 82.026383 
C 253.486466 79.67759 250.300371 78.357866 246.978676 78.357866 
C 243.65698 78.357866 240.470885 79.67759 238.122092 82.026383 
C 235.773298 84.375176 234.453575 87.561271 234.453575 90.882967 
C 234.453575 94.204662 235.773298 97.390757 238.122092 99.73955 
C 240.470885 102.088344 243.65698 103.408067 246.978676 103.408067 
z
" clip-path="url(#p8a32aafd77)" style="fill: #287c8e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 522.234653 186.794985 
C 523.419499 186.794985 524.555976 186.324241 525.393788 185.486429 
C 526.2316 184.648617 526.702344 183.51214 526.702344 182.327295 
C 526.702344 181.142449 526.2316 180.005972 525.393788 179.16816 
C 524.555976 178.330348 523.419499 177.859604 522.234653 177.859604 
C 521.049808 177.859604 519.913331 178.330348 519.075519 179.16816 
C 518.237707 180.005972 517.766963 181.142449 517.766963 182.327295 
C 517.766963 183.51214 518.237707 184.648617 519.075519 185.486429 
C 519.913331 186.324241 521.049808 186.794985 522.234653 186.794985 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 369.753364 112.438496 
C 371.428071 112.438496 373.034412 111.773128 374.218608 110.588932 
C 375.402805 109.404735 376.068173 107.798395 376.068173 106.123688 
C 376.068173 104.448981 375.402805 102.842641 374.218608 101.658444 
C 373.034412 100.474247 371.428071 99.808879 369.753364 99.808879 
C 368.078657 99.808879 366.472317 100.474247 365.28812 101.658444 
C 364.103924 102.842641 363.438556 104.448981 363.438556 106.123688 
C 363.438556 107.798395 364.103924 109.404735 365.28812 110.588932 
C 366.472317 111.773128 368.078657 112.438496 369.753364 112.438496 
z
" clip-path="url(#p8a32aafd77)" style="fill: #48186a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 271.055663 112.958754 
C 272.868344 112.958754 274.607026 112.238568 275.888784 110.956809 
C 277.170543 109.675051 277.890729 107.936369 277.890729 106.123688 
C 277.890729 104.311007 277.170543 102.572325 275.888784 101.290566 
C 274.607026 100.008808 272.868344 99.288622 271.055663 99.288622 
C 269.242982 99.288622 267.5043 100.008808 266.222541 101.290566 
C 264.940783 102.572325 264.220597 104.311007 264.220597 106.123688 
C 264.220597 107.936369 264.940783 109.675051 266.222541 110.956809 
C 267.5043 112.238568 269.242982 112.958754 271.055663 112.958754 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481f70; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 378.112773 185.626944 
C 378.98785 185.626944 379.827205 185.279272 380.445978 184.660499 
C 381.064751 184.041726 381.412423 183.202372 381.412423 182.327295 
C 381.412423 181.452217 381.064751 180.612863 380.445978 179.99409 
C 379.827205 179.375317 378.98785 179.027645 378.112773 179.027645 
C 377.237696 179.027645 376.398342 179.375317 375.779569 179.99409 
C 375.160796 180.612863 374.813124 181.452217 374.813124 182.327295 
C 374.813124 183.202372 375.160796 184.041726 375.779569 184.660499 
C 376.398342 185.279272 377.237696 185.626944 378.112773 185.626944 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 229.409748 187.186637 
C 230.698461 187.186637 231.934565 186.674626 232.845822 185.763369 
C 233.75708 184.852111 234.26909 183.616007 234.26909 182.327295 
C 234.26909 181.038582 233.75708 179.802478 232.845822 178.89122 
C 231.934565 177.979963 230.698461 177.467952 229.409748 177.467952 
C 228.121035 177.467952 226.884931 177.979963 225.973674 178.89122 
C 225.062416 179.802478 224.550405 181.038582 224.550405 182.327295 
C 224.550405 183.616007 225.062416 184.852111 225.973674 185.763369 
C 226.884931 186.674626 228.121035 187.186637 229.409748 187.186637 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460b5e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 476.687681 155.13595 
C 477.560225 155.13595 478.397149 154.789284 479.014131 154.172302 
C 479.631113 153.55532 479.977779 152.718396 479.977779 151.845852 
C 479.977779 150.973308 479.631113 150.136383 479.014131 149.519402 
C 478.397149 148.90242 477.560225 148.555754 476.687681 148.555754 
C 475.815137 148.555754 474.978212 148.90242 474.361231 149.519402 
C 473.744249 150.136383 473.397583 150.973308 473.397583 151.845852 
C 473.397583 152.718396 473.744249 153.55532 474.361231 154.172302 
C 474.978212 154.789284 475.815137 155.13595 476.687681 155.13595 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 332.121855 172.007586 
C 333.426923 172.007586 334.678714 171.489077 335.601537 170.566255 
C 336.524359 169.643433 337.042868 168.391641 337.042868 167.086573 
C 337.042868 165.781505 336.524359 164.529714 335.601537 163.606891 
C 334.678714 162.684069 333.426923 162.16556 332.121855 162.16556 
C 330.816787 162.16556 329.564995 162.684069 328.642173 163.606891 
C 327.719351 164.529714 327.200842 165.781505 327.200842 167.086573 
C 327.200842 168.391641 327.719351 169.643433 328.642173 170.566255 
C 329.564995 171.489077 330.816787 172.007586 332.121855 172.007586 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460b5e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 527.845375 80.890252 
C 529.237163 80.890252 530.572134 80.337289 531.556277 79.353146 
C 532.540419 78.369004 533.093382 77.034033 533.093382 75.642245 
C 533.093382 74.250458 532.540419 72.915487 531.556277 71.931344 
C 530.572134 70.947202 529.237163 70.394239 527.845375 70.394239 
C 526.453588 70.394239 525.118617 70.947202 524.134474 71.931344 
C 523.150332 72.915487 522.597369 74.250458 522.597369 75.642245 
C 522.597369 77.034033 523.150332 78.369004 524.134474 79.353146 
C 525.118617 80.337289 526.453588 80.890252 527.845375 80.890252 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470e61; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 208.884329 81.729425 
C 210.498668 81.729425 212.047105 81.088041 213.188615 79.946531 
C 214.330125 78.805021 214.971509 77.256584 214.971509 75.642245 
C 214.971509 74.027906 214.330125 72.479469 213.188615 71.337959 
C 212.047105 70.196449 210.498668 69.555066 208.884329 69.555066 
C 207.26999 69.555066 205.721553 70.196449 204.580043 71.337959 
C 203.438533 72.479469 202.797149 74.027906 202.797149 75.642245 
C 202.797149 77.256584 203.438533 78.805021 204.580043 79.946531 
C 205.721553 81.088041 207.26999 81.729425 208.884329 81.729425 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481769; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 515.924953 110.178106 
C 517.000197 110.178106 518.031547 109.750907 518.791859 108.990595 
C 519.552172 108.230282 519.979371 107.198932 519.979371 106.123688 
C 519.979371 105.048444 519.552172 104.017094 518.791859 103.256781 
C 518.031547 102.496468 517.000197 102.069269 515.924953 102.069269 
C 514.849708 102.069269 513.818358 102.496468 513.058046 103.256781 
C 512.297733 104.017094 511.870534 105.048444 511.870534 106.123688 
C 511.870534 107.198932 512.297733 108.230282 513.058046 108.990595 
C 513.818358 109.750907 514.849708 110.178106 515.924953 110.178106 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 383.487354 110.568374 
C 384.666098 110.568374 385.796723 110.100054 386.630221 109.266556 
C 387.46372 108.433057 387.93204 107.302432 387.93204 106.123688 
C 387.93204 104.944943 387.46372 103.814319 386.630221 102.98082 
C 385.796723 102.147322 384.666098 101.679002 383.487354 101.679002 
C 382.308609 101.679002 381.177984 102.147322 380.344486 102.98082 
C 379.510988 103.814319 379.042668 104.944943 379.042668 106.123688 
C 379.042668 107.302432 379.510988 108.433057 380.344486 109.266556 
C 381.177984 110.100054 382.308609 110.568374 383.487354 110.568374 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 688.714411 110.609615 
C 689.904093 110.609615 691.045208 110.136949 691.88644 109.295717 
C 692.727672 108.454485 693.200338 107.31337 693.200338 106.123688 
C 693.200338 104.934006 692.727672 103.792891 691.88644 102.951658 
C 691.045208 102.110426 689.904093 101.637761 688.714411 101.637761 
C 687.524729 101.637761 686.383613 102.110426 685.542381 102.951658 
C 684.701149 103.792891 684.228484 104.934006 684.228484 106.123688 
C 684.228484 107.31337 684.701149 108.454485 685.542381 109.295717 
C 686.383613 110.136949 687.524729 110.609615 688.714411 110.609615 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 424.689323 215.735668 
C 429.50744 215.735668 434.128869 213.821409 437.535793 210.414486 
C 440.942716 207.007562 442.856975 202.386133 442.856975 197.568016 
C 442.856975 192.749898 440.942716 188.12847 437.535793 184.721546 
C 434.128869 181.314622 429.50744 179.400364 424.689323 179.400364 
C 419.871205 179.400364 415.249776 181.314622 411.842853 184.721546 
C 408.435929 188.12847 406.521671 192.749898 406.521671 197.568016 
C 406.521671 202.386133 408.435929 207.007562 411.842853 210.414486 
C 415.249776 213.821409 419.871205 215.735668 424.689323 215.735668 
z
" clip-path="url(#p8a32aafd77)" style="fill: #fde725; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 486.48283 141.476145 
C 487.774639 141.476145 489.013712 140.962905 489.927158 140.049458 
C 490.840604 139.136012 491.353845 137.896939 491.353845 136.605131 
C 491.353845 135.313322 490.840604 134.074249 489.927158 133.160803 
C 489.013712 132.247357 487.774639 131.734116 486.48283 131.734116 
C 485.191022 131.734116 483.951949 132.247357 483.038503 133.160803 
C 482.125056 134.074249 481.611816 135.313322 481.611816 136.605131 
C 481.611816 137.896939 482.125056 139.136012 483.038503 140.049458 
C 483.951949 140.962905 485.191022 141.476145 486.48283 141.476145 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460b5e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 839.117655 263.039419 
C 840.313328 263.039419 841.46019 262.564373 842.305659 261.718905 
C 843.151127 260.873436 843.626173 259.726574 843.626173 258.530901 
C 843.626173 257.335228 843.151127 256.188366 842.305659 255.342897 
C 841.46019 254.497429 840.313328 254.022383 839.117655 254.022383 
C 837.921982 254.022383 836.77512 254.497429 835.929651 255.342897 
C 835.084183 256.188366 834.609137 257.335228 834.609137 258.530901 
C 834.609137 259.726574 835.084183 260.873436 835.929651 261.718905 
C 836.77512 262.564373 837.921982 263.039419 839.117655 263.039419 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 207.080208 210.173797 
C 210.4233 210.173797 213.629918 208.845573 215.993841 206.481649 
C 218.357764 204.117726 219.685989 200.911108 219.685989 197.568016 
C 219.685989 194.224924 218.357764 191.018306 215.993841 188.654382 
C 213.629918 186.290459 210.4233 184.962234 207.080208 184.962234 
C 203.737115 184.962234 200.530498 186.290459 198.166574 188.654382 
C 195.802651 191.018306 194.474426 194.224924 194.474426 197.568016 
C 194.474426 200.911108 195.802651 204.117726 198.166574 206.481649 
C 200.530498 208.845573 203.737115 210.173797 207.080208 210.173797 
z
" clip-path="url(#p8a32aafd77)" style="fill: #277e8e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 251.512592 141.969876 
C 252.935339 141.969876 254.300006 141.404612 255.30604 140.398578 
C 256.312074 139.392544 256.877338 138.027878 256.877338 136.605131 
C 256.877338 135.182383 256.312074 133.817717 255.30604 132.811683 
C 254.300006 131.805649 252.935339 131.240385 251.512592 131.240385 
C 250.089845 131.240385 248.725179 131.805649 247.719145 132.811683 
C 246.71311 133.817717 246.147847 135.182383 246.147847 136.605131 
C 246.147847 138.027878 246.71311 139.392544 247.719145 140.398578 
C 248.725179 141.404612 250.089845 141.969876 251.512592 141.969876 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470e61; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 377.536588 250.136391 
C 379.352224 250.136391 381.093741 249.415031 382.37759 248.131182 
C 383.661439 246.847333 384.382799 245.105816 384.382799 243.29018 
C 384.382799 241.474543 383.661439 239.733026 382.37759 238.449178 
C 381.093741 237.165329 379.352224 236.443969 377.536588 236.443969 
C 375.720952 236.443969 373.979435 237.165329 372.695586 238.449178 
C 371.411737 239.733026 370.690377 241.474543 370.690377 243.29018 
C 370.690377 245.105816 371.411737 246.847333 372.695586 248.131182 
C 373.979435 249.415031 375.720952 250.136391 377.536588 250.136391 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481f70; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 625.419043 80.786489 
C 626.783313 80.786489 628.091889 80.244459 629.056573 79.279775 
C 630.021257 78.315091 630.563287 77.006515 630.563287 75.642245 
C 630.563287 74.277976 630.021257 72.9694 629.056573 72.004716 
C 628.091889 71.040032 626.783313 70.498002 625.419043 70.498002 
C 624.054774 70.498002 622.746198 71.040032 621.781514 72.004716 
C 620.81683 72.9694 620.2748 74.277976 620.2748 75.642245 
C 620.2748 77.006515 620.81683 78.315091 621.781514 79.279775 
C 622.746198 80.244459 624.054774 80.786489 625.419043 80.786489 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 353.931884 263.696189 
C 355.301734 263.696189 356.615663 263.151942 357.584294 262.183311 
C 358.552924 261.214681 359.097172 259.900752 359.097172 258.530901 
C 359.097172 257.161051 358.552924 255.847121 357.584294 254.878491 
C 356.615663 253.90986 355.301734 253.365613 353.931884 253.365613 
C 352.562033 253.365613 351.248104 253.90986 350.279473 254.878491 
C 349.310843 255.847121 348.766596 257.161051 348.766596 258.530901 
C 348.766596 259.900752 349.310843 261.214681 350.279473 262.183311 
C 351.248104 263.151942 352.562033 263.696189 353.931884 263.696189 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 425.397747 127.149571 
C 426.93199 127.149571 428.403601 126.54001 429.488475 125.455137 
C 430.573348 124.370263 431.182909 122.898652 431.182909 121.364409 
C 431.182909 119.830166 430.573348 118.358555 429.488475 117.273682 
C 428.403601 116.188808 426.93199 115.579247 425.397747 115.579247 
C 423.863504 115.579247 422.391893 116.188808 421.30702 117.273682 
C 420.222146 118.358555 419.612585 119.830166 419.612585 121.364409 
C 419.612585 122.898652 420.222146 124.370263 421.30702 125.455137 
C 422.391893 126.54001 423.863504 127.149571 425.397747 127.149571 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471365; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 294.726487 109.963792 
C 295.744894 109.963792 296.721728 109.559175 297.441851 108.839052 
C 298.161974 108.118929 298.566591 107.142096 298.566591 106.123688 
C 298.566591 105.10528 298.161974 104.128447 297.441851 103.408324 
C 296.721728 102.688201 295.744894 102.283583 294.726487 102.283583 
C 293.708079 102.283583 292.731246 102.688201 292.011123 103.408324 
C 291.291 104.128447 290.886382 105.10528 290.886382 106.123688 
C 290.886382 107.142096 291.291 108.118929 292.011123 108.839052 
C 292.731246 109.559175 293.708079 109.963792 294.726487 109.963792 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 418.823568 308.636796 
C 419.986147 308.636796 421.101266 308.174899 421.923334 307.352831 
C 422.745401 306.530764 423.207299 305.415644 423.207299 304.253065 
C 423.207299 303.090486 422.745401 301.975367 421.923334 301.153299 
C 421.101266 300.331231 419.986147 299.869334 418.823568 299.869334 
C 417.660989 299.869334 416.545869 300.331231 415.723802 301.153299 
C 414.901734 301.975367 414.439837 303.090486 414.439837 304.253065 
C 414.439837 305.415644 414.901734 306.530764 415.723802 307.352831 
C 416.545869 308.174899 417.660989 308.636796 418.823568 308.636796 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 232.234 125.841237 
C 233.421269 125.841237 234.56007 125.36953 235.399595 124.530004 
C 236.239121 123.690479 236.710828 122.551678 236.710828 121.364409 
C 236.710828 120.177141 236.239121 119.03834 235.399595 118.198814 
C 234.56007 117.359289 233.421269 116.887582 232.234 116.887582 
C 231.046732 116.887582 229.907931 117.359289 229.068405 118.198814 
C 228.22888 119.03834 227.757173 120.177141 227.757173 121.364409 
C 227.757173 122.551678 228.22888 123.690479 229.068405 124.530004 
C 229.907931 125.36953 231.046732 125.841237 232.234 125.841237 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 427.608032 207.562672 
C 430.258645 207.562672 432.801054 206.509572 434.675321 204.635305 
C 436.549588 202.761038 437.602688 200.21863 437.602688 197.568016 
C 437.602688 194.917402 436.549588 192.374994 434.675321 190.500727 
C 432.801054 188.62646 430.258645 187.57336 427.608032 187.57336 
C 424.957418 187.57336 422.41501 188.62646 420.540743 190.500727 
C 418.666476 192.374994 417.613376 194.917402 417.613376 197.568016 
C 417.613376 200.21863 418.666476 202.761038 420.540743 204.635305 
C 422.41501 206.509572 424.957418 207.562672 427.608032 207.562672 
z
" clip-path="url(#p8a32aafd77)" style="fill: #3d4e8a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 243.549901 95.675167 
C 244.820807 95.675167 246.039832 95.170231 246.938499 94.271564 
C 247.837165 93.372898 248.342102 92.153873 248.342102 90.882967 
C 248.342102 89.61206 247.837165 88.393036 246.938499 87.494369 
C 246.039832 86.595703 244.820807 86.090766 243.549901 86.090766 
C 242.278995 86.090766 241.05997 86.595703 240.161303 87.494369 
C 239.262637 88.393036 238.7577 89.61206 238.7577 90.882967 
C 238.7577 92.153873 239.262637 93.372898 240.161303 94.271564 
C 241.05997 95.170231 242.278995 95.675167 243.549901 95.675167 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460a5d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 568.508942 187.609109 
C 569.909695 187.609109 571.253266 187.052583 572.243748 186.062101 
C 573.234231 185.071619 573.790756 183.728048 573.790756 182.327295 
C 573.790756 180.926541 573.234231 179.58297 572.243748 178.592488 
C 571.253266 177.602006 569.909695 177.04548 568.508942 177.04548 
C 567.108188 177.04548 565.764618 177.602006 564.774135 178.592488 
C 563.783653 179.58297 563.227128 180.926541 563.227128 182.327295 
C 563.227128 183.728048 563.783653 185.071619 564.774135 186.062101 
C 565.764618 187.052583 567.108188 187.609109 568.508942 187.609109 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470e61; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 416.122109 372.271166 
C 417.993174 372.271166 419.787857 371.527784 421.1109 370.204741 
C 422.433943 368.881699 423.177325 367.087016 423.177325 365.21595 
C 423.177325 363.344885 422.433943 361.550202 421.1109 360.227159 
C 419.787857 358.904116 417.993174 358.160734 416.122109 358.160734 
C 414.251044 358.160734 412.456361 358.904116 411.133318 360.227159 
C 409.810275 361.550202 409.066893 363.344885 409.066893 365.21595 
C 409.066893 367.087016 409.810275 368.881699 411.133318 370.204741 
C 412.456361 371.527784 414.251044 372.271166 416.122109 372.271166 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482173; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 689.148911 109.86564 
C 690.141288 109.86564 691.093154 109.471364 691.794871 108.769647 
C 692.496587 108.067931 692.890863 107.116065 692.890863 106.123688 
C 692.890863 105.131311 692.496587 104.179445 691.794871 103.477729 
C 691.093154 102.776012 690.141288 102.381736 689.148911 102.381736 
C 688.156534 102.381736 687.204668 102.776012 686.502952 103.477729 
C 685.801235 104.179445 685.40696 105.131311 685.40696 106.123688 
C 685.40696 107.116065 685.801235 108.067931 686.502952 108.769647 
C 687.204668 109.471364 688.156534 109.86564 689.148911 109.86564 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 683.6232 280.366101 
C 685.372076 280.366101 687.049558 279.671265 688.286201 278.434623 
C 689.522843 277.197981 690.217679 275.520499 690.217679 273.771622 
C 690.217679 272.022746 689.522843 270.345264 688.286201 269.108622 
C 687.049558 267.87198 685.372076 267.177144 683.6232 267.177144 
C 681.874324 267.177144 680.196842 267.87198 678.9602 269.108622 
C 677.723557 270.345264 677.028722 272.022746 677.028722 273.771622 
C 677.028722 275.520499 677.723557 277.197981 678.9602 278.434623 
C 680.196842 279.671265 681.874324 280.366101 683.6232 280.366101 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481c6e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 948.016669 172.35153 
C 949.412952 172.35153 950.752235 171.796781 951.739556 170.80946 
C 952.726877 169.822139 953.281626 168.482856 953.281626 167.086573 
C 953.281626 165.69029 952.726877 164.351007 951.739556 163.363686 
C 950.752235 162.376365 949.412952 161.821616 948.016669 161.821616 
C 946.620386 161.821616 945.281103 162.376365 944.293782 163.363686 
C 943.306461 164.351007 942.751712 165.69029 942.751712 167.086573 
C 942.751712 168.482856 943.306461 169.822139 944.293782 170.80946 
C 945.281103 171.796781 946.620386 172.35153 948.016669 172.35153 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470e61; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 257.378347 232.35573 
C 258.520384 232.35573 259.615799 231.901994 260.423341 231.094452 
C 261.230883 230.286911 261.684619 229.191495 261.684619 228.049458 
C 261.684619 226.907422 261.230883 225.812006 260.423341 225.004465 
C 259.615799 224.196923 258.520384 223.743187 257.378347 223.743187 
C 256.236311 223.743187 255.140895 224.196923 254.333353 225.004465 
C 253.525812 225.812006 253.072076 226.907422 253.072076 228.049458 
C 253.072076 229.191495 253.525812 230.286911 254.333353 231.094452 
C 255.140895 231.901994 256.236311 232.35573 257.378347 232.35573 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 415.593152 140.495232 
C 416.624819 140.495232 417.614371 140.085347 418.34387 139.355848 
C 419.073368 138.626349 419.483254 137.636798 419.483254 136.605131 
C 419.483254 135.573463 419.073368 134.583912 418.34387 133.854413 
C 417.614371 133.124914 416.624819 132.715029 415.593152 132.715029 
C 414.561485 132.715029 413.571933 133.124914 412.842435 133.854413 
C 412.112936 134.583912 411.70305 135.573463 411.70305 136.605131 
C 411.70305 137.636798 412.112936 138.626349 412.842435 139.355848 
C 413.571933 140.085347 414.561485 140.495232 415.593152 140.495232 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 481.930022 171.112744 
C 482.997775 171.112744 484.021939 170.688521 484.776955 169.933506 
C 485.53197 169.17849 485.956193 168.154326 485.956193 167.086573 
C 485.956193 166.01882 485.53197 164.994656 484.776955 164.239641 
C 484.021939 163.484626 482.997775 163.060403 481.930022 163.060403 
C 480.862269 163.060403 479.838105 163.484626 479.08309 164.239641 
C 478.328075 164.994656 477.903852 166.01882 477.903852 167.086573 
C 477.903852 168.154326 478.328075 169.17849 479.08309 169.933506 
C 479.838105 170.688521 480.862269 171.112744 481.930022 171.112744 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 504.070649 111.481879 
C 505.491658 111.481879 506.854658 110.917306 507.859463 109.912501 
C 508.864268 108.907696 509.428841 107.544697 509.428841 106.123688 
C 509.428841 104.702679 508.864268 103.33968 507.859463 102.334874 
C 506.854658 101.330069 505.491658 100.765497 504.070649 100.765497 
C 502.64964 100.765497 501.286641 101.330069 500.281836 102.334874 
C 499.277031 103.33968 498.712458 104.702679 498.712458 106.123688 
C 498.712458 107.544697 499.277031 108.907696 500.281836 109.912501 
C 501.286641 110.917306 502.64964 111.481879 504.070649 111.481879 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470e61; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 269.440455 96.946107 
C 271.048419 96.946107 272.590741 96.307256 273.727743 95.170254 
C 274.864745 94.033252 275.503596 92.49093 275.503596 90.882967 
C 275.503596 89.275003 274.864745 87.732681 273.727743 86.595679 
C 272.590741 85.458677 271.048419 84.819826 269.440455 84.819826 
C 267.832491 84.819826 266.290169 85.458677 265.153167 86.595679 
C 264.016165 87.732681 263.377314 89.275003 263.377314 90.882967 
C 263.377314 92.49093 264.016165 94.033252 265.153167 95.170254 
C 266.290169 96.307256 267.832491 96.946107 269.440455 96.946107 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481668; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 430.498404 157.59327 
C 432.022637 157.59327 433.484646 156.987686 434.562442 155.90989 
C 435.640238 154.832095 436.245822 153.370085 436.245822 151.845852 
C 436.245822 150.321619 435.640238 148.859609 434.562442 147.781813 
C 433.484646 146.704018 432.022637 146.098434 430.498404 146.098434 
C 428.97417 146.098434 427.512161 146.704018 426.434365 147.781813 
C 425.35657 148.859609 424.750985 150.321619 424.750985 151.845852 
C 424.750985 153.370085 425.35657 154.832095 426.434365 155.90989 
C 427.512161 156.987686 428.97417 157.59327 430.498404 157.59327 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471365; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 889.226881 80.782967 
C 890.590216 80.782967 891.897896 80.241308 892.86192 79.277284 
C 893.825944 78.313261 894.367602 77.00558 894.367602 75.642245 
C 894.367602 74.27891 893.825944 72.97123 892.86192 72.007206 
C 891.897896 71.043183 890.590216 70.501524 889.226881 70.501524 
C 887.863546 70.501524 886.555866 71.043183 885.591842 72.007206 
C 884.627819 72.97123 884.08616 74.27891 884.08616 75.642245 
C 884.08616 77.00558 884.627819 78.313261 885.591842 79.277284 
C 886.555866 80.241308 887.863546 80.782967 889.226881 80.782967 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 294.140856 81.357408 
C 295.656535 81.357408 297.11034 80.755223 298.182087 79.683476 
C 299.253833 78.611729 299.856019 77.157924 299.856019 75.642245 
C 299.856019 74.126566 299.253833 72.672762 298.182087 71.601015 
C 297.11034 70.529268 295.656535 69.927082 294.140856 69.927082 
C 292.625177 69.927082 291.171372 70.529268 290.099625 71.601015 
C 289.027878 72.672762 288.425693 74.126566 288.425693 75.642245 
C 288.425693 77.157924 289.027878 78.611729 290.099625 79.683476 
C 291.171372 80.755223 292.625177 81.357408 294.140856 81.357408 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471365; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 787.005949 79.938632 
C 788.145364 79.938632 789.238265 79.485937 790.043953 78.680249 
C 790.849641 77.874561 791.302335 76.78166 791.302335 75.642245 
C 791.302335 74.50283 790.849641 73.409929 790.043953 72.604241 
C 789.238265 71.798553 788.145364 71.345859 787.005949 71.345859 
C 785.866534 71.345859 784.773633 71.798553 783.967945 72.604241 
C 783.162257 73.409929 782.709562 74.50283 782.709562 75.642245 
C 782.709562 76.78166 783.162257 77.874561 783.967945 78.680249 
C 784.773633 79.485937 785.866534 79.938632 787.005949 79.938632 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 392.838557 94.981701 
C 393.925554 94.981701 394.968177 94.549833 395.7368 93.78121 
C 396.505423 93.012587 396.937292 91.969964 396.937292 90.882967 
C 396.937292 89.795969 396.505423 88.753347 395.7368 87.984724 
C 394.968177 87.216101 393.925554 86.784232 392.838557 86.784232 
C 391.75156 86.784232 390.708937 87.216101 389.940314 87.984724 
C 389.171691 88.753347 388.739823 89.795969 388.739823 90.882967 
C 388.739823 91.969964 389.171691 93.012587 389.940314 93.78121 
C 390.708937 94.549833 391.75156 94.981701 392.838557 94.981701 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 605.006972 94.490692 
C 605.963752 94.490692 606.881474 94.110559 607.558019 93.434014 
C 608.234565 92.757468 608.614698 91.839747 608.614698 90.882967 
C 608.614698 89.926187 608.234565 89.008465 607.558019 88.331919 
C 606.881474 87.655374 605.963752 87.275241 605.006972 87.275241 
C 604.050192 87.275241 603.13247 87.655374 602.455925 88.331919 
C 601.779379 89.008465 601.399246 89.926187 601.399246 90.882967 
C 601.399246 91.839747 601.779379 92.757468 602.455925 93.434014 
C 603.13247 94.110559 604.050192 94.490692 605.006972 94.490692 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 299.279295 80.497686 
C 300.566973 80.497686 301.802084 79.986086 302.71261 79.07556 
C 303.623135 78.165034 304.134735 76.929923 304.134735 75.642245 
C 304.134735 74.354567 303.623135 73.119456 302.71261 72.208931 
C 301.802084 71.298405 300.566973 70.786805 299.279295 70.786805 
C 297.991617 70.786805 296.756506 71.298405 295.84598 72.208931 
C 294.935455 73.119456 294.423855 74.354567 294.423855 75.642245 
C 294.423855 76.929923 294.935455 78.165034 295.84598 79.07556 
C 296.756506 79.986086 297.991617 80.497686 299.279295 80.497686 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460b5e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 855.411418 232.580348 
C 856.613024 232.580348 857.765577 232.102944 858.615241 231.253281 
C 859.464904 230.403617 859.942307 229.251064 859.942307 228.049458 
C 859.942307 226.847853 859.464904 225.6953 858.615241 224.845636 
C 857.765577 223.995972 856.613024 223.518569 855.411418 223.518569 
C 854.209813 223.518569 853.05726 223.995972 852.207596 224.845636 
C 851.357932 225.6953 850.880529 226.847853 850.880529 228.049458 
C 850.880529 229.251064 851.357932 230.403617 852.207596 231.253281 
C 853.05726 232.102944 854.209813 232.580348 855.411418 232.580348 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 303.973788 94.987168 
C 305.062235 94.987168 306.106248 94.554723 306.875896 93.785075 
C 307.645544 93.015427 308.077989 91.971413 308.077989 90.882967 
C 308.077989 89.79452 307.645544 88.750506 306.875896 87.980858 
C 306.106248 87.21121 305.062235 86.778766 303.973788 86.778766 
C 302.885341 86.778766 301.841328 87.21121 301.07168 87.980858 
C 300.302031 88.750506 299.869587 89.79452 299.869587 90.882967 
C 299.869587 91.971413 300.302031 93.015427 301.07168 93.785075 
C 301.841328 94.554723 302.885341 94.987168 303.973788 94.987168 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 259.768099 385.54045 
C 261.116333 385.54045 262.409528 385.004791 263.362873 384.051446 
C 264.316219 383.098101 264.851878 381.804905 264.851878 380.456672 
C 264.851878 379.108438 264.316219 377.815243 263.362873 376.861897 
C 262.409528 375.908552 261.116333 375.372893 259.768099 375.372893 
C 258.419865 375.372893 257.12667 375.908552 256.173325 376.861897 
C 255.21998 377.815243 254.684321 379.108438 254.684321 380.456672 
C 254.684321 381.804905 255.21998 383.098101 256.173325 384.051446 
C 257.12667 385.004791 258.419865 385.54045 259.768099 385.54045 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 360.118791 248.025744 
C 361.374677 248.025744 362.579295 247.526775 363.467341 246.638729 
C 364.355386 245.750684 364.854355 244.546066 364.854355 243.29018 
C 364.854355 242.034293 364.355386 240.829676 363.467341 239.94163 
C 362.579295 239.053584 361.374677 238.554615 360.118791 238.554615 
C 358.862905 238.554615 357.658287 239.053584 356.770241 239.94163 
C 355.882196 240.829676 355.383227 242.034293 355.383227 243.29018 
C 355.383227 244.546066 355.882196 245.750684 356.770241 246.638729 
C 357.658287 247.526775 358.862905 248.025744 360.118791 248.025744 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460a5d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 536.403143 211.770567 
C 540.169704 211.770567 543.782503 210.274096 546.445863 207.610736 
C 549.109224 204.947375 550.605694 201.334576 550.605694 197.568016 
C 550.605694 193.801455 549.109224 190.188656 546.445863 187.525296 
C 543.782503 184.861935 540.169704 183.365465 536.403143 183.365465 
C 532.636583 183.365465 529.023784 184.861935 526.360423 187.525296 
C 523.697063 190.188656 522.200593 193.801455 522.200593 197.568016 
C 522.200593 201.334576 523.697063 204.947375 526.360423 207.610736 
C 529.023784 210.274096 532.636583 211.770567 536.403143 211.770567 
z
" clip-path="url(#p8a32aafd77)" style="fill: #1fa088; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 647.153507 171.107041 
C 648.219747 171.107041 649.242461 170.683419 649.996407 169.929473 
C 650.750353 169.175527 651.173975 168.152814 651.173975 167.086573 
C 651.173975 166.020333 650.750353 164.997619 649.996407 164.243673 
C 649.242461 163.489727 648.219747 163.066106 647.153507 163.066106 
C 646.087266 163.066106 645.064553 163.489727 644.310607 164.243673 
C 643.556661 164.997619 643.133039 166.020333 643.133039 167.086573 
C 643.133039 168.152814 643.556661 169.175527 644.310607 169.929473 
C 645.064553 170.683419 646.087266 171.107041 647.153507 171.107041 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 364.369338 263.057333 
C 365.569762 263.057333 366.721181 262.5804 367.570009 261.731572 
C 368.418837 260.882744 368.89577 259.731325 368.89577 258.530901 
C 368.89577 257.330477 368.418837 256.179058 367.570009 255.33023 
C 366.721181 254.481402 365.569762 254.004469 364.369338 254.004469 
C 363.168914 254.004469 362.017495 254.481402 361.168667 255.33023 
C 360.319839 256.179058 359.842906 257.330477 359.842906 258.530901 
C 359.842906 259.731325 360.319839 260.882744 361.168667 261.731572 
C 362.017495 262.5804 363.168914 263.057333 364.369338 263.057333 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 448.407375 170.894632 
C 449.417284 170.894632 450.385966 170.493391 451.100079 169.779278 
C 451.814193 169.065164 452.215434 168.096482 452.215434 167.086573 
C 452.215434 166.076664 451.814193 165.107982 451.100079 164.393869 
C 450.385966 163.679755 449.417284 163.278514 448.407375 163.278514 
C 447.397466 163.278514 446.428784 163.679755 445.71467 164.393869 
C 445.000557 165.107982 444.599316 166.076664 444.599316 167.086573 
C 444.599316 168.096482 445.000557 169.065164 445.71467 169.779278 
C 446.428784 170.493391 447.397466 170.894632 448.407375 170.894632 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 383.288995 140.602605 
C 384.349138 140.602605 385.366002 140.181406 386.115636 139.431772 
C 386.86527 138.682138 387.286469 137.665273 387.286469 136.605131 
C 387.286469 135.544988 386.86527 134.528123 386.115636 133.778489 
C 385.366002 133.028855 384.349138 132.607656 383.288995 132.607656 
C 382.228852 132.607656 381.211988 133.028855 380.462354 133.778489 
C 379.71272 134.528123 379.291521 135.544988 379.291521 136.605131 
C 379.291521 137.665273 379.71272 138.682138 380.462354 139.431772 
C 381.211988 140.181406 382.228852 140.602605 383.288995 140.602605 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 266.427289 295.489903 
C 268.145158 295.489903 269.792899 294.807387 271.007616 293.59267 
C 272.222332 292.377953 272.904849 290.730213 272.904849 289.012344 
C 272.904849 287.294475 272.222332 285.646734 271.007616 284.432018 
C 269.792899 283.217301 268.145158 282.534784 266.427289 282.534784 
C 264.709421 282.534784 263.06168 283.217301 261.846963 284.432018 
C 260.632247 285.646734 259.94973 287.294475 259.94973 289.012344 
C 259.94973 290.730213 260.632247 292.377953 261.846963 293.59267 
C 263.06168 294.807387 264.709421 295.489903 266.427289 295.489903 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481b6d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 634.033485 79.329174 
C 635.01127 79.329174 635.949139 78.940696 636.640537 78.249298 
C 637.331936 77.557899 637.720414 76.62003 637.720414 75.642245 
C 637.720414 74.66446 637.331936 73.726591 636.640537 73.035193 
C 635.949139 72.343795 635.01127 71.955317 634.033485 71.955317 
C 633.0557 71.955317 632.117831 72.343795 631.426433 73.035193 
C 630.735035 73.726591 630.346557 74.66446 630.346557 75.642245 
C 630.346557 76.62003 630.735035 77.557899 631.426433 78.249298 
C 632.117831 78.940696 633.0557 79.329174 634.033485 79.329174 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 465.248987 185.451006 
C 466.077405 185.451006 466.872004 185.121872 467.457784 184.536092 
C 468.043564 183.950312 468.372698 183.155712 468.372698 182.327295 
C 468.372698 181.498877 468.043564 180.704277 467.457784 180.118497 
C 466.872004 179.532717 466.077405 179.203583 465.248987 179.203583 
C 464.420569 179.203583 463.625969 179.532717 463.040189 180.118497 
C 462.454409 180.704277 462.125276 181.498877 462.125276 182.327295 
C 462.125276 183.155712 462.454409 183.950312 463.040189 184.536092 
C 463.625969 185.121872 464.420569 185.451006 465.248987 185.451006 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 227.690638 125.704917 
C 228.841754 125.704917 229.945878 125.247574 230.75984 124.433612 
C 231.573802 123.61965 232.031145 122.515525 232.031145 121.364409 
C 232.031145 120.213293 231.573802 119.109169 230.75984 118.295207 
C 229.945878 117.481245 228.841754 117.023902 227.690638 117.023902 
C 226.539522 117.023902 225.435397 117.481245 224.621435 118.295207 
C 223.807474 119.109169 223.35013 120.213293 223.35013 121.364409 
C 223.35013 122.515525 223.807474 123.61965 224.621435 124.433612 
C 225.435397 125.247574 226.539522 125.704917 227.690638 125.704917 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 297.097347 231.90849 
C 298.120775 231.90849 299.102423 231.501878 299.826095 230.778206 
C 300.549767 230.054534 300.956379 229.072886 300.956379 228.049458 
C 300.956379 227.026031 300.549767 226.044383 299.826095 225.320711 
C 299.102423 224.597039 298.120775 224.190427 297.097347 224.190427 
C 296.07392 224.190427 295.092272 224.597039 294.3686 225.320711 
C 293.644928 226.044383 293.238316 227.026031 293.238316 228.049458 
C 293.238316 229.072886 293.644928 230.054534 294.3686 230.778206 
C 295.092272 231.501878 296.07392 231.90849 297.097347 231.90849 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 382.14607 216.251139 
C 383.059006 216.251139 383.934673 215.888426 384.580216 215.242883 
C 385.225759 214.59734 385.588472 213.721673 385.588472 212.808737 
C 385.588472 211.895801 385.225759 211.020134 384.580216 210.374591 
C 383.934673 209.729048 383.059006 209.366335 382.14607 209.366335 
C 381.233134 209.366335 380.357467 209.729048 379.711924 210.374591 
C 379.066381 211.020134 378.703668 211.895801 378.703668 212.808737 
C 378.703668 213.721673 379.066381 214.59734 379.711924 215.242883 
C 380.357467 215.888426 381.233134 216.251139 382.14607 216.251139 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 311.983708 124.205872 
C 312.737272 124.205872 313.460074 123.906477 313.992925 123.373627 
C 314.525776 122.840776 314.82517 122.117974 314.82517 121.364409 
C 314.82517 120.610845 314.525776 119.888043 313.992925 119.355192 
C 313.460074 118.822341 312.737272 118.522947 311.983708 118.522947 
C 311.230143 118.522947 310.507341 118.822341 309.97449 119.355192 
C 309.44164 119.888043 309.142245 120.610845 309.142245 121.364409 
C 309.142245 122.117974 309.44164 122.840776 309.97449 123.373627 
C 310.507341 123.906477 311.230143 124.205872 311.983708 124.205872 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 319.379659 206.699801 
C 321.801437 206.699801 324.124351 205.737619 325.836807 204.025163 
C 327.549262 202.312708 328.511445 199.989794 328.511445 197.568016 
C 328.511445 195.146238 327.549262 192.823324 325.836807 191.110869 
C 324.124351 189.398413 321.801437 188.436231 319.379659 188.436231 
C 316.957882 188.436231 314.634968 189.398413 312.922512 191.110869 
C 311.210057 192.823324 310.247874 195.146238 310.247874 197.568016 
C 310.247874 199.989794 311.210057 202.312708 312.922512 204.025163 
C 314.634968 205.737619 316.957882 206.699801 319.379659 206.699801 
z
" clip-path="url(#p8a32aafd77)" style="fill: #424086; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 434.871744 156.823431 
C 436.191814 156.823431 437.457994 156.298962 438.391424 155.365532 
C 439.324854 154.432102 439.849323 153.165921 439.849323 151.845852 
C 439.849323 150.525782 439.324854 149.259602 438.391424 148.326172 
C 437.457994 147.392742 436.191814 146.868273 434.871744 146.868273 
C 433.551675 146.868273 432.285494 147.392742 431.352064 148.326172 
C 430.418634 149.259602 429.894165 150.525782 429.894165 151.845852 
C 429.894165 153.165921 430.418634 154.432102 431.352064 155.365532 
C 432.285494 156.298962 433.551675 156.823431 434.871744 156.823431 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460b5e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 301.300666 154.55883 
C 302.020156 154.55883 302.710275 154.272974 303.219031 153.764217 
C 303.727788 153.255461 304.013644 152.565342 304.013644 151.845852 
C 304.013644 151.126362 303.727788 150.436243 303.219031 149.927487 
C 302.710275 149.41873 302.020156 149.132874 301.300666 149.132874 
C 300.581176 149.132874 299.891057 149.41873 299.382301 149.927487 
C 298.873544 150.436243 298.587688 151.126362 298.587688 151.845852 
C 298.587688 152.565342 298.873544 153.255461 299.382301 153.764217 
C 299.891057 154.272974 300.581176 154.55883 301.300666 154.55883 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 335.059455 235.020874 
C 336.908296 235.020874 338.681662 234.286322 339.98899 232.978994 
C 341.296318 231.671666 342.030871 229.898299 342.030871 228.049458 
C 342.030871 226.200617 341.296318 224.427251 339.98899 223.119923 
C 338.681662 221.812595 336.908296 221.078043 335.059455 221.078043 
C 333.210614 221.078043 331.437248 221.812595 330.12992 223.119923 
C 328.822592 224.427251 328.088039 226.200617 328.088039 228.049458 
C 328.088039 229.898299 328.822592 231.671666 330.12992 232.978994 
C 331.437248 234.286322 333.210614 235.020874 335.059455 235.020874 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482071; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 195.717079 140.064225 
C 196.634441 140.064225 197.514355 139.699753 198.163028 139.05108 
C 198.811701 138.402406 199.176173 137.522493 199.176173 136.605131 
C 199.176173 135.687768 198.811701 134.807855 198.163028 134.159181 
C 197.514355 133.510508 196.634441 133.146036 195.717079 133.146036 
C 194.799716 133.146036 193.919803 133.510508 193.27113 134.159181 
C 192.622456 134.807855 192.257984 135.687768 192.257984 136.605131 
C 192.257984 137.522493 192.622456 138.402406 193.27113 139.05108 
C 193.919803 139.699753 194.799716 140.064225 195.717079 140.064225 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 381.853255 400.485589 
C 383.123099 400.485589 384.341105 399.981075 385.239021 399.083159 
C 386.136937 398.185243 386.641451 396.967238 386.641451 395.697393 
C 386.641451 394.427548 386.136937 393.209542 385.239021 392.311627 
C 384.341105 391.413711 383.123099 390.909196 381.853255 390.909196 
C 380.58341 390.909196 379.365404 391.413711 378.467488 392.311627 
C 377.569573 393.209542 377.065058 394.427548 377.065058 395.697393 
C 377.065058 396.967238 377.569573 398.185243 378.467488 399.083159 
C 379.365404 399.981075 380.58341 400.485589 381.853255 400.485589 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460a5d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 562.274806 414.388891 
C 563.189963 414.388891 564.06776 414.025295 564.714874 413.378182 
C 565.361987 412.731068 565.725583 411.853271 565.725583 410.938114 
C 565.725583 410.022958 565.361987 409.14516 564.714874 408.498047 
C 564.06776 407.850933 563.189963 407.487338 562.274806 407.487338 
C 561.35965 407.487338 560.481852 407.850933 559.834739 408.498047 
C 559.187625 409.14516 558.82403 410.022958 558.82403 410.938114 
C 558.82403 411.853271 559.187625 412.731068 559.834739 413.378182 
C 560.481852 414.025295 561.35965 414.388891 562.274806 414.388891 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 211.368537 79.48235 
C 212.386945 79.48235 213.363778 79.077732 214.083901 78.357609 
C 214.804024 77.637486 215.208642 76.660653 215.208642 75.642245 
C 215.208642 74.623838 214.804024 73.647004 214.083901 72.926881 
C 213.363778 72.206758 212.386945 71.802141 211.368537 71.802141 
C 210.35013 71.802141 209.373296 72.206758 208.653173 72.926881 
C 207.933051 73.647004 207.528433 74.623838 207.528433 75.642245 
C 207.528433 76.660653 207.933051 77.637486 208.653173 78.357609 
C 209.373296 79.077732 210.35013 79.48235 211.368537 79.48235 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 308.828857 339.179194 
C 310.007602 339.179194 311.138227 338.710874 311.971725 337.877375 
C 312.805223 337.043877 313.273543 335.913252 313.273543 334.734508 
C 313.273543 333.555763 312.805223 332.425138 311.971725 331.59164 
C 311.138227 330.758142 310.007602 330.289822 308.828857 330.289822 
C 307.650113 330.289822 306.519488 330.758142 305.68599 331.59164 
C 304.852491 332.425138 304.384171 333.555763 304.384171 334.734508 
C 304.384171 335.913252 304.852491 337.043877 305.68599 337.877375 
C 306.519488 338.710874 307.650113 339.179194 308.828857 339.179194 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 217.319303 79.580895 
C 218.363845 79.580895 219.365746 79.165894 220.104349 78.427291 
C 220.842951 77.688688 221.257952 76.686787 221.257952 75.642245 
C 221.257952 74.597703 220.842951 73.595802 220.104349 72.8572 
C 219.365746 72.118597 218.363845 71.703596 217.319303 71.703596 
C 216.274761 71.703596 215.27286 72.118597 214.534258 72.8572 
C 213.795655 73.595802 213.380654 74.597703 213.380654 75.642245 
C 213.380654 76.686787 213.795655 77.688688 214.534258 78.427291 
C 215.27286 79.165894 216.274761 79.580895 217.319303 79.580895 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 746.701318 80.828429 
C 748.07671 80.828429 749.395954 80.28198 750.368503 79.309431 
C 751.341052 78.336882 751.887501 77.017637 751.887501 75.642245 
C 751.887501 74.266853 751.341052 72.947609 750.368503 71.97506 
C 749.395954 71.002511 748.07671 70.456062 746.701318 70.456062 
C 745.325926 70.456062 744.006681 71.002511 743.034132 71.97506 
C 742.061583 72.947609 741.515134 74.266853 741.515134 75.642245 
C 741.515134 77.017637 742.061583 78.336882 743.034132 79.309431 
C 744.006681 80.28198 745.325926 80.828429 746.701318 80.828429 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 363.868718 216.680267 
C 364.89546 216.680267 365.880287 216.272338 366.606303 215.546322 
C 367.332319 214.820306 367.740248 213.835479 367.740248 212.808737 
C 367.740248 211.781995 367.332319 210.797168 366.606303 210.071152 
C 365.880287 209.345136 364.89546 208.937207 363.868718 208.937207 
C 362.841976 208.937207 361.857149 209.345136 361.131133 210.071152 
C 360.405117 210.797168 359.997188 211.781995 359.997188 212.808737 
C 359.997188 213.835479 360.405117 214.820306 361.131133 215.546322 
C 361.857149 216.272338 362.841976 216.680267 363.868718 216.680267 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 202.329041 216.019126 
C 203.180446 216.019126 203.997094 215.680859 204.599129 215.078825 
C 205.201163 214.476791 205.53943 213.660142 205.53943 212.808737 
C 205.53943 211.957332 205.201163 211.140684 204.599129 210.538649 
C 203.997094 209.936615 203.180446 209.598348 202.329041 209.598348 
C 201.477636 209.598348 200.660987 209.936615 200.058953 210.538649 
C 199.456919 211.140684 199.118652 211.957332 199.118652 212.808737 
C 199.118652 213.660142 199.456919 214.476791 200.058953 215.078825 
C 200.660987 215.680859 201.477636 216.019126 202.329041 216.019126 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 841.564081 431.768008 
C 843.046347 431.768008 844.468102 431.179097 845.516222 430.130977 
C 846.564343 429.082857 847.153253 427.661101 847.153253 426.178836 
C 847.153253 424.69657 846.564343 423.274814 845.516222 422.226694 
C 844.468102 421.178574 843.046347 420.589663 841.564081 420.589663 
C 840.081815 420.589663 838.66006 421.178574 837.611939 422.226694 
C 836.563819 423.274814 835.974909 424.69657 835.974909 426.178836 
C 835.974909 427.661101 836.563819 429.082857 837.611939 430.130977 
C 838.66006 431.179097 840.081815 431.768008 841.564081 431.768008 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471164; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 213.720507 217.494723 
C 214.963245 217.494723 216.155251 217.000978 217.033999 216.12223 
C 217.912748 215.243481 218.406493 214.051475 218.406493 212.808737 
C 218.406493 211.565999 217.912748 210.373993 217.033999 209.495245 
C 216.155251 208.616496 214.963245 208.122751 213.720507 208.122751 
C 212.477769 208.122751 211.285763 208.616496 210.407014 209.495245 
C 209.528266 210.373993 209.034521 211.565999 209.034521 212.808737 
C 209.034521 214.051475 209.528266 215.243481 210.407014 216.12223 
C 211.285763 217.000978 212.477769 217.494723 213.720507 217.494723 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460a5d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 575.035893 279.418364 
C 576.533426 279.418364 577.969826 278.823387 579.028742 277.764471 
C 580.087658 276.705555 580.682634 275.269156 580.682634 273.771622 
C 580.682634 272.274089 580.087658 270.837689 579.028742 269.778773 
C 577.969826 268.719857 576.533426 268.124881 575.035893 268.124881 
C 573.53836 268.124881 572.10196 268.719857 571.043044 269.778773 
C 569.984128 270.837689 569.389152 272.274089 569.389152 273.771622 
C 569.389152 275.269156 569.984128 276.705555 571.043044 277.764471 
C 572.10196 278.823387 573.53836 279.418364 575.035893 279.418364 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471164; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 385.130899 231.310378 
C 385.995705 231.310378 386.825207 230.966787 387.436717 230.355277 
C 388.048227 229.743767 388.391818 228.914264 388.391818 228.049458 
C 388.391818 227.184653 388.048227 226.35515 387.436717 225.74364 
C 386.825207 225.13213 385.995705 224.788539 385.130899 224.788539 
C 384.266093 224.788539 383.436591 225.13213 382.82508 225.74364 
C 382.21357 226.35515 381.869979 227.184653 381.869979 228.049458 
C 381.869979 228.914264 382.21357 229.743767 382.82508 230.355277 
C 383.436591 230.966787 384.266093 231.310378 385.130899 231.310378 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 364.699936 97.415801 
C 366.432464 97.415801 368.094265 96.72746 369.319347 95.502378 
C 370.54443 94.277296 371.23277 92.615494 371.23277 90.882967 
C 371.23277 89.150439 370.54443 87.488637 369.319347 86.263555 
C 368.094265 85.038473 366.432464 84.350132 364.699936 84.350132 
C 362.967408 84.350132 361.305607 85.038473 360.080525 86.263555 
C 358.855443 87.488637 358.167102 89.150439 358.167102 90.882967 
C 358.167102 92.615494 358.855443 94.277296 360.080525 95.502378 
C 361.305607 96.72746 362.967408 97.415801 364.699936 97.415801 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481b6d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 219.964088 128.632228 
C 221.891536 128.632228 223.740301 127.866445 225.103212 126.503534 
C 226.466124 125.140622 227.231907 123.291857 227.231907 121.364409 
C 227.231907 119.436961 226.466124 117.588197 225.103212 116.225285 
C 223.740301 114.862373 221.891536 114.09659 219.964088 114.09659 
C 218.03664 114.09659 216.187875 114.862373 214.824964 116.225285 
C 213.462052 117.588197 212.696269 119.436961 212.696269 121.364409 
C 212.696269 123.291857 213.462052 125.140622 214.824964 126.503534 
C 216.187875 127.866445 218.03664 128.632228 219.964088 128.632228 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482475; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 815.626299 97.873851 
C 817.480303 97.873851 819.258621 97.137248 820.5696 95.826269 
C 821.88058 94.51529 822.617183 92.736971 822.617183 90.882967 
C 822.617183 89.028962 821.88058 87.250644 820.5696 85.939665 
C 819.258621 84.628686 817.480303 83.892082 815.626299 83.892082 
C 813.772294 83.892082 811.993976 84.628686 810.682997 85.939665 
C 809.372018 87.250644 808.635414 89.028962 808.635414 90.882967 
C 808.635414 92.736971 809.372018 94.51529 810.682997 95.826269 
C 811.993976 97.137248 813.772294 97.873851 815.626299 97.873851 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482071; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 778.174257 127.825003 
C 779.887626 127.825003 781.531051 127.144274 782.742586 125.932739 
C 783.954121 124.721204 784.63485 123.077779 784.63485 121.364409 
C 784.63485 119.65104 783.954121 118.007615 782.742586 116.79608 
C 781.531051 115.584544 779.887626 114.903816 778.174257 114.903816 
C 776.460887 114.903816 774.817462 115.584544 773.605927 116.79608 
C 772.394392 118.007615 771.713663 119.65104 771.713663 121.364409 
C 771.713663 123.077779 772.394392 124.721204 773.605927 125.932739 
C 774.817462 127.144274 776.460887 127.825003 778.174257 127.825003 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481b6d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 338.837719 99.582389 
C 341.144833 99.582389 343.357764 98.665763 344.989139 97.034387 
C 346.620515 95.403011 347.537141 93.19008 347.537141 90.882967 
C 347.537141 88.575853 346.620515 86.362922 344.989139 84.731546 
C 343.357764 83.10017 341.144833 82.183544 338.837719 82.183544 
C 336.530605 82.183544 334.317674 83.10017 332.686299 84.731546 
C 331.054923 86.362922 330.138297 88.575853 330.138297 90.882967 
C 330.138297 93.19008 331.054923 95.403011 332.686299 97.034387 
C 334.317674 98.665763 336.530605 99.582389 338.837719 99.582389 
z
" clip-path="url(#p8a32aafd77)" style="fill: #443983; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 257.13276 129.051496 
C 259.171399 129.051496 261.126816 128.241536 262.568352 126.800001 
C 264.009887 125.358465 264.819847 123.403049 264.819847 121.364409 
C 264.819847 119.32577 264.009887 117.370353 262.568352 115.928818 
C 261.126816 114.487282 259.171399 113.677322 257.13276 113.677322 
C 255.094121 113.677322 253.138704 114.487282 251.697169 115.928818 
C 250.255633 117.370353 249.445673 119.32577 249.445673 121.364409 
C 249.445673 123.403049 250.255633 125.358465 251.697169 126.800001 
C 253.138704 128.241536 255.094121 129.051496 257.13276 129.051496 
z
" clip-path="url(#p8a32aafd77)" style="fill: #472a7a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 328.91033 112.654134 
C 330.642225 112.654134 332.303418 111.966045 333.528053 110.74141 
C 334.752687 109.516776 335.440776 107.855582 335.440776 106.123688 
C 335.440776 104.391794 334.752687 102.7306 333.528053 101.505966 
C 332.303418 100.281331 330.642225 99.593242 328.91033 99.593242 
C 327.178436 99.593242 325.517242 100.281331 324.292608 101.505966 
C 323.067974 102.7306 322.379885 104.391794 322.379885 106.123688 
C 322.379885 107.855582 323.067974 109.516776 324.292608 110.74141 
C 325.517242 111.966045 327.178436 112.654134 328.91033 112.654134 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481b6d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 374.891803 161.528107 
C 377.459567 161.528107 379.922508 160.507924 381.738192 158.69224 
C 383.553875 156.876557 384.574059 154.413616 384.574059 151.845852 
C 384.574059 149.278088 383.553875 146.815147 381.738192 144.999463 
C 379.922508 143.18378 377.459567 142.163596 374.891803 142.163596 
C 372.324039 142.163596 369.861098 143.18378 368.045415 144.999463 
C 366.229731 146.815147 365.209548 149.278088 365.209548 151.845852 
C 365.209548 154.413616 366.229731 156.876557 368.045415 158.69224 
C 369.861098 160.507924 372.324039 161.528107 374.891803 161.528107 
z
" clip-path="url(#p8a32aafd77)" style="fill: #3e4989; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 424.160366 97.051829 
C 425.796367 97.051829 427.365583 96.401839 428.52241 95.245011 
C 429.679238 94.088184 430.329229 92.518968 430.329229 90.882967 
C 430.329229 89.246965 429.679238 87.67775 428.52241 86.520922 
C 427.365583 85.364094 425.796367 84.714104 424.160366 84.714104 
C 422.524364 84.714104 420.955149 85.364094 419.798321 86.520922 
C 418.641493 87.67775 417.991503 89.246965 417.991503 90.882967 
C 417.991503 92.518968 418.641493 94.088184 419.798321 95.245011 
C 420.955149 96.401839 422.524364 97.051829 424.160366 97.051829 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481769; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 363.150848 96.051748 
C 364.521625 96.051748 365.836442 95.507132 366.805728 94.537847 
C 367.775013 93.568561 368.319629 92.253743 368.319629 90.882967 
C 368.319629 89.51219 367.775013 88.197372 366.805728 87.228087 
C 365.836442 86.258801 364.521625 85.714186 363.150848 85.714186 
C 361.780071 85.714186 360.465253 86.258801 359.495968 87.228087 
C 358.526682 88.197372 357.982067 89.51219 357.982067 90.882967 
C 357.982067 92.253743 358.526682 93.568561 359.495968 94.537847 
C 360.465253 95.507132 361.780071 96.051748 363.150848 96.051748 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 258.587392 143.384065 
C 260.385186 143.384065 262.109589 142.669793 263.380822 141.398561 
C 264.652054 140.127328 265.366326 138.402925 265.366326 136.605131 
C 265.366326 134.807336 264.652054 133.082933 263.380822 131.8117 
C 262.109589 130.540468 260.385186 129.826197 258.587392 129.826197 
C 256.789597 129.826197 255.065194 130.540468 253.793962 131.8117 
C 252.522729 133.082933 251.808458 134.807336 251.808458 136.605131 
C 251.808458 138.402925 252.522729 140.127328 253.793962 141.398561 
C 255.065194 142.669793 256.789597 143.384065 258.587392 143.384065 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481d6f; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 870.477246 98.219693 
C 872.422969 98.219693 874.289261 97.446649 875.665095 96.070815 
C 877.040928 94.694982 877.813972 92.828689 877.813972 90.882967 
C 877.813972 88.937244 877.040928 87.070951 875.665095 85.695118 
C 874.289261 84.319284 872.422969 83.546241 870.477246 83.546241 
C 868.531524 83.546241 866.665231 84.319284 865.289397 85.695118 
C 863.913564 87.070951 863.14052 88.937244 863.14052 90.882967 
C 863.14052 92.828689 863.913564 94.694982 865.289397 96.070815 
C 866.665231 97.446649 868.531524 98.219693 870.477246 98.219693 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482576; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 449.663648 98.219693 
C 451.60937 98.219693 453.475663 97.446649 454.851496 96.070815 
C 456.22733 94.694982 457.000374 92.828689 457.000374 90.882967 
C 457.000374 88.937244 456.22733 87.070951 454.851496 85.695118 
C 453.475663 84.319284 451.60937 83.546241 449.663648 83.546241 
C 447.717925 83.546241 445.851633 84.319284 444.475799 85.695118 
C 443.099965 87.070951 442.326922 88.937244 442.326922 90.882967 
C 442.326922 92.828689 443.099965 94.694982 444.475799 96.070815 
C 445.851633 97.446649 447.717925 98.219693 449.663648 98.219693 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482576; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 326.284437 251.928899 
C 328.575452 251.928899 330.772942 251.018669 332.392934 249.398677 
C 334.012926 247.778685 334.923156 245.581195 334.923156 243.29018 
C 334.923156 240.999165 334.012926 238.801675 332.392934 237.181683 
C 330.772942 235.56169 328.575452 234.65146 326.284437 234.65146 
C 323.993422 234.65146 321.795932 235.56169 320.17594 237.181683 
C 318.555947 238.801675 317.645717 240.999165 317.645717 243.29018 
C 317.645717 245.581195 318.555947 247.778685 320.17594 249.398677 
C 321.795932 251.018669 323.993422 251.928899 326.284437 251.928899 
z
" clip-path="url(#p8a32aafd77)" style="fill: #453882; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 220.502491 81.459035 
C 222.045121 81.459035 223.524778 80.846142 224.615582 79.755337 
C 225.706387 78.664532 226.319281 77.184876 226.319281 75.642245 
C 226.319281 74.099615 225.706387 72.619958 224.615582 71.529154 
C 223.524778 70.438349 222.045121 69.825455 220.502491 69.825455 
C 218.95986 69.825455 217.480204 70.438349 216.389399 71.529154 
C 215.298594 72.619958 214.6857 74.099615 214.6857 75.642245 
C 214.6857 77.184876 215.298594 78.664532 216.389399 79.755337 
C 217.480204 80.846142 218.95986 81.459035 220.502491 81.459035 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481467; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 587.334142 142.967446 
C 589.021448 142.967446 590.639873 142.297073 591.832979 141.103967 
C 593.026084 139.910862 593.696458 138.292436 593.696458 136.605131 
C 593.696458 134.917825 593.026084 133.299399 591.832979 132.106294 
C 590.639873 130.913188 589.021448 130.242815 587.334142 130.242815 
C 585.646836 130.242815 584.028411 130.913188 582.835305 132.106294 
C 581.6422 133.299399 580.971826 134.917825 580.971826 136.605131 
C 580.971826 138.292436 581.6422 139.910862 582.835305 141.103967 
C 584.028411 142.297073 585.646836 142.967446 587.334142 142.967446 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481a6c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 290.570396 81.855193 
C 292.21809 81.855193 293.798519 81.200558 294.963614 80.035463 
C 296.128709 78.870368 296.783345 77.289938 296.783345 75.642245 
C 296.783345 73.994552 296.128709 72.414122 294.963614 71.249028 
C 293.798519 70.083933 292.21809 69.429297 290.570396 69.429297 
C 288.922703 69.429297 287.342274 70.083933 286.177179 71.249028 
C 285.012084 72.414122 284.357448 73.994552 284.357448 75.642245 
C 284.357448 77.289938 285.012084 78.870368 286.177179 80.035463 
C 287.342274 81.200558 288.922703 81.855193 290.570396 81.855193 
z
" clip-path="url(#p8a32aafd77)" style="fill: #48186a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 607.991801 111.553238 
C 609.431734 111.553238 610.812885 110.981146 611.831072 109.96296 
C 612.849259 108.944773 613.421351 107.563621 613.421351 106.123688 
C 613.421351 104.683754 612.849259 103.302603 611.831072 102.284416 
C 610.812885 101.26623 609.431734 100.694138 607.991801 100.694138 
C 606.551867 100.694138 605.170716 101.26623 604.152529 102.284416 
C 603.134342 103.302603 602.562251 104.683754 602.562251 106.123688 
C 602.562251 107.563621 603.134342 108.944773 604.152529 109.96296 
C 605.170716 110.981146 606.551867 111.553238 607.991801 111.553238 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471063; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 541.28655 176.144931 
C 543.688854 176.144931 545.99309 175.190485 547.691776 173.491799 
C 549.390462 171.793114 550.344907 169.488878 550.344907 167.086573 
C 550.344907 164.684269 549.390462 162.380033 547.691776 160.681347 
C 545.99309 158.982661 543.688854 158.028215 541.28655 158.028215 
C 538.884245 158.028215 536.580009 158.982661 534.881323 160.681347 
C 533.182638 162.380033 532.228192 164.684269 532.228192 167.086573 
C 532.228192 169.488878 533.182638 171.793114 534.881323 173.491799 
C 536.580009 175.190485 538.884245 176.144931 541.28655 176.144931 
z
" clip-path="url(#p8a32aafd77)" style="fill: #423f85; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 374.410075 82.729308 
C 376.289586 82.729308 378.09237 81.982571 379.421385 80.653556 
C 380.7504 79.324541 381.497138 77.521756 381.497138 75.642245 
C 381.497138 73.762734 380.7504 71.95995 379.421385 70.630935 
C 378.09237 69.30192 376.289586 68.555182 374.410075 68.555182 
C 372.530563 68.555182 370.727779 69.30192 369.398764 70.630935 
C 368.069749 71.95995 367.323011 73.762734 367.323011 75.642245 
C 367.323011 77.521756 368.069749 79.324541 369.398764 80.653556 
C 370.727779 81.982571 372.530563 82.729308 374.410075 82.729308 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482173; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 434.134983 325.401045 
C 435.701606 325.401045 437.204275 324.778619 438.312045 323.670849 
C 439.419815 322.563079 440.042242 321.06041 440.042242 319.493786 
C 440.042242 317.927163 439.419815 316.424494 438.312045 315.316724 
C 437.204275 314.208954 435.701606 313.586528 434.134983 313.586528 
C 432.568359 313.586528 431.06569 314.208954 429.95792 315.316724 
C 428.85015 316.424494 428.227724 317.927163 428.227724 319.493786 
C 428.227724 321.06041 428.85015 322.563079 429.95792 323.670849 
C 431.06569 324.778619 432.568359 325.401045 434.134983 325.401045 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481467; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 380.729221 110.132696 
C 381.792422 110.132696 382.812221 109.710281 383.564018 108.958485 
C 384.315815 108.206688 384.738229 107.186889 384.738229 106.123688 
C 384.738229 105.060487 384.315815 104.040688 383.564018 103.288891 
C 382.812221 102.537094 381.792422 102.11468 380.729221 102.11468 
C 379.66602 102.11468 378.646221 102.537094 377.894424 103.288891 
C 377.142628 104.040688 376.720213 105.060487 376.720213 106.123688 
C 376.720213 107.186889 377.142628 108.206688 377.894424 108.958485 
C 378.646221 109.710281 379.66602 110.132696 380.729221 110.132696 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 768.473564 157.217138 
C 769.898045 157.217138 771.264376 156.651185 772.271636 155.643924 
C 773.278897 154.636664 773.84485 153.270334 773.84485 151.845852 
C 773.84485 150.42137 773.278897 149.05504 772.271636 148.047779 
C 771.264376 147.040519 769.898045 146.474566 768.473564 146.474566 
C 767.049082 146.474566 765.682752 147.040519 764.675491 148.047779 
C 763.668231 149.05504 763.102278 150.42137 763.102278 151.845852 
C 763.102278 153.270334 763.668231 154.636664 764.675491 155.643924 
C 765.682752 156.651185 767.049082 157.217138 768.473564 157.217138 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471063; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 246.978676 103.408067 
C 250.300371 103.408067 253.486466 102.088344 255.835259 99.73955 
C 258.184053 97.390757 259.503776 94.204662 259.503776 90.882967 
C 259.503776 87.561271 258.184053 84.375176 255.835259 82.026383 
C 253.486466 79.67759 250.300371 78.357866 246.978676 78.357866 
C 243.65698 78.357866 240.470885 79.67759 238.122092 82.026383 
C 235.773298 84.375176 234.453575 87.561271 234.453575 90.882967 
C 234.453575 94.204662 235.773298 97.390757 238.122092 99.73955 
C 240.470885 102.088344 243.65698 103.408067 246.978676 103.408067 
z
" clip-path="url(#p8a32aafd77)" style="fill: #287c8e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 522.234653 186.794985 
C 523.419499 186.794985 524.555976 186.324241 525.393788 185.486429 
C 526.2316 184.648617 526.702344 183.51214 526.702344 182.327295 
C 526.702344 181.142449 526.2316 180.005972 525.393788 179.16816 
C 524.555976 178.330348 523.419499 177.859604 522.234653 177.859604 
C 521.049808 177.859604 519.913331 178.330348 519.075519 179.16816 
C 518.237707 180.005972 517.766963 181.142449 517.766963 182.327295 
C 517.766963 183.51214 518.237707 184.648617 519.075519 185.486429 
C 519.913331 186.324241 521.049808 186.794985 522.234653 186.794985 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 369.753364 112.438496 
C 371.428071 112.438496 373.034412 111.773128 374.218608 110.588932 
C 375.402805 109.404735 376.068173 107.798395 376.068173 106.123688 
C 376.068173 104.448981 375.402805 102.842641 374.218608 101.658444 
C 373.034412 100.474247 371.428071 99.808879 369.753364 99.808879 
C 368.078657 99.808879 366.472317 100.474247 365.28812 101.658444 
C 364.103924 102.842641 363.438556 104.448981 363.438556 106.123688 
C 363.438556 107.798395 364.103924 109.404735 365.28812 110.588932 
C 366.472317 111.773128 368.078657 112.438496 369.753364 112.438496 
z
" clip-path="url(#p8a32aafd77)" style="fill: #48186a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 271.055663 112.958754 
C 272.868344 112.958754 274.607026 112.238568 275.888784 110.956809 
C 277.170543 109.675051 277.890729 107.936369 277.890729 106.123688 
C 277.890729 104.311007 277.170543 102.572325 275.888784 101.290566 
C 274.607026 100.008808 272.868344 99.288622 271.055663 99.288622 
C 269.242982 99.288622 267.5043 100.008808 266.222541 101.290566 
C 264.940783 102.572325 264.220597 104.311007 264.220597 106.123688 
C 264.220597 107.936369 264.940783 109.675051 266.222541 110.956809 
C 267.5043 112.238568 269.242982 112.958754 271.055663 112.958754 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481f70; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 378.112773 185.626944 
C 378.98785 185.626944 379.827205 185.279272 380.445978 184.660499 
C 381.064751 184.041726 381.412423 183.202372 381.412423 182.327295 
C 381.412423 181.452217 381.064751 180.612863 380.445978 179.99409 
C 379.827205 179.375317 378.98785 179.027645 378.112773 179.027645 
C 377.237696 179.027645 376.398342 179.375317 375.779569 179.99409 
C 375.160796 180.612863 374.813124 181.452217 374.813124 182.327295 
C 374.813124 183.202372 375.160796 184.041726 375.779569 184.660499 
C 376.398342 185.279272 377.237696 185.626944 378.112773 185.626944 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 229.409748 187.186637 
C 230.698461 187.186637 231.934565 186.674626 232.845822 185.763369 
C 233.75708 184.852111 234.26909 183.616007 234.26909 182.327295 
C 234.26909 181.038582 233.75708 179.802478 232.845822 178.89122 
C 231.934565 177.979963 230.698461 177.467952 229.409748 177.467952 
C 228.121035 177.467952 226.884931 177.979963 225.973674 178.89122 
C 225.062416 179.802478 224.550405 181.038582 224.550405 182.327295 
C 224.550405 183.616007 225.062416 184.852111 225.973674 185.763369 
C 226.884931 186.674626 228.121035 187.186637 229.409748 187.186637 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460b5e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 476.687681 155.13595 
C 477.560225 155.13595 478.397149 154.789284 479.014131 154.172302 
C 479.631113 153.55532 479.977779 152.718396 479.977779 151.845852 
C 479.977779 150.973308 479.631113 150.136383 479.014131 149.519402 
C 478.397149 148.90242 477.560225 148.555754 476.687681 148.555754 
C 475.815137 148.555754 474.978212 148.90242 474.361231 149.519402 
C 473.744249 150.136383 473.397583 150.973308 473.397583 151.845852 
C 473.397583 152.718396 473.744249 153.55532 474.361231 154.172302 
C 474.978212 154.789284 475.815137 155.13595 476.687681 155.13595 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 332.121855 172.007586 
C 333.426923 172.007586 334.678714 171.489077 335.601537 170.566255 
C 336.524359 169.643433 337.042868 168.391641 337.042868 167.086573 
C 337.042868 165.781505 336.524359 164.529714 335.601537 163.606891 
C 334.678714 162.684069 333.426923 162.16556 332.121855 162.16556 
C 330.816787 162.16556 329.564995 162.684069 328.642173 163.606891 
C 327.719351 164.529714 327.200842 165.781505 327.200842 167.086573 
C 327.200842 168.391641 327.719351 169.643433 328.642173 170.566255 
C 329.564995 171.489077 330.816787 172.007586 332.121855 172.007586 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460b5e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 527.845375 80.890252 
C 529.237163 80.890252 530.572134 80.337289 531.556277 79.353146 
C 532.540419 78.369004 533.093382 77.034033 533.093382 75.642245 
C 533.093382 74.250458 532.540419 72.915487 531.556277 71.931344 
C 530.572134 70.947202 529.237163 70.394239 527.845375 70.394239 
C 526.453588 70.394239 525.118617 70.947202 524.134474 71.931344 
C 523.150332 72.915487 522.597369 74.250458 522.597369 75.642245 
C 522.597369 77.034033 523.150332 78.369004 524.134474 79.353146 
C 525.118617 80.337289 526.453588 80.890252 527.845375 80.890252 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470e61; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 208.884329 81.729425 
C 210.498668 81.729425 212.047105 81.088041 213.188615 79.946531 
C 214.330125 78.805021 214.971509 77.256584 214.971509 75.642245 
C 214.971509 74.027906 214.330125 72.479469 213.188615 71.337959 
C 212.047105 70.196449 210.498668 69.555066 208.884329 69.555066 
C 207.26999 69.555066 205.721553 70.196449 204.580043 71.337959 
C 203.438533 72.479469 202.797149 74.027906 202.797149 75.642245 
C 202.797149 77.256584 203.438533 78.805021 204.580043 79.946531 
C 205.721553 81.088041 207.26999 81.729425 208.884329 81.729425 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481769; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 515.924953 110.178106 
C 517.000197 110.178106 518.031547 109.750907 518.791859 108.990595 
C 519.552172 108.230282 519.979371 107.198932 519.979371 106.123688 
C 519.979371 105.048444 519.552172 104.017094 518.791859 103.256781 
C 518.031547 102.496468 517.000197 102.069269 515.924953 102.069269 
C 514.849708 102.069269 513.818358 102.496468 513.058046 103.256781 
C 512.297733 104.017094 511.870534 105.048444 511.870534 106.123688 
C 511.870534 107.198932 512.297733 108.230282 513.058046 108.990595 
C 513.818358 109.750907 514.849708 110.178106 515.924953 110.178106 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 383.487354 110.568374 
C 384.666098 110.568374 385.796723 110.100054 386.630221 109.266556 
C 387.46372 108.433057 387.93204 107.302432 387.93204 106.123688 
C 387.93204 104.944943 387.46372 103.814319 386.630221 102.98082 
C 385.796723 102.147322 384.666098 101.679002 383.487354 101.679002 
C 382.308609 101.679002 381.177984 102.147322 380.344486 102.98082 
C 379.510988 103.814319 379.042668 104.944943 379.042668 106.123688 
C 379.042668 107.302432 379.510988 108.433057 380.344486 109.266556 
C 381.177984 110.100054 382.308609 110.568374 383.487354 110.568374 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 688.714411 110.609615 
C 689.904093 110.609615 691.045208 110.136949 691.88644 109.295717 
C 692.727672 108.454485 693.200338 107.31337 693.200338 106.123688 
C 693.200338 104.934006 692.727672 103.792891 691.88644 102.951658 
C 691.045208 102.110426 689.904093 101.637761 688.714411 101.637761 
C 687.524729 101.637761 686.383613 102.110426 685.542381 102.951658 
C 684.701149 103.792891 684.228484 104.934006 684.228484 106.123688 
C 684.228484 107.31337 684.701149 108.454485 685.542381 109.295717 
C 686.383613 110.136949 687.524729 110.609615 688.714411 110.609615 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 424.689323 215.735668 
C 429.50744 215.735668 434.128869 213.821409 437.535793 210.414486 
C 440.942716 207.007562 442.856975 202.386133 442.856975 197.568016 
C 442.856975 192.749898 440.942716 188.12847 437.535793 184.721546 
C 434.128869 181.314622 429.50744 179.400364 424.689323 179.400364 
C 419.871205 179.400364 415.249776 181.314622 411.842853 184.721546 
C 408.435929 188.12847 406.521671 192.749898 406.521671 197.568016 
C 406.521671 202.386133 408.435929 207.007562 411.842853 210.414486 
C 415.249776 213.821409 419.871205 215.735668 424.689323 215.735668 
z
" clip-path="url(#p8a32aafd77)" style="fill: #fde725; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 486.48283 141.476145 
C 487.774639 141.476145 489.013712 140.962905 489.927158 140.049458 
C 490.840604 139.136012 491.353845 137.896939 491.353845 136.605131 
C 491.353845 135.313322 490.840604 134.074249 489.927158 133.160803 
C 489.013712 132.247357 487.774639 131.734116 486.48283 131.734116 
C 485.191022 131.734116 483.951949 132.247357 483.038503 133.160803 
C 482.125056 134.074249 481.611816 135.313322 481.611816 136.605131 
C 481.611816 137.896939 482.125056 139.136012 483.038503 140.049458 
C 483.951949 140.962905 485.191022 141.476145 486.48283 141.476145 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460b5e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 839.117655 263.039419 
C 840.313328 263.039419 841.46019 262.564373 842.305659 261.718905 
C 843.151127 260.873436 843.626173 259.726574 843.626173 258.530901 
C 843.626173 257.335228 843.151127 256.188366 842.305659 255.342897 
C 841.46019 254.497429 840.313328 254.022383 839.117655 254.022383 
C 837.921982 254.022383 836.77512 254.497429 835.929651 255.342897 
C 835.084183 256.188366 834.609137 257.335228 834.609137 258.530901 
C 834.609137 259.726574 835.084183 260.873436 835.929651 261.718905 
C 836.77512 262.564373 837.921982 263.039419 839.117655 263.039419 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 207.080208 210.173797 
C 210.4233 210.173797 213.629918 208.845573 215.993841 206.481649 
C 218.357764 204.117726 219.685989 200.911108 219.685989 197.568016 
C 219.685989 194.224924 218.357764 191.018306 215.993841 188.654382 
C 213.629918 186.290459 210.4233 184.962234 207.080208 184.962234 
C 203.737115 184.962234 200.530498 186.290459 198.166574 188.654382 
C 195.802651 191.018306 194.474426 194.224924 194.474426 197.568016 
C 194.474426 200.911108 195.802651 204.117726 198.166574 206.481649 
C 200.530498 208.845573 203.737115 210.173797 207.080208 210.173797 
z
" clip-path="url(#p8a32aafd77)" style="fill: #277e8e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 251.512592 141.969876 
C 252.935339 141.969876 254.300006 141.404612 255.30604 140.398578 
C 256.312074 139.392544 256.877338 138.027878 256.877338 136.605131 
C 256.877338 135.182383 256.312074 133.817717 255.30604 132.811683 
C 254.300006 131.805649 252.935339 131.240385 251.512592 131.240385 
C 250.089845 131.240385 248.725179 131.805649 247.719145 132.811683 
C 246.71311 133.817717 246.147847 135.182383 246.147847 136.605131 
C 246.147847 138.027878 246.71311 139.392544 247.719145 140.398578 
C 248.725179 141.404612 250.089845 141.969876 251.512592 141.969876 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470e61; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 377.536588 250.136391 
C 379.352224 250.136391 381.093741 249.415031 382.37759 248.131182 
C 383.661439 246.847333 384.382799 245.105816 384.382799 243.29018 
C 384.382799 241.474543 383.661439 239.733026 382.37759 238.449178 
C 381.093741 237.165329 379.352224 236.443969 377.536588 236.443969 
C 375.720952 236.443969 373.979435 237.165329 372.695586 238.449178 
C 371.411737 239.733026 370.690377 241.474543 370.690377 243.29018 
C 370.690377 245.105816 371.411737 246.847333 372.695586 248.131182 
C 373.979435 249.415031 375.720952 250.136391 377.536588 250.136391 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481f70; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 625.419043 80.786489 
C 626.783313 80.786489 628.091889 80.244459 629.056573 79.279775 
C 630.021257 78.315091 630.563287 77.006515 630.563287 75.642245 
C 630.563287 74.277976 630.021257 72.9694 629.056573 72.004716 
C 628.091889 71.040032 626.783313 70.498002 625.419043 70.498002 
C 624.054774 70.498002 622.746198 71.040032 621.781514 72.004716 
C 620.81683 72.9694 620.2748 74.277976 620.2748 75.642245 
C 620.2748 77.006515 620.81683 78.315091 621.781514 79.279775 
C 622.746198 80.244459 624.054774 80.786489 625.419043 80.786489 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 353.931884 263.696189 
C 355.301734 263.696189 356.615663 263.151942 357.584294 262.183311 
C 358.552924 261.214681 359.097172 259.900752 359.097172 258.530901 
C 359.097172 257.161051 358.552924 255.847121 357.584294 254.878491 
C 356.615663 253.90986 355.301734 253.365613 353.931884 253.365613 
C 352.562033 253.365613 351.248104 253.90986 350.279473 254.878491 
C 349.310843 255.847121 348.766596 257.161051 348.766596 258.530901 
C 348.766596 259.900752 349.310843 261.214681 350.279473 262.183311 
C 351.248104 263.151942 352.562033 263.696189 353.931884 263.696189 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 425.397747 127.149571 
C 426.93199 127.149571 428.403601 126.54001 429.488475 125.455137 
C 430.573348 124.370263 431.182909 122.898652 431.182909 121.364409 
C 431.182909 119.830166 430.573348 118.358555 429.488475 117.273682 
C 428.403601 116.188808 426.93199 115.579247 425.397747 115.579247 
C 423.863504 115.579247 422.391893 116.188808 421.30702 117.273682 
C 420.222146 118.358555 419.612585 119.830166 419.612585 121.364409 
C 419.612585 122.898652 420.222146 124.370263 421.30702 125.455137 
C 422.391893 126.54001 423.863504 127.149571 425.397747 127.149571 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471365; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 294.726487 109.963792 
C 295.744894 109.963792 296.721728 109.559175 297.441851 108.839052 
C 298.161974 108.118929 298.566591 107.142096 298.566591 106.123688 
C 298.566591 105.10528 298.161974 104.128447 297.441851 103.408324 
C 296.721728 102.688201 295.744894 102.283583 294.726487 102.283583 
C 293.708079 102.283583 292.731246 102.688201 292.011123 103.408324 
C 291.291 104.128447 290.886382 105.10528 290.886382 106.123688 
C 290.886382 107.142096 291.291 108.118929 292.011123 108.839052 
C 292.731246 109.559175 293.708079 109.963792 294.726487 109.963792 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 418.823568 308.636796 
C 419.986147 308.636796 421.101266 308.174899 421.923334 307.352831 
C 422.745401 306.530764 423.207299 305.415644 423.207299 304.253065 
C 423.207299 303.090486 422.745401 301.975367 421.923334 301.153299 
C 421.101266 300.331231 419.986147 299.869334 418.823568 299.869334 
C 417.660989 299.869334 416.545869 300.331231 415.723802 301.153299 
C 414.901734 301.975367 414.439837 303.090486 414.439837 304.253065 
C 414.439837 305.415644 414.901734 306.530764 415.723802 307.352831 
C 416.545869 308.174899 417.660989 308.636796 418.823568 308.636796 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 232.234 125.841237 
C 233.421269 125.841237 234.56007 125.36953 235.399595 124.530004 
C 236.239121 123.690479 236.710828 122.551678 236.710828 121.364409 
C 236.710828 120.177141 236.239121 119.03834 235.399595 118.198814 
C 234.56007 117.359289 233.421269 116.887582 232.234 116.887582 
C 231.046732 116.887582 229.907931 117.359289 229.068405 118.198814 
C 228.22888 119.03834 227.757173 120.177141 227.757173 121.364409 
C 227.757173 122.551678 228.22888 123.690479 229.068405 124.530004 
C 229.907931 125.36953 231.046732 125.841237 232.234 125.841237 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 427.608032 207.562672 
C 430.258645 207.562672 432.801054 206.509572 434.675321 204.635305 
C 436.549588 202.761038 437.602688 200.21863 437.602688 197.568016 
C 437.602688 194.917402 436.549588 192.374994 434.675321 190.500727 
C 432.801054 188.62646 430.258645 187.57336 427.608032 187.57336 
C 424.957418 187.57336 422.41501 188.62646 420.540743 190.500727 
C 418.666476 192.374994 417.613376 194.917402 417.613376 197.568016 
C 417.613376 200.21863 418.666476 202.761038 420.540743 204.635305 
C 422.41501 206.509572 424.957418 207.562672 427.608032 207.562672 
z
" clip-path="url(#p8a32aafd77)" style="fill: #3d4e8a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 243.549901 95.675167 
C 244.820807 95.675167 246.039832 95.170231 246.938499 94.271564 
C 247.837165 93.372898 248.342102 92.153873 248.342102 90.882967 
C 248.342102 89.61206 247.837165 88.393036 246.938499 87.494369 
C 246.039832 86.595703 244.820807 86.090766 243.549901 86.090766 
C 242.278995 86.090766 241.05997 86.595703 240.161303 87.494369 
C 239.262637 88.393036 238.7577 89.61206 238.7577 90.882967 
C 238.7577 92.153873 239.262637 93.372898 240.161303 94.271564 
C 241.05997 95.170231 242.278995 95.675167 243.549901 95.675167 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460a5d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 568.508942 187.609109 
C 569.909695 187.609109 571.253266 187.052583 572.243748 186.062101 
C 573.234231 185.071619 573.790756 183.728048 573.790756 182.327295 
C 573.790756 180.926541 573.234231 179.58297 572.243748 178.592488 
C 571.253266 177.602006 569.909695 177.04548 568.508942 177.04548 
C 567.108188 177.04548 565.764618 177.602006 564.774135 178.592488 
C 563.783653 179.58297 563.227128 180.926541 563.227128 182.327295 
C 563.227128 183.728048 563.783653 185.071619 564.774135 186.062101 
C 565.764618 187.052583 567.108188 187.609109 568.508942 187.609109 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470e61; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 416.122109 372.271166 
C 417.993174 372.271166 419.787857 371.527784 421.1109 370.204741 
C 422.433943 368.881699 423.177325 367.087016 423.177325 365.21595 
C 423.177325 363.344885 422.433943 361.550202 421.1109 360.227159 
C 419.787857 358.904116 417.993174 358.160734 416.122109 358.160734 
C 414.251044 358.160734 412.456361 358.904116 411.133318 360.227159 
C 409.810275 361.550202 409.066893 363.344885 409.066893 365.21595 
C 409.066893 367.087016 409.810275 368.881699 411.133318 370.204741 
C 412.456361 371.527784 414.251044 372.271166 416.122109 372.271166 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482173; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 689.148911 109.86564 
C 690.141288 109.86564 691.093154 109.471364 691.794871 108.769647 
C 692.496587 108.067931 692.890863 107.116065 692.890863 106.123688 
C 692.890863 105.131311 692.496587 104.179445 691.794871 103.477729 
C 691.093154 102.776012 690.141288 102.381736 689.148911 102.381736 
C 688.156534 102.381736 687.204668 102.776012 686.502952 103.477729 
C 685.801235 104.179445 685.40696 105.131311 685.40696 106.123688 
C 685.40696 107.116065 685.801235 108.067931 686.502952 108.769647 
C 687.204668 109.471364 688.156534 109.86564 689.148911 109.86564 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 683.6232 280.366101 
C 685.372076 280.366101 687.049558 279.671265 688.286201 278.434623 
C 689.522843 277.197981 690.217679 275.520499 690.217679 273.771622 
C 690.217679 272.022746 689.522843 270.345264 688.286201 269.108622 
C 687.049558 267.87198 685.372076 267.177144 683.6232 267.177144 
C 681.874324 267.177144 680.196842 267.87198 678.9602 269.108622 
C 677.723557 270.345264 677.028722 272.022746 677.028722 273.771622 
C 677.028722 275.520499 677.723557 277.197981 678.9602 278.434623 
C 680.196842 279.671265 681.874324 280.366101 683.6232 280.366101 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481c6e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 948.016669 172.35153 
C 949.412952 172.35153 950.752235 171.796781 951.739556 170.80946 
C 952.726877 169.822139 953.281626 168.482856 953.281626 167.086573 
C 953.281626 165.69029 952.726877 164.351007 951.739556 163.363686 
C 950.752235 162.376365 949.412952 161.821616 948.016669 161.821616 
C 946.620386 161.821616 945.281103 162.376365 944.293782 163.363686 
C 943.306461 164.351007 942.751712 165.69029 942.751712 167.086573 
C 942.751712 168.482856 943.306461 169.822139 944.293782 170.80946 
C 945.281103 171.796781 946.620386 172.35153 948.016669 172.35153 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470e61; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 257.378347 232.35573 
C 258.520384 232.35573 259.615799 231.901994 260.423341 231.094452 
C 261.230883 230.286911 261.684619 229.191495 261.684619 228.049458 
C 261.684619 226.907422 261.230883 225.812006 260.423341 225.004465 
C 259.615799 224.196923 258.520384 223.743187 257.378347 223.743187 
C 256.236311 223.743187 255.140895 224.196923 254.333353 225.004465 
C 253.525812 225.812006 253.072076 226.907422 253.072076 228.049458 
C 253.072076 229.191495 253.525812 230.286911 254.333353 231.094452 
C 255.140895 231.901994 256.236311 232.35573 257.378347 232.35573 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 415.593152 140.495232 
C 416.624819 140.495232 417.614371 140.085347 418.34387 139.355848 
C 419.073368 138.626349 419.483254 137.636798 419.483254 136.605131 
C 419.483254 135.573463 419.073368 134.583912 418.34387 133.854413 
C 417.614371 133.124914 416.624819 132.715029 415.593152 132.715029 
C 414.561485 132.715029 413.571933 133.124914 412.842435 133.854413 
C 412.112936 134.583912 411.70305 135.573463 411.70305 136.605131 
C 411.70305 137.636798 412.112936 138.626349 412.842435 139.355848 
C 413.571933 140.085347 414.561485 140.495232 415.593152 140.495232 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 481.930022 171.112744 
C 482.997775 171.112744 484.021939 170.688521 484.776955 169.933506 
C 485.53197 169.17849 485.956193 168.154326 485.956193 167.086573 
C 485.956193 166.01882 485.53197 164.994656 484.776955 164.239641 
C 484.021939 163.484626 482.997775 163.060403 481.930022 163.060403 
C 480.862269 163.060403 479.838105 163.484626 479.08309 164.239641 
C 478.328075 164.994656 477.903852 166.01882 477.903852 167.086573 
C 477.903852 168.154326 478.328075 169.17849 479.08309 169.933506 
C 479.838105 170.688521 480.862269 171.112744 481.930022 171.112744 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 504.070649 111.481879 
C 505.491658 111.481879 506.854658 110.917306 507.859463 109.912501 
C 508.864268 108.907696 509.428841 107.544697 509.428841 106.123688 
C 509.428841 104.702679 508.864268 103.33968 507.859463 102.334874 
C 506.854658 101.330069 505.491658 100.765497 504.070649 100.765497 
C 502.64964 100.765497 501.286641 101.330069 500.281836 102.334874 
C 499.277031 103.33968 498.712458 104.702679 498.712458 106.123688 
C 498.712458 107.544697 499.277031 108.907696 500.281836 109.912501 
C 501.286641 110.917306 502.64964 111.481879 504.070649 111.481879 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470e61; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 269.440455 96.946107 
C 271.048419 96.946107 272.590741 96.307256 273.727743 95.170254 
C 274.864745 94.033252 275.503596 92.49093 275.503596 90.882967 
C 275.503596 89.275003 274.864745 87.732681 273.727743 86.595679 
C 272.590741 85.458677 271.048419 84.819826 269.440455 84.819826 
C 267.832491 84.819826 266.290169 85.458677 265.153167 86.595679 
C 264.016165 87.732681 263.377314 89.275003 263.377314 90.882967 
C 263.377314 92.49093 264.016165 94.033252 265.153167 95.170254 
C 266.290169 96.307256 267.832491 96.946107 269.440455 96.946107 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481668; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 430.498404 157.59327 
C 432.022637 157.59327 433.484646 156.987686 434.562442 155.90989 
C 435.640238 154.832095 436.245822 153.370085 436.245822 151.845852 
C 436.245822 150.321619 435.640238 148.859609 434.562442 147.781813 
C 433.484646 146.704018 432.022637 146.098434 430.498404 146.098434 
C 428.97417 146.098434 427.512161 146.704018 426.434365 147.781813 
C 425.35657 148.859609 424.750985 150.321619 424.750985 151.845852 
C 424.750985 153.370085 425.35657 154.832095 426.434365 155.90989 
C 427.512161 156.987686 428.97417 157.59327 430.498404 157.59327 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471365; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 889.226881 80.782967 
C 890.590216 80.782967 891.897896 80.241308 892.86192 79.277284 
C 893.825944 78.313261 894.367602 77.00558 894.367602 75.642245 
C 894.367602 74.27891 893.825944 72.97123 892.86192 72.007206 
C 891.897896 71.043183 890.590216 70.501524 889.226881 70.501524 
C 887.863546 70.501524 886.555866 71.043183 885.591842 72.007206 
C 884.627819 72.97123 884.08616 74.27891 884.08616 75.642245 
C 884.08616 77.00558 884.627819 78.313261 885.591842 79.277284 
C 886.555866 80.241308 887.863546 80.782967 889.226881 80.782967 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 294.140856 81.357408 
C 295.656535 81.357408 297.11034 80.755223 298.182087 79.683476 
C 299.253833 78.611729 299.856019 77.157924 299.856019 75.642245 
C 299.856019 74.126566 299.253833 72.672762 298.182087 71.601015 
C 297.11034 70.529268 295.656535 69.927082 294.140856 69.927082 
C 292.625177 69.927082 291.171372 70.529268 290.099625 71.601015 
C 289.027878 72.672762 288.425693 74.126566 288.425693 75.642245 
C 288.425693 77.157924 289.027878 78.611729 290.099625 79.683476 
C 291.171372 80.755223 292.625177 81.357408 294.140856 81.357408 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471365; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 787.005949 79.938632 
C 788.145364 79.938632 789.238265 79.485937 790.043953 78.680249 
C 790.849641 77.874561 791.302335 76.78166 791.302335 75.642245 
C 791.302335 74.50283 790.849641 73.409929 790.043953 72.604241 
C 789.238265 71.798553 788.145364 71.345859 787.005949 71.345859 
C 785.866534 71.345859 784.773633 71.798553 783.967945 72.604241 
C 783.162257 73.409929 782.709562 74.50283 782.709562 75.642245 
C 782.709562 76.78166 783.162257 77.874561 783.967945 78.680249 
C 784.773633 79.485937 785.866534 79.938632 787.005949 79.938632 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 392.838557 94.981701 
C 393.925554 94.981701 394.968177 94.549833 395.7368 93.78121 
C 396.505423 93.012587 396.937292 91.969964 396.937292 90.882967 
C 396.937292 89.795969 396.505423 88.753347 395.7368 87.984724 
C 394.968177 87.216101 393.925554 86.784232 392.838557 86.784232 
C 391.75156 86.784232 390.708937 87.216101 389.940314 87.984724 
C 389.171691 88.753347 388.739823 89.795969 388.739823 90.882967 
C 388.739823 91.969964 389.171691 93.012587 389.940314 93.78121 
C 390.708937 94.549833 391.75156 94.981701 392.838557 94.981701 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 605.006972 94.490692 
C 605.963752 94.490692 606.881474 94.110559 607.558019 93.434014 
C 608.234565 92.757468 608.614698 91.839747 608.614698 90.882967 
C 608.614698 89.926187 608.234565 89.008465 607.558019 88.331919 
C 606.881474 87.655374 605.963752 87.275241 605.006972 87.275241 
C 604.050192 87.275241 603.13247 87.655374 602.455925 88.331919 
C 601.779379 89.008465 601.399246 89.926187 601.399246 90.882967 
C 601.399246 91.839747 601.779379 92.757468 602.455925 93.434014 
C 603.13247 94.110559 604.050192 94.490692 605.006972 94.490692 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 299.279295 80.497686 
C 300.566973 80.497686 301.802084 79.986086 302.71261 79.07556 
C 303.623135 78.165034 304.134735 76.929923 304.134735 75.642245 
C 304.134735 74.354567 303.623135 73.119456 302.71261 72.208931 
C 301.802084 71.298405 300.566973 70.786805 299.279295 70.786805 
C 297.991617 70.786805 296.756506 71.298405 295.84598 72.208931 
C 294.935455 73.119456 294.423855 74.354567 294.423855 75.642245 
C 294.423855 76.929923 294.935455 78.165034 295.84598 79.07556 
C 296.756506 79.986086 297.991617 80.497686 299.279295 80.497686 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460b5e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 855.411418 232.580348 
C 856.613024 232.580348 857.765577 232.102944 858.615241 231.253281 
C 859.464904 230.403617 859.942307 229.251064 859.942307 228.049458 
C 859.942307 226.847853 859.464904 225.6953 858.615241 224.845636 
C 857.765577 223.995972 856.613024 223.518569 855.411418 223.518569 
C 854.209813 223.518569 853.05726 223.995972 852.207596 224.845636 
C 851.357932 225.6953 850.880529 226.847853 850.880529 228.049458 
C 850.880529 229.251064 851.357932 230.403617 852.207596 231.253281 
C 853.05726 232.102944 854.209813 232.580348 855.411418 232.580348 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 303.973788 94.987168 
C 305.062235 94.987168 306.106248 94.554723 306.875896 93.785075 
C 307.645544 93.015427 308.077989 91.971413 308.077989 90.882967 
C 308.077989 89.79452 307.645544 88.750506 306.875896 87.980858 
C 306.106248 87.21121 305.062235 86.778766 303.973788 86.778766 
C 302.885341 86.778766 301.841328 87.21121 301.07168 87.980858 
C 300.302031 88.750506 299.869587 89.79452 299.869587 90.882967 
C 299.869587 91.971413 300.302031 93.015427 301.07168 93.785075 
C 301.841328 94.554723 302.885341 94.987168 303.973788 94.987168 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 259.768099 385.54045 
C 261.116333 385.54045 262.409528 385.004791 263.362873 384.051446 
C 264.316219 383.098101 264.851878 381.804905 264.851878 380.456672 
C 264.851878 379.108438 264.316219 377.815243 263.362873 376.861897 
C 262.409528 375.908552 261.116333 375.372893 259.768099 375.372893 
C 258.419865 375.372893 257.12667 375.908552 256.173325 376.861897 
C 255.21998 377.815243 254.684321 379.108438 254.684321 380.456672 
C 254.684321 381.804905 255.21998 383.098101 256.173325 384.051446 
C 257.12667 385.004791 258.419865 385.54045 259.768099 385.54045 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 360.118791 248.025744 
C 361.374677 248.025744 362.579295 247.526775 363.467341 246.638729 
C 364.355386 245.750684 364.854355 244.546066 364.854355 243.29018 
C 364.854355 242.034293 364.355386 240.829676 363.467341 239.94163 
C 362.579295 239.053584 361.374677 238.554615 360.118791 238.554615 
C 358.862905 238.554615 357.658287 239.053584 356.770241 239.94163 
C 355.882196 240.829676 355.383227 242.034293 355.383227 243.29018 
C 355.383227 244.546066 355.882196 245.750684 356.770241 246.638729 
C 357.658287 247.526775 358.862905 248.025744 360.118791 248.025744 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460a5d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 536.403143 211.770567 
C 540.169704 211.770567 543.782503 210.274096 546.445863 207.610736 
C 549.109224 204.947375 550.605694 201.334576 550.605694 197.568016 
C 550.605694 193.801455 549.109224 190.188656 546.445863 187.525296 
C 543.782503 184.861935 540.169704 183.365465 536.403143 183.365465 
C 532.636583 183.365465 529.023784 184.861935 526.360423 187.525296 
C 523.697063 190.188656 522.200593 193.801455 522.200593 197.568016 
C 522.200593 201.334576 523.697063 204.947375 526.360423 207.610736 
C 529.023784 210.274096 532.636583 211.770567 536.403143 211.770567 
z
" clip-path="url(#p8a32aafd77)" style="fill: #1fa088; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 647.153507 171.107041 
C 648.219747 171.107041 649.242461 170.683419 649.996407 169.929473 
C 650.750353 169.175527 651.173975 168.152814 651.173975 167.086573 
C 651.173975 166.020333 650.750353 164.997619 649.996407 164.243673 
C 649.242461 163.489727 648.219747 163.066106 647.153507 163.066106 
C 646.087266 163.066106 645.064553 163.489727 644.310607 164.243673 
C 643.556661 164.997619 643.133039 166.020333 643.133039 167.086573 
C 643.133039 168.152814 643.556661 169.175527 644.310607 169.929473 
C 645.064553 170.683419 646.087266 171.107041 647.153507 171.107041 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 364.369338 263.057333 
C 365.569762 263.057333 366.721181 262.5804 367.570009 261.731572 
C 368.418837 260.882744 368.89577 259.731325 368.89577 258.530901 
C 368.89577 257.330477 368.418837 256.179058 367.570009 255.33023 
C 366.721181 254.481402 365.569762 254.004469 364.369338 254.004469 
C 363.168914 254.004469 362.017495 254.481402 361.168667 255.33023 
C 360.319839 256.179058 359.842906 257.330477 359.842906 258.530901 
C 359.842906 259.731325 360.319839 260.882744 361.168667 261.731572 
C 362.017495 262.5804 363.168914 263.057333 364.369338 263.057333 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 448.407375 170.894632 
C 449.417284 170.894632 450.385966 170.493391 451.100079 169.779278 
C 451.814193 169.065164 452.215434 168.096482 452.215434 167.086573 
C 452.215434 166.076664 451.814193 165.107982 451.100079 164.393869 
C 450.385966 163.679755 449.417284 163.278514 448.407375 163.278514 
C 447.397466 163.278514 446.428784 163.679755 445.71467 164.393869 
C 445.000557 165.107982 444.599316 166.076664 444.599316 167.086573 
C 444.599316 168.096482 445.000557 169.065164 445.71467 169.779278 
C 446.428784 170.493391 447.397466 170.894632 448.407375 170.894632 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 383.288995 140.602605 
C 384.349138 140.602605 385.366002 140.181406 386.115636 139.431772 
C 386.86527 138.682138 387.286469 137.665273 387.286469 136.605131 
C 387.286469 135.544988 386.86527 134.528123 386.115636 133.778489 
C 385.366002 133.028855 384.349138 132.607656 383.288995 132.607656 
C 382.228852 132.607656 381.211988 133.028855 380.462354 133.778489 
C 379.71272 134.528123 379.291521 135.544988 379.291521 136.605131 
C 379.291521 137.665273 379.71272 138.682138 380.462354 139.431772 
C 381.211988 140.181406 382.228852 140.602605 383.288995 140.602605 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 266.427289 295.489903 
C 268.145158 295.489903 269.792899 294.807387 271.007616 293.59267 
C 272.222332 292.377953 272.904849 290.730213 272.904849 289.012344 
C 272.904849 287.294475 272.222332 285.646734 271.007616 284.432018 
C 269.792899 283.217301 268.145158 282.534784 266.427289 282.534784 
C 264.709421 282.534784 263.06168 283.217301 261.846963 284.432018 
C 260.632247 285.646734 259.94973 287.294475 259.94973 289.012344 
C 259.94973 290.730213 260.632247 292.377953 261.846963 293.59267 
C 263.06168 294.807387 264.709421 295.489903 266.427289 295.489903 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481b6d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 634.033485 79.329174 
C 635.01127 79.329174 635.949139 78.940696 636.640537 78.249298 
C 637.331936 77.557899 637.720414 76.62003 637.720414 75.642245 
C 637.720414 74.66446 637.331936 73.726591 636.640537 73.035193 
C 635.949139 72.343795 635.01127 71.955317 634.033485 71.955317 
C 633.0557 71.955317 632.117831 72.343795 631.426433 73.035193 
C 630.735035 73.726591 630.346557 74.66446 630.346557 75.642245 
C 630.346557 76.62003 630.735035 77.557899 631.426433 78.249298 
C 632.117831 78.940696 633.0557 79.329174 634.033485 79.329174 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 465.248987 185.451006 
C 466.077405 185.451006 466.872004 185.121872 467.457784 184.536092 
C 468.043564 183.950312 468.372698 183.155712 468.372698 182.327295 
C 468.372698 181.498877 468.043564 180.704277 467.457784 180.118497 
C 466.872004 179.532717 466.077405 179.203583 465.248987 179.203583 
C 464.420569 179.203583 463.625969 179.532717 463.040189 180.118497 
C 462.454409 180.704277 462.125276 181.498877 462.125276 182.327295 
C 462.125276 183.155712 462.454409 183.950312 463.040189 184.536092 
C 463.625969 185.121872 464.420569 185.451006 465.248987 185.451006 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 227.690638 125.704917 
C 228.841754 125.704917 229.945878 125.247574 230.75984 124.433612 
C 231.573802 123.61965 232.031145 122.515525 232.031145 121.364409 
C 232.031145 120.213293 231.573802 119.109169 230.75984 118.295207 
C 229.945878 117.481245 228.841754 117.023902 227.690638 117.023902 
C 226.539522 117.023902 225.435397 117.481245 224.621435 118.295207 
C 223.807474 119.109169 223.35013 120.213293 223.35013 121.364409 
C 223.35013 122.515525 223.807474 123.61965 224.621435 124.433612 
C 225.435397 125.247574 226.539522 125.704917 227.690638 125.704917 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 297.097347 231.90849 
C 298.120775 231.90849 299.102423 231.501878 299.826095 230.778206 
C 300.549767 230.054534 300.956379 229.072886 300.956379 228.049458 
C 300.956379 227.026031 300.549767 226.044383 299.826095 225.320711 
C 299.102423 224.597039 298.120775 224.190427 297.097347 224.190427 
C 296.07392 224.190427 295.092272 224.597039 294.3686 225.320711 
C 293.644928 226.044383 293.238316 227.026031 293.238316 228.049458 
C 293.238316 229.072886 293.644928 230.054534 294.3686 230.778206 
C 295.092272 231.501878 296.07392 231.90849 297.097347 231.90849 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 382.14607 216.251139 
C 383.059006 216.251139 383.934673 215.888426 384.580216 215.242883 
C 385.225759 214.59734 385.588472 213.721673 385.588472 212.808737 
C 385.588472 211.895801 385.225759 211.020134 384.580216 210.374591 
C 383.934673 209.729048 383.059006 209.366335 382.14607 209.366335 
C 381.233134 209.366335 380.357467 209.729048 379.711924 210.374591 
C 379.066381 211.020134 378.703668 211.895801 378.703668 212.808737 
C 378.703668 213.721673 379.066381 214.59734 379.711924 215.242883 
C 380.357467 215.888426 381.233134 216.251139 382.14607 216.251139 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 311.983708 124.205872 
C 312.737272 124.205872 313.460074 123.906477 313.992925 123.373627 
C 314.525776 122.840776 314.82517 122.117974 314.82517 121.364409 
C 314.82517 120.610845 314.525776 119.888043 313.992925 119.355192 
C 313.460074 118.822341 312.737272 118.522947 311.983708 118.522947 
C 311.230143 118.522947 310.507341 118.822341 309.97449 119.355192 
C 309.44164 119.888043 309.142245 120.610845 309.142245 121.364409 
C 309.142245 122.117974 309.44164 122.840776 309.97449 123.373627 
C 310.507341 123.906477 311.230143 124.205872 311.983708 124.205872 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 319.379659 206.699801 
C 321.801437 206.699801 324.124351 205.737619 325.836807 204.025163 
C 327.549262 202.312708 328.511445 199.989794 328.511445 197.568016 
C 328.511445 195.146238 327.549262 192.823324 325.836807 191.110869 
C 324.124351 189.398413 321.801437 188.436231 319.379659 188.436231 
C 316.957882 188.436231 314.634968 189.398413 312.922512 191.110869 
C 311.210057 192.823324 310.247874 195.146238 310.247874 197.568016 
C 310.247874 199.989794 311.210057 202.312708 312.922512 204.025163 
C 314.634968 205.737619 316.957882 206.699801 319.379659 206.699801 
z
" clip-path="url(#p8a32aafd77)" style="fill: #424086; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 434.871744 156.823431 
C 436.191814 156.823431 437.457994 156.298962 438.391424 155.365532 
C 439.324854 154.432102 439.849323 153.165921 439.849323 151.845852 
C 439.849323 150.525782 439.324854 149.259602 438.391424 148.326172 
C 437.457994 147.392742 436.191814 146.868273 434.871744 146.868273 
C 433.551675 146.868273 432.285494 147.392742 431.352064 148.326172 
C 430.418634 149.259602 429.894165 150.525782 429.894165 151.845852 
C 429.894165 153.165921 430.418634 154.432102 431.352064 155.365532 
C 432.285494 156.298962 433.551675 156.823431 434.871744 156.823431 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460b5e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 301.300666 154.55883 
C 302.020156 154.55883 302.710275 154.272974 303.219031 153.764217 
C 303.727788 153.255461 304.013644 152.565342 304.013644 151.845852 
C 304.013644 151.126362 303.727788 150.436243 303.219031 149.927487 
C 302.710275 149.41873 302.020156 149.132874 301.300666 149.132874 
C 300.581176 149.132874 299.891057 149.41873 299.382301 149.927487 
C 298.873544 150.436243 298.587688 151.126362 298.587688 151.845852 
C 298.587688 152.565342 298.873544 153.255461 299.382301 153.764217 
C 299.891057 154.272974 300.581176 154.55883 301.300666 154.55883 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 335.059455 235.020874 
C 336.908296 235.020874 338.681662 234.286322 339.98899 232.978994 
C 341.296318 231.671666 342.030871 229.898299 342.030871 228.049458 
C 342.030871 226.200617 341.296318 224.427251 339.98899 223.119923 
C 338.681662 221.812595 336.908296 221.078043 335.059455 221.078043 
C 333.210614 221.078043 331.437248 221.812595 330.12992 223.119923 
C 328.822592 224.427251 328.088039 226.200617 328.088039 228.049458 
C 328.088039 229.898299 328.822592 231.671666 330.12992 232.978994 
C 331.437248 234.286322 333.210614 235.020874 335.059455 235.020874 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482071; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 195.717079 140.064225 
C 196.634441 140.064225 197.514355 139.699753 198.163028 139.05108 
C 198.811701 138.402406 199.176173 137.522493 199.176173 136.605131 
C 199.176173 135.687768 198.811701 134.807855 198.163028 134.159181 
C 197.514355 133.510508 196.634441 133.146036 195.717079 133.146036 
C 194.799716 133.146036 193.919803 133.510508 193.27113 134.159181 
C 192.622456 134.807855 192.257984 135.687768 192.257984 136.605131 
C 192.257984 137.522493 192.622456 138.402406 193.27113 139.05108 
C 193.919803 139.699753 194.799716 140.064225 195.717079 140.064225 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 381.853255 400.485589 
C 383.123099 400.485589 384.341105 399.981075 385.239021 399.083159 
C 386.136937 398.185243 386.641451 396.967238 386.641451 395.697393 
C 386.641451 394.427548 386.136937 393.209542 385.239021 392.311627 
C 384.341105 391.413711 383.123099 390.909196 381.853255 390.909196 
C 380.58341 390.909196 379.365404 391.413711 378.467488 392.311627 
C 377.569573 393.209542 377.065058 394.427548 377.065058 395.697393 
C 377.065058 396.967238 377.569573 398.185243 378.467488 399.083159 
C 379.365404 399.981075 380.58341 400.485589 381.853255 400.485589 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460a5d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 562.274806 414.388891 
C 563.189963 414.388891 564.06776 414.025295 564.714874 413.378182 
C 565.361987 412.731068 565.725583 411.853271 565.725583 410.938114 
C 565.725583 410.022958 565.361987 409.14516 564.714874 408.498047 
C 564.06776 407.850933 563.189963 407.487338 562.274806 407.487338 
C 561.35965 407.487338 560.481852 407.850933 559.834739 408.498047 
C 559.187625 409.14516 558.82403 410.022958 558.82403 410.938114 
C 558.82403 411.853271 559.187625 412.731068 559.834739 413.378182 
C 560.481852 414.025295 561.35965 414.388891 562.274806 414.388891 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 211.368537 79.48235 
C 212.386945 79.48235 213.363778 79.077732 214.083901 78.357609 
C 214.804024 77.637486 215.208642 76.660653 215.208642 75.642245 
C 215.208642 74.623838 214.804024 73.647004 214.083901 72.926881 
C 213.363778 72.206758 212.386945 71.802141 211.368537 71.802141 
C 210.35013 71.802141 209.373296 72.206758 208.653173 72.926881 
C 207.933051 73.647004 207.528433 74.623838 207.528433 75.642245 
C 207.528433 76.660653 207.933051 77.637486 208.653173 78.357609 
C 209.373296 79.077732 210.35013 79.48235 211.368537 79.48235 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 308.828857 339.179194 
C 310.007602 339.179194 311.138227 338.710874 311.971725 337.877375 
C 312.805223 337.043877 313.273543 335.913252 313.273543 334.734508 
C 313.273543 333.555763 312.805223 332.425138 311.971725 331.59164 
C 311.138227 330.758142 310.007602 330.289822 308.828857 330.289822 
C 307.650113 330.289822 306.519488 330.758142 305.68599 331.59164 
C 304.852491 332.425138 304.384171 333.555763 304.384171 334.734508 
C 304.384171 335.913252 304.852491 337.043877 305.68599 337.877375 
C 306.519488 338.710874 307.650113 339.179194 308.828857 339.179194 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 217.319303 79.580895 
C 218.363845 79.580895 219.365746 79.165894 220.104349 78.427291 
C 220.842951 77.688688 221.257952 76.686787 221.257952 75.642245 
C 221.257952 74.597703 220.842951 73.595802 220.104349 72.8572 
C 219.365746 72.118597 218.363845 71.703596 217.319303 71.703596 
C 216.274761 71.703596 215.27286 72.118597 214.534258 72.8572 
C 213.795655 73.595802 213.380654 74.597703 213.380654 75.642245 
C 213.380654 76.686787 213.795655 77.688688 214.534258 78.427291 
C 215.27286 79.165894 216.274761 79.580895 217.319303 79.580895 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 746.701318 80.828429 
C 748.07671 80.828429 749.395954 80.28198 750.368503 79.309431 
C 751.341052 78.336882 751.887501 77.017637 751.887501 75.642245 
C 751.887501 74.266853 751.341052 72.947609 750.368503 71.97506 
C 749.395954 71.002511 748.07671 70.456062 746.701318 70.456062 
C 745.325926 70.456062 744.006681 71.002511 743.034132 71.97506 
C 742.061583 72.947609 741.515134 74.266853 741.515134 75.642245 
C 741.515134 77.017637 742.061583 78.336882 743.034132 79.309431 
C 744.006681 80.28198 745.325926 80.828429 746.701318 80.828429 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 363.868718 216.680267 
C 364.89546 216.680267 365.880287 216.272338 366.606303 215.546322 
C 367.332319 214.820306 367.740248 213.835479 367.740248 212.808737 
C 367.740248 211.781995 367.332319 210.797168 366.606303 210.071152 
C 365.880287 209.345136 364.89546 208.937207 363.868718 208.937207 
C 362.841976 208.937207 361.857149 209.345136 361.131133 210.071152 
C 360.405117 210.797168 359.997188 211.781995 359.997188 212.808737 
C 359.997188 213.835479 360.405117 214.820306 361.131133 215.546322 
C 361.857149 216.272338 362.841976 216.680267 363.868718 216.680267 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 202.329041 216.019126 
C 203.180446 216.019126 203.997094 215.680859 204.599129 215.078825 
C 205.201163 214.476791 205.53943 213.660142 205.53943 212.808737 
C 205.53943 211.957332 205.201163 211.140684 204.599129 210.538649 
C 203.997094 209.936615 203.180446 209.598348 202.329041 209.598348 
C 201.477636 209.598348 200.660987 209.936615 200.058953 210.538649 
C 199.456919 211.140684 199.118652 211.957332 199.118652 212.808737 
C 199.118652 213.660142 199.456919 214.476791 200.058953 215.078825 
C 200.660987 215.680859 201.477636 216.019126 202.329041 216.019126 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 841.564081 431.768008 
C 843.046347 431.768008 844.468102 431.179097 845.516222 430.130977 
C 846.564343 429.082857 847.153253 427.661101 847.153253 426.178836 
C 847.153253 424.69657 846.564343 423.274814 845.516222 422.226694 
C 844.468102 421.178574 843.046347 420.589663 841.564081 420.589663 
C 840.081815 420.589663 838.66006 421.178574 837.611939 422.226694 
C 836.563819 423.274814 835.974909 424.69657 835.974909 426.178836 
C 835.974909 427.661101 836.563819 429.082857 837.611939 430.130977 
C 838.66006 431.179097 840.081815 431.768008 841.564081 431.768008 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471164; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 213.720507 217.494723 
C 214.963245 217.494723 216.155251 217.000978 217.033999 216.12223 
C 217.912748 215.243481 218.406493 214.051475 218.406493 212.808737 
C 218.406493 211.565999 217.912748 210.373993 217.033999 209.495245 
C 216.155251 208.616496 214.963245 208.122751 213.720507 208.122751 
C 212.477769 208.122751 211.285763 208.616496 210.407014 209.495245 
C 209.528266 210.373993 209.034521 211.565999 209.034521 212.808737 
C 209.034521 214.051475 209.528266 215.243481 210.407014 216.12223 
C 211.285763 217.000978 212.477769 217.494723 213.720507 217.494723 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460a5d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 575.035893 279.418364 
C 576.533426 279.418364 577.969826 278.823387 579.028742 277.764471 
C 580.087658 276.705555 580.682634 275.269156 580.682634 273.771622 
C 580.682634 272.274089 580.087658 270.837689 579.028742 269.778773 
C 577.969826 268.719857 576.533426 268.124881 575.035893 268.124881 
C 573.53836 268.124881 572.10196 268.719857 571.043044 269.778773 
C 569.984128 270.837689 569.389152 272.274089 569.389152 273.771622 
C 569.389152 275.269156 569.984128 276.705555 571.043044 277.764471 
C 572.10196 278.823387 573.53836 279.418364 575.035893 279.418364 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471164; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 385.130899 231.310378 
C 385.995705 231.310378 386.825207 230.966787 387.436717 230.355277 
C 388.048227 229.743767 388.391818 228.914264 388.391818 228.049458 
C 388.391818 227.184653 388.048227 226.35515 387.436717 225.74364 
C 386.825207 225.13213 385.995705 224.788539 385.130899 224.788539 
C 384.266093 224.788539 383.436591 225.13213 382.82508 225.74364 
C 382.21357 226.35515 381.869979 227.184653 381.869979 228.049458 
C 381.869979 228.914264 382.21357 229.743767 382.82508 230.355277 
C 383.436591 230.966787 384.266093 231.310378 385.130899 231.310378 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 364.699936 97.415801 
C 366.432464 97.415801 368.094265 96.72746 369.319347 95.502378 
C 370.54443 94.277296 371.23277 92.615494 371.23277 90.882967 
C 371.23277 89.150439 370.54443 87.488637 369.319347 86.263555 
C 368.094265 85.038473 366.432464 84.350132 364.699936 84.350132 
C 362.967408 84.350132 361.305607 85.038473 360.080525 86.263555 
C 358.855443 87.488637 358.167102 89.150439 358.167102 90.882967 
C 358.167102 92.615494 358.855443 94.277296 360.080525 95.502378 
C 361.305607 96.72746 362.967408 97.415801 364.699936 97.415801 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481b6d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 219.964088 128.632228 
C 221.891536 128.632228 223.740301 127.866445 225.103212 126.503534 
C 226.466124 125.140622 227.231907 123.291857 227.231907 121.364409 
C 227.231907 119.436961 226.466124 117.588197 225.103212 116.225285 
C 223.740301 114.862373 221.891536 114.09659 219.964088 114.09659 
C 218.03664 114.09659 216.187875 114.862373 214.824964 116.225285 
C 213.462052 117.588197 212.696269 119.436961 212.696269 121.364409 
C 212.696269 123.291857 213.462052 125.140622 214.824964 126.503534 
C 216.187875 127.866445 218.03664 128.632228 219.964088 128.632228 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482475; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 815.626299 97.873851 
C 817.480303 97.873851 819.258621 97.137248 820.5696 95.826269 
C 821.88058 94.51529 822.617183 92.736971 822.617183 90.882967 
C 822.617183 89.028962 821.88058 87.250644 820.5696 85.939665 
C 819.258621 84.628686 817.480303 83.892082 815.626299 83.892082 
C 813.772294 83.892082 811.993976 84.628686 810.682997 85.939665 
C 809.372018 87.250644 808.635414 89.028962 808.635414 90.882967 
C 808.635414 92.736971 809.372018 94.51529 810.682997 95.826269 
C 811.993976 97.137248 813.772294 97.873851 815.626299 97.873851 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482071; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 778.174257 127.825003 
C 779.887626 127.825003 781.531051 127.144274 782.742586 125.932739 
C 783.954121 124.721204 784.63485 123.077779 784.63485 121.364409 
C 784.63485 119.65104 783.954121 118.007615 782.742586 116.79608 
C 781.531051 115.584544 779.887626 114.903816 778.174257 114.903816 
C 776.460887 114.903816 774.817462 115.584544 773.605927 116.79608 
C 772.394392 118.007615 771.713663 119.65104 771.713663 121.364409 
C 771.713663 123.077779 772.394392 124.721204 773.605927 125.932739 
C 774.817462 127.144274 776.460887 127.825003 778.174257 127.825003 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481b6d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 338.837719 99.582389 
C 341.144833 99.582389 343.357764 98.665763 344.989139 97.034387 
C 346.620515 95.403011 347.537141 93.19008 347.537141 90.882967 
C 347.537141 88.575853 346.620515 86.362922 344.989139 84.731546 
C 343.357764 83.10017 341.144833 82.183544 338.837719 82.183544 
C 336.530605 82.183544 334.317674 83.10017 332.686299 84.731546 
C 331.054923 86.362922 330.138297 88.575853 330.138297 90.882967 
C 330.138297 93.19008 331.054923 95.403011 332.686299 97.034387 
C 334.317674 98.665763 336.530605 99.582389 338.837719 99.582389 
z
" clip-path="url(#p8a32aafd77)" style="fill: #443983; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 257.13276 129.051496 
C 259.171399 129.051496 261.126816 128.241536 262.568352 126.800001 
C 264.009887 125.358465 264.819847 123.403049 264.819847 121.364409 
C 264.819847 119.32577 264.009887 117.370353 262.568352 115.928818 
C 261.126816 114.487282 259.171399 113.677322 257.13276 113.677322 
C 255.094121 113.677322 253.138704 114.487282 251.697169 115.928818 
C 250.255633 117.370353 249.445673 119.32577 249.445673 121.364409 
C 249.445673 123.403049 250.255633 125.358465 251.697169 126.800001 
C 253.138704 128.241536 255.094121 129.051496 257.13276 129.051496 
z
" clip-path="url(#p8a32aafd77)" style="fill: #472a7a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 328.91033 112.654134 
C 330.642225 112.654134 332.303418 111.966045 333.528053 110.74141 
C 334.752687 109.516776 335.440776 107.855582 335.440776 106.123688 
C 335.440776 104.391794 334.752687 102.7306 333.528053 101.505966 
C 332.303418 100.281331 330.642225 99.593242 328.91033 99.593242 
C 327.178436 99.593242 325.517242 100.281331 324.292608 101.505966 
C 323.067974 102.7306 322.379885 104.391794 322.379885 106.123688 
C 322.379885 107.855582 323.067974 109.516776 324.292608 110.74141 
C 325.517242 111.966045 327.178436 112.654134 328.91033 112.654134 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481b6d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 374.891803 161.528107 
C 377.459567 161.528107 379.922508 160.507924 381.738192 158.69224 
C 383.553875 156.876557 384.574059 154.413616 384.574059 151.845852 
C 384.574059 149.278088 383.553875 146.815147 381.738192 144.999463 
C 379.922508 143.18378 377.459567 142.163596 374.891803 142.163596 
C 372.324039 142.163596 369.861098 143.18378 368.045415 144.999463 
C 366.229731 146.815147 365.209548 149.278088 365.209548 151.845852 
C 365.209548 154.413616 366.229731 156.876557 368.045415 158.69224 
C 369.861098 160.507924 372.324039 161.528107 374.891803 161.528107 
z
" clip-path="url(#p8a32aafd77)" style="fill: #3e4989; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 424.160366 97.051829 
C 425.796367 97.051829 427.365583 96.401839 428.52241 95.245011 
C 429.679238 94.088184 430.329229 92.518968 430.329229 90.882967 
C 430.329229 89.246965 429.679238 87.67775 428.52241 86.520922 
C 427.365583 85.364094 425.796367 84.714104 424.160366 84.714104 
C 422.524364 84.714104 420.955149 85.364094 419.798321 86.520922 
C 418.641493 87.67775 417.991503 89.246965 417.991503 90.882967 
C 417.991503 92.518968 418.641493 94.088184 419.798321 95.245011 
C 420.955149 96.401839 422.524364 97.051829 424.160366 97.051829 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481769; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 363.150848 96.051748 
C 364.521625 96.051748 365.836442 95.507132 366.805728 94.537847 
C 367.775013 93.568561 368.319629 92.253743 368.319629 90.882967 
C 368.319629 89.51219 367.775013 88.197372 366.805728 87.228087 
C 365.836442 86.258801 364.521625 85.714186 363.150848 85.714186 
C 361.780071 85.714186 360.465253 86.258801 359.495968 87.228087 
C 358.526682 88.197372 357.982067 89.51219 357.982067 90.882967 
C 357.982067 92.253743 358.526682 93.568561 359.495968 94.537847 
C 360.465253 95.507132 361.780071 96.051748 363.150848 96.051748 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 258.587392 143.384065 
C 260.385186 143.384065 262.109589 142.669793 263.380822 141.398561 
C 264.652054 140.127328 265.366326 138.402925 265.366326 136.605131 
C 265.366326 134.807336 264.652054 133.082933 263.380822 131.8117 
C 262.109589 130.540468 260.385186 129.826197 258.587392 129.826197 
C 256.789597 129.826197 255.065194 130.540468 253.793962 131.8117 
C 252.522729 133.082933 251.808458 134.807336 251.808458 136.605131 
C 251.808458 138.402925 252.522729 140.127328 253.793962 141.398561 
C 255.065194 142.669793 256.789597 143.384065 258.587392 143.384065 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481d6f; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 870.477246 98.219693 
C 872.422969 98.219693 874.289261 97.446649 875.665095 96.070815 
C 877.040928 94.694982 877.813972 92.828689 877.813972 90.882967 
C 877.813972 88.937244 877.040928 87.070951 875.665095 85.695118 
C 874.289261 84.319284 872.422969 83.546241 870.477246 83.546241 
C 868.531524 83.546241 866.665231 84.319284 865.289397 85.695118 
C 863.913564 87.070951 863.14052 88.937244 863.14052 90.882967 
C 863.14052 92.828689 863.913564 94.694982 865.289397 96.070815 
C 866.665231 97.446649 868.531524 98.219693 870.477246 98.219693 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482576; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 449.663648 98.219693 
C 451.60937 98.219693 453.475663 97.446649 454.851496 96.070815 
C 456.22733 94.694982 457.000374 92.828689 457.000374 90.882967 
C 457.000374 88.937244 456.22733 87.070951 454.851496 85.695118 
C 453.475663 84.319284 451.60937 83.546241 449.663648 83.546241 
C 447.717925 83.546241 445.851633 84.319284 444.475799 85.695118 
C 443.099965 87.070951 442.326922 88.937244 442.326922 90.882967 
C 442.326922 92.828689 443.099965 94.694982 444.475799 96.070815 
C 445.851633 97.446649 447.717925 98.219693 449.663648 98.219693 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482576; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 326.284437 251.928899 
C 328.575452 251.928899 330.772942 251.018669 332.392934 249.398677 
C 334.012926 247.778685 334.923156 245.581195 334.923156 243.29018 
C 334.923156 240.999165 334.012926 238.801675 332.392934 237.181683 
C 330.772942 235.56169 328.575452 234.65146 326.284437 234.65146 
C 323.993422 234.65146 321.795932 235.56169 320.17594 237.181683 
C 318.555947 238.801675 317.645717 240.999165 317.645717 243.29018 
C 317.645717 245.581195 318.555947 247.778685 320.17594 249.398677 
C 321.795932 251.018669 323.993422 251.928899 326.284437 251.928899 
z
" clip-path="url(#p8a32aafd77)" style="fill: #453882; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 220.502491 81.459035 
C 222.045121 81.459035 223.524778 80.846142 224.615582 79.755337 
C 225.706387 78.664532 226.319281 77.184876 226.319281 75.642245 
C 226.319281 74.099615 225.706387 72.619958 224.615582 71.529154 
C 223.524778 70.438349 222.045121 69.825455 220.502491 69.825455 
C 218.95986 69.825455 217.480204 70.438349 216.389399 71.529154 
C 215.298594 72.619958 214.6857 74.099615 214.6857 75.642245 
C 214.6857 77.184876 215.298594 78.664532 216.389399 79.755337 
C 217.480204 80.846142 218.95986 81.459035 220.502491 81.459035 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481467; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 587.334142 142.967446 
C 589.021448 142.967446 590.639873 142.297073 591.832979 141.103967 
C 593.026084 139.910862 593.696458 138.292436 593.696458 136.605131 
C 593.696458 134.917825 593.026084 133.299399 591.832979 132.106294 
C 590.639873 130.913188 589.021448 130.242815 587.334142 130.242815 
C 585.646836 130.242815 584.028411 130.913188 582.835305 132.106294 
C 581.6422 133.299399 580.971826 134.917825 580.971826 136.605131 
C 580.971826 138.292436 581.6422 139.910862 582.835305 141.103967 
C 584.028411 142.297073 585.646836 142.967446 587.334142 142.967446 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481a6c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 290.570396 81.855193 
C 292.21809 81.855193 293.798519 81.200558 294.963614 80.035463 
C 296.128709 78.870368 296.783345 77.289938 296.783345 75.642245 
C 296.783345 73.994552 296.128709 72.414122 294.963614 71.249028 
C 293.798519 70.083933 292.21809 69.429297 290.570396 69.429297 
C 288.922703 69.429297 287.342274 70.083933 286.177179 71.249028 
C 285.012084 72.414122 284.357448 73.994552 284.357448 75.642245 
C 284.357448 77.289938 285.012084 78.870368 286.177179 80.035463 
C 287.342274 81.200558 288.922703 81.855193 290.570396 81.855193 
z
" clip-path="url(#p8a32aafd77)" style="fill: #48186a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 607.991801 111.553238 
C 609.431734 111.553238 610.812885 110.981146 611.831072 109.96296 
C 612.849259 108.944773 613.421351 107.563621 613.421351 106.123688 
C 613.421351 104.683754 612.849259 103.302603 611.831072 102.284416 
C 610.812885 101.26623 609.431734 100.694138 607.991801 100.694138 
C 606.551867 100.694138 605.170716 101.26623 604.152529 102.284416 
C 603.134342 103.302603 602.562251 104.683754 602.562251 106.123688 
C 602.562251 107.563621 603.134342 108.944773 604.152529 109.96296 
C 605.170716 110.981146 606.551867 111.553238 607.991801 111.553238 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471063; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 541.28655 176.144931 
C 543.688854 176.144931 545.99309 175.190485 547.691776 173.491799 
C 549.390462 171.793114 550.344907 169.488878 550.344907 167.086573 
C 550.344907 164.684269 549.390462 162.380033 547.691776 160.681347 
C 545.99309 158.982661 543.688854 158.028215 541.28655 158.028215 
C 538.884245 158.028215 536.580009 158.982661 534.881323 160.681347 
C 533.182638 162.380033 532.228192 164.684269 532.228192 167.086573 
C 532.228192 169.488878 533.182638 171.793114 534.881323 173.491799 
C 536.580009 175.190485 538.884245 176.144931 541.28655 176.144931 
z
" clip-path="url(#p8a32aafd77)" style="fill: #423f85; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 374.410075 82.729308 
C 376.289586 82.729308 378.09237 81.982571 379.421385 80.653556 
C 380.7504 79.324541 381.497138 77.521756 381.497138 75.642245 
C 381.497138 73.762734 380.7504 71.95995 379.421385 70.630935 
C 378.09237 69.30192 376.289586 68.555182 374.410075 68.555182 
C 372.530563 68.555182 370.727779 69.30192 369.398764 70.630935 
C 368.069749 71.95995 367.323011 73.762734 367.323011 75.642245 
C 367.323011 77.521756 368.069749 79.324541 369.398764 80.653556 
C 370.727779 81.982571 372.530563 82.729308 374.410075 82.729308 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482173; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 434.134983 325.401045 
C 435.701606 325.401045 437.204275 324.778619 438.312045 323.670849 
C 439.419815 322.563079 440.042242 321.06041 440.042242 319.493786 
C 440.042242 317.927163 439.419815 316.424494 438.312045 315.316724 
C 437.204275 314.208954 435.701606 313.586528 434.134983 313.586528 
C 432.568359 313.586528 431.06569 314.208954 429.95792 315.316724 
C 428.85015 316.424494 428.227724 317.927163 428.227724 319.493786 
C 428.227724 321.06041 428.85015 322.563079 429.95792 323.670849 
C 431.06569 324.778619 432.568359 325.401045 434.134983 325.401045 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481467; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 380.729221 110.132696 
C 381.792422 110.132696 382.812221 109.710281 383.564018 108.958485 
C 384.315815 108.206688 384.738229 107.186889 384.738229 106.123688 
C 384.738229 105.060487 384.315815 104.040688 383.564018 103.288891 
C 382.812221 102.537094 381.792422 102.11468 380.729221 102.11468 
C 379.66602 102.11468 378.646221 102.537094 377.894424 103.288891 
C 377.142628 104.040688 376.720213 105.060487 376.720213 106.123688 
C 376.720213 107.186889 377.142628 108.206688 377.894424 108.958485 
C 378.646221 109.710281 379.66602 110.132696 380.729221 110.132696 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 768.473564 157.217138 
C 769.898045 157.217138 771.264376 156.651185 772.271636 155.643924 
C 773.278897 154.636664 773.84485 153.270334 773.84485 151.845852 
C 773.84485 150.42137 773.278897 149.05504 772.271636 148.047779 
C 771.264376 147.040519 769.898045 146.474566 768.473564 146.474566 
C 767.049082 146.474566 765.682752 147.040519 764.675491 148.047779 
C 763.668231 149.05504 763.102278 150.42137 763.102278 151.845852 
C 763.102278 153.270334 763.668231 154.636664 764.675491 155.643924 
C 765.682752 156.651185 767.049082 157.217138 768.473564 157.217138 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471063; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 246.978676 103.408067 
C 250.300371 103.408067 253.486466 102.088344 255.835259 99.73955 
C 258.184053 97.390757 259.503776 94.204662 259.503776 90.882967 
C 259.503776 87.561271 258.184053 84.375176 255.835259 82.026383 
C 253.486466 79.67759 250.300371 78.357866 246.978676 78.357866 
C 243.65698 78.357866 240.470885 79.67759 238.122092 82.026383 
C 235.773298 84.375176 234.453575 87.561271 234.453575 90.882967 
C 234.453575 94.204662 235.773298 97.390757 238.122092 99.73955 
C 240.470885 102.088344 243.65698 103.408067 246.978676 103.408067 
z
" clip-path="url(#p8a32aafd77)" style="fill: #287c8e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 522.234653 186.794985 
C 523.419499 186.794985 524.555976 186.324241 525.393788 185.486429 
C 526.2316 184.648617 526.702344 183.51214 526.702344 182.327295 
C 526.702344 181.142449 526.2316 180.005972 525.393788 179.16816 
C 524.555976 178.330348 523.419499 177.859604 522.234653 177.859604 
C 521.049808 177.859604 519.913331 178.330348 519.075519 179.16816 
C 518.237707 180.005972 517.766963 181.142449 517.766963 182.327295 
C 517.766963 183.51214 518.237707 184.648617 519.075519 185.486429 
C 519.913331 186.324241 521.049808 186.794985 522.234653 186.794985 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 369.753364 112.438496 
C 371.428071 112.438496 373.034412 111.773128 374.218608 110.588932 
C 375.402805 109.404735 376.068173 107.798395 376.068173 106.123688 
C 376.068173 104.448981 375.402805 102.842641 374.218608 101.658444 
C 373.034412 100.474247 371.428071 99.808879 369.753364 99.808879 
C 368.078657 99.808879 366.472317 100.474247 365.28812 101.658444 
C 364.103924 102.842641 363.438556 104.448981 363.438556 106.123688 
C 363.438556 107.798395 364.103924 109.404735 365.28812 110.588932 
C 366.472317 111.773128 368.078657 112.438496 369.753364 112.438496 
z
" clip-path="url(#p8a32aafd77)" style="fill: #48186a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 271.055663 112.958754 
C 272.868344 112.958754 274.607026 112.238568 275.888784 110.956809 
C 277.170543 109.675051 277.890729 107.936369 277.890729 106.123688 
C 277.890729 104.311007 277.170543 102.572325 275.888784 101.290566 
C 274.607026 100.008808 272.868344 99.288622 271.055663 99.288622 
C 269.242982 99.288622 267.5043 100.008808 266.222541 101.290566 
C 264.940783 102.572325 264.220597 104.311007 264.220597 106.123688 
C 264.220597 107.936369 264.940783 109.675051 266.222541 110.956809 
C 267.5043 112.238568 269.242982 112.958754 271.055663 112.958754 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481f70; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 378.112773 185.626944 
C 378.98785 185.626944 379.827205 185.279272 380.445978 184.660499 
C 381.064751 184.041726 381.412423 183.202372 381.412423 182.327295 
C 381.412423 181.452217 381.064751 180.612863 380.445978 179.99409 
C 379.827205 179.375317 378.98785 179.027645 378.112773 179.027645 
C 377.237696 179.027645 376.398342 179.375317 375.779569 179.99409 
C 375.160796 180.612863 374.813124 181.452217 374.813124 182.327295 
C 374.813124 183.202372 375.160796 184.041726 375.779569 184.660499 
C 376.398342 185.279272 377.237696 185.626944 378.112773 185.626944 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 229.409748 187.186637 
C 230.698461 187.186637 231.934565 186.674626 232.845822 185.763369 
C 233.75708 184.852111 234.26909 183.616007 234.26909 182.327295 
C 234.26909 181.038582 233.75708 179.802478 232.845822 178.89122 
C 231.934565 177.979963 230.698461 177.467952 229.409748 177.467952 
C 228.121035 177.467952 226.884931 177.979963 225.973674 178.89122 
C 225.062416 179.802478 224.550405 181.038582 224.550405 182.327295 
C 224.550405 183.616007 225.062416 184.852111 225.973674 185.763369 
C 226.884931 186.674626 228.121035 187.186637 229.409748 187.186637 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460b5e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 476.687681 155.13595 
C 477.560225 155.13595 478.397149 154.789284 479.014131 154.172302 
C 479.631113 153.55532 479.977779 152.718396 479.977779 151.845852 
C 479.977779 150.973308 479.631113 150.136383 479.014131 149.519402 
C 478.397149 148.90242 477.560225 148.555754 476.687681 148.555754 
C 475.815137 148.555754 474.978212 148.90242 474.361231 149.519402 
C 473.744249 150.136383 473.397583 150.973308 473.397583 151.845852 
C 473.397583 152.718396 473.744249 153.55532 474.361231 154.172302 
C 474.978212 154.789284 475.815137 155.13595 476.687681 155.13595 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 332.121855 172.007586 
C 333.426923 172.007586 334.678714 171.489077 335.601537 170.566255 
C 336.524359 169.643433 337.042868 168.391641 337.042868 167.086573 
C 337.042868 165.781505 336.524359 164.529714 335.601537 163.606891 
C 334.678714 162.684069 333.426923 162.16556 332.121855 162.16556 
C 330.816787 162.16556 329.564995 162.684069 328.642173 163.606891 
C 327.719351 164.529714 327.200842 165.781505 327.200842 167.086573 
C 327.200842 168.391641 327.719351 169.643433 328.642173 170.566255 
C 329.564995 171.489077 330.816787 172.007586 332.121855 172.007586 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460b5e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 527.845375 80.890252 
C 529.237163 80.890252 530.572134 80.337289 531.556277 79.353146 
C 532.540419 78.369004 533.093382 77.034033 533.093382 75.642245 
C 533.093382 74.250458 532.540419 72.915487 531.556277 71.931344 
C 530.572134 70.947202 529.237163 70.394239 527.845375 70.394239 
C 526.453588 70.394239 525.118617 70.947202 524.134474 71.931344 
C 523.150332 72.915487 522.597369 74.250458 522.597369 75.642245 
C 522.597369 77.034033 523.150332 78.369004 524.134474 79.353146 
C 525.118617 80.337289 526.453588 80.890252 527.845375 80.890252 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470e61; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 208.884329 81.729425 
C 210.498668 81.729425 212.047105 81.088041 213.188615 79.946531 
C 214.330125 78.805021 214.971509 77.256584 214.971509 75.642245 
C 214.971509 74.027906 214.330125 72.479469 213.188615 71.337959 
C 212.047105 70.196449 210.498668 69.555066 208.884329 69.555066 
C 207.26999 69.555066 205.721553 70.196449 204.580043 71.337959 
C 203.438533 72.479469 202.797149 74.027906 202.797149 75.642245 
C 202.797149 77.256584 203.438533 78.805021 204.580043 79.946531 
C 205.721553 81.088041 207.26999 81.729425 208.884329 81.729425 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481769; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 515.924953 110.178106 
C 517.000197 110.178106 518.031547 109.750907 518.791859 108.990595 
C 519.552172 108.230282 519.979371 107.198932 519.979371 106.123688 
C 519.979371 105.048444 519.552172 104.017094 518.791859 103.256781 
C 518.031547 102.496468 517.000197 102.069269 515.924953 102.069269 
C 514.849708 102.069269 513.818358 102.496468 513.058046 103.256781 
C 512.297733 104.017094 511.870534 105.048444 511.870534 106.123688 
C 511.870534 107.198932 512.297733 108.230282 513.058046 108.990595 
C 513.818358 109.750907 514.849708 110.178106 515.924953 110.178106 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 383.487354 110.568374 
C 384.666098 110.568374 385.796723 110.100054 386.630221 109.266556 
C 387.46372 108.433057 387.93204 107.302432 387.93204 106.123688 
C 387.93204 104.944943 387.46372 103.814319 386.630221 102.98082 
C 385.796723 102.147322 384.666098 101.679002 383.487354 101.679002 
C 382.308609 101.679002 381.177984 102.147322 380.344486 102.98082 
C 379.510988 103.814319 379.042668 104.944943 379.042668 106.123688 
C 379.042668 107.302432 379.510988 108.433057 380.344486 109.266556 
C 381.177984 110.100054 382.308609 110.568374 383.487354 110.568374 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 688.714411 110.609615 
C 689.904093 110.609615 691.045208 110.136949 691.88644 109.295717 
C 692.727672 108.454485 693.200338 107.31337 693.200338 106.123688 
C 693.200338 104.934006 692.727672 103.792891 691.88644 102.951658 
C 691.045208 102.110426 689.904093 101.637761 688.714411 101.637761 
C 687.524729 101.637761 686.383613 102.110426 685.542381 102.951658 
C 684.701149 103.792891 684.228484 104.934006 684.228484 106.123688 
C 684.228484 107.31337 684.701149 108.454485 685.542381 109.295717 
C 686.383613 110.136949 687.524729 110.609615 688.714411 110.609615 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 424.689323 215.735668 
C 429.50744 215.735668 434.128869 213.821409 437.535793 210.414486 
C 440.942716 207.007562 442.856975 202.386133 442.856975 197.568016 
C 442.856975 192.749898 440.942716 188.12847 437.535793 184.721546 
C 434.128869 181.314622 429.50744 179.400364 424.689323 179.400364 
C 419.871205 179.400364 415.249776 181.314622 411.842853 184.721546 
C 408.435929 188.12847 406.521671 192.749898 406.521671 197.568016 
C 406.521671 202.386133 408.435929 207.007562 411.842853 210.414486 
C 415.249776 213.821409 419.871205 215.735668 424.689323 215.735668 
z
" clip-path="url(#p8a32aafd77)" style="fill: #fde725; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 486.48283 141.476145 
C 487.774639 141.476145 489.013712 140.962905 489.927158 140.049458 
C 490.840604 139.136012 491.353845 137.896939 491.353845 136.605131 
C 491.353845 135.313322 490.840604 134.074249 489.927158 133.160803 
C 489.013712 132.247357 487.774639 131.734116 486.48283 131.734116 
C 485.191022 131.734116 483.951949 132.247357 483.038503 133.160803 
C 482.125056 134.074249 481.611816 135.313322 481.611816 136.605131 
C 481.611816 137.896939 482.125056 139.136012 483.038503 140.049458 
C 483.951949 140.962905 485.191022 141.476145 486.48283 141.476145 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460b5e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 839.117655 263.039419 
C 840.313328 263.039419 841.46019 262.564373 842.305659 261.718905 
C 843.151127 260.873436 843.626173 259.726574 843.626173 258.530901 
C 843.626173 257.335228 843.151127 256.188366 842.305659 255.342897 
C 841.46019 254.497429 840.313328 254.022383 839.117655 254.022383 
C 837.921982 254.022383 836.77512 254.497429 835.929651 255.342897 
C 835.084183 256.188366 834.609137 257.335228 834.609137 258.530901 
C 834.609137 259.726574 835.084183 260.873436 835.929651 261.718905 
C 836.77512 262.564373 837.921982 263.039419 839.117655 263.039419 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 207.080208 210.173797 
C 210.4233 210.173797 213.629918 208.845573 215.993841 206.481649 
C 218.357764 204.117726 219.685989 200.911108 219.685989 197.568016 
C 219.685989 194.224924 218.357764 191.018306 215.993841 188.654382 
C 213.629918 186.290459 210.4233 184.962234 207.080208 184.962234 
C 203.737115 184.962234 200.530498 186.290459 198.166574 188.654382 
C 195.802651 191.018306 194.474426 194.224924 194.474426 197.568016 
C 194.474426 200.911108 195.802651 204.117726 198.166574 206.481649 
C 200.530498 208.845573 203.737115 210.173797 207.080208 210.173797 
z
" clip-path="url(#p8a32aafd77)" style="fill: #277e8e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 251.512592 141.969876 
C 252.935339 141.969876 254.300006 141.404612 255.30604 140.398578 
C 256.312074 139.392544 256.877338 138.027878 256.877338 136.605131 
C 256.877338 135.182383 256.312074 133.817717 255.30604 132.811683 
C 254.300006 131.805649 252.935339 131.240385 251.512592 131.240385 
C 250.089845 131.240385 248.725179 131.805649 247.719145 132.811683 
C 246.71311 133.817717 246.147847 135.182383 246.147847 136.605131 
C 246.147847 138.027878 246.71311 139.392544 247.719145 140.398578 
C 248.725179 141.404612 250.089845 141.969876 251.512592 141.969876 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470e61; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 377.536588 250.136391 
C 379.352224 250.136391 381.093741 249.415031 382.37759 248.131182 
C 383.661439 246.847333 384.382799 245.105816 384.382799 243.29018 
C 384.382799 241.474543 383.661439 239.733026 382.37759 238.449178 
C 381.093741 237.165329 379.352224 236.443969 377.536588 236.443969 
C 375.720952 236.443969 373.979435 237.165329 372.695586 238.449178 
C 371.411737 239.733026 370.690377 241.474543 370.690377 243.29018 
C 370.690377 245.105816 371.411737 246.847333 372.695586 248.131182 
C 373.979435 249.415031 375.720952 250.136391 377.536588 250.136391 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481f70; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 625.419043 80.786489 
C 626.783313 80.786489 628.091889 80.244459 629.056573 79.279775 
C 630.021257 78.315091 630.563287 77.006515 630.563287 75.642245 
C 630.563287 74.277976 630.021257 72.9694 629.056573 72.004716 
C 628.091889 71.040032 626.783313 70.498002 625.419043 70.498002 
C 624.054774 70.498002 622.746198 71.040032 621.781514 72.004716 
C 620.81683 72.9694 620.2748 74.277976 620.2748 75.642245 
C 620.2748 77.006515 620.81683 78.315091 621.781514 79.279775 
C 622.746198 80.244459 624.054774 80.786489 625.419043 80.786489 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 353.931884 263.696189 
C 355.301734 263.696189 356.615663 263.151942 357.584294 262.183311 
C 358.552924 261.214681 359.097172 259.900752 359.097172 258.530901 
C 359.097172 257.161051 358.552924 255.847121 357.584294 254.878491 
C 356.615663 253.90986 355.301734 253.365613 353.931884 253.365613 
C 352.562033 253.365613 351.248104 253.90986 350.279473 254.878491 
C 349.310843 255.847121 348.766596 257.161051 348.766596 258.530901 
C 348.766596 259.900752 349.310843 261.214681 350.279473 262.183311 
C 351.248104 263.151942 352.562033 263.696189 353.931884 263.696189 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 425.397747 127.149571 
C 426.93199 127.149571 428.403601 126.54001 429.488475 125.455137 
C 430.573348 124.370263 431.182909 122.898652 431.182909 121.364409 
C 431.182909 119.830166 430.573348 118.358555 429.488475 117.273682 
C 428.403601 116.188808 426.93199 115.579247 425.397747 115.579247 
C 423.863504 115.579247 422.391893 116.188808 421.30702 117.273682 
C 420.222146 118.358555 419.612585 119.830166 419.612585 121.364409 
C 419.612585 122.898652 420.222146 124.370263 421.30702 125.455137 
C 422.391893 126.54001 423.863504 127.149571 425.397747 127.149571 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471365; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 294.726487 109.963792 
C 295.744894 109.963792 296.721728 109.559175 297.441851 108.839052 
C 298.161974 108.118929 298.566591 107.142096 298.566591 106.123688 
C 298.566591 105.10528 298.161974 104.128447 297.441851 103.408324 
C 296.721728 102.688201 295.744894 102.283583 294.726487 102.283583 
C 293.708079 102.283583 292.731246 102.688201 292.011123 103.408324 
C 291.291 104.128447 290.886382 105.10528 290.886382 106.123688 
C 290.886382 107.142096 291.291 108.118929 292.011123 108.839052 
C 292.731246 109.559175 293.708079 109.963792 294.726487 109.963792 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 418.823568 308.636796 
C 419.986147 308.636796 421.101266 308.174899 421.923334 307.352831 
C 422.745401 306.530764 423.207299 305.415644 423.207299 304.253065 
C 423.207299 303.090486 422.745401 301.975367 421.923334 301.153299 
C 421.101266 300.331231 419.986147 299.869334 418.823568 299.869334 
C 417.660989 299.869334 416.545869 300.331231 415.723802 301.153299 
C 414.901734 301.975367 414.439837 303.090486 414.439837 304.253065 
C 414.439837 305.415644 414.901734 306.530764 415.723802 307.352831 
C 416.545869 308.174899 417.660989 308.636796 418.823568 308.636796 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 232.234 125.841237 
C 233.421269 125.841237 234.56007 125.36953 235.399595 124.530004 
C 236.239121 123.690479 236.710828 122.551678 236.710828 121.364409 
C 236.710828 120.177141 236.239121 119.03834 235.399595 118.198814 
C 234.56007 117.359289 233.421269 116.887582 232.234 116.887582 
C 231.046732 116.887582 229.907931 117.359289 229.068405 118.198814 
C 228.22888 119.03834 227.757173 120.177141 227.757173 121.364409 
C 227.757173 122.551678 228.22888 123.690479 229.068405 124.530004 
C 229.907931 125.36953 231.046732 125.841237 232.234 125.841237 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 427.608032 207.562672 
C 430.258645 207.562672 432.801054 206.509572 434.675321 204.635305 
C 436.549588 202.761038 437.602688 200.21863 437.602688 197.568016 
C 437.602688 194.917402 436.549588 192.374994 434.675321 190.500727 
C 432.801054 188.62646 430.258645 187.57336 427.608032 187.57336 
C 424.957418 187.57336 422.41501 188.62646 420.540743 190.500727 
C 418.666476 192.374994 417.613376 194.917402 417.613376 197.568016 
C 417.613376 200.21863 418.666476 202.761038 420.540743 204.635305 
C 422.41501 206.509572 424.957418 207.562672 427.608032 207.562672 
z
" clip-path="url(#p8a32aafd77)" style="fill: #3d4e8a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 243.549901 95.675167 
C 244.820807 95.675167 246.039832 95.170231 246.938499 94.271564 
C 247.837165 93.372898 248.342102 92.153873 248.342102 90.882967 
C 248.342102 89.61206 247.837165 88.393036 246.938499 87.494369 
C 246.039832 86.595703 244.820807 86.090766 243.549901 86.090766 
C 242.278995 86.090766 241.05997 86.595703 240.161303 87.494369 
C 239.262637 88.393036 238.7577 89.61206 238.7577 90.882967 
C 238.7577 92.153873 239.262637 93.372898 240.161303 94.271564 
C 241.05997 95.170231 242.278995 95.675167 243.549901 95.675167 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460a5d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 568.508942 187.609109 
C 569.909695 187.609109 571.253266 187.052583 572.243748 186.062101 
C 573.234231 185.071619 573.790756 183.728048 573.790756 182.327295 
C 573.790756 180.926541 573.234231 179.58297 572.243748 178.592488 
C 571.253266 177.602006 569.909695 177.04548 568.508942 177.04548 
C 567.108188 177.04548 565.764618 177.602006 564.774135 178.592488 
C 563.783653 179.58297 563.227128 180.926541 563.227128 182.327295 
C 563.227128 183.728048 563.783653 185.071619 564.774135 186.062101 
C 565.764618 187.052583 567.108188 187.609109 568.508942 187.609109 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470e61; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 416.122109 372.271166 
C 417.993174 372.271166 419.787857 371.527784 421.1109 370.204741 
C 422.433943 368.881699 423.177325 367.087016 423.177325 365.21595 
C 423.177325 363.344885 422.433943 361.550202 421.1109 360.227159 
C 419.787857 358.904116 417.993174 358.160734 416.122109 358.160734 
C 414.251044 358.160734 412.456361 358.904116 411.133318 360.227159 
C 409.810275 361.550202 409.066893 363.344885 409.066893 365.21595 
C 409.066893 367.087016 409.810275 368.881699 411.133318 370.204741 
C 412.456361 371.527784 414.251044 372.271166 416.122109 372.271166 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482173; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 689.148911 109.86564 
C 690.141288 109.86564 691.093154 109.471364 691.794871 108.769647 
C 692.496587 108.067931 692.890863 107.116065 692.890863 106.123688 
C 692.890863 105.131311 692.496587 104.179445 691.794871 103.477729 
C 691.093154 102.776012 690.141288 102.381736 689.148911 102.381736 
C 688.156534 102.381736 687.204668 102.776012 686.502952 103.477729 
C 685.801235 104.179445 685.40696 105.131311 685.40696 106.123688 
C 685.40696 107.116065 685.801235 108.067931 686.502952 108.769647 
C 687.204668 109.471364 688.156534 109.86564 689.148911 109.86564 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 683.6232 280.366101 
C 685.372076 280.366101 687.049558 279.671265 688.286201 278.434623 
C 689.522843 277.197981 690.217679 275.520499 690.217679 273.771622 
C 690.217679 272.022746 689.522843 270.345264 688.286201 269.108622 
C 687.049558 267.87198 685.372076 267.177144 683.6232 267.177144 
C 681.874324 267.177144 680.196842 267.87198 678.9602 269.108622 
C 677.723557 270.345264 677.028722 272.022746 677.028722 273.771622 
C 677.028722 275.520499 677.723557 277.197981 678.9602 278.434623 
C 680.196842 279.671265 681.874324 280.366101 683.6232 280.366101 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481c6e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 948.016669 172.35153 
C 949.412952 172.35153 950.752235 171.796781 951.739556 170.80946 
C 952.726877 169.822139 953.281626 168.482856 953.281626 167.086573 
C 953.281626 165.69029 952.726877 164.351007 951.739556 163.363686 
C 950.752235 162.376365 949.412952 161.821616 948.016669 161.821616 
C 946.620386 161.821616 945.281103 162.376365 944.293782 163.363686 
C 943.306461 164.351007 942.751712 165.69029 942.751712 167.086573 
C 942.751712 168.482856 943.306461 169.822139 944.293782 170.80946 
C 945.281103 171.796781 946.620386 172.35153 948.016669 172.35153 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470e61; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 257.378347 232.35573 
C 258.520384 232.35573 259.615799 231.901994 260.423341 231.094452 
C 261.230883 230.286911 261.684619 229.191495 261.684619 228.049458 
C 261.684619 226.907422 261.230883 225.812006 260.423341 225.004465 
C 259.615799 224.196923 258.520384 223.743187 257.378347 223.743187 
C 256.236311 223.743187 255.140895 224.196923 254.333353 225.004465 
C 253.525812 225.812006 253.072076 226.907422 253.072076 228.049458 
C 253.072076 229.191495 253.525812 230.286911 254.333353 231.094452 
C 255.140895 231.901994 256.236311 232.35573 257.378347 232.35573 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 415.593152 140.495232 
C 416.624819 140.495232 417.614371 140.085347 418.34387 139.355848 
C 419.073368 138.626349 419.483254 137.636798 419.483254 136.605131 
C 419.483254 135.573463 419.073368 134.583912 418.34387 133.854413 
C 417.614371 133.124914 416.624819 132.715029 415.593152 132.715029 
C 414.561485 132.715029 413.571933 133.124914 412.842435 133.854413 
C 412.112936 134.583912 411.70305 135.573463 411.70305 136.605131 
C 411.70305 137.636798 412.112936 138.626349 412.842435 139.355848 
C 413.571933 140.085347 414.561485 140.495232 415.593152 140.495232 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 481.930022 171.112744 
C 482.997775 171.112744 484.021939 170.688521 484.776955 169.933506 
C 485.53197 169.17849 485.956193 168.154326 485.956193 167.086573 
C 485.956193 166.01882 485.53197 164.994656 484.776955 164.239641 
C 484.021939 163.484626 482.997775 163.060403 481.930022 163.060403 
C 480.862269 163.060403 479.838105 163.484626 479.08309 164.239641 
C 478.328075 164.994656 477.903852 166.01882 477.903852 167.086573 
C 477.903852 168.154326 478.328075 169.17849 479.08309 169.933506 
C 479.838105 170.688521 480.862269 171.112744 481.930022 171.112744 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 504.070649 111.481879 
C 505.491658 111.481879 506.854658 110.917306 507.859463 109.912501 
C 508.864268 108.907696 509.428841 107.544697 509.428841 106.123688 
C 509.428841 104.702679 508.864268 103.33968 507.859463 102.334874 
C 506.854658 101.330069 505.491658 100.765497 504.070649 100.765497 
C 502.64964 100.765497 501.286641 101.330069 500.281836 102.334874 
C 499.277031 103.33968 498.712458 104.702679 498.712458 106.123688 
C 498.712458 107.544697 499.277031 108.907696 500.281836 109.912501 
C 501.286641 110.917306 502.64964 111.481879 504.070649 111.481879 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470e61; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 269.440455 96.946107 
C 271.048419 96.946107 272.590741 96.307256 273.727743 95.170254 
C 274.864745 94.033252 275.503596 92.49093 275.503596 90.882967 
C 275.503596 89.275003 274.864745 87.732681 273.727743 86.595679 
C 272.590741 85.458677 271.048419 84.819826 269.440455 84.819826 
C 267.832491 84.819826 266.290169 85.458677 265.153167 86.595679 
C 264.016165 87.732681 263.377314 89.275003 263.377314 90.882967 
C 263.377314 92.49093 264.016165 94.033252 265.153167 95.170254 
C 266.290169 96.307256 267.832491 96.946107 269.440455 96.946107 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481668; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 430.498404 157.59327 
C 432.022637 157.59327 433.484646 156.987686 434.562442 155.90989 
C 435.640238 154.832095 436.245822 153.370085 436.245822 151.845852 
C 436.245822 150.321619 435.640238 148.859609 434.562442 147.781813 
C 433.484646 146.704018 432.022637 146.098434 430.498404 146.098434 
C 428.97417 146.098434 427.512161 146.704018 426.434365 147.781813 
C 425.35657 148.859609 424.750985 150.321619 424.750985 151.845852 
C 424.750985 153.370085 425.35657 154.832095 426.434365 155.90989 
C 427.512161 156.987686 428.97417 157.59327 430.498404 157.59327 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471365; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 889.226881 80.782967 
C 890.590216 80.782967 891.897896 80.241308 892.86192 79.277284 
C 893.825944 78.313261 894.367602 77.00558 894.367602 75.642245 
C 894.367602 74.27891 893.825944 72.97123 892.86192 72.007206 
C 891.897896 71.043183 890.590216 70.501524 889.226881 70.501524 
C 887.863546 70.501524 886.555866 71.043183 885.591842 72.007206 
C 884.627819 72.97123 884.08616 74.27891 884.08616 75.642245 
C 884.08616 77.00558 884.627819 78.313261 885.591842 79.277284 
C 886.555866 80.241308 887.863546 80.782967 889.226881 80.782967 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 294.140856 81.357408 
C 295.656535 81.357408 297.11034 80.755223 298.182087 79.683476 
C 299.253833 78.611729 299.856019 77.157924 299.856019 75.642245 
C 299.856019 74.126566 299.253833 72.672762 298.182087 71.601015 
C 297.11034 70.529268 295.656535 69.927082 294.140856 69.927082 
C 292.625177 69.927082 291.171372 70.529268 290.099625 71.601015 
C 289.027878 72.672762 288.425693 74.126566 288.425693 75.642245 
C 288.425693 77.157924 289.027878 78.611729 290.099625 79.683476 
C 291.171372 80.755223 292.625177 81.357408 294.140856 81.357408 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471365; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 787.005949 79.938632 
C 788.145364 79.938632 789.238265 79.485937 790.043953 78.680249 
C 790.849641 77.874561 791.302335 76.78166 791.302335 75.642245 
C 791.302335 74.50283 790.849641 73.409929 790.043953 72.604241 
C 789.238265 71.798553 788.145364 71.345859 787.005949 71.345859 
C 785.866534 71.345859 784.773633 71.798553 783.967945 72.604241 
C 783.162257 73.409929 782.709562 74.50283 782.709562 75.642245 
C 782.709562 76.78166 783.162257 77.874561 783.967945 78.680249 
C 784.773633 79.485937 785.866534 79.938632 787.005949 79.938632 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 392.838557 94.981701 
C 393.925554 94.981701 394.968177 94.549833 395.7368 93.78121 
C 396.505423 93.012587 396.937292 91.969964 396.937292 90.882967 
C 396.937292 89.795969 396.505423 88.753347 395.7368 87.984724 
C 394.968177 87.216101 393.925554 86.784232 392.838557 86.784232 
C 391.75156 86.784232 390.708937 87.216101 389.940314 87.984724 
C 389.171691 88.753347 388.739823 89.795969 388.739823 90.882967 
C 388.739823 91.969964 389.171691 93.012587 389.940314 93.78121 
C 390.708937 94.549833 391.75156 94.981701 392.838557 94.981701 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 605.006972 94.490692 
C 605.963752 94.490692 606.881474 94.110559 607.558019 93.434014 
C 608.234565 92.757468 608.614698 91.839747 608.614698 90.882967 
C 608.614698 89.926187 608.234565 89.008465 607.558019 88.331919 
C 606.881474 87.655374 605.963752 87.275241 605.006972 87.275241 
C 604.050192 87.275241 603.13247 87.655374 602.455925 88.331919 
C 601.779379 89.008465 601.399246 89.926187 601.399246 90.882967 
C 601.399246 91.839747 601.779379 92.757468 602.455925 93.434014 
C 603.13247 94.110559 604.050192 94.490692 605.006972 94.490692 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 299.279295 80.497686 
C 300.566973 80.497686 301.802084 79.986086 302.71261 79.07556 
C 303.623135 78.165034 304.134735 76.929923 304.134735 75.642245 
C 304.134735 74.354567 303.623135 73.119456 302.71261 72.208931 
C 301.802084 71.298405 300.566973 70.786805 299.279295 70.786805 
C 297.991617 70.786805 296.756506 71.298405 295.84598 72.208931 
C 294.935455 73.119456 294.423855 74.354567 294.423855 75.642245 
C 294.423855 76.929923 294.935455 78.165034 295.84598 79.07556 
C 296.756506 79.986086 297.991617 80.497686 299.279295 80.497686 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460b5e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 855.411418 232.580348 
C 856.613024 232.580348 857.765577 232.102944 858.615241 231.253281 
C 859.464904 230.403617 859.942307 229.251064 859.942307 228.049458 
C 859.942307 226.847853 859.464904 225.6953 858.615241 224.845636 
C 857.765577 223.995972 856.613024 223.518569 855.411418 223.518569 
C 854.209813 223.518569 853.05726 223.995972 852.207596 224.845636 
C 851.357932 225.6953 850.880529 226.847853 850.880529 228.049458 
C 850.880529 229.251064 851.357932 230.403617 852.207596 231.253281 
C 853.05726 232.102944 854.209813 232.580348 855.411418 232.580348 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 303.973788 94.987168 
C 305.062235 94.987168 306.106248 94.554723 306.875896 93.785075 
C 307.645544 93.015427 308.077989 91.971413 308.077989 90.882967 
C 308.077989 89.79452 307.645544 88.750506 306.875896 87.980858 
C 306.106248 87.21121 305.062235 86.778766 303.973788 86.778766 
C 302.885341 86.778766 301.841328 87.21121 301.07168 87.980858 
C 300.302031 88.750506 299.869587 89.79452 299.869587 90.882967 
C 299.869587 91.971413 300.302031 93.015427 301.07168 93.785075 
C 301.841328 94.554723 302.885341 94.987168 303.973788 94.987168 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 259.768099 385.54045 
C 261.116333 385.54045 262.409528 385.004791 263.362873 384.051446 
C 264.316219 383.098101 264.851878 381.804905 264.851878 380.456672 
C 264.851878 379.108438 264.316219 377.815243 263.362873 376.861897 
C 262.409528 375.908552 261.116333 375.372893 259.768099 375.372893 
C 258.419865 375.372893 257.12667 375.908552 256.173325 376.861897 
C 255.21998 377.815243 254.684321 379.108438 254.684321 380.456672 
C 254.684321 381.804905 255.21998 383.098101 256.173325 384.051446 
C 257.12667 385.004791 258.419865 385.54045 259.768099 385.54045 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 360.118791 248.025744 
C 361.374677 248.025744 362.579295 247.526775 363.467341 246.638729 
C 364.355386 245.750684 364.854355 244.546066 364.854355 243.29018 
C 364.854355 242.034293 364.355386 240.829676 363.467341 239.94163 
C 362.579295 239.053584 361.374677 238.554615 360.118791 238.554615 
C 358.862905 238.554615 357.658287 239.053584 356.770241 239.94163 
C 355.882196 240.829676 355.383227 242.034293 355.383227 243.29018 
C 355.383227 244.546066 355.882196 245.750684 356.770241 246.638729 
C 357.658287 247.526775 358.862905 248.025744 360.118791 248.025744 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460a5d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 536.403143 211.770567 
C 540.169704 211.770567 543.782503 210.274096 546.445863 207.610736 
C 549.109224 204.947375 550.605694 201.334576 550.605694 197.568016 
C 550.605694 193.801455 549.109224 190.188656 546.445863 187.525296 
C 543.782503 184.861935 540.169704 183.365465 536.403143 183.365465 
C 532.636583 183.365465 529.023784 184.861935 526.360423 187.525296 
C 523.697063 190.188656 522.200593 193.801455 522.200593 197.568016 
C 522.200593 201.334576 523.697063 204.947375 526.360423 207.610736 
C 529.023784 210.274096 532.636583 211.770567 536.403143 211.770567 
z
" clip-path="url(#p8a32aafd77)" style="fill: #1fa088; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 647.153507 171.107041 
C 648.219747 171.107041 649.242461 170.683419 649.996407 169.929473 
C 650.750353 169.175527 651.173975 168.152814 651.173975 167.086573 
C 651.173975 166.020333 650.750353 164.997619 649.996407 164.243673 
C 649.242461 163.489727 648.219747 163.066106 647.153507 163.066106 
C 646.087266 163.066106 645.064553 163.489727 644.310607 164.243673 
C 643.556661 164.997619 643.133039 166.020333 643.133039 167.086573 
C 643.133039 168.152814 643.556661 169.175527 644.310607 169.929473 
C 645.064553 170.683419 646.087266 171.107041 647.153507 171.107041 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 364.369338 263.057333 
C 365.569762 263.057333 366.721181 262.5804 367.570009 261.731572 
C 368.418837 260.882744 368.89577 259.731325 368.89577 258.530901 
C 368.89577 257.330477 368.418837 256.179058 367.570009 255.33023 
C 366.721181 254.481402 365.569762 254.004469 364.369338 254.004469 
C 363.168914 254.004469 362.017495 254.481402 361.168667 255.33023 
C 360.319839 256.179058 359.842906 257.330477 359.842906 258.530901 
C 359.842906 259.731325 360.319839 260.882744 361.168667 261.731572 
C 362.017495 262.5804 363.168914 263.057333 364.369338 263.057333 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 448.407375 170.894632 
C 449.417284 170.894632 450.385966 170.493391 451.100079 169.779278 
C 451.814193 169.065164 452.215434 168.096482 452.215434 167.086573 
C 452.215434 166.076664 451.814193 165.107982 451.100079 164.393869 
C 450.385966 163.679755 449.417284 163.278514 448.407375 163.278514 
C 447.397466 163.278514 446.428784 163.679755 445.71467 164.393869 
C 445.000557 165.107982 444.599316 166.076664 444.599316 167.086573 
C 444.599316 168.096482 445.000557 169.065164 445.71467 169.779278 
C 446.428784 170.493391 447.397466 170.894632 448.407375 170.894632 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 383.288995 140.602605 
C 384.349138 140.602605 385.366002 140.181406 386.115636 139.431772 
C 386.86527 138.682138 387.286469 137.665273 387.286469 136.605131 
C 387.286469 135.544988 386.86527 134.528123 386.115636 133.778489 
C 385.366002 133.028855 384.349138 132.607656 383.288995 132.607656 
C 382.228852 132.607656 381.211988 133.028855 380.462354 133.778489 
C 379.71272 134.528123 379.291521 135.544988 379.291521 136.605131 
C 379.291521 137.665273 379.71272 138.682138 380.462354 139.431772 
C 381.211988 140.181406 382.228852 140.602605 383.288995 140.602605 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 266.427289 295.489903 
C 268.145158 295.489903 269.792899 294.807387 271.007616 293.59267 
C 272.222332 292.377953 272.904849 290.730213 272.904849 289.012344 
C 272.904849 287.294475 272.222332 285.646734 271.007616 284.432018 
C 269.792899 283.217301 268.145158 282.534784 266.427289 282.534784 
C 264.709421 282.534784 263.06168 283.217301 261.846963 284.432018 
C 260.632247 285.646734 259.94973 287.294475 259.94973 289.012344 
C 259.94973 290.730213 260.632247 292.377953 261.846963 293.59267 
C 263.06168 294.807387 264.709421 295.489903 266.427289 295.489903 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481b6d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 634.033485 79.329174 
C 635.01127 79.329174 635.949139 78.940696 636.640537 78.249298 
C 637.331936 77.557899 637.720414 76.62003 637.720414 75.642245 
C 637.720414 74.66446 637.331936 73.726591 636.640537 73.035193 
C 635.949139 72.343795 635.01127 71.955317 634.033485 71.955317 
C 633.0557 71.955317 632.117831 72.343795 631.426433 73.035193 
C 630.735035 73.726591 630.346557 74.66446 630.346557 75.642245 
C 630.346557 76.62003 630.735035 77.557899 631.426433 78.249298 
C 632.117831 78.940696 633.0557 79.329174 634.033485 79.329174 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 465.248987 185.451006 
C 466.077405 185.451006 466.872004 185.121872 467.457784 184.536092 
C 468.043564 183.950312 468.372698 183.155712 468.372698 182.327295 
C 468.372698 181.498877 468.043564 180.704277 467.457784 180.118497 
C 466.872004 179.532717 466.077405 179.203583 465.248987 179.203583 
C 464.420569 179.203583 463.625969 179.532717 463.040189 180.118497 
C 462.454409 180.704277 462.125276 181.498877 462.125276 182.327295 
C 462.125276 183.155712 462.454409 183.950312 463.040189 184.536092 
C 463.625969 185.121872 464.420569 185.451006 465.248987 185.451006 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 227.690638 125.704917 
C 228.841754 125.704917 229.945878 125.247574 230.75984 124.433612 
C 231.573802 123.61965 232.031145 122.515525 232.031145 121.364409 
C 232.031145 120.213293 231.573802 119.109169 230.75984 118.295207 
C 229.945878 117.481245 228.841754 117.023902 227.690638 117.023902 
C 226.539522 117.023902 225.435397 117.481245 224.621435 118.295207 
C 223.807474 119.109169 223.35013 120.213293 223.35013 121.364409 
C 223.35013 122.515525 223.807474 123.61965 224.621435 124.433612 
C 225.435397 125.247574 226.539522 125.704917 227.690638 125.704917 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 297.097347 231.90849 
C 298.120775 231.90849 299.102423 231.501878 299.826095 230.778206 
C 300.549767 230.054534 300.956379 229.072886 300.956379 228.049458 
C 300.956379 227.026031 300.549767 226.044383 299.826095 225.320711 
C 299.102423 224.597039 298.120775 224.190427 297.097347 224.190427 
C 296.07392 224.190427 295.092272 224.597039 294.3686 225.320711 
C 293.644928 226.044383 293.238316 227.026031 293.238316 228.049458 
C 293.238316 229.072886 293.644928 230.054534 294.3686 230.778206 
C 295.092272 231.501878 296.07392 231.90849 297.097347 231.90849 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 382.14607 216.251139 
C 383.059006 216.251139 383.934673 215.888426 384.580216 215.242883 
C 385.225759 214.59734 385.588472 213.721673 385.588472 212.808737 
C 385.588472 211.895801 385.225759 211.020134 384.580216 210.374591 
C 383.934673 209.729048 383.059006 209.366335 382.14607 209.366335 
C 381.233134 209.366335 380.357467 209.729048 379.711924 210.374591 
C 379.066381 211.020134 378.703668 211.895801 378.703668 212.808737 
C 378.703668 213.721673 379.066381 214.59734 379.711924 215.242883 
C 380.357467 215.888426 381.233134 216.251139 382.14607 216.251139 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 311.983708 124.205872 
C 312.737272 124.205872 313.460074 123.906477 313.992925 123.373627 
C 314.525776 122.840776 314.82517 122.117974 314.82517 121.364409 
C 314.82517 120.610845 314.525776 119.888043 313.992925 119.355192 
C 313.460074 118.822341 312.737272 118.522947 311.983708 118.522947 
C 311.230143 118.522947 310.507341 118.822341 309.97449 119.355192 
C 309.44164 119.888043 309.142245 120.610845 309.142245 121.364409 
C 309.142245 122.117974 309.44164 122.840776 309.97449 123.373627 
C 310.507341 123.906477 311.230143 124.205872 311.983708 124.205872 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 319.379659 206.699801 
C 321.801437 206.699801 324.124351 205.737619 325.836807 204.025163 
C 327.549262 202.312708 328.511445 199.989794 328.511445 197.568016 
C 328.511445 195.146238 327.549262 192.823324 325.836807 191.110869 
C 324.124351 189.398413 321.801437 188.436231 319.379659 188.436231 
C 316.957882 188.436231 314.634968 189.398413 312.922512 191.110869 
C 311.210057 192.823324 310.247874 195.146238 310.247874 197.568016 
C 310.247874 199.989794 311.210057 202.312708 312.922512 204.025163 
C 314.634968 205.737619 316.957882 206.699801 319.379659 206.699801 
z
" clip-path="url(#p8a32aafd77)" style="fill: #424086; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 434.871744 156.823431 
C 436.191814 156.823431 437.457994 156.298962 438.391424 155.365532 
C 439.324854 154.432102 439.849323 153.165921 439.849323 151.845852 
C 439.849323 150.525782 439.324854 149.259602 438.391424 148.326172 
C 437.457994 147.392742 436.191814 146.868273 434.871744 146.868273 
C 433.551675 146.868273 432.285494 147.392742 431.352064 148.326172 
C 430.418634 149.259602 429.894165 150.525782 429.894165 151.845852 
C 429.894165 153.165921 430.418634 154.432102 431.352064 155.365532 
C 432.285494 156.298962 433.551675 156.823431 434.871744 156.823431 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460b5e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 301.300666 154.55883 
C 302.020156 154.55883 302.710275 154.272974 303.219031 153.764217 
C 303.727788 153.255461 304.013644 152.565342 304.013644 151.845852 
C 304.013644 151.126362 303.727788 150.436243 303.219031 149.927487 
C 302.710275 149.41873 302.020156 149.132874 301.300666 149.132874 
C 300.581176 149.132874 299.891057 149.41873 299.382301 149.927487 
C 298.873544 150.436243 298.587688 151.126362 298.587688 151.845852 
C 298.587688 152.565342 298.873544 153.255461 299.382301 153.764217 
C 299.891057 154.272974 300.581176 154.55883 301.300666 154.55883 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 335.059455 235.020874 
C 336.908296 235.020874 338.681662 234.286322 339.98899 232.978994 
C 341.296318 231.671666 342.030871 229.898299 342.030871 228.049458 
C 342.030871 226.200617 341.296318 224.427251 339.98899 223.119923 
C 338.681662 221.812595 336.908296 221.078043 335.059455 221.078043 
C 333.210614 221.078043 331.437248 221.812595 330.12992 223.119923 
C 328.822592 224.427251 328.088039 226.200617 328.088039 228.049458 
C 328.088039 229.898299 328.822592 231.671666 330.12992 232.978994 
C 331.437248 234.286322 333.210614 235.020874 335.059455 235.020874 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482071; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 195.717079 140.064225 
C 196.634441 140.064225 197.514355 139.699753 198.163028 139.05108 
C 198.811701 138.402406 199.176173 137.522493 199.176173 136.605131 
C 199.176173 135.687768 198.811701 134.807855 198.163028 134.159181 
C 197.514355 133.510508 196.634441 133.146036 195.717079 133.146036 
C 194.799716 133.146036 193.919803 133.510508 193.27113 134.159181 
C 192.622456 134.807855 192.257984 135.687768 192.257984 136.605131 
C 192.257984 137.522493 192.622456 138.402406 193.27113 139.05108 
C 193.919803 139.699753 194.799716 140.064225 195.717079 140.064225 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 381.853255 400.485589 
C 383.123099 400.485589 384.341105 399.981075 385.239021 399.083159 
C 386.136937 398.185243 386.641451 396.967238 386.641451 395.697393 
C 386.641451 394.427548 386.136937 393.209542 385.239021 392.311627 
C 384.341105 391.413711 383.123099 390.909196 381.853255 390.909196 
C 380.58341 390.909196 379.365404 391.413711 378.467488 392.311627 
C 377.569573 393.209542 377.065058 394.427548 377.065058 395.697393 
C 377.065058 396.967238 377.569573 398.185243 378.467488 399.083159 
C 379.365404 399.981075 380.58341 400.485589 381.853255 400.485589 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460a5d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 562.274806 414.388891 
C 563.189963 414.388891 564.06776 414.025295 564.714874 413.378182 
C 565.361987 412.731068 565.725583 411.853271 565.725583 410.938114 
C 565.725583 410.022958 565.361987 409.14516 564.714874 408.498047 
C 564.06776 407.850933 563.189963 407.487338 562.274806 407.487338 
C 561.35965 407.487338 560.481852 407.850933 559.834739 408.498047 
C 559.187625 409.14516 558.82403 410.022958 558.82403 410.938114 
C 558.82403 411.853271 559.187625 412.731068 559.834739 413.378182 
C 560.481852 414.025295 561.35965 414.388891 562.274806 414.388891 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 211.368537 79.48235 
C 212.386945 79.48235 213.363778 79.077732 214.083901 78.357609 
C 214.804024 77.637486 215.208642 76.660653 215.208642 75.642245 
C 215.208642 74.623838 214.804024 73.647004 214.083901 72.926881 
C 213.363778 72.206758 212.386945 71.802141 211.368537 71.802141 
C 210.35013 71.802141 209.373296 72.206758 208.653173 72.926881 
C 207.933051 73.647004 207.528433 74.623838 207.528433 75.642245 
C 207.528433 76.660653 207.933051 77.637486 208.653173 78.357609 
C 209.373296 79.077732 210.35013 79.48235 211.368537 79.48235 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 308.828857 339.179194 
C 310.007602 339.179194 311.138227 338.710874 311.971725 337.877375 
C 312.805223 337.043877 313.273543 335.913252 313.273543 334.734508 
C 313.273543 333.555763 312.805223 332.425138 311.971725 331.59164 
C 311.138227 330.758142 310.007602 330.289822 308.828857 330.289822 
C 307.650113 330.289822 306.519488 330.758142 305.68599 331.59164 
C 304.852491 332.425138 304.384171 333.555763 304.384171 334.734508 
C 304.384171 335.913252 304.852491 337.043877 305.68599 337.877375 
C 306.519488 338.710874 307.650113 339.179194 308.828857 339.179194 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 217.319303 79.580895 
C 218.363845 79.580895 219.365746 79.165894 220.104349 78.427291 
C 220.842951 77.688688 221.257952 76.686787 221.257952 75.642245 
C 221.257952 74.597703 220.842951 73.595802 220.104349 72.8572 
C 219.365746 72.118597 218.363845 71.703596 217.319303 71.703596 
C 216.274761 71.703596 215.27286 72.118597 214.534258 72.8572 
C 213.795655 73.595802 213.380654 74.597703 213.380654 75.642245 
C 213.380654 76.686787 213.795655 77.688688 214.534258 78.427291 
C 215.27286 79.165894 216.274761 79.580895 217.319303 79.580895 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 746.701318 80.828429 
C 748.07671 80.828429 749.395954 80.28198 750.368503 79.309431 
C 751.341052 78.336882 751.887501 77.017637 751.887501 75.642245 
C 751.887501 74.266853 751.341052 72.947609 750.368503 71.97506 
C 749.395954 71.002511 748.07671 70.456062 746.701318 70.456062 
C 745.325926 70.456062 744.006681 71.002511 743.034132 71.97506 
C 742.061583 72.947609 741.515134 74.266853 741.515134 75.642245 
C 741.515134 77.017637 742.061583 78.336882 743.034132 79.309431 
C 744.006681 80.28198 745.325926 80.828429 746.701318 80.828429 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 363.868718 216.680267 
C 364.89546 216.680267 365.880287 216.272338 366.606303 215.546322 
C 367.332319 214.820306 367.740248 213.835479 367.740248 212.808737 
C 367.740248 211.781995 367.332319 210.797168 366.606303 210.071152 
C 365.880287 209.345136 364.89546 208.937207 363.868718 208.937207 
C 362.841976 208.937207 361.857149 209.345136 361.131133 210.071152 
C 360.405117 210.797168 359.997188 211.781995 359.997188 212.808737 
C 359.997188 213.835479 360.405117 214.820306 361.131133 215.546322 
C 361.857149 216.272338 362.841976 216.680267 363.868718 216.680267 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 202.329041 216.019126 
C 203.180446 216.019126 203.997094 215.680859 204.599129 215.078825 
C 205.201163 214.476791 205.53943 213.660142 205.53943 212.808737 
C 205.53943 211.957332 205.201163 211.140684 204.599129 210.538649 
C 203.997094 209.936615 203.180446 209.598348 202.329041 209.598348 
C 201.477636 209.598348 200.660987 209.936615 200.058953 210.538649 
C 199.456919 211.140684 199.118652 211.957332 199.118652 212.808737 
C 199.118652 213.660142 199.456919 214.476791 200.058953 215.078825 
C 200.660987 215.680859 201.477636 216.019126 202.329041 216.019126 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 841.564081 431.768008 
C 843.046347 431.768008 844.468102 431.179097 845.516222 430.130977 
C 846.564343 429.082857 847.153253 427.661101 847.153253 426.178836 
C 847.153253 424.69657 846.564343 423.274814 845.516222 422.226694 
C 844.468102 421.178574 843.046347 420.589663 841.564081 420.589663 
C 840.081815 420.589663 838.66006 421.178574 837.611939 422.226694 
C 836.563819 423.274814 835.974909 424.69657 835.974909 426.178836 
C 835.974909 427.661101 836.563819 429.082857 837.611939 430.130977 
C 838.66006 431.179097 840.081815 431.768008 841.564081 431.768008 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471164; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 213.720507 217.494723 
C 214.963245 217.494723 216.155251 217.000978 217.033999 216.12223 
C 217.912748 215.243481 218.406493 214.051475 218.406493 212.808737 
C 218.406493 211.565999 217.912748 210.373993 217.033999 209.495245 
C 216.155251 208.616496 214.963245 208.122751 213.720507 208.122751 
C 212.477769 208.122751 211.285763 208.616496 210.407014 209.495245 
C 209.528266 210.373993 209.034521 211.565999 209.034521 212.808737 
C 209.034521 214.051475 209.528266 215.243481 210.407014 216.12223 
C 211.285763 217.000978 212.477769 217.494723 213.720507 217.494723 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460a5d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 575.035893 279.418364 
C 576.533426 279.418364 577.969826 278.823387 579.028742 277.764471 
C 580.087658 276.705555 580.682634 275.269156 580.682634 273.771622 
C 580.682634 272.274089 580.087658 270.837689 579.028742 269.778773 
C 577.969826 268.719857 576.533426 268.124881 575.035893 268.124881 
C 573.53836 268.124881 572.10196 268.719857 571.043044 269.778773 
C 569.984128 270.837689 569.389152 272.274089 569.389152 273.771622 
C 569.389152 275.269156 569.984128 276.705555 571.043044 277.764471 
C 572.10196 278.823387 573.53836 279.418364 575.035893 279.418364 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471164; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 385.130899 231.310378 
C 385.995705 231.310378 386.825207 230.966787 387.436717 230.355277 
C 388.048227 229.743767 388.391818 228.914264 388.391818 228.049458 
C 388.391818 227.184653 388.048227 226.35515 387.436717 225.74364 
C 386.825207 225.13213 385.995705 224.788539 385.130899 224.788539 
C 384.266093 224.788539 383.436591 225.13213 382.82508 225.74364 
C 382.21357 226.35515 381.869979 227.184653 381.869979 228.049458 
C 381.869979 228.914264 382.21357 229.743767 382.82508 230.355277 
C 383.436591 230.966787 384.266093 231.310378 385.130899 231.310378 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 364.699936 97.415801 
C 366.432464 97.415801 368.094265 96.72746 369.319347 95.502378 
C 370.54443 94.277296 371.23277 92.615494 371.23277 90.882967 
C 371.23277 89.150439 370.54443 87.488637 369.319347 86.263555 
C 368.094265 85.038473 366.432464 84.350132 364.699936 84.350132 
C 362.967408 84.350132 361.305607 85.038473 360.080525 86.263555 
C 358.855443 87.488637 358.167102 89.150439 358.167102 90.882967 
C 358.167102 92.615494 358.855443 94.277296 360.080525 95.502378 
C 361.305607 96.72746 362.967408 97.415801 364.699936 97.415801 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481b6d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 219.964088 128.632228 
C 221.891536 128.632228 223.740301 127.866445 225.103212 126.503534 
C 226.466124 125.140622 227.231907 123.291857 227.231907 121.364409 
C 227.231907 119.436961 226.466124 117.588197 225.103212 116.225285 
C 223.740301 114.862373 221.891536 114.09659 219.964088 114.09659 
C 218.03664 114.09659 216.187875 114.862373 214.824964 116.225285 
C 213.462052 117.588197 212.696269 119.436961 212.696269 121.364409 
C 212.696269 123.291857 213.462052 125.140622 214.824964 126.503534 
C 216.187875 127.866445 218.03664 128.632228 219.964088 128.632228 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482475; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 815.626299 97.873851 
C 817.480303 97.873851 819.258621 97.137248 820.5696 95.826269 
C 821.88058 94.51529 822.617183 92.736971 822.617183 90.882967 
C 822.617183 89.028962 821.88058 87.250644 820.5696 85.939665 
C 819.258621 84.628686 817.480303 83.892082 815.626299 83.892082 
C 813.772294 83.892082 811.993976 84.628686 810.682997 85.939665 
C 809.372018 87.250644 808.635414 89.028962 808.635414 90.882967 
C 808.635414 92.736971 809.372018 94.51529 810.682997 95.826269 
C 811.993976 97.137248 813.772294 97.873851 815.626299 97.873851 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482071; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 778.174257 127.825003 
C 779.887626 127.825003 781.531051 127.144274 782.742586 125.932739 
C 783.954121 124.721204 784.63485 123.077779 784.63485 121.364409 
C 784.63485 119.65104 783.954121 118.007615 782.742586 116.79608 
C 781.531051 115.584544 779.887626 114.903816 778.174257 114.903816 
C 776.460887 114.903816 774.817462 115.584544 773.605927 116.79608 
C 772.394392 118.007615 771.713663 119.65104 771.713663 121.364409 
C 771.713663 123.077779 772.394392 124.721204 773.605927 125.932739 
C 774.817462 127.144274 776.460887 127.825003 778.174257 127.825003 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481b6d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 338.837719 99.582389 
C 341.144833 99.582389 343.357764 98.665763 344.989139 97.034387 
C 346.620515 95.403011 347.537141 93.19008 347.537141 90.882967 
C 347.537141 88.575853 346.620515 86.362922 344.989139 84.731546 
C 343.357764 83.10017 341.144833 82.183544 338.837719 82.183544 
C 336.530605 82.183544 334.317674 83.10017 332.686299 84.731546 
C 331.054923 86.362922 330.138297 88.575853 330.138297 90.882967 
C 330.138297 93.19008 331.054923 95.403011 332.686299 97.034387 
C 334.317674 98.665763 336.530605 99.582389 338.837719 99.582389 
z
" clip-path="url(#p8a32aafd77)" style="fill: #443983; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 257.13276 129.051496 
C 259.171399 129.051496 261.126816 128.241536 262.568352 126.800001 
C 264.009887 125.358465 264.819847 123.403049 264.819847 121.364409 
C 264.819847 119.32577 264.009887 117.370353 262.568352 115.928818 
C 261.126816 114.487282 259.171399 113.677322 257.13276 113.677322 
C 255.094121 113.677322 253.138704 114.487282 251.697169 115.928818 
C 250.255633 117.370353 249.445673 119.32577 249.445673 121.364409 
C 249.445673 123.403049 250.255633 125.358465 251.697169 126.800001 
C 253.138704 128.241536 255.094121 129.051496 257.13276 129.051496 
z
" clip-path="url(#p8a32aafd77)" style="fill: #472a7a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 328.91033 112.654134 
C 330.642225 112.654134 332.303418 111.966045 333.528053 110.74141 
C 334.752687 109.516776 335.440776 107.855582 335.440776 106.123688 
C 335.440776 104.391794 334.752687 102.7306 333.528053 101.505966 
C 332.303418 100.281331 330.642225 99.593242 328.91033 99.593242 
C 327.178436 99.593242 325.517242 100.281331 324.292608 101.505966 
C 323.067974 102.7306 322.379885 104.391794 322.379885 106.123688 
C 322.379885 107.855582 323.067974 109.516776 324.292608 110.74141 
C 325.517242 111.966045 327.178436 112.654134 328.91033 112.654134 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481b6d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 374.891803 161.528107 
C 377.459567 161.528107 379.922508 160.507924 381.738192 158.69224 
C 383.553875 156.876557 384.574059 154.413616 384.574059 151.845852 
C 384.574059 149.278088 383.553875 146.815147 381.738192 144.999463 
C 379.922508 143.18378 377.459567 142.163596 374.891803 142.163596 
C 372.324039 142.163596 369.861098 143.18378 368.045415 144.999463 
C 366.229731 146.815147 365.209548 149.278088 365.209548 151.845852 
C 365.209548 154.413616 366.229731 156.876557 368.045415 158.69224 
C 369.861098 160.507924 372.324039 161.528107 374.891803 161.528107 
z
" clip-path="url(#p8a32aafd77)" style="fill: #3e4989; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 424.160366 97.051829 
C 425.796367 97.051829 427.365583 96.401839 428.52241 95.245011 
C 429.679238 94.088184 430.329229 92.518968 430.329229 90.882967 
C 430.329229 89.246965 429.679238 87.67775 428.52241 86.520922 
C 427.365583 85.364094 425.796367 84.714104 424.160366 84.714104 
C 422.524364 84.714104 420.955149 85.364094 419.798321 86.520922 
C 418.641493 87.67775 417.991503 89.246965 417.991503 90.882967 
C 417.991503 92.518968 418.641493 94.088184 419.798321 95.245011 
C 420.955149 96.401839 422.524364 97.051829 424.160366 97.051829 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481769; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 363.150848 96.051748 
C 364.521625 96.051748 365.836442 95.507132 366.805728 94.537847 
C 367.775013 93.568561 368.319629 92.253743 368.319629 90.882967 
C 368.319629 89.51219 367.775013 88.197372 366.805728 87.228087 
C 365.836442 86.258801 364.521625 85.714186 363.150848 85.714186 
C 361.780071 85.714186 360.465253 86.258801 359.495968 87.228087 
C 358.526682 88.197372 357.982067 89.51219 357.982067 90.882967 
C 357.982067 92.253743 358.526682 93.568561 359.495968 94.537847 
C 360.465253 95.507132 361.780071 96.051748 363.150848 96.051748 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 258.587392 143.384065 
C 260.385186 143.384065 262.109589 142.669793 263.380822 141.398561 
C 264.652054 140.127328 265.366326 138.402925 265.366326 136.605131 
C 265.366326 134.807336 264.652054 133.082933 263.380822 131.8117 
C 262.109589 130.540468 260.385186 129.826197 258.587392 129.826197 
C 256.789597 129.826197 255.065194 130.540468 253.793962 131.8117 
C 252.522729 133.082933 251.808458 134.807336 251.808458 136.605131 
C 251.808458 138.402925 252.522729 140.127328 253.793962 141.398561 
C 255.065194 142.669793 256.789597 143.384065 258.587392 143.384065 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481d6f; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 870.477246 98.219693 
C 872.422969 98.219693 874.289261 97.446649 875.665095 96.070815 
C 877.040928 94.694982 877.813972 92.828689 877.813972 90.882967 
C 877.813972 88.937244 877.040928 87.070951 875.665095 85.695118 
C 874.289261 84.319284 872.422969 83.546241 870.477246 83.546241 
C 868.531524 83.546241 866.665231 84.319284 865.289397 85.695118 
C 863.913564 87.070951 863.14052 88.937244 863.14052 90.882967 
C 863.14052 92.828689 863.913564 94.694982 865.289397 96.070815 
C 866.665231 97.446649 868.531524 98.219693 870.477246 98.219693 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482576; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 449.663648 98.219693 
C 451.60937 98.219693 453.475663 97.446649 454.851496 96.070815 
C 456.22733 94.694982 457.000374 92.828689 457.000374 90.882967 
C 457.000374 88.937244 456.22733 87.070951 454.851496 85.695118 
C 453.475663 84.319284 451.60937 83.546241 449.663648 83.546241 
C 447.717925 83.546241 445.851633 84.319284 444.475799 85.695118 
C 443.099965 87.070951 442.326922 88.937244 442.326922 90.882967 
C 442.326922 92.828689 443.099965 94.694982 444.475799 96.070815 
C 445.851633 97.446649 447.717925 98.219693 449.663648 98.219693 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482576; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 326.284437 251.928899 
C 328.575452 251.928899 330.772942 251.018669 332.392934 249.398677 
C 334.012926 247.778685 334.923156 245.581195 334.923156 243.29018 
C 334.923156 240.999165 334.012926 238.801675 332.392934 237.181683 
C 330.772942 235.56169 328.575452 234.65146 326.284437 234.65146 
C 323.993422 234.65146 321.795932 235.56169 320.17594 237.181683 
C 318.555947 238.801675 317.645717 240.999165 317.645717 243.29018 
C 317.645717 245.581195 318.555947 247.778685 320.17594 249.398677 
C 321.795932 251.018669 323.993422 251.928899 326.284437 251.928899 
z
" clip-path="url(#p8a32aafd77)" style="fill: #453882; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 220.502491 81.459035 
C 222.045121 81.459035 223.524778 80.846142 224.615582 79.755337 
C 225.706387 78.664532 226.319281 77.184876 226.319281 75.642245 
C 226.319281 74.099615 225.706387 72.619958 224.615582 71.529154 
C 223.524778 70.438349 222.045121 69.825455 220.502491 69.825455 
C 218.95986 69.825455 217.480204 70.438349 216.389399 71.529154 
C 215.298594 72.619958 214.6857 74.099615 214.6857 75.642245 
C 214.6857 77.184876 215.298594 78.664532 216.389399 79.755337 
C 217.480204 80.846142 218.95986 81.459035 220.502491 81.459035 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481467; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 587.334142 142.967446 
C 589.021448 142.967446 590.639873 142.297073 591.832979 141.103967 
C 593.026084 139.910862 593.696458 138.292436 593.696458 136.605131 
C 593.696458 134.917825 593.026084 133.299399 591.832979 132.106294 
C 590.639873 130.913188 589.021448 130.242815 587.334142 130.242815 
C 585.646836 130.242815 584.028411 130.913188 582.835305 132.106294 
C 581.6422 133.299399 580.971826 134.917825 580.971826 136.605131 
C 580.971826 138.292436 581.6422 139.910862 582.835305 141.103967 
C 584.028411 142.297073 585.646836 142.967446 587.334142 142.967446 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481a6c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 290.570396 81.855193 
C 292.21809 81.855193 293.798519 81.200558 294.963614 80.035463 
C 296.128709 78.870368 296.783345 77.289938 296.783345 75.642245 
C 296.783345 73.994552 296.128709 72.414122 294.963614 71.249028 
C 293.798519 70.083933 292.21809 69.429297 290.570396 69.429297 
C 288.922703 69.429297 287.342274 70.083933 286.177179 71.249028 
C 285.012084 72.414122 284.357448 73.994552 284.357448 75.642245 
C 284.357448 77.289938 285.012084 78.870368 286.177179 80.035463 
C 287.342274 81.200558 288.922703 81.855193 290.570396 81.855193 
z
" clip-path="url(#p8a32aafd77)" style="fill: #48186a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 607.991801 111.553238 
C 609.431734 111.553238 610.812885 110.981146 611.831072 109.96296 
C 612.849259 108.944773 613.421351 107.563621 613.421351 106.123688 
C 613.421351 104.683754 612.849259 103.302603 611.831072 102.284416 
C 610.812885 101.26623 609.431734 100.694138 607.991801 100.694138 
C 606.551867 100.694138 605.170716 101.26623 604.152529 102.284416 
C 603.134342 103.302603 602.562251 104.683754 602.562251 106.123688 
C 602.562251 107.563621 603.134342 108.944773 604.152529 109.96296 
C 605.170716 110.981146 606.551867 111.553238 607.991801 111.553238 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471063; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 541.28655 176.144931 
C 543.688854 176.144931 545.99309 175.190485 547.691776 173.491799 
C 549.390462 171.793114 550.344907 169.488878 550.344907 167.086573 
C 550.344907 164.684269 549.390462 162.380033 547.691776 160.681347 
C 545.99309 158.982661 543.688854 158.028215 541.28655 158.028215 
C 538.884245 158.028215 536.580009 158.982661 534.881323 160.681347 
C 533.182638 162.380033 532.228192 164.684269 532.228192 167.086573 
C 532.228192 169.488878 533.182638 171.793114 534.881323 173.491799 
C 536.580009 175.190485 538.884245 176.144931 541.28655 176.144931 
z
" clip-path="url(#p8a32aafd77)" style="fill: #423f85; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 374.410075 82.729308 
C 376.289586 82.729308 378.09237 81.982571 379.421385 80.653556 
C 380.7504 79.324541 381.497138 77.521756 381.497138 75.642245 
C 381.497138 73.762734 380.7504 71.95995 379.421385 70.630935 
C 378.09237 69.30192 376.289586 68.555182 374.410075 68.555182 
C 372.530563 68.555182 370.727779 69.30192 369.398764 70.630935 
C 368.069749 71.95995 367.323011 73.762734 367.323011 75.642245 
C 367.323011 77.521756 368.069749 79.324541 369.398764 80.653556 
C 370.727779 81.982571 372.530563 82.729308 374.410075 82.729308 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482173; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 434.134983 325.401045 
C 435.701606 325.401045 437.204275 324.778619 438.312045 323.670849 
C 439.419815 322.563079 440.042242 321.06041 440.042242 319.493786 
C 440.042242 317.927163 439.419815 316.424494 438.312045 315.316724 
C 437.204275 314.208954 435.701606 313.586528 434.134983 313.586528 
C 432.568359 313.586528 431.06569 314.208954 429.95792 315.316724 
C 428.85015 316.424494 428.227724 317.927163 428.227724 319.493786 
C 428.227724 321.06041 428.85015 322.563079 429.95792 323.670849 
C 431.06569 324.778619 432.568359 325.401045 434.134983 325.401045 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481467; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 380.729221 110.132696 
C 381.792422 110.132696 382.812221 109.710281 383.564018 108.958485 
C 384.315815 108.206688 384.738229 107.186889 384.738229 106.123688 
C 384.738229 105.060487 384.315815 104.040688 383.564018 103.288891 
C 382.812221 102.537094 381.792422 102.11468 380.729221 102.11468 
C 379.66602 102.11468 378.646221 102.537094 377.894424 103.288891 
C 377.142628 104.040688 376.720213 105.060487 376.720213 106.123688 
C 376.720213 107.186889 377.142628 108.206688 377.894424 108.958485 
C 378.646221 109.710281 379.66602 110.132696 380.729221 110.132696 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 768.473564 157.217138 
C 769.898045 157.217138 771.264376 156.651185 772.271636 155.643924 
C 773.278897 154.636664 773.84485 153.270334 773.84485 151.845852 
C 773.84485 150.42137 773.278897 149.05504 772.271636 148.047779 
C 771.264376 147.040519 769.898045 146.474566 768.473564 146.474566 
C 767.049082 146.474566 765.682752 147.040519 764.675491 148.047779 
C 763.668231 149.05504 763.102278 150.42137 763.102278 151.845852 
C 763.102278 153.270334 763.668231 154.636664 764.675491 155.643924 
C 765.682752 156.651185 767.049082 157.217138 768.473564 157.217138 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471063; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 246.978676 103.408067 
C 250.300371 103.408067 253.486466 102.088344 255.835259 99.73955 
C 258.184053 97.390757 259.503776 94.204662 259.503776 90.882967 
C 259.503776 87.561271 258.184053 84.375176 255.835259 82.026383 
C 253.486466 79.67759 250.300371 78.357866 246.978676 78.357866 
C 243.65698 78.357866 240.470885 79.67759 238.122092 82.026383 
C 235.773298 84.375176 234.453575 87.561271 234.453575 90.882967 
C 234.453575 94.204662 235.773298 97.390757 238.122092 99.73955 
C 240.470885 102.088344 243.65698 103.408067 246.978676 103.408067 
z
" clip-path="url(#p8a32aafd77)" style="fill: #287c8e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 522.234653 186.794985 
C 523.419499 186.794985 524.555976 186.324241 525.393788 185.486429 
C 526.2316 184.648617 526.702344 183.51214 526.702344 182.327295 
C 526.702344 181.142449 526.2316 180.005972 525.393788 179.16816 
C 524.555976 178.330348 523.419499 177.859604 522.234653 177.859604 
C 521.049808 177.859604 519.913331 178.330348 519.075519 179.16816 
C 518.237707 180.005972 517.766963 181.142449 517.766963 182.327295 
C 517.766963 183.51214 518.237707 184.648617 519.075519 185.486429 
C 519.913331 186.324241 521.049808 186.794985 522.234653 186.794985 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 369.753364 112.438496 
C 371.428071 112.438496 373.034412 111.773128 374.218608 110.588932 
C 375.402805 109.404735 376.068173 107.798395 376.068173 106.123688 
C 376.068173 104.448981 375.402805 102.842641 374.218608 101.658444 
C 373.034412 100.474247 371.428071 99.808879 369.753364 99.808879 
C 368.078657 99.808879 366.472317 100.474247 365.28812 101.658444 
C 364.103924 102.842641 363.438556 104.448981 363.438556 106.123688 
C 363.438556 107.798395 364.103924 109.404735 365.28812 110.588932 
C 366.472317 111.773128 368.078657 112.438496 369.753364 112.438496 
z
" clip-path="url(#p8a32aafd77)" style="fill: #48186a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 271.055663 112.958754 
C 272.868344 112.958754 274.607026 112.238568 275.888784 110.956809 
C 277.170543 109.675051 277.890729 107.936369 277.890729 106.123688 
C 277.890729 104.311007 277.170543 102.572325 275.888784 101.290566 
C 274.607026 100.008808 272.868344 99.288622 271.055663 99.288622 
C 269.242982 99.288622 267.5043 100.008808 266.222541 101.290566 
C 264.940783 102.572325 264.220597 104.311007 264.220597 106.123688 
C 264.220597 107.936369 264.940783 109.675051 266.222541 110.956809 
C 267.5043 112.238568 269.242982 112.958754 271.055663 112.958754 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481f70; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 378.112773 185.626944 
C 378.98785 185.626944 379.827205 185.279272 380.445978 184.660499 
C 381.064751 184.041726 381.412423 183.202372 381.412423 182.327295 
C 381.412423 181.452217 381.064751 180.612863 380.445978 179.99409 
C 379.827205 179.375317 378.98785 179.027645 378.112773 179.027645 
C 377.237696 179.027645 376.398342 179.375317 375.779569 179.99409 
C 375.160796 180.612863 374.813124 181.452217 374.813124 182.327295 
C 374.813124 183.202372 375.160796 184.041726 375.779569 184.660499 
C 376.398342 185.279272 377.237696 185.626944 378.112773 185.626944 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 229.409748 187.186637 
C 230.698461 187.186637 231.934565 186.674626 232.845822 185.763369 
C 233.75708 184.852111 234.26909 183.616007 234.26909 182.327295 
C 234.26909 181.038582 233.75708 179.802478 232.845822 178.89122 
C 231.934565 177.979963 230.698461 177.467952 229.409748 177.467952 
C 228.121035 177.467952 226.884931 177.979963 225.973674 178.89122 
C 225.062416 179.802478 224.550405 181.038582 224.550405 182.327295 
C 224.550405 183.616007 225.062416 184.852111 225.973674 185.763369 
C 226.884931 186.674626 228.121035 187.186637 229.409748 187.186637 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460b5e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 476.687681 155.13595 
C 477.560225 155.13595 478.397149 154.789284 479.014131 154.172302 
C 479.631113 153.55532 479.977779 152.718396 479.977779 151.845852 
C 479.977779 150.973308 479.631113 150.136383 479.014131 149.519402 
C 478.397149 148.90242 477.560225 148.555754 476.687681 148.555754 
C 475.815137 148.555754 474.978212 148.90242 474.361231 149.519402 
C 473.744249 150.136383 473.397583 150.973308 473.397583 151.845852 
C 473.397583 152.718396 473.744249 153.55532 474.361231 154.172302 
C 474.978212 154.789284 475.815137 155.13595 476.687681 155.13595 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 332.121855 172.007586 
C 333.426923 172.007586 334.678714 171.489077 335.601537 170.566255 
C 336.524359 169.643433 337.042868 168.391641 337.042868 167.086573 
C 337.042868 165.781505 336.524359 164.529714 335.601537 163.606891 
C 334.678714 162.684069 333.426923 162.16556 332.121855 162.16556 
C 330.816787 162.16556 329.564995 162.684069 328.642173 163.606891 
C 327.719351 164.529714 327.200842 165.781505 327.200842 167.086573 
C 327.200842 168.391641 327.719351 169.643433 328.642173 170.566255 
C 329.564995 171.489077 330.816787 172.007586 332.121855 172.007586 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460b5e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 527.845375 80.890252 
C 529.237163 80.890252 530.572134 80.337289 531.556277 79.353146 
C 532.540419 78.369004 533.093382 77.034033 533.093382 75.642245 
C 533.093382 74.250458 532.540419 72.915487 531.556277 71.931344 
C 530.572134 70.947202 529.237163 70.394239 527.845375 70.394239 
C 526.453588 70.394239 525.118617 70.947202 524.134474 71.931344 
C 523.150332 72.915487 522.597369 74.250458 522.597369 75.642245 
C 522.597369 77.034033 523.150332 78.369004 524.134474 79.353146 
C 525.118617 80.337289 526.453588 80.890252 527.845375 80.890252 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470e61; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 208.884329 81.729425 
C 210.498668 81.729425 212.047105 81.088041 213.188615 79.946531 
C 214.330125 78.805021 214.971509 77.256584 214.971509 75.642245 
C 214.971509 74.027906 214.330125 72.479469 213.188615 71.337959 
C 212.047105 70.196449 210.498668 69.555066 208.884329 69.555066 
C 207.26999 69.555066 205.721553 70.196449 204.580043 71.337959 
C 203.438533 72.479469 202.797149 74.027906 202.797149 75.642245 
C 202.797149 77.256584 203.438533 78.805021 204.580043 79.946531 
C 205.721553 81.088041 207.26999 81.729425 208.884329 81.729425 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481769; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 515.924953 110.178106 
C 517.000197 110.178106 518.031547 109.750907 518.791859 108.990595 
C 519.552172 108.230282 519.979371 107.198932 519.979371 106.123688 
C 519.979371 105.048444 519.552172 104.017094 518.791859 103.256781 
C 518.031547 102.496468 517.000197 102.069269 515.924953 102.069269 
C 514.849708 102.069269 513.818358 102.496468 513.058046 103.256781 
C 512.297733 104.017094 511.870534 105.048444 511.870534 106.123688 
C 511.870534 107.198932 512.297733 108.230282 513.058046 108.990595 
C 513.818358 109.750907 514.849708 110.178106 515.924953 110.178106 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 383.487354 110.568374 
C 384.666098 110.568374 385.796723 110.100054 386.630221 109.266556 
C 387.46372 108.433057 387.93204 107.302432 387.93204 106.123688 
C 387.93204 104.944943 387.46372 103.814319 386.630221 102.98082 
C 385.796723 102.147322 384.666098 101.679002 383.487354 101.679002 
C 382.308609 101.679002 381.177984 102.147322 380.344486 102.98082 
C 379.510988 103.814319 379.042668 104.944943 379.042668 106.123688 
C 379.042668 107.302432 379.510988 108.433057 380.344486 109.266556 
C 381.177984 110.100054 382.308609 110.568374 383.487354 110.568374 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 688.714411 110.609615 
C 689.904093 110.609615 691.045208 110.136949 691.88644 109.295717 
C 692.727672 108.454485 693.200338 107.31337 693.200338 106.123688 
C 693.200338 104.934006 692.727672 103.792891 691.88644 102.951658 
C 691.045208 102.110426 689.904093 101.637761 688.714411 101.637761 
C 687.524729 101.637761 686.383613 102.110426 685.542381 102.951658 
C 684.701149 103.792891 684.228484 104.934006 684.228484 106.123688 
C 684.228484 107.31337 684.701149 108.454485 685.542381 109.295717 
C 686.383613 110.136949 687.524729 110.609615 688.714411 110.609615 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 424.689323 215.735668 
C 429.50744 215.735668 434.128869 213.821409 437.535793 210.414486 
C 440.942716 207.007562 442.856975 202.386133 442.856975 197.568016 
C 442.856975 192.749898 440.942716 188.12847 437.535793 184.721546 
C 434.128869 181.314622 429.50744 179.400364 424.689323 179.400364 
C 419.871205 179.400364 415.249776 181.314622 411.842853 184.721546 
C 408.435929 188.12847 406.521671 192.749898 406.521671 197.568016 
C 406.521671 202.386133 408.435929 207.007562 411.842853 210.414486 
C 415.249776 213.821409 419.871205 215.735668 424.689323 215.735668 
z
" clip-path="url(#p8a32aafd77)" style="fill: #fde725; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 486.48283 141.476145 
C 487.774639 141.476145 489.013712 140.962905 489.927158 140.049458 
C 490.840604 139.136012 491.353845 137.896939 491.353845 136.605131 
C 491.353845 135.313322 490.840604 134.074249 489.927158 133.160803 
C 489.013712 132.247357 487.774639 131.734116 486.48283 131.734116 
C 485.191022 131.734116 483.951949 132.247357 483.038503 133.160803 
C 482.125056 134.074249 481.611816 135.313322 481.611816 136.605131 
C 481.611816 137.896939 482.125056 139.136012 483.038503 140.049458 
C 483.951949 140.962905 485.191022 141.476145 486.48283 141.476145 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460b5e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 839.117655 263.039419 
C 840.313328 263.039419 841.46019 262.564373 842.305659 261.718905 
C 843.151127 260.873436 843.626173 259.726574 843.626173 258.530901 
C 843.626173 257.335228 843.151127 256.188366 842.305659 255.342897 
C 841.46019 254.497429 840.313328 254.022383 839.117655 254.022383 
C 837.921982 254.022383 836.77512 254.497429 835.929651 255.342897 
C 835.084183 256.188366 834.609137 257.335228 834.609137 258.530901 
C 834.609137 259.726574 835.084183 260.873436 835.929651 261.718905 
C 836.77512 262.564373 837.921982 263.039419 839.117655 263.039419 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 207.080208 210.173797 
C 210.4233 210.173797 213.629918 208.845573 215.993841 206.481649 
C 218.357764 204.117726 219.685989 200.911108 219.685989 197.568016 
C 219.685989 194.224924 218.357764 191.018306 215.993841 188.654382 
C 213.629918 186.290459 210.4233 184.962234 207.080208 184.962234 
C 203.737115 184.962234 200.530498 186.290459 198.166574 188.654382 
C 195.802651 191.018306 194.474426 194.224924 194.474426 197.568016 
C 194.474426 200.911108 195.802651 204.117726 198.166574 206.481649 
C 200.530498 208.845573 203.737115 210.173797 207.080208 210.173797 
z
" clip-path="url(#p8a32aafd77)" style="fill: #277e8e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 251.512592 141.969876 
C 252.935339 141.969876 254.300006 141.404612 255.30604 140.398578 
C 256.312074 139.392544 256.877338 138.027878 256.877338 136.605131 
C 256.877338 135.182383 256.312074 133.817717 255.30604 132.811683 
C 254.300006 131.805649 252.935339 131.240385 251.512592 131.240385 
C 250.089845 131.240385 248.725179 131.805649 247.719145 132.811683 
C 246.71311 133.817717 246.147847 135.182383 246.147847 136.605131 
C 246.147847 138.027878 246.71311 139.392544 247.719145 140.398578 
C 248.725179 141.404612 250.089845 141.969876 251.512592 141.969876 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470e61; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 377.536588 250.136391 
C 379.352224 250.136391 381.093741 249.415031 382.37759 248.131182 
C 383.661439 246.847333 384.382799 245.105816 384.382799 243.29018 
C 384.382799 241.474543 383.661439 239.733026 382.37759 238.449178 
C 381.093741 237.165329 379.352224 236.443969 377.536588 236.443969 
C 375.720952 236.443969 373.979435 237.165329 372.695586 238.449178 
C 371.411737 239.733026 370.690377 241.474543 370.690377 243.29018 
C 370.690377 245.105816 371.411737 246.847333 372.695586 248.131182 
C 373.979435 249.415031 375.720952 250.136391 377.536588 250.136391 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481f70; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 625.419043 80.786489 
C 626.783313 80.786489 628.091889 80.244459 629.056573 79.279775 
C 630.021257 78.315091 630.563287 77.006515 630.563287 75.642245 
C 630.563287 74.277976 630.021257 72.9694 629.056573 72.004716 
C 628.091889 71.040032 626.783313 70.498002 625.419043 70.498002 
C 624.054774 70.498002 622.746198 71.040032 621.781514 72.004716 
C 620.81683 72.9694 620.2748 74.277976 620.2748 75.642245 
C 620.2748 77.006515 620.81683 78.315091 621.781514 79.279775 
C 622.746198 80.244459 624.054774 80.786489 625.419043 80.786489 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 353.931884 263.696189 
C 355.301734 263.696189 356.615663 263.151942 357.584294 262.183311 
C 358.552924 261.214681 359.097172 259.900752 359.097172 258.530901 
C 359.097172 257.161051 358.552924 255.847121 357.584294 254.878491 
C 356.615663 253.90986 355.301734 253.365613 353.931884 253.365613 
C 352.562033 253.365613 351.248104 253.90986 350.279473 254.878491 
C 349.310843 255.847121 348.766596 257.161051 348.766596 258.530901 
C 348.766596 259.900752 349.310843 261.214681 350.279473 262.183311 
C 351.248104 263.151942 352.562033 263.696189 353.931884 263.696189 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 425.397747 127.149571 
C 426.93199 127.149571 428.403601 126.54001 429.488475 125.455137 
C 430.573348 124.370263 431.182909 122.898652 431.182909 121.364409 
C 431.182909 119.830166 430.573348 118.358555 429.488475 117.273682 
C 428.403601 116.188808 426.93199 115.579247 425.397747 115.579247 
C 423.863504 115.579247 422.391893 116.188808 421.30702 117.273682 
C 420.222146 118.358555 419.612585 119.830166 419.612585 121.364409 
C 419.612585 122.898652 420.222146 124.370263 421.30702 125.455137 
C 422.391893 126.54001 423.863504 127.149571 425.397747 127.149571 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471365; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 294.726487 109.963792 
C 295.744894 109.963792 296.721728 109.559175 297.441851 108.839052 
C 298.161974 108.118929 298.566591 107.142096 298.566591 106.123688 
C 298.566591 105.10528 298.161974 104.128447 297.441851 103.408324 
C 296.721728 102.688201 295.744894 102.283583 294.726487 102.283583 
C 293.708079 102.283583 292.731246 102.688201 292.011123 103.408324 
C 291.291 104.128447 290.886382 105.10528 290.886382 106.123688 
C 290.886382 107.142096 291.291 108.118929 292.011123 108.839052 
C 292.731246 109.559175 293.708079 109.963792 294.726487 109.963792 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 418.823568 308.636796 
C 419.986147 308.636796 421.101266 308.174899 421.923334 307.352831 
C 422.745401 306.530764 423.207299 305.415644 423.207299 304.253065 
C 423.207299 303.090486 422.745401 301.975367 421.923334 301.153299 
C 421.101266 300.331231 419.986147 299.869334 418.823568 299.869334 
C 417.660989 299.869334 416.545869 300.331231 415.723802 301.153299 
C 414.901734 301.975367 414.439837 303.090486 414.439837 304.253065 
C 414.439837 305.415644 414.901734 306.530764 415.723802 307.352831 
C 416.545869 308.174899 417.660989 308.636796 418.823568 308.636796 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 232.234 125.841237 
C 233.421269 125.841237 234.56007 125.36953 235.399595 124.530004 
C 236.239121 123.690479 236.710828 122.551678 236.710828 121.364409 
C 236.710828 120.177141 236.239121 119.03834 235.399595 118.198814 
C 234.56007 117.359289 233.421269 116.887582 232.234 116.887582 
C 231.046732 116.887582 229.907931 117.359289 229.068405 118.198814 
C 228.22888 119.03834 227.757173 120.177141 227.757173 121.364409 
C 227.757173 122.551678 228.22888 123.690479 229.068405 124.530004 
C 229.907931 125.36953 231.046732 125.841237 232.234 125.841237 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 427.608032 207.562672 
C 430.258645 207.562672 432.801054 206.509572 434.675321 204.635305 
C 436.549588 202.761038 437.602688 200.21863 437.602688 197.568016 
C 437.602688 194.917402 436.549588 192.374994 434.675321 190.500727 
C 432.801054 188.62646 430.258645 187.57336 427.608032 187.57336 
C 424.957418 187.57336 422.41501 188.62646 420.540743 190.500727 
C 418.666476 192.374994 417.613376 194.917402 417.613376 197.568016 
C 417.613376 200.21863 418.666476 202.761038 420.540743 204.635305 
C 422.41501 206.509572 424.957418 207.562672 427.608032 207.562672 
z
" clip-path="url(#p8a32aafd77)" style="fill: #3d4e8a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 243.549901 95.675167 
C 244.820807 95.675167 246.039832 95.170231 246.938499 94.271564 
C 247.837165 93.372898 248.342102 92.153873 248.342102 90.882967 
C 248.342102 89.61206 247.837165 88.393036 246.938499 87.494369 
C 246.039832 86.595703 244.820807 86.090766 243.549901 86.090766 
C 242.278995 86.090766 241.05997 86.595703 240.161303 87.494369 
C 239.262637 88.393036 238.7577 89.61206 238.7577 90.882967 
C 238.7577 92.153873 239.262637 93.372898 240.161303 94.271564 
C 241.05997 95.170231 242.278995 95.675167 243.549901 95.675167 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460a5d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 568.508942 187.609109 
C 569.909695 187.609109 571.253266 187.052583 572.243748 186.062101 
C 573.234231 185.071619 573.790756 183.728048 573.790756 182.327295 
C 573.790756 180.926541 573.234231 179.58297 572.243748 178.592488 
C 571.253266 177.602006 569.909695 177.04548 568.508942 177.04548 
C 567.108188 177.04548 565.764618 177.602006 564.774135 178.592488 
C 563.783653 179.58297 563.227128 180.926541 563.227128 182.327295 
C 563.227128 183.728048 563.783653 185.071619 564.774135 186.062101 
C 565.764618 187.052583 567.108188 187.609109 568.508942 187.609109 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470e61; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 416.122109 372.271166 
C 417.993174 372.271166 419.787857 371.527784 421.1109 370.204741 
C 422.433943 368.881699 423.177325 367.087016 423.177325 365.21595 
C 423.177325 363.344885 422.433943 361.550202 421.1109 360.227159 
C 419.787857 358.904116 417.993174 358.160734 416.122109 358.160734 
C 414.251044 358.160734 412.456361 358.904116 411.133318 360.227159 
C 409.810275 361.550202 409.066893 363.344885 409.066893 365.21595 
C 409.066893 367.087016 409.810275 368.881699 411.133318 370.204741 
C 412.456361 371.527784 414.251044 372.271166 416.122109 372.271166 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482173; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 689.148911 109.86564 
C 690.141288 109.86564 691.093154 109.471364 691.794871 108.769647 
C 692.496587 108.067931 692.890863 107.116065 692.890863 106.123688 
C 692.890863 105.131311 692.496587 104.179445 691.794871 103.477729 
C 691.093154 102.776012 690.141288 102.381736 689.148911 102.381736 
C 688.156534 102.381736 687.204668 102.776012 686.502952 103.477729 
C 685.801235 104.179445 685.40696 105.131311 685.40696 106.123688 
C 685.40696 107.116065 685.801235 108.067931 686.502952 108.769647 
C 687.204668 109.471364 688.156534 109.86564 689.148911 109.86564 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 683.6232 280.366101 
C 685.372076 280.366101 687.049558 279.671265 688.286201 278.434623 
C 689.522843 277.197981 690.217679 275.520499 690.217679 273.771622 
C 690.217679 272.022746 689.522843 270.345264 688.286201 269.108622 
C 687.049558 267.87198 685.372076 267.177144 683.6232 267.177144 
C 681.874324 267.177144 680.196842 267.87198 678.9602 269.108622 
C 677.723557 270.345264 677.028722 272.022746 677.028722 273.771622 
C 677.028722 275.520499 677.723557 277.197981 678.9602 278.434623 
C 680.196842 279.671265 681.874324 280.366101 683.6232 280.366101 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481c6e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 948.016669 172.35153 
C 949.412952 172.35153 950.752235 171.796781 951.739556 170.80946 
C 952.726877 169.822139 953.281626 168.482856 953.281626 167.086573 
C 953.281626 165.69029 952.726877 164.351007 951.739556 163.363686 
C 950.752235 162.376365 949.412952 161.821616 948.016669 161.821616 
C 946.620386 161.821616 945.281103 162.376365 944.293782 163.363686 
C 943.306461 164.351007 942.751712 165.69029 942.751712 167.086573 
C 942.751712 168.482856 943.306461 169.822139 944.293782 170.80946 
C 945.281103 171.796781 946.620386 172.35153 948.016669 172.35153 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470e61; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 257.378347 232.35573 
C 258.520384 232.35573 259.615799 231.901994 260.423341 231.094452 
C 261.230883 230.286911 261.684619 229.191495 261.684619 228.049458 
C 261.684619 226.907422 261.230883 225.812006 260.423341 225.004465 
C 259.615799 224.196923 258.520384 223.743187 257.378347 223.743187 
C 256.236311 223.743187 255.140895 224.196923 254.333353 225.004465 
C 253.525812 225.812006 253.072076 226.907422 253.072076 228.049458 
C 253.072076 229.191495 253.525812 230.286911 254.333353 231.094452 
C 255.140895 231.901994 256.236311 232.35573 257.378347 232.35573 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 415.593152 140.495232 
C 416.624819 140.495232 417.614371 140.085347 418.34387 139.355848 
C 419.073368 138.626349 419.483254 137.636798 419.483254 136.605131 
C 419.483254 135.573463 419.073368 134.583912 418.34387 133.854413 
C 417.614371 133.124914 416.624819 132.715029 415.593152 132.715029 
C 414.561485 132.715029 413.571933 133.124914 412.842435 133.854413 
C 412.112936 134.583912 411.70305 135.573463 411.70305 136.605131 
C 411.70305 137.636798 412.112936 138.626349 412.842435 139.355848 
C 413.571933 140.085347 414.561485 140.495232 415.593152 140.495232 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 481.930022 171.112744 
C 482.997775 171.112744 484.021939 170.688521 484.776955 169.933506 
C 485.53197 169.17849 485.956193 168.154326 485.956193 167.086573 
C 485.956193 166.01882 485.53197 164.994656 484.776955 164.239641 
C 484.021939 163.484626 482.997775 163.060403 481.930022 163.060403 
C 480.862269 163.060403 479.838105 163.484626 479.08309 164.239641 
C 478.328075 164.994656 477.903852 166.01882 477.903852 167.086573 
C 477.903852 168.154326 478.328075 169.17849 479.08309 169.933506 
C 479.838105 170.688521 480.862269 171.112744 481.930022 171.112744 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 504.070649 111.481879 
C 505.491658 111.481879 506.854658 110.917306 507.859463 109.912501 
C 508.864268 108.907696 509.428841 107.544697 509.428841 106.123688 
C 509.428841 104.702679 508.864268 103.33968 507.859463 102.334874 
C 506.854658 101.330069 505.491658 100.765497 504.070649 100.765497 
C 502.64964 100.765497 501.286641 101.330069 500.281836 102.334874 
C 499.277031 103.33968 498.712458 104.702679 498.712458 106.123688 
C 498.712458 107.544697 499.277031 108.907696 500.281836 109.912501 
C 501.286641 110.917306 502.64964 111.481879 504.070649 111.481879 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470e61; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 269.440455 96.946107 
C 271.048419 96.946107 272.590741 96.307256 273.727743 95.170254 
C 274.864745 94.033252 275.503596 92.49093 275.503596 90.882967 
C 275.503596 89.275003 274.864745 87.732681 273.727743 86.595679 
C 272.590741 85.458677 271.048419 84.819826 269.440455 84.819826 
C 267.832491 84.819826 266.290169 85.458677 265.153167 86.595679 
C 264.016165 87.732681 263.377314 89.275003 263.377314 90.882967 
C 263.377314 92.49093 264.016165 94.033252 265.153167 95.170254 
C 266.290169 96.307256 267.832491 96.946107 269.440455 96.946107 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481668; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 430.498404 157.59327 
C 432.022637 157.59327 433.484646 156.987686 434.562442 155.90989 
C 435.640238 154.832095 436.245822 153.370085 436.245822 151.845852 
C 436.245822 150.321619 435.640238 148.859609 434.562442 147.781813 
C 433.484646 146.704018 432.022637 146.098434 430.498404 146.098434 
C 428.97417 146.098434 427.512161 146.704018 426.434365 147.781813 
C 425.35657 148.859609 424.750985 150.321619 424.750985 151.845852 
C 424.750985 153.370085 425.35657 154.832095 426.434365 155.90989 
C 427.512161 156.987686 428.97417 157.59327 430.498404 157.59327 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471365; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 889.226881 80.782967 
C 890.590216 80.782967 891.897896 80.241308 892.86192 79.277284 
C 893.825944 78.313261 894.367602 77.00558 894.367602 75.642245 
C 894.367602 74.27891 893.825944 72.97123 892.86192 72.007206 
C 891.897896 71.043183 890.590216 70.501524 889.226881 70.501524 
C 887.863546 70.501524 886.555866 71.043183 885.591842 72.007206 
C 884.627819 72.97123 884.08616 74.27891 884.08616 75.642245 
C 884.08616 77.00558 884.627819 78.313261 885.591842 79.277284 
C 886.555866 80.241308 887.863546 80.782967 889.226881 80.782967 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 294.140856 81.357408 
C 295.656535 81.357408 297.11034 80.755223 298.182087 79.683476 
C 299.253833 78.611729 299.856019 77.157924 299.856019 75.642245 
C 299.856019 74.126566 299.253833 72.672762 298.182087 71.601015 
C 297.11034 70.529268 295.656535 69.927082 294.140856 69.927082 
C 292.625177 69.927082 291.171372 70.529268 290.099625 71.601015 
C 289.027878 72.672762 288.425693 74.126566 288.425693 75.642245 
C 288.425693 77.157924 289.027878 78.611729 290.099625 79.683476 
C 291.171372 80.755223 292.625177 81.357408 294.140856 81.357408 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471365; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 787.005949 79.938632 
C 788.145364 79.938632 789.238265 79.485937 790.043953 78.680249 
C 790.849641 77.874561 791.302335 76.78166 791.302335 75.642245 
C 791.302335 74.50283 790.849641 73.409929 790.043953 72.604241 
C 789.238265 71.798553 788.145364 71.345859 787.005949 71.345859 
C 785.866534 71.345859 784.773633 71.798553 783.967945 72.604241 
C 783.162257 73.409929 782.709562 74.50283 782.709562 75.642245 
C 782.709562 76.78166 783.162257 77.874561 783.967945 78.680249 
C 784.773633 79.485937 785.866534 79.938632 787.005949 79.938632 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 392.838557 94.981701 
C 393.925554 94.981701 394.968177 94.549833 395.7368 93.78121 
C 396.505423 93.012587 396.937292 91.969964 396.937292 90.882967 
C 396.937292 89.795969 396.505423 88.753347 395.7368 87.984724 
C 394.968177 87.216101 393.925554 86.784232 392.838557 86.784232 
C 391.75156 86.784232 390.708937 87.216101 389.940314 87.984724 
C 389.171691 88.753347 388.739823 89.795969 388.739823 90.882967 
C 388.739823 91.969964 389.171691 93.012587 389.940314 93.78121 
C 390.708937 94.549833 391.75156 94.981701 392.838557 94.981701 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 605.006972 94.490692 
C 605.963752 94.490692 606.881474 94.110559 607.558019 93.434014 
C 608.234565 92.757468 608.614698 91.839747 608.614698 90.882967 
C 608.614698 89.926187 608.234565 89.008465 607.558019 88.331919 
C 606.881474 87.655374 605.963752 87.275241 605.006972 87.275241 
C 604.050192 87.275241 603.13247 87.655374 602.455925 88.331919 
C 601.779379 89.008465 601.399246 89.926187 601.399246 90.882967 
C 601.399246 91.839747 601.779379 92.757468 602.455925 93.434014 
C 603.13247 94.110559 604.050192 94.490692 605.006972 94.490692 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 299.279295 80.497686 
C 300.566973 80.497686 301.802084 79.986086 302.71261 79.07556 
C 303.623135 78.165034 304.134735 76.929923 304.134735 75.642245 
C 304.134735 74.354567 303.623135 73.119456 302.71261 72.208931 
C 301.802084 71.298405 300.566973 70.786805 299.279295 70.786805 
C 297.991617 70.786805 296.756506 71.298405 295.84598 72.208931 
C 294.935455 73.119456 294.423855 74.354567 294.423855 75.642245 
C 294.423855 76.929923 294.935455 78.165034 295.84598 79.07556 
C 296.756506 79.986086 297.991617 80.497686 299.279295 80.497686 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460b5e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 855.411418 232.580348 
C 856.613024 232.580348 857.765577 232.102944 858.615241 231.253281 
C 859.464904 230.403617 859.942307 229.251064 859.942307 228.049458 
C 859.942307 226.847853 859.464904 225.6953 858.615241 224.845636 
C 857.765577 223.995972 856.613024 223.518569 855.411418 223.518569 
C 854.209813 223.518569 853.05726 223.995972 852.207596 224.845636 
C 851.357932 225.6953 850.880529 226.847853 850.880529 228.049458 
C 850.880529 229.251064 851.357932 230.403617 852.207596 231.253281 
C 853.05726 232.102944 854.209813 232.580348 855.411418 232.580348 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 303.973788 94.987168 
C 305.062235 94.987168 306.106248 94.554723 306.875896 93.785075 
C 307.645544 93.015427 308.077989 91.971413 308.077989 90.882967 
C 308.077989 89.79452 307.645544 88.750506 306.875896 87.980858 
C 306.106248 87.21121 305.062235 86.778766 303.973788 86.778766 
C 302.885341 86.778766 301.841328 87.21121 301.07168 87.980858 
C 300.302031 88.750506 299.869587 89.79452 299.869587 90.882967 
C 299.869587 91.971413 300.302031 93.015427 301.07168 93.785075 
C 301.841328 94.554723 302.885341 94.987168 303.973788 94.987168 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 259.768099 385.54045 
C 261.116333 385.54045 262.409528 385.004791 263.362873 384.051446 
C 264.316219 383.098101 264.851878 381.804905 264.851878 380.456672 
C 264.851878 379.108438 264.316219 377.815243 263.362873 376.861897 
C 262.409528 375.908552 261.116333 375.372893 259.768099 375.372893 
C 258.419865 375.372893 257.12667 375.908552 256.173325 376.861897 
C 255.21998 377.815243 254.684321 379.108438 254.684321 380.456672 
C 254.684321 381.804905 255.21998 383.098101 256.173325 384.051446 
C 257.12667 385.004791 258.419865 385.54045 259.768099 385.54045 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 360.118791 248.025744 
C 361.374677 248.025744 362.579295 247.526775 363.467341 246.638729 
C 364.355386 245.750684 364.854355 244.546066 364.854355 243.29018 
C 364.854355 242.034293 364.355386 240.829676 363.467341 239.94163 
C 362.579295 239.053584 361.374677 238.554615 360.118791 238.554615 
C 358.862905 238.554615 357.658287 239.053584 356.770241 239.94163 
C 355.882196 240.829676 355.383227 242.034293 355.383227 243.29018 
C 355.383227 244.546066 355.882196 245.750684 356.770241 246.638729 
C 357.658287 247.526775 358.862905 248.025744 360.118791 248.025744 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460a5d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 536.403143 211.770567 
C 540.169704 211.770567 543.782503 210.274096 546.445863 207.610736 
C 549.109224 204.947375 550.605694 201.334576 550.605694 197.568016 
C 550.605694 193.801455 549.109224 190.188656 546.445863 187.525296 
C 543.782503 184.861935 540.169704 183.365465 536.403143 183.365465 
C 532.636583 183.365465 529.023784 184.861935 526.360423 187.525296 
C 523.697063 190.188656 522.200593 193.801455 522.200593 197.568016 
C 522.200593 201.334576 523.697063 204.947375 526.360423 207.610736 
C 529.023784 210.274096 532.636583 211.770567 536.403143 211.770567 
z
" clip-path="url(#p8a32aafd77)" style="fill: #1fa088; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 647.153507 171.107041 
C 648.219747 171.107041 649.242461 170.683419 649.996407 169.929473 
C 650.750353 169.175527 651.173975 168.152814 651.173975 167.086573 
C 651.173975 166.020333 650.750353 164.997619 649.996407 164.243673 
C 649.242461 163.489727 648.219747 163.066106 647.153507 163.066106 
C 646.087266 163.066106 645.064553 163.489727 644.310607 164.243673 
C 643.556661 164.997619 643.133039 166.020333 643.133039 167.086573 
C 643.133039 168.152814 643.556661 169.175527 644.310607 169.929473 
C 645.064553 170.683419 646.087266 171.107041 647.153507 171.107041 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 364.369338 263.057333 
C 365.569762 263.057333 366.721181 262.5804 367.570009 261.731572 
C 368.418837 260.882744 368.89577 259.731325 368.89577 258.530901 
C 368.89577 257.330477 368.418837 256.179058 367.570009 255.33023 
C 366.721181 254.481402 365.569762 254.004469 364.369338 254.004469 
C 363.168914 254.004469 362.017495 254.481402 361.168667 255.33023 
C 360.319839 256.179058 359.842906 257.330477 359.842906 258.530901 
C 359.842906 259.731325 360.319839 260.882744 361.168667 261.731572 
C 362.017495 262.5804 363.168914 263.057333 364.369338 263.057333 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 448.407375 170.894632 
C 449.417284 170.894632 450.385966 170.493391 451.100079 169.779278 
C 451.814193 169.065164 452.215434 168.096482 452.215434 167.086573 
C 452.215434 166.076664 451.814193 165.107982 451.100079 164.393869 
C 450.385966 163.679755 449.417284 163.278514 448.407375 163.278514 
C 447.397466 163.278514 446.428784 163.679755 445.71467 164.393869 
C 445.000557 165.107982 444.599316 166.076664 444.599316 167.086573 
C 444.599316 168.096482 445.000557 169.065164 445.71467 169.779278 
C 446.428784 170.493391 447.397466 170.894632 448.407375 170.894632 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 383.288995 140.602605 
C 384.349138 140.602605 385.366002 140.181406 386.115636 139.431772 
C 386.86527 138.682138 387.286469 137.665273 387.286469 136.605131 
C 387.286469 135.544988 386.86527 134.528123 386.115636 133.778489 
C 385.366002 133.028855 384.349138 132.607656 383.288995 132.607656 
C 382.228852 132.607656 381.211988 133.028855 380.462354 133.778489 
C 379.71272 134.528123 379.291521 135.544988 379.291521 136.605131 
C 379.291521 137.665273 379.71272 138.682138 380.462354 139.431772 
C 381.211988 140.181406 382.228852 140.602605 383.288995 140.602605 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 266.427289 295.489903 
C 268.145158 295.489903 269.792899 294.807387 271.007616 293.59267 
C 272.222332 292.377953 272.904849 290.730213 272.904849 289.012344 
C 272.904849 287.294475 272.222332 285.646734 271.007616 284.432018 
C 269.792899 283.217301 268.145158 282.534784 266.427289 282.534784 
C 264.709421 282.534784 263.06168 283.217301 261.846963 284.432018 
C 260.632247 285.646734 259.94973 287.294475 259.94973 289.012344 
C 259.94973 290.730213 260.632247 292.377953 261.846963 293.59267 
C 263.06168 294.807387 264.709421 295.489903 266.427289 295.489903 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481b6d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 634.033485 79.329174 
C 635.01127 79.329174 635.949139 78.940696 636.640537 78.249298 
C 637.331936 77.557899 637.720414 76.62003 637.720414 75.642245 
C 637.720414 74.66446 637.331936 73.726591 636.640537 73.035193 
C 635.949139 72.343795 635.01127 71.955317 634.033485 71.955317 
C 633.0557 71.955317 632.117831 72.343795 631.426433 73.035193 
C 630.735035 73.726591 630.346557 74.66446 630.346557 75.642245 
C 630.346557 76.62003 630.735035 77.557899 631.426433 78.249298 
C 632.117831 78.940696 633.0557 79.329174 634.033485 79.329174 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 465.248987 185.451006 
C 466.077405 185.451006 466.872004 185.121872 467.457784 184.536092 
C 468.043564 183.950312 468.372698 183.155712 468.372698 182.327295 
C 468.372698 181.498877 468.043564 180.704277 467.457784 180.118497 
C 466.872004 179.532717 466.077405 179.203583 465.248987 179.203583 
C 464.420569 179.203583 463.625969 179.532717 463.040189 180.118497 
C 462.454409 180.704277 462.125276 181.498877 462.125276 182.327295 
C 462.125276 183.155712 462.454409 183.950312 463.040189 184.536092 
C 463.625969 185.121872 464.420569 185.451006 465.248987 185.451006 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 227.690638 125.704917 
C 228.841754 125.704917 229.945878 125.247574 230.75984 124.433612 
C 231.573802 123.61965 232.031145 122.515525 232.031145 121.364409 
C 232.031145 120.213293 231.573802 119.109169 230.75984 118.295207 
C 229.945878 117.481245 228.841754 117.023902 227.690638 117.023902 
C 226.539522 117.023902 225.435397 117.481245 224.621435 118.295207 
C 223.807474 119.109169 223.35013 120.213293 223.35013 121.364409 
C 223.35013 122.515525 223.807474 123.61965 224.621435 124.433612 
C 225.435397 125.247574 226.539522 125.704917 227.690638 125.704917 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 297.097347 231.90849 
C 298.120775 231.90849 299.102423 231.501878 299.826095 230.778206 
C 300.549767 230.054534 300.956379 229.072886 300.956379 228.049458 
C 300.956379 227.026031 300.549767 226.044383 299.826095 225.320711 
C 299.102423 224.597039 298.120775 224.190427 297.097347 224.190427 
C 296.07392 224.190427 295.092272 224.597039 294.3686 225.320711 
C 293.644928 226.044383 293.238316 227.026031 293.238316 228.049458 
C 293.238316 229.072886 293.644928 230.054534 294.3686 230.778206 
C 295.092272 231.501878 296.07392 231.90849 297.097347 231.90849 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 382.14607 216.251139 
C 383.059006 216.251139 383.934673 215.888426 384.580216 215.242883 
C 385.225759 214.59734 385.588472 213.721673 385.588472 212.808737 
C 385.588472 211.895801 385.225759 211.020134 384.580216 210.374591 
C 383.934673 209.729048 383.059006 209.366335 382.14607 209.366335 
C 381.233134 209.366335 380.357467 209.729048 379.711924 210.374591 
C 379.066381 211.020134 378.703668 211.895801 378.703668 212.808737 
C 378.703668 213.721673 379.066381 214.59734 379.711924 215.242883 
C 380.357467 215.888426 381.233134 216.251139 382.14607 216.251139 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 311.983708 124.205872 
C 312.737272 124.205872 313.460074 123.906477 313.992925 123.373627 
C 314.525776 122.840776 314.82517 122.117974 314.82517 121.364409 
C 314.82517 120.610845 314.525776 119.888043 313.992925 119.355192 
C 313.460074 118.822341 312.737272 118.522947 311.983708 118.522947 
C 311.230143 118.522947 310.507341 118.822341 309.97449 119.355192 
C 309.44164 119.888043 309.142245 120.610845 309.142245 121.364409 
C 309.142245 122.117974 309.44164 122.840776 309.97449 123.373627 
C 310.507341 123.906477 311.230143 124.205872 311.983708 124.205872 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 319.379659 206.699801 
C 321.801437 206.699801 324.124351 205.737619 325.836807 204.025163 
C 327.549262 202.312708 328.511445 199.989794 328.511445 197.568016 
C 328.511445 195.146238 327.549262 192.823324 325.836807 191.110869 
C 324.124351 189.398413 321.801437 188.436231 319.379659 188.436231 
C 316.957882 188.436231 314.634968 189.398413 312.922512 191.110869 
C 311.210057 192.823324 310.247874 195.146238 310.247874 197.568016 
C 310.247874 199.989794 311.210057 202.312708 312.922512 204.025163 
C 314.634968 205.737619 316.957882 206.699801 319.379659 206.699801 
z
" clip-path="url(#p8a32aafd77)" style="fill: #424086; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 434.871744 156.823431 
C 436.191814 156.823431 437.457994 156.298962 438.391424 155.365532 
C 439.324854 154.432102 439.849323 153.165921 439.849323 151.845852 
C 439.849323 150.525782 439.324854 149.259602 438.391424 148.326172 
C 437.457994 147.392742 436.191814 146.868273 434.871744 146.868273 
C 433.551675 146.868273 432.285494 147.392742 431.352064 148.326172 
C 430.418634 149.259602 429.894165 150.525782 429.894165 151.845852 
C 429.894165 153.165921 430.418634 154.432102 431.352064 155.365532 
C 432.285494 156.298962 433.551675 156.823431 434.871744 156.823431 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460b5e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 301.300666 154.55883 
C 302.020156 154.55883 302.710275 154.272974 303.219031 153.764217 
C 303.727788 153.255461 304.013644 152.565342 304.013644 151.845852 
C 304.013644 151.126362 303.727788 150.436243 303.219031 149.927487 
C 302.710275 149.41873 302.020156 149.132874 301.300666 149.132874 
C 300.581176 149.132874 299.891057 149.41873 299.382301 149.927487 
C 298.873544 150.436243 298.587688 151.126362 298.587688 151.845852 
C 298.587688 152.565342 298.873544 153.255461 299.382301 153.764217 
C 299.891057 154.272974 300.581176 154.55883 301.300666 154.55883 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 335.059455 235.020874 
C 336.908296 235.020874 338.681662 234.286322 339.98899 232.978994 
C 341.296318 231.671666 342.030871 229.898299 342.030871 228.049458 
C 342.030871 226.200617 341.296318 224.427251 339.98899 223.119923 
C 338.681662 221.812595 336.908296 221.078043 335.059455 221.078043 
C 333.210614 221.078043 331.437248 221.812595 330.12992 223.119923 
C 328.822592 224.427251 328.088039 226.200617 328.088039 228.049458 
C 328.088039 229.898299 328.822592 231.671666 330.12992 232.978994 
C 331.437248 234.286322 333.210614 235.020874 335.059455 235.020874 
z
" clip-path="url(#p8a32aafd77)" style="fill: #482071; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 195.717079 140.064225 
C 196.634441 140.064225 197.514355 139.699753 198.163028 139.05108 
C 198.811701 138.402406 199.176173 137.522493 199.176173 136.605131 
C 199.176173 135.687768 198.811701 134.807855 198.163028 134.159181 
C 197.514355 133.510508 196.634441 133.146036 195.717079 133.146036 
C 194.799716 133.146036 193.919803 133.510508 193.27113 134.159181 
C 192.622456 134.807855 192.257984 135.687768 192.257984 136.605131 
C 192.257984 137.522493 192.622456 138.402406 193.27113 139.05108 
C 193.919803 139.699753 194.799716 140.064225 195.717079 140.064225 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 381.853255 400.485589 
C 383.123099 400.485589 384.341105 399.981075 385.239021 399.083159 
C 386.136937 398.185243 386.641451 396.967238 386.641451 395.697393 
C 386.641451 394.427548 386.136937 393.209542 385.239021 392.311627 
C 384.341105 391.413711 383.123099 390.909196 381.853255 390.909196 
C 380.58341 390.909196 379.365404 391.413711 378.467488 392.311627 
C 377.569573 393.209542 377.065058 394.427548 377.065058 395.697393 
C 377.065058 396.967238 377.569573 398.185243 378.467488 399.083159 
C 379.365404 399.981075 380.58341 400.485589 381.853255 400.485589 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460a5d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 562.274806 414.388891 
C 563.189963 414.388891 564.06776 414.025295 564.714874 413.378182 
C 565.361987 412.731068 565.725583 411.853271 565.725583 410.938114 
C 565.725583 410.022958 565.361987 409.14516 564.714874 408.498047 
C 564.06776 407.850933 563.189963 407.487338 562.274806 407.487338 
C 561.35965 407.487338 560.481852 407.850933 559.834739 408.498047 
C 559.187625 409.14516 558.82403 410.022958 558.82403 410.938114 
C 558.82403 411.853271 559.187625 412.731068 559.834739 413.378182 
C 560.481852 414.025295 561.35965 414.388891 562.274806 414.388891 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 211.368537 79.48235 
C 212.386945 79.48235 213.363778 79.077732 214.083901 78.357609 
C 214.804024 77.637486 215.208642 76.660653 215.208642 75.642245 
C 215.208642 74.623838 214.804024 73.647004 214.083901 72.926881 
C 213.363778 72.206758 212.386945 71.802141 211.368537 71.802141 
C 210.35013 71.802141 209.373296 72.206758 208.653173 72.926881 
C 207.933051 73.647004 207.528433 74.623838 207.528433 75.642245 
C 207.528433 76.660653 207.933051 77.637486 208.653173 78.357609 
C 209.373296 79.077732 210.35013 79.48235 211.368537 79.48235 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 308.828857 339.179194 
C 310.007602 339.179194 311.138227 338.710874 311.971725 337.877375 
C 312.805223 337.043877 313.273543 335.913252 313.273543 334.734508 
C 313.273543 333.555763 312.805223 332.425138 311.971725 331.59164 
C 311.138227 330.758142 310.007602 330.289822 308.828857 330.289822 
C 307.650113 330.289822 306.519488 330.758142 305.68599 331.59164 
C 304.852491 332.425138 304.384171 333.555763 304.384171 334.734508 
C 304.384171 335.913252 304.852491 337.043877 305.68599 337.877375 
C 306.519488 338.710874 307.650113 339.179194 308.828857 339.179194 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 217.319303 79.580895 
C 218.363845 79.580895 219.365746 79.165894 220.104349 78.427291 
C 220.842951 77.688688 221.257952 76.686787 221.257952 75.642245 
C 221.257952 74.597703 220.842951 73.595802 220.104349 72.8572 
C 219.365746 72.118597 218.363845 71.703596 217.319303 71.703596 
C 216.274761 71.703596 215.27286 72.118597 214.534258 72.8572 
C 213.795655 73.595802 213.380654 74.597703 213.380654 75.642245 
C 213.380654 76.686787 213.795655 77.688688 214.534258 78.427291 
C 215.27286 79.165894 216.274761 79.580895 217.319303 79.580895 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 746.701318 80.828429 
C 748.07671 80.828429 749.395954 80.28198 750.368503 79.309431 
C 751.341052 78.336882 751.887501 77.017637 751.887501 75.642245 
C 751.887501 74.266853 751.341052 72.947609 750.368503 71.97506 
C 749.395954 71.002511 748.07671 70.456062 746.701318 70.456062 
C 745.325926 70.456062 744.006681 71.002511 743.034132 71.97506 
C 742.061583 72.947609 741.515134 74.266853 741.515134 75.642245 
C 741.515134 77.017637 742.061583 78.336882 743.034132 79.309431 
C 744.006681 80.28198 745.325926 80.828429 746.701318 80.828429 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 363.868718 216.680267 
C 364.89546 216.680267 365.880287 216.272338 366.606303 215.546322 
C 367.332319 214.820306 367.740248 213.835479 367.740248 212.808737 
C 367.740248 211.781995 367.332319 210.797168 366.606303 210.071152 
C 365.880287 209.345136 364.89546 208.937207 363.868718 208.937207 
C 362.841976 208.937207 361.857149 209.345136 361.131133 210.071152 
C 360.405117 210.797168 359.997188 211.781995 359.997188 212.808737 
C 359.997188 213.835479 360.405117 214.820306 361.131133 215.546322 
C 361.857149 216.272338 362.841976 216.680267 363.868718 216.680267 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 202.329041 216.019126 
C 203.180446 216.019126 203.997094 215.680859 204.599129 215.078825 
C 205.201163 214.476791 205.53943 213.660142 205.53943 212.808737 
C 205.53943 211.957332 205.201163 211.140684 204.599129 210.538649 
C 203.997094 209.936615 203.180446 209.598348 202.329041 209.598348 
C 201.477636 209.598348 200.660987 209.936615 200.058953 210.538649 
C 199.456919 211.140684 199.118652 211.957332 199.118652 212.808737 
C 199.118652 213.660142 199.456919 214.476791 200.058953 215.078825 
C 200.660987 215.680859 201.477636 216.019126 202.329041 216.019126 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 841.564081 431.768008 
C 843.046347 431.768008 844.468102 431.179097 845.516222 430.130977 
C 846.564343 429.082857 847.153253 427.661101 847.153253 426.178836 
C 847.153253 424.69657 846.564343 423.274814 845.516222 422.226694 
C 844.468102 421.178574 843.046347 420.589663 841.564081 420.589663 
C 840.081815 420.589663 838.66006 421.178574 837.611939 422.226694 
C 836.563819 423.274814 835.974909 424.69657 835.974909 426.178836 
C 835.974909 427.661101 836.563819 429.082857 837.611939 430.130977 
C 838.66006 431.179097 840.081815 431.768008 841.564081 431.768008 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471164; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 213.720507 217.494723 
C 214.963245 217.494723 216.155251 217.000978 217.033999 216.12223 
C 217.912748 215.243481 218.406493 214.051475 218.406493 212.808737 
C 218.406493 211.565999 217.912748 210.373993 217.033999 209.495245 
C 216.155251 208.616496 214.963245 208.122751 213.720507 208.122751 
C 212.477769 208.122751 211.285763 208.616496 210.407014 209.495245 
C 209.528266 210.373993 209.034521 211.565999 209.034521 212.808737 
C 209.034521 214.051475 209.528266 215.243481 210.407014 216.12223 
C 211.285763 217.000978 212.477769 217.494723 213.720507 217.494723 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460a5d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 575.035893 279.418364 
C 576.533426 279.418364 577.969826 278.823387 579.028742 277.764471 
C 580.087658 276.705555 580.682634 275.269156 580.682634 273.771622 
C 580.682634 272.274089 580.087658 270.837689 579.028742 269.778773 
C 577.969826 268.719857 576.533426 268.124881 575.035893 268.124881 
C 573.53836 268.124881 572.10196 268.719857 571.043044 269.778773 
C 569.984128 270.837689 569.389152 272.274089 569.389152 273.771622 
C 569.389152 275.269156 569.984128 276.705555 571.043044 277.764471 
C 572.10196 278.823387 573.53836 279.418364 575.035893 279.418364 
z
" clip-path="url(#p8a32aafd77)" style="fill: #471164; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 385.130899 231.310378 
C 385.995705 231.310378 386.825207 230.966787 387.436717 230.355277 
C 388.048227 229.743767 388.391818 228.914264 388.391818 228.049458 
C 388.391818 227.184653 388.048227 226.35515 387.436717 225.74364 
C 386.825207 225.13213 385.995705 224.788539 385.130899 224.788539 
C 384.266093 224.788539 383.436591 225.13213 382.82508 225.74364 
C 382.21357 226.35515 381.869979 227.184653 381.869979 228.049458 
C 381.869979 228.914264 382.21357 229.743767 382.82508 230.355277 
C 383.436591 230.966787 384.266093 231.310378 385.130899 231.310378 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 290.40982 215.885845 
C 291.225879 215.885845 292.008624 215.561622 292.585664 214.984581 
C 293.162705 214.407541 293.486928 213.624796 293.486928 212.808737 
C 293.486928 211.992679 293.162705 211.209934 292.585664 210.632893 
C 292.008624 210.055852 291.225879 209.731629 290.40982 209.731629 
C 289.593762 209.731629 288.811017 210.055852 288.233976 210.632893 
C 287.656935 211.209934 287.332712 211.992679 287.332712 212.808737 
C 287.332712 213.624796 287.656935 214.407541 288.233976 214.984581 
C 288.811017 215.561622 289.593762 215.885845 290.40982 215.885845 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 519.353727 216.923824 
C 520.445061 216.923824 521.491843 216.490232 522.263533 215.718543 
C 523.035222 214.946853 523.468814 213.900071 523.468814 212.808737 
C 523.468814 211.717403 523.035222 210.670621 522.263533 209.898932 
C 521.491843 209.127242 520.445061 208.693651 519.353727 208.693651 
C 518.262393 208.693651 517.215611 209.127242 516.443922 209.898932 
C 515.672232 210.670621 515.238641 211.717403 515.238641 212.808737 
C 515.238641 213.900071 515.672232 214.946853 516.443922 215.718543 
C 517.215611 216.490232 518.262393 216.923824 519.353727 216.923824 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 402.492022 474.834518 
C 403.27 474.834518 404.016219 474.525424 404.566332 473.97531 
C 405.116446 473.425197 405.42554 472.678978 405.42554 471.901 
C 405.42554 471.123021 405.116446 470.376803 404.566332 469.826689 
C 404.016219 469.276575 403.27 468.967481 402.492022 468.967481 
C 401.714044 468.967481 400.967825 469.276575 400.417711 469.826689 
C 399.867598 470.376803 399.558504 471.123021 399.558504 471.901 
C 399.558504 472.678978 399.867598 473.425197 400.417711 473.97531 
C 400.967825 474.525424 401.714044 474.834518 402.492022 474.834518 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 193.440675 353.949409 
C 194.49464 353.949409 195.505579 353.530665 196.250845 352.785399 
C 196.99611 352.040133 197.414855 351.029194 197.414855 349.975229 
C 197.414855 348.921264 196.99611 347.910325 196.250845 347.165059 
C 195.505579 346.419793 194.49464 346.001049 193.440675 346.001049 
C 192.38671 346.001049 191.375771 346.419793 190.630505 347.165059 
C 189.885239 347.910325 189.466494 348.921264 189.466494 349.975229 
C 189.466494 351.029194 189.885239 352.040133 190.630505 352.785399 
C 191.375771 353.530665 192.38671 353.949409 193.440675 353.949409 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 789.96244 155.966358 
C 791.055211 155.966358 792.103372 155.532195 792.876078 154.75949 
C 793.648784 153.986784 794.082946 152.938623 794.082946 151.845852 
C 794.082946 150.753081 793.648784 149.70492 792.876078 148.932214 
C 792.103372 148.159508 791.055211 147.725346 789.96244 147.725346 
C 788.869669 147.725346 787.821508 148.159508 787.048803 148.932214 
C 786.276097 149.70492 785.841934 150.753081 785.841934 151.845852 
C 785.841934 152.938623 786.276097 153.986784 787.048803 154.75949 
C 787.821508 155.532195 788.869669 155.966358 789.96244 155.966358 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 504.325682 155.345729 
C 505.25386 155.345729 506.144148 154.97696 506.800469 154.320638 
C 507.45679 153.664317 507.825559 152.77403 507.825559 151.845852 
C 507.825559 150.917674 507.45679 150.027386 506.800469 149.371065 
C 506.144148 148.714744 505.25386 148.345975 504.325682 148.345975 
C 503.397504 148.345975 502.507217 148.714744 501.850896 149.371065 
C 501.194574 150.027386 500.825805 150.917674 500.825805 151.845852 
C 500.825805 152.77403 501.194574 153.664317 501.850896 154.320638 
C 502.507217 154.97696 503.397504 155.345729 504.325682 155.345729 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 610.12652 140.773735 
C 611.232047 140.773735 612.292443 140.334505 613.074168 139.552779 
C 613.855894 138.771054 614.295124 137.710657 614.295124 136.605131 
C 614.295124 135.499604 613.855894 134.439208 613.074168 133.657482 
C 612.292443 132.875756 611.232047 132.436526 610.12652 132.436526 
C 609.020993 132.436526 607.960597 132.875756 607.178871 133.657482 
C 606.397146 134.439208 605.957915 135.499604 605.957915 136.605131 
C 605.957915 137.710657 606.397146 138.771054 607.178871 139.552779 
C 607.960597 140.334505 609.020993 140.773735 610.12652 140.773735 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 448.558506 262.885914 
C 449.713468 262.885914 450.821282 262.427042 451.637964 261.61036 
C 452.454646 260.793678 452.913518 259.685864 452.913518 258.530901 
C 452.913518 257.375938 452.454646 256.268124 451.637964 255.451442 
C 450.821282 254.63476 449.713468 254.175889 448.558506 254.175889 
C 447.403543 254.175889 446.295729 254.63476 445.479047 255.451442 
C 444.662365 256.268124 444.203493 257.375938 444.203493 258.530901 
C 444.203493 259.685864 444.662365 260.793678 445.479047 261.61036 
C 446.295729 262.427042 447.403543 262.885914 448.558506 262.885914 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 430.413393 353.889778 
C 431.451543 353.889778 432.447314 353.477316 433.181397 352.743233 
C 433.91548 352.00915 434.327942 351.01338 434.327942 349.975229 
C 434.327942 348.937078 433.91548 347.941308 433.181397 347.207225 
C 432.447314 346.473142 431.451543 346.06068 430.413393 346.06068 
C 429.375242 346.06068 428.379472 346.473142 427.645389 347.207225 
C 426.911305 347.941308 426.498844 348.937078 426.498844 349.975229 
C 426.498844 351.01338 426.911305 352.00915 427.645389 352.743233 
C 428.379472 353.477316 429.375242 353.889778 430.413393 353.889778 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 417.529512 171.30212 
C 418.647488 171.30212 419.719826 170.857943 420.510354 170.067415 
C 421.300883 169.276886 421.745059 168.204549 421.745059 167.086573 
C 421.745059 165.968597 421.300883 164.89626 420.510354 164.105731 
C 419.719826 163.315203 418.647488 162.871026 417.529512 162.871026 
C 416.411536 162.871026 415.339199 163.315203 414.548671 164.105731 
C 413.758142 164.89626 413.313966 165.968597 413.313966 167.086573 
C 413.313966 168.204549 413.758142 169.276886 414.548671 170.067415 
C 415.339199 170.857943 416.411536 171.30212 417.529512 171.30212 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 441.927652 444.966725 
C 442.868372 444.966725 443.770689 444.592973 444.435878 443.927783 
C 445.101068 443.262594 445.47482 442.360277 445.47482 441.419557 
C 445.47482 440.478837 445.101068 439.57652 444.435878 438.911331 
C 443.770689 438.246141 442.868372 437.872389 441.927652 437.872389 
C 440.986932 437.872389 440.084615 438.246141 439.419426 438.911331 
C 438.754236 439.57652 438.380485 440.478837 438.380485 441.419557 
C 438.380485 442.360277 438.754236 443.262594 439.419426 443.927783 
C 440.084615 444.592973 440.986932 444.966725 441.927652 444.966725 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 354.517515 185.462287 
C 355.348924 185.462287 356.146394 185.131965 356.734289 184.544069 
C 357.322185 183.956174 357.652508 183.158704 357.652508 182.327295 
C 357.652508 181.495885 357.322185 180.698415 356.734289 180.11052 
C 356.146394 179.522624 355.348924 179.192302 354.517515 179.192302 
C 353.686105 179.192302 352.888635 179.522624 352.30074 180.11052 
C 351.712844 180.698415 351.382522 181.495885 351.382522 182.327295 
C 351.382522 183.158704 351.712844 183.956174 352.30074 184.544069 
C 352.888635 185.131965 353.686105 185.462287 354.517515 185.462287 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 367.32583 125.030166 
C 368.298 125.030166 369.230483 124.643919 369.917911 123.956491 
C 370.605339 123.269063 370.991586 122.336579 370.991586 121.364409 
C 370.991586 120.392239 370.605339 119.459756 369.917911 118.772328 
C 369.230483 118.0849 368.298 117.698652 367.32583 117.698652 
C 366.353659 117.698652 365.421176 118.0849 364.733748 118.772328 
C 364.04632 119.459756 363.660073 120.392239 363.660073 121.364409 
C 363.660073 122.336579 364.04632 123.269063 364.733748 123.956491 
C 365.421176 124.643919 366.353659 125.030166 367.32583 125.030166 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 362.508543 293.702499 
C 363.752387 293.702499 364.945453 293.208315 365.824984 292.328784 
C 366.704514 291.449254 367.198698 290.256187 367.198698 289.012344 
C 367.198698 287.7685 366.704514 286.575433 365.824984 285.695903 
C 364.945453 284.816373 363.752387 284.322188 362.508543 284.322188 
C 361.264699 284.322188 360.071633 284.816373 359.192102 285.695903 
C 358.312572 286.575433 357.818388 287.7685 357.818388 289.012344 
C 357.818388 290.256187 358.312572 291.449254 359.192102 292.328784 
C 360.071633 293.208315 361.264699 293.702499 362.508543 293.702499 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460a5d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 538.736221 109.670856 
C 539.676941 109.670856 540.579258 109.297104 541.244448 108.631914 
C 541.909637 107.966725 542.283389 107.064408 542.283389 106.123688 
C 542.283389 105.182968 541.909637 104.280651 541.244448 103.615462 
C 540.579258 102.950272 539.676941 102.57652 538.736221 102.57652 
C 537.795502 102.57652 536.893185 102.950272 536.227995 103.615462 
C 535.562806 104.280651 535.189054 105.182968 535.189054 106.123688 
C 535.189054 107.064408 535.562806 107.966725 536.227995 108.631914 
C 536.893185 109.297104 537.795502 109.670856 538.736221 109.670856 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 284.392935 207.183702 
C 286.943045 207.183702 289.389052 206.170533 291.192252 204.367333 
C 292.995452 202.564133 294.008621 200.118126 294.008621 197.568016 
C 294.008621 195.017906 292.995452 192.571899 291.192252 190.768699 
C 289.389052 188.965499 286.943045 187.952329 284.392935 187.952329 
C 281.842825 187.952329 279.396818 188.965499 277.593618 190.768699 
C 275.790418 192.571899 274.777248 195.017906 274.777248 197.568016 
C 274.777248 200.118126 275.790418 202.564133 277.593618 204.367333 
C 279.396818 206.170533 281.842825 207.183702 284.392935 207.183702 
z
" clip-path="url(#p8a32aafd77)" style="fill: #3f4889; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 495.229512 292.733897 
C 496.216479 292.733897 497.163156 292.341771 497.861047 291.64388 
C 498.558939 290.945988 498.951065 289.999311 498.951065 289.012344 
C 498.951065 288.025376 498.558939 287.078699 497.861047 286.380808 
C 497.163156 285.682917 496.216479 285.29079 495.229512 285.29079 
C 494.242544 285.29079 493.295867 285.682917 492.597976 286.380808 
C 491.900084 287.078699 491.507958 288.025376 491.507958 289.012344 
C 491.507958 289.999311 491.900084 290.945988 492.597976 291.64388 
C 493.295867 292.341771 494.242544 292.733897 495.229512 292.733897 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 833.988662 354.127933 
C 835.089972 354.127933 836.146323 353.690378 836.925067 352.911635 
C 837.703811 352.132891 838.141366 351.076539 838.141366 349.975229 
C 838.141366 348.873919 837.703811 347.817567 836.925067 347.038824 
C 836.146323 346.26008 835.089972 345.822525 833.988662 345.822525 
C 832.887351 345.822525 831.831 346.26008 831.052256 347.038824 
C 830.273512 347.817567 829.835957 348.873919 829.835957 349.975229 
C 829.835957 351.076539 830.273512 352.132891 831.052256 352.911635 
C 831.831 353.690378 832.887351 354.127933 833.988662 354.127933 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 763.76018 355.11595 
C 765.123515 355.11595 766.431195 354.574291 767.395218 353.610268 
C 768.359242 352.646244 768.900901 351.338564 768.900901 349.975229 
C 768.900901 348.611894 768.359242 347.304214 767.395218 346.34019 
C 766.431195 345.376167 765.123515 344.834508 763.76018 344.834508 
C 762.396844 344.834508 761.089164 345.376167 760.125141 346.34019 
C 759.161117 347.304214 758.619458 348.611894 758.619458 349.975229 
C 758.619458 351.338564 759.161117 352.646244 760.125141 353.610268 
C 761.089164 354.574291 762.396844 355.11595 763.76018 355.11595 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 862.977392 141.122623 
C 864.175445 141.122623 865.32459 140.646632 866.171742 139.79948 
C 867.018893 138.952329 867.494885 137.803184 867.494885 136.605131 
C 867.494885 135.407078 867.018893 134.257932 866.171742 133.410781 
C 865.32459 132.563629 864.175445 132.087638 862.977392 132.087638 
C 861.779339 132.087638 860.630194 132.563629 859.783042 133.410781 
C 858.935891 134.257932 858.459899 135.407078 858.459899 136.605131 
C 858.459899 137.803184 858.935891 138.952329 859.783042 139.79948 
C 860.630194 140.646632 861.779339 141.122623 862.977392 141.122623 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 918.385634 140.648302 
C 919.457895 140.648302 920.486384 140.222288 921.244588 139.464085 
C 922.002791 138.705881 922.428805 137.677392 922.428805 136.605131 
C 922.428805 135.532869 922.002791 134.50438 921.244588 133.746176 
C 920.486384 132.987973 919.457895 132.561959 918.385634 132.561959 
C 917.313372 132.561959 916.284883 132.987973 915.52668 133.746176 
C 914.768476 134.50438 914.342462 135.532869 914.342462 136.605131 
C 914.342462 137.677392 914.768476 138.705881 915.52668 139.464085 
C 916.284883 140.222288 917.313372 140.648302 918.385634 140.648302 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 871.261236 124.48812 
C 872.089654 124.48812 872.884253 124.158987 873.470033 123.573207 
C 874.055813 122.987427 874.384947 122.192827 874.384947 121.364409 
C 874.384947 120.535991 874.055813 119.741392 873.470033 119.155612 
C 872.884253 118.569832 872.089654 118.240698 871.261236 118.240698 
C 870.432818 118.240698 869.638218 118.569832 869.052439 119.155612 
C 868.466659 119.741392 868.137525 120.535991 868.137525 121.364409 
C 868.137525 122.192827 868.466659 122.987427 869.052439 123.573207 
C 869.638218 124.158987 870.432818 124.48812 871.261236 124.48812 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 657.836548 109.505787 
C 658.733492 109.505787 659.593819 109.149428 660.228054 108.515193 
C 660.862288 107.880959 661.218648 107.020631 661.218648 106.123688 
C 661.218648 105.226745 660.862288 104.366417 660.228054 103.732183 
C 659.593819 103.097948 658.733492 102.741589 657.836548 102.741589 
C 656.939605 102.741589 656.079278 103.097948 655.445043 103.732183 
C 654.810808 104.366417 654.454449 105.226745 654.454449 106.123688 
C 654.454449 107.020631 654.810808 107.880959 655.445043 108.515193 
C 656.079278 109.149428 656.939605 109.505787 657.836548 109.505787 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 548.701393 252.728204 
C 551.204386 252.728204 553.6052 251.733754 555.375083 249.96387 
C 557.144967 248.193987 558.139417 245.793173 558.139417 243.29018 
C 558.139417 240.787187 557.144967 238.386373 555.375083 236.616489 
C 553.6052 234.846606 551.204386 233.852156 548.701393 233.852156 
C 546.1984 233.852156 543.797586 234.846606 542.027702 236.616489 
C 540.257819 238.386373 539.263369 240.787187 539.263369 243.29018 
C 539.263369 245.793173 540.257819 248.193987 542.027702 249.96387 
C 543.797586 251.733754 546.1984 252.728204 548.701393 252.728204 
z
" clip-path="url(#p8a32aafd77)" style="fill: #404588; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 291.543299 78.603929 
C 292.328747 78.603929 293.082131 78.291867 293.637526 77.736472 
C 294.192921 77.181077 294.504983 76.427693 294.504983 75.642245 
C 294.504983 74.856798 294.192921 74.103414 293.637526 73.548019 
C 293.082131 72.992623 292.328747 72.680562 291.543299 72.680562 
C 290.757852 72.680562 290.004468 72.992623 289.449073 73.548019 
C 288.893677 74.103414 288.581616 74.856798 288.581616 75.642245 
C 288.581616 76.427693 288.893677 77.181077 289.449073 77.736472 
C 290.004468 78.291867 290.757852 78.603929 291.543299 78.603929 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 423.631409 461.354596 
C 424.876356 461.354596 426.070482 460.859973 426.950793 459.979662 
C 427.831104 459.099351 428.325727 457.905226 428.325727 456.660278 
C 428.325727 455.415331 427.831104 454.221205 426.950793 453.340894 
C 426.070482 452.460583 424.876356 451.96596 423.631409 451.96596 
C 422.386461 451.96596 421.192336 452.460583 420.312025 453.340894 
C 419.431714 454.221205 418.937091 455.415331 418.937091 456.660278 
C 418.937091 457.905226 419.431714 459.099351 420.312025 459.979662 
C 421.192336 460.859973 422.386461 461.354596 423.631409 461.354596 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460a5d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 536.705405 79.538492 
C 537.738701 79.538492 538.729816 79.127959 539.460467 78.397308 
C 540.191118 77.666657 540.601652 76.675542 540.601652 75.642245 
C 540.601652 74.608949 540.191118 73.617834 539.460467 72.887183 
C 538.729816 72.156531 537.738701 71.745998 536.705405 71.745998 
C 535.672108 71.745998 534.680993 72.156531 533.950342 72.887183 
C 533.219691 73.617834 532.809158 74.608949 532.809158 75.642245 
C 532.809158 76.675542 533.219691 77.666657 533.950342 78.397308 
C 534.680993 79.127959 535.672108 79.538492 536.705405 79.538492 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 634.723018 204.17425 
C 636.475012 204.17425 638.155485 203.478175 639.394331 202.239329 
C 640.633178 201.000482 641.329252 199.32001 641.329252 197.568016 
C 641.329252 195.816022 640.633178 194.13555 639.394331 192.896703 
C 638.155485 191.657856 636.475012 190.961782 634.723018 190.961782 
C 632.971025 190.961782 631.290552 191.657856 630.051705 192.896703 
C 628.812859 194.13555 628.116784 195.816022 628.116784 197.568016 
C 628.116784 199.32001 628.812859 201.000482 630.051705 202.239329 
C 631.290552 203.478175 632.971025 204.17425 634.723018 204.17425 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481c6e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 262.006721 263.467114 
C 263.315819 263.467114 264.571477 262.947003 265.49715 262.02133 
C 266.422823 261.095658 266.942933 259.84 266.942933 258.530901 
C 266.942933 257.221802 266.422823 255.966144 265.49715 255.040472 
C 264.571477 254.114799 263.315819 253.594689 262.006721 253.594689 
C 260.697622 253.594689 259.441964 254.114799 258.516291 255.040472 
C 257.590619 255.966144 257.070508 257.221802 257.070508 258.530901 
C 257.070508 259.84 257.590619 261.095658 258.516291 262.02133 
C 259.441964 262.947003 260.697622 263.467114 262.006721 263.467114 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460b5e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 680.081078 123.723567 
C 680.706734 123.723567 681.306848 123.474991 681.749254 123.032585 
C 682.191659 122.59018 682.440235 121.990065 682.440235 121.364409 
C 682.440235 120.738753 682.191659 120.138639 681.749254 119.696233 
C 681.306848 119.253827 680.706734 119.005252 680.081078 119.005252 
C 679.455422 119.005252 678.855307 119.253827 678.412901 119.696233 
C 677.970496 120.138639 677.72192 120.738753 677.72192 121.364409 
C 677.72192 121.990065 677.970496 122.59018 678.412901 123.032585 
C 678.855307 123.474991 679.455422 123.723567 680.081078 123.723567 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 425.029366 170.175565 
C 425.848577 170.175565 426.634345 169.85009 427.213614 169.27082 
C 427.792883 168.691551 428.118359 167.905783 428.118359 167.086573 
C 428.118359 166.267363 427.792883 165.481595 427.213614 164.902326 
C 426.634345 164.323057 425.848577 163.997581 425.029366 163.997581 
C 424.210156 163.997581 423.424388 164.323057 422.845119 164.902326 
C 422.26585 165.481595 421.940374 166.267363 421.940374 167.086573 
C 421.940374 167.905783 422.26585 168.691551 422.845119 169.27082 
C 423.424388 169.85009 424.210156 170.175565 425.029366 170.175565 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 610.853836 94.291283 
C 611.757732 94.291283 612.624728 93.932162 613.263879 93.29301 
C 613.903031 92.653859 614.262152 91.786863 614.262152 90.882967 
C 614.262152 89.97907 613.903031 89.112074 613.263879 88.472923 
C 612.624728 87.833772 611.757732 87.47465 610.853836 87.47465 
C 609.949939 87.47465 609.082943 87.833772 608.443792 88.472923 
C 607.804641 89.112074 607.445519 89.97907 607.445519 90.882967 
C 607.445519 91.786863 607.804641 92.653859 608.443792 93.29301 
C 609.082943 93.932162 609.949939 94.291283 610.853836 94.291283 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 532.936586 247.04558 
C 533.93253 247.04558 534.887817 246.649887 535.592055 245.945649 
C 536.296294 245.24141 536.691986 244.286124 536.691986 243.29018 
C 536.691986 242.294236 536.296294 241.338949 535.592055 240.634711 
C 534.887817 239.930472 533.93253 239.53478 532.936586 239.53478 
C 531.940642 239.53478 530.985356 239.930472 530.281117 240.634711 
C 529.576879 241.338949 529.181186 242.294236 529.181186 243.29018 
C 529.181186 244.286124 529.576879 245.24141 530.281117 245.945649 
C 530.985356 246.649887 531.940642 247.04558 532.936586 247.04558 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 806.520682 79.377428 
C 807.511264 79.377428 808.461408 78.983866 809.161855 78.283418 
C 809.862303 77.582971 810.255865 76.632827 810.255865 75.642245 
C 810.255865 74.651663 809.862303 73.70152 809.161855 73.001072 
C 808.461408 72.300625 807.511264 71.907063 806.520682 71.907063 
C 805.5301 71.907063 804.579957 72.300625 803.879509 73.001072 
C 803.179062 73.70152 802.7855 74.651663 802.7855 75.642245 
C 802.7855 76.632827 803.179062 77.582971 803.879509 78.283418 
C 804.579957 78.983866 805.5301 79.377428 806.520682 79.377428 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 229.834803 79.475992 
C 230.851524 79.475992 231.82674 79.072044 232.545671 78.353113 
C 233.264601 77.634183 233.668549 76.658967 233.668549 75.642245 
C 233.668549 74.625524 233.264601 73.650308 232.545671 72.931377 
C 231.82674 72.212447 230.851524 71.808499 229.834803 71.808499 
C 228.818081 71.808499 227.842865 72.212447 227.123935 72.931377 
C 226.405004 73.650308 226.001056 74.625524 226.001056 75.642245 
C 226.001056 76.658967 226.405004 77.634183 227.123935 78.353113 
C 227.842865 79.072044 228.818081 79.475992 229.834803 79.475992 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 872.168019 170.139408 
C 872.97764 170.139408 873.754211 169.817742 874.326699 169.245253 
C 874.899188 168.672765 875.220854 167.896194 875.220854 167.086573 
C 875.220854 166.276952 874.899188 165.500382 874.326699 164.927893 
C 873.754211 164.355404 872.97764 164.033739 872.168019 164.033739 
C 871.358398 164.033739 870.581828 164.355404 870.009339 164.927893 
C 869.436851 165.500382 869.115185 166.276952 869.115185 167.086573 
C 869.115185 167.896194 869.436851 168.672765 870.009339 169.245253 
C 870.581828 169.817742 871.358398 170.139408 872.168019 170.139408 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 513.506864 184.745929 
C 514.148293 184.745929 514.763537 184.491086 515.217096 184.037527 
C 515.670656 183.583968 515.925498 182.968724 515.925498 182.327295 
C 515.925498 181.685865 515.670656 181.070621 515.217096 180.617062 
C 514.763537 180.163503 514.148293 179.90866 513.506864 179.90866 
C 512.865434 179.90866 512.25019 180.163503 511.796631 180.617062 
C 511.343072 181.070621 511.088229 181.685865 511.088229 182.327295 
C 511.088229 182.968724 511.343072 183.583968 511.796631 184.037527 
C 512.25019 184.491086 512.865434 184.745929 513.506864 184.745929 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 680.959524 124.312146 
C 681.741273 124.312146 682.491108 124.001553 683.043888 123.448774 
C 683.596668 122.895994 683.90726 122.146158 683.90726 121.364409 
C 683.90726 120.58266 683.596668 119.832825 683.043888 119.280045 
C 682.491108 118.727265 681.741273 118.416673 680.959524 118.416673 
C 680.177775 118.416673 679.42794 118.727265 678.87516 119.280045 
C 678.32238 119.832825 678.011788 120.58266 678.011788 121.364409 
C 678.011788 122.146158 678.32238 122.895994 678.87516 123.448774 
C 679.42794 124.001553 680.177775 124.312146 680.959524 124.312146 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 265.529952 215.94373 
C 266.361362 215.94373 267.158831 215.613407 267.746727 215.025512 
C 268.334622 214.437616 268.664945 213.640147 268.664945 212.808737 
C 268.664945 211.977327 268.334622 211.179858 267.746727 210.591962 
C 267.158831 210.004067 266.361362 209.673744 265.529952 209.673744 
C 264.698542 209.673744 263.901073 210.004067 263.313177 210.591962 
C 262.725281 211.179858 262.394959 211.977327 262.394959 212.808737 
C 262.394959 213.640147 262.725281 214.437616 263.313177 215.025512 
C 263.901073 215.613407 264.698542 215.94373 265.529952 215.94373 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 872.961455 124.283422 
C 873.735586 124.283422 874.478115 123.975856 875.025508 123.428463 
C 875.572902 122.881069 875.880467 122.13854 875.880467 121.364409 
C 875.880467 120.590278 875.572902 119.847749 875.025508 119.300356 
C 874.478115 118.752962 873.735586 118.445397 872.961455 118.445397 
C 872.187324 118.445397 871.444795 118.752962 870.897401 119.300356 
C 870.350008 119.847749 870.042442 120.590278 870.042442 121.364409 
C 870.042442 122.13854 870.350008 122.881069 870.897401 123.428463 
C 871.444795 123.975856 872.187324 124.283422 872.961455 124.283422 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 531.12302 489.931649 
C 531.862917 489.931649 532.57261 489.637684 533.095796 489.114498 
C 533.618983 488.591311 533.912947 487.881618 533.912947 487.141721 
C 533.912947 486.401823 533.618983 485.69213 533.095796 485.168944 
C 532.57261 484.645757 531.862917 484.351793 531.12302 484.351793 
C 530.383122 484.351793 529.673429 484.645757 529.150243 485.168944 
C 528.627056 485.69213 528.333092 486.401823 528.333092 487.141721 
C 528.333092 487.881618 528.627056 488.591311 529.150243 489.114498 
C 529.673429 489.637684 530.383122 489.931649 531.12302 489.931649 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 222.438851 247.52624 
C 223.562267 247.52624 224.639822 247.079902 225.434198 246.285527 
C 226.228573 245.491151 226.674911 244.413596 226.674911 243.29018 
C 226.674911 242.166764 226.228573 241.089208 225.434198 240.294833 
C 224.639822 239.500458 223.562267 239.05412 222.438851 239.05412 
C 221.315435 239.05412 220.237879 239.500458 219.443504 240.294833 
C 218.649129 241.089208 218.202791 242.166764 218.202791 243.29018 
C 218.202791 244.413596 218.649129 245.491151 219.443504 246.285527 
C 220.237879 247.079902 221.315435 247.52624 222.438851 247.52624 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 925.299857 80.454374 
C 926.576048 80.454374 927.800142 79.947338 928.702545 79.044934 
C 929.604949 78.14253 930.111985 76.918437 930.111985 75.642245 
C 930.111985 74.366054 929.604949 73.14196 928.702545 72.239557 
C 927.800142 71.337153 926.576048 70.830117 925.299857 70.830117 
C 924.023665 70.830117 922.799572 71.337153 921.897168 72.239557 
C 920.994765 73.14196 920.487728 74.366054 920.487728 75.642245 
C 920.487728 76.918437 920.994765 78.14253 921.897168 79.044934 
C 922.799572 79.947338 924.023665 80.454374 925.299857 80.454374 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460a5d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 198.069048 460.042378 
C 198.965991 460.042378 199.826319 459.686018 200.460553 459.051784 
C 201.094788 458.417549 201.451147 457.557221 201.451147 456.660278 
C 201.451147 455.763335 201.094788 454.903008 200.460553 454.268773 
C 199.826319 453.634538 198.965991 453.278179 198.069048 453.278179 
C 197.172105 453.278179 196.311777 453.634538 195.677543 454.268773 
C 195.043308 454.903008 194.686949 455.763335 194.686949 456.660278 
C 194.686949 457.557221 195.043308 458.417549 195.677543 459.051784 
C 196.311777 459.686018 197.172105 460.042378 198.069048 460.042378 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 605.394244 262.351855 
C 606.407573 262.351855 607.379535 261.949255 608.096067 261.232724 
C 608.812598 260.516192 609.215198 259.54423 609.215198 258.530901 
C 609.215198 257.517572 608.812598 256.54561 608.096067 255.829079 
C 607.379535 255.112547 606.407573 254.709947 605.394244 254.709947 
C 604.380915 254.709947 603.408953 255.112547 602.692422 255.829079 
C 601.97589 256.54561 601.57329 257.517572 601.57329 258.530901 
C 601.57329 259.54423 601.97589 260.516192 602.692422 261.232724 
C 603.408953 261.949255 604.380915 262.351855 605.394244 262.351855 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 601.993806 444.861959 
C 602.906742 444.861959 603.782409 444.499246 604.427952 443.853703 
C 605.073495 443.20816 605.436209 442.332493 605.436209 441.419557 
C 605.436209 440.506621 605.073495 439.630954 604.427952 438.985411 
C 603.782409 438.339868 602.906742 437.977155 601.993806 437.977155 
C 601.080871 437.977155 600.205204 438.339868 599.559661 438.985411 
C 598.914117 439.630954 598.551404 440.506621 598.551404 441.419557 
C 598.551404 442.332493 598.914117 443.20816 599.559661 443.853703 
C 600.205204 444.499246 601.080871 444.861959 601.993806 444.861959 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 477.405551 307.494071 
C 478.265076 307.494071 479.089513 307.152578 479.697289 306.544802 
C 480.305064 305.937027 480.646557 305.11259 480.646557 304.253065 
C 480.646557 303.39354 480.305064 302.569104 479.697289 301.961328 
C 479.089513 301.353552 478.265076 301.012059 477.405551 301.012059 
C 476.546026 301.012059 475.72159 301.353552 475.113814 301.961328 
C 474.506038 302.569104 474.164545 303.39354 474.164545 304.253065 
C 474.164545 305.11259 474.506038 305.937027 475.113814 306.544802 
C 475.72159 307.152578 476.546026 307.494071 477.405551 307.494071 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 884.324584 78.979288 
C 885.209578 78.979288 886.058444 78.627676 886.684229 78.001891 
C 887.310014 77.376105 887.661626 76.527239 887.661626 75.642245 
C 887.661626 74.757251 887.310014 73.908385 886.684229 73.2826 
C 886.058444 72.656815 885.209578 72.305203 884.324584 72.305203 
C 883.43959 72.305203 882.590724 72.656815 881.964938 73.2826 
C 881.339153 73.908385 880.987541 74.757251 880.987541 75.642245 
C 880.987541 76.527239 881.339153 77.376105 881.964938 78.001891 
C 882.590724 78.627676 883.43959 78.979288 884.324584 78.979288 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 871.431258 109.354591 
C 872.288103 109.354591 873.10997 109.014163 873.715851 108.408281 
C 874.321733 107.8024 874.662161 106.980533 874.662161 106.123688 
C 874.662161 105.266842 874.321733 104.444976 873.715851 103.839094 
C 873.10997 103.233213 872.288103 102.892785 871.431258 102.892785 
C 870.574412 102.892785 869.752546 103.233213 869.146664 103.839094 
C 868.540783 104.444976 868.200355 105.266842 868.200355 106.123688 
C 868.200355 106.980533 868.540783 107.8024 869.146664 108.408281 
C 869.752546 109.014163 870.574412 109.354591 871.431258 109.354591 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 603.108394 249.35332 
C 604.716358 249.35332 606.25868 248.71447 607.395682 247.577468 
C 608.532684 246.440466 609.171535 244.898143 609.171535 243.29018 
C 609.171535 241.682216 608.532684 240.139894 607.395682 239.002892 
C 606.25868 237.86589 604.716358 237.227039 603.108394 237.227039 
C 601.500431 237.227039 599.958109 237.86589 598.821107 239.002892 
C 597.684105 240.139894 597.045254 241.682216 597.045254 243.29018 
C 597.045254 244.898143 597.684105 246.440466 598.821107 247.577468 
C 599.958109 248.71447 601.500431 249.35332 603.108394 249.35332 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481668; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 481.193261 474.365272 
C 481.846794 474.365272 482.473647 474.105621 482.935765 473.643504 
C 483.397882 473.181386 483.657534 472.554532 483.657534 471.901 
C 483.657534 471.247467 483.397882 470.620613 482.935765 470.158496 
C 482.473647 469.696378 481.846794 469.436727 481.193261 469.436727 
C 480.539728 469.436727 479.912874 469.696378 479.450757 470.158496 
C 478.988639 470.620613 478.728988 471.247467 478.728988 471.901 
C 478.728988 472.554532 478.988639 473.181386 479.450757 473.643504 
C 479.912874 474.105621 480.539728 474.365272 481.193261 474.365272 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 584.632683 185.019097 
C 585.346558 185.019097 586.03129 184.735471 586.536075 184.230686 
C 587.04086 183.725901 587.324485 183.041169 587.324485 182.327295 
C 587.324485 181.61342 587.04086 180.928688 586.536075 180.423903 
C 586.03129 179.919118 585.346558 179.635493 584.632683 179.635493 
C 583.918809 179.635493 583.234077 179.919118 582.729292 180.423903 
C 582.224507 180.928688 581.940881 181.61342 581.940881 182.327295 
C 581.940881 183.041169 582.224507 183.725901 582.729292 184.230686 
C 583.234077 184.735471 583.918809 185.019097 584.632683 185.019097 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 329.297602 79.076216 
C 330.208302 79.076216 331.081824 78.714391 331.725786 78.070429 
C 332.369748 77.426467 332.731573 76.552945 332.731573 75.642245 
C 332.731573 74.731546 332.369748 73.858023 331.725786 73.214062 
C 331.081824 72.5701 330.208302 72.208275 329.297602 72.208275 
C 328.386903 72.208275 327.513381 72.5701 326.869419 73.214062 
C 326.225457 73.858023 325.863632 74.731546 325.863632 75.642245 
C 325.863632 76.552945 326.225457 77.426467 326.869419 78.070429 
C 327.513381 78.714391 328.386903 79.076216 329.297602 79.076216 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 567.715506 109.607409 
C 568.6394 109.607409 569.525578 109.240342 570.178869 108.587051 
C 570.832161 107.933759 571.199228 107.047582 571.199228 106.123688 
C 571.199228 105.199794 570.832161 104.313616 570.178869 103.660325 
C 569.525578 103.007034 568.6394 102.639967 567.715506 102.639967 
C 566.791613 102.639967 565.905435 103.007034 565.252143 103.660325 
C 564.598852 104.313616 564.231785 105.199794 564.231785 106.123688 
C 564.231785 107.047582 564.598852 107.933759 565.252143 108.587051 
C 565.905435 109.240342 566.791613 109.607409 567.715506 109.607409 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 870.326116 234.718636 
C 872.094802 234.718636 873.791286 234.015929 875.041936 232.765279 
C 876.292587 231.514629 876.995293 229.818145 876.995293 228.049458 
C 876.995293 226.280772 876.292587 224.584288 875.041936 223.333638 
C 873.791286 222.082988 872.094802 221.380281 870.326116 221.380281 
C 868.557429 221.380281 866.860945 222.082988 865.610295 223.333638 
C 864.359645 224.584288 863.656938 226.280772 863.656938 228.049458 
C 863.656938 229.818145 864.359645 231.514629 865.610295 232.765279 
C 866.860945 234.015929 868.557429 234.718636 870.326116 234.718636 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481c6e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 334.927216 445.161509 
C 335.919593 445.161509 336.871459 444.767233 337.573175 444.065516 
C 338.274892 443.3638 338.669167 442.411934 338.669167 441.419557 
C 338.669167 440.42718 338.274892 439.475314 337.573175 438.773598 
C 336.871459 438.071881 335.919593 437.677605 334.927216 437.677605 
C 333.934839 437.677605 332.982973 438.071881 332.281256 438.773598 
C 331.57954 439.475314 331.185264 440.42718 331.185264 441.419557 
C 331.185264 442.411934 331.57954 443.3638 332.281256 444.065516 
C 332.982973 444.767233 333.934839 445.161509 334.927216 445.161509 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 473.825646 124.564381 
C 474.674288 124.564381 475.488287 124.227212 476.088368 123.627131 
C 476.688449 123.02705 477.025618 122.213052 477.025618 121.364409 
C 477.025618 120.515767 476.688449 119.701768 476.088368 119.101687 
C 475.488287 118.501607 474.674288 118.164437 473.825646 118.164437 
C 472.977004 118.164437 472.163005 118.501607 471.562924 119.101687 
C 470.962843 119.701768 470.625674 120.515767 470.625674 121.364409 
C 470.625674 122.213052 470.962843 123.02705 471.562924 123.627131 
C 472.163005 124.227212 472.977004 124.564381 473.825646 124.564381 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 197.143373 124.056211 
C 197.857248 124.056211 198.54198 123.772586 199.046765 123.267801 
C 199.55155 122.763015 199.835175 122.078283 199.835175 121.364409 
C 199.835175 120.650535 199.55155 119.965803 199.046765 119.461018 
C 198.54198 118.956232 197.857248 118.672607 197.143373 118.672607 
C 196.429499 118.672607 195.744767 118.956232 195.239982 119.461018 
C 194.735197 119.965803 194.451571 120.650535 194.451571 121.364409 
C 194.451571 122.078283 194.735197 122.763015 195.239982 123.267801 
C 195.744767 123.772586 196.429499 124.056211 197.143373 124.056211 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 223.241732 109.200796 
C 224.057791 109.200796 224.840536 108.876573 225.417576 108.299532 
C 225.994617 107.722491 226.31884 106.939747 226.31884 106.123688 
C 226.31884 105.307629 225.994617 104.524884 225.417576 103.947844 
C 224.840536 103.370803 224.057791 103.04658 223.241732 103.04658 
C 222.425673 103.04658 221.642928 103.370803 221.065888 103.947844 
C 220.488847 104.524884 220.164624 105.307629 220.164624 106.123688 
C 220.164624 106.939747 220.488847 107.722491 221.065888 108.299532 
C 221.642928 108.876573 222.425673 109.200796 223.241732 109.200796 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 577.227286 278.377006 
C 578.448648 278.377006 579.620151 277.891754 580.483784 277.028121 
C 581.347417 276.164487 581.83267 274.992985 581.83267 273.771622 
C 581.83267 272.55026 581.347417 271.378758 580.483784 270.515124 
C 579.620151 269.651491 578.448648 269.166239 577.227286 269.166239 
C 576.005924 269.166239 574.834421 269.651491 573.970788 270.515124 
C 573.107154 271.378758 572.621902 272.55026 572.621902 273.771622 
C 572.621902 274.992985 573.107154 276.164487 573.970788 277.028121 
C 574.834421 277.891754 576.005924 278.377006 577.227286 278.377006 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 478.916857 155.271331 
C 479.825305 155.271331 480.696667 154.910401 481.339037 154.268032 
C 481.981406 153.625662 482.342336 152.7543 482.342336 151.845852 
C 482.342336 150.937404 481.981406 150.066042 481.339037 149.423672 
C 480.696667 148.781303 479.825305 148.420372 478.916857 148.420372 
C 478.008409 148.420372 477.137047 148.781303 476.494677 149.423672 
C 475.852307 150.066042 475.491377 150.937404 475.491377 151.845852 
C 475.491377 152.7543 475.852307 153.625662 476.494677 154.268032 
C 477.137047 154.910401 478.008409 155.271331 478.916857 155.271331 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 357.511789 342.535345 
C 359.580595 342.535345 361.564947 341.713399 363.027813 340.250532 
C 364.49068 338.787666 365.312626 336.803314 365.312626 334.734508 
C 365.312626 332.665702 364.49068 330.68135 363.027813 329.218483 
C 361.564947 327.755616 359.580595 326.933671 357.511789 326.933671 
C 355.442983 326.933671 353.458631 327.755616 351.995764 329.218483 
C 350.532897 330.68135 349.710952 332.665702 349.710952 334.734508 
C 349.710952 336.803314 350.532897 338.787666 351.995764 340.250532 
C 353.458631 341.713399 355.442983 342.535345 357.511789 342.535345 
z
" clip-path="url(#p8a32aafd77)" style="fill: #472c7a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 270.536152 490.727051 
C 271.486992 490.727051 272.399017 490.349278 273.071363 489.676932 
C 273.743709 489.004586 274.121482 488.092562 274.121482 487.141721 
C 274.121482 486.19088 273.743709 485.278856 273.071363 484.60651 
C 272.399017 483.934164 271.486992 483.556391 270.536152 483.556391 
C 269.585311 483.556391 268.673286 483.934164 268.00094 484.60651 
C 267.328594 485.278856 266.950821 486.19088 266.950821 487.141721 
C 266.950821 488.092562 267.328594 489.004586 268.00094 489.676932 
C 268.673286 490.349278 269.585311 490.727051 270.536152 490.727051 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 902.743621 216.284303 
C 903.665352 216.284303 904.549455 215.918095 905.201217 215.266333 
C 905.852979 214.614571 906.219187 213.730468 906.219187 212.808737 
C 906.219187 211.887006 905.852979 211.002903 905.201217 210.351141 
C 904.549455 209.699379 903.665352 209.333171 902.743621 209.333171 
C 901.82189 209.333171 900.937787 209.699379 900.286025 210.351141 
C 899.634262 211.002903 899.268055 211.887006 899.268055 212.808737 
C 899.268055 213.730468 899.634262 214.614571 900.286025 215.266333 
C 900.937787 215.918095 901.82189 216.284303 902.743621 216.284303 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 554.066528 505.790759 
C 554.970424 505.790759 555.83742 505.431637 556.476572 504.792486 
C 557.115723 504.153335 557.474844 503.286338 557.474844 502.382442 
C 557.474844 501.478546 557.115723 500.611549 556.476572 499.972398 
C 555.83742 499.333247 554.970424 498.974125 554.066528 498.974125 
C 553.162631 498.974125 552.295635 499.333247 551.656484 499.972398 
C 551.017333 500.611549 550.658211 501.478546 550.658211 502.382442 
C 550.658211 503.286338 551.017333 504.153335 551.656484 504.792486 
C 552.295635 505.431637 553.162631 505.790759 554.066528 505.790759 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 203.736444 78.777238 
C 204.567854 78.777238 205.365323 78.446916 205.953219 77.85902 
C 206.541114 77.271125 206.871437 76.473655 206.871437 75.642245 
C 206.871437 74.810835 206.541114 74.013366 205.953219 73.425471 
C 205.365323 72.837575 204.567854 72.507252 203.736444 72.507252 
C 202.905034 72.507252 202.107565 72.837575 201.519669 73.425471 
C 200.931774 74.013366 200.601451 74.810835 200.601451 75.642245 
C 200.601451 76.473655 200.931774 77.271125 201.519669 77.85902 
C 202.107565 78.446916 202.905034 78.777238 203.736444 78.777238 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 280.085714 507.4734 
C 281.435852 507.4734 282.730873 506.936985 283.685565 505.982293 
C 284.640256 505.027602 285.176672 503.73258 285.176672 502.382442 
C 285.176672 501.032304 284.640256 499.737283 283.685565 498.782591 
C 282.730873 497.8279 281.435852 497.291484 280.085714 497.291484 
C 278.735576 497.291484 277.440555 497.8279 276.485863 498.782591 
C 275.531171 499.737283 274.994756 501.032304 274.994756 502.382442 
C 274.994756 503.73258 275.531171 505.027602 276.485863 505.982293 
C 277.440555 506.936985 278.735576 507.4734 280.085714 507.4734 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 531.387498 93.88501 
C 532.183649 93.88501 532.947299 93.568695 533.510263 93.005732 
C 534.073227 92.442768 534.389541 91.679118 534.389541 90.882967 
C 534.389541 90.086815 534.073227 89.323165 533.510263 88.760202 
C 532.947299 88.197238 532.183649 87.880924 531.387498 87.880924 
C 530.591347 87.880924 529.827697 88.197238 529.264733 88.760202 
C 528.701769 89.323165 528.385455 90.086815 528.385455 90.882967 
C 528.385455 91.679118 528.701769 92.442768 529.264733 93.005732 
C 529.827697 93.568695 530.591347 93.88501 531.387498 93.88501 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 352.1561 109.188746 
C 352.968963 109.188746 353.748642 108.865792 354.323423 108.291011 
C 354.898204 107.71623 355.221158 106.936551 355.221158 106.123688 
C 355.221158 105.310825 354.898204 104.531145 354.323423 103.956365 
C 353.748642 103.381584 352.968963 103.05863 352.1561 103.05863 
C 351.343237 103.05863 350.563557 103.381584 349.988776 103.956365 
C 349.413995 104.531145 349.091041 105.310825 349.091041 106.123688 
C 349.091041 106.936551 349.413995 107.71623 349.988776 108.291011 
C 350.563557 108.865792 351.343237 109.188746 352.1561 109.188746 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 517.086769 139.670189 
C 517.899632 139.670189 518.679311 139.347235 519.254092 138.772454 
C 519.828873 138.197673 520.151827 137.417993 520.151827 136.605131 
C 520.151827 135.792268 519.828873 135.012588 519.254092 134.437807 
C 518.679311 133.863026 517.899632 133.540072 517.086769 133.540072 
C 516.273906 133.540072 515.494226 133.863026 514.919445 134.437807 
C 514.344664 135.012588 514.021711 135.792268 514.021711 136.605131 
C 514.021711 137.417993 514.344664 138.197673 514.919445 138.772454 
C 515.494226 139.347235 516.273906 139.670189 517.086769 139.670189 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 393.990928 261.930543 
C 394.892523 261.930543 395.757313 261.572335 396.394838 260.934811 
C 397.032362 260.297287 397.39057 259.432497 397.39057 258.530901 
C 397.39057 257.629305 397.032362 256.764516 396.394838 256.126991 
C 395.757313 255.489467 394.892523 255.131259 393.990928 255.131259 
C 393.089332 255.131259 392.224542 255.489467 391.587018 256.126991 
C 390.949493 256.764516 390.591286 257.629305 390.591286 258.530901 
C 390.591286 259.432497 390.949493 260.297287 391.587018 260.934811 
C 392.224542 261.572335 393.089332 261.930543 393.990928 261.930543 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 250.823059 353.321426 
C 251.710481 353.321426 252.561676 352.96885 253.189178 352.341348 
C 253.81668 351.713846 254.169257 350.862651 254.169257 349.975229 
C 254.169257 349.087807 253.81668 348.236612 253.189178 347.60911 
C 252.561676 346.981608 251.710481 346.629032 250.823059 346.629032 
C 249.935637 346.629032 249.084442 346.981608 248.45694 347.60911 
C 247.829438 348.236612 247.476862 349.087807 247.476862 349.975229 
C 247.476862 350.862651 247.829438 351.713846 248.45694 352.341348 
C 249.084442 352.96885 249.935637 353.321426 250.823059 353.321426 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 327.162883 277.864875 
C 328.248426 277.864875 329.289655 277.433584 330.05725 276.665989 
C 330.824845 275.898394 331.256136 274.857166 331.256136 273.771622 
C 331.256136 272.686079 330.824845 271.644851 330.05725 270.877256 
C 329.289655 270.109661 328.248426 269.67837 327.162883 269.67837 
C 326.07734 269.67837 325.036112 270.109661 324.268517 270.877256 
C 323.500922 271.644851 323.069631 272.686079 323.069631 273.771622 
C 323.069631 274.857166 323.500922 275.898394 324.268517 276.665989 
C 325.036112 277.433584 326.07734 277.864875 327.162883 277.864875 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 318.888485 184.894584 
C 319.569338 184.894584 320.222397 184.624079 320.703833 184.142643 
C 321.185269 183.661207 321.455775 183.008148 321.455775 182.327295 
C 321.455775 181.646441 321.185269 180.993382 320.703833 180.511946 
C 320.222397 180.03051 319.569338 179.760005 318.888485 179.760005 
C 318.207632 179.760005 317.554573 180.03051 317.073137 180.511946 
C 316.591701 180.993382 316.321195 181.646441 316.321195 182.327295 
C 316.321195 183.008148 316.591701 183.661207 317.073137 184.142643 
C 317.554573 184.624079 318.207632 184.894584 318.888485 184.894584 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 347.811096 216.692671 
C 348.841127 216.692671 349.82911 216.283436 350.557452 215.555093 
C 351.285794 214.826751 351.69503 213.838769 351.69503 212.808737 
C 351.69503 211.778706 351.285794 210.790723 350.557452 210.062381 
C 349.82911 209.334039 348.841127 208.924803 347.811096 208.924803 
C 346.781065 208.924803 345.793082 209.334039 345.06474 210.062381 
C 344.336398 210.790723 343.927162 211.778706 343.927162 212.808737 
C 343.927162 213.838769 344.336398 214.826751 345.06474 215.555093 
C 345.793082 216.283436 346.781065 216.692671 347.811096 216.692671 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 253.779551 184.542862 
C 254.367126 184.542862 254.930715 184.309416 255.346193 183.893937 
C 255.761672 183.478459 255.995118 182.91487 255.995118 182.327295 
C 255.995118 181.739719 255.761672 181.17613 255.346193 180.760652 
C 254.930715 180.345173 254.367126 180.111727 253.779551 180.111727 
C 253.191975 180.111727 252.628387 180.345173 252.212908 180.760652 
C 251.79743 181.17613 251.563983 181.739719 251.563983 182.327295 
C 251.563983 182.91487 251.79743 183.478459 252.212908 183.893937 
C 252.628387 184.309416 253.191975 184.542862 253.779551 184.542862 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 581.581735 206.885129 
C 584.052663 206.885129 586.42272 205.903419 588.169929 204.15621 
C 589.917139 202.409 590.898848 200.038943 590.898848 197.568016 
C 590.898848 195.097089 589.917139 192.727031 588.169929 190.979822 
C 586.42272 189.232612 584.052663 188.250903 581.581735 188.250903 
C 579.110808 188.250903 576.740751 189.232612 574.993541 190.979822 
C 573.246332 192.727031 572.264622 195.097089 572.264622 197.568016 
C 572.264622 200.038943 573.246332 202.409 574.993541 204.15621 
C 576.740751 205.903419 579.110808 206.885129 581.581735 206.885129 
z
" clip-path="url(#p8a32aafd77)" style="fill: #414287; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 322.610075 154.598684 
C 323.340135 154.598684 324.040391 154.308629 324.556622 153.792398 
C 325.072852 153.276168 325.362908 152.575912 325.362908 151.845852 
C 325.362908 151.115792 325.072852 150.415536 324.556622 149.899305 
C 324.040391 149.383075 323.340135 149.093019 322.610075 149.093019 
C 321.880015 149.093019 321.179759 149.383075 320.663529 149.899305 
C 320.147298 150.415536 319.857243 151.115792 319.857243 151.845852 
C 319.857243 152.575912 320.147298 153.276168 320.663529 153.792398 
C 321.179759 154.308629 321.880015 154.598684 322.610075 154.598684 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 583.263063 80.349009 
C 584.511311 80.349009 585.708602 79.853074 586.591247 78.97043 
C 587.473892 78.087785 587.969826 76.890494 587.969826 75.642245 
C 587.969826 74.393997 587.473892 73.196706 586.591247 72.314061 
C 585.708602 71.431416 584.511311 70.935482 583.263063 70.935482 
C 582.014814 70.935482 580.817523 71.431416 579.934878 72.314061 
C 579.052234 73.196706 578.556299 74.393997 578.556299 75.642245 
C 578.556299 76.890494 579.052234 78.087785 579.934878 78.97043 
C 580.817523 79.853074 582.014814 80.349009 583.263063 80.349009 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460a5d; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 302.245232 246.707109 
C 303.151412 246.707109 304.0206 246.347079 304.661366 245.706313 
C 305.302132 245.065547 305.662161 244.19636 305.662161 243.29018 
C 305.662161 242.384 305.302132 241.514812 304.661366 240.874046 
C 304.0206 240.23328 303.151412 239.873251 302.245232 239.873251 
C 301.339052 239.873251 300.469865 240.23328 299.829099 240.874046 
C 299.188333 241.514812 298.828303 242.384 298.828303 243.29018 
C 298.828303 244.19636 299.188333 245.065547 299.829099 245.706313 
C 300.469865 246.347079 301.339052 246.707109 302.245232 246.707109 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 817.402083 79.033149 
C 818.301361 79.033149 819.163928 78.675862 819.799813 78.039976 
C 820.435699 77.40409 820.792986 76.541523 820.792986 75.642245 
C 820.792986 74.742967 820.435699 73.8804 819.799813 73.244514 
C 819.163928 72.608629 818.301361 72.251342 817.402083 72.251342 
C 816.502805 72.251342 815.640237 72.608629 815.004352 73.244514 
C 814.368466 73.8804 814.011179 74.742967 814.011179 75.642245 
C 814.011179 76.541523 814.368466 77.40409 815.004352 78.039976 
C 815.640237 78.675862 816.502805 79.033149 817.402083 79.033149 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 868.729799 155.21908 
C 869.62439 155.21908 870.482461 154.863655 871.115032 154.231084 
C 871.747603 153.598513 872.103027 152.740442 872.103027 151.845852 
C 872.103027 150.951261 871.747603 150.09319 871.115032 149.460619 
C 870.482461 148.828048 869.62439 148.472624 868.729799 148.472624 
C 867.835208 148.472624 866.977138 148.828048 866.344567 149.460619 
C 865.711995 150.09319 865.356571 150.951261 865.356571 151.845852 
C 865.356571 152.740442 865.711995 153.598513 866.344567 154.231084 
C 866.977138 154.863655 867.835208 155.21908 868.729799 155.21908 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 301.451797 79.857792 
C 302.569773 79.857792 303.64211 79.413615 304.432638 78.623087 
C 305.223167 77.832559 305.667344 76.760221 305.667344 75.642245 
C 305.667344 74.524269 305.223167 73.451932 304.432638 72.661404 
C 303.64211 71.870875 302.569773 71.426698 301.451797 71.426698 
C 300.333821 71.426698 299.261483 71.870875 298.470955 72.661404 
C 297.680427 73.451932 297.23625 74.524269 297.23625 75.642245 
C 297.23625 76.760221 297.680427 77.832559 298.470955 78.623087 
C 299.261483 79.413615 300.333821 79.857792 301.451797 79.857792 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46075a; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 696.35595 124.781338 
C 697.26213 124.781338 698.131317 124.421309 698.772083 123.780543 
C 699.412849 123.139777 699.772879 122.270589 699.772879 121.364409 
C 699.772879 120.458229 699.412849 119.589042 698.772083 118.948276 
C 698.131317 118.30751 697.26213 117.94748 696.35595 117.94748 
C 695.44977 117.94748 694.580582 118.30751 693.939816 118.948276 
C 693.29905 119.589042 692.939021 120.458229 692.939021 121.364409 
C 692.939021 122.270589 693.29905 123.139777 693.939816 123.780543 
C 694.580582 124.421309 695.44977 124.781338 696.35595 124.781338 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 196.501069 79.475992 
C 197.51779 79.475992 198.493006 79.072044 199.211937 78.353113 
C 199.930867 77.634183 200.334815 76.658967 200.334815 75.642245 
C 200.334815 74.625524 199.930867 73.650308 199.211937 72.931377 
C 198.493006 72.212447 197.51779 71.808499 196.501069 71.808499 
C 195.484347 71.808499 194.509131 72.212447 193.790201 72.931377 
C 193.07127 73.650308 192.667322 74.625524 192.667322 75.642245 
C 192.667322 76.658967 193.07127 77.634183 193.790201 78.353113 
C 194.509131 79.072044 195.484347 79.475992 196.501069 79.475992 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450457; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 360.46828 308.447886 
C 361.58076 308.447886 362.647825 308.005893 363.434467 307.219251 
C 364.221109 306.43261 364.663101 305.365545 364.663101 304.253065 
C 364.663101 303.140586 364.221109 302.07352 363.434467 301.286879 
C 362.647825 300.500237 361.58076 300.058244 360.46828 300.058244 
C 359.355801 300.058244 358.288736 300.500237 357.502094 301.286879 
C 356.715452 302.07352 356.273459 303.140586 356.273459 304.253065 
C 356.273459 305.365545 356.715452 306.43261 357.502094 307.219251 
C 358.288736 308.005893 359.355801 308.447886 360.46828 308.447886 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 425.917258 78.69508 
C 426.72688 78.69508 427.50345 78.373414 428.075939 77.800925 
C 428.648427 77.228437 428.970093 76.451866 428.970093 75.642245 
C 428.970093 74.832624 428.648427 74.056054 428.075939 73.483565 
C 427.50345 72.911077 426.72688 72.589411 425.917258 72.589411 
C 425.107637 72.589411 424.331067 72.911077 423.758578 73.483565 
C 423.18609 74.056054 422.864424 74.832624 422.864424 75.642245 
C 422.864424 76.451866 423.18609 77.228437 423.758578 77.800925 
C 424.331067 78.373414 425.107637 78.69508 425.917258 78.69508 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 480.248695 324.463891 
C 481.566782 324.463891 482.831061 323.940209 483.763089 323.008181 
C 484.695117 322.076152 485.218799 320.811873 485.218799 319.493786 
C 485.218799 318.175699 484.695117 316.91142 483.763089 315.979392 
C 482.831061 315.047364 481.566782 314.523682 480.248695 314.523682 
C 478.930608 314.523682 477.666329 315.047364 476.7343 315.979392 
C 475.802272 316.91142 475.278591 318.175699 475.278591 319.493786 
C 475.278591 320.811873 475.802272 322.076152 476.7343 323.008181 
C 477.666329 323.940209 478.930608 324.463891 480.248695 324.463891 
z
" clip-path="url(#p8a32aafd77)" style="fill: #460b5e; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 370.934072 203.994473 
C 372.638388 203.994473 374.27313 203.317341 375.478263 202.112207 
C 376.683397 200.907074 377.360529 199.272332 377.360529 197.568016 
C 377.360529 195.863699 376.683397 194.228958 375.478263 193.023824 
C 374.27313 191.818691 372.638388 191.141558 370.934072 191.141558 
C 369.229755 191.141558 367.595014 191.818691 366.38988 193.023824 
C 365.184746 194.228958 364.507614 195.863699 364.507614 197.568016 
C 364.507614 199.272332 365.184746 200.907074 366.38988 202.112207 
C 367.595014 203.317341 369.229755 203.994473 370.934072 203.994473 
z
" clip-path="url(#p8a32aafd77)" style="fill: #481a6c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 533.116054 93.923397 
C 533.922385 93.923397 534.6958 93.603038 535.265962 93.032875 
C 535.836125 92.462713 536.156484 91.689298 536.156484 90.882967 
C 536.156484 90.076635 535.836125 89.30322 535.265962 88.733058 
C 534.6958 88.162896 533.922385 87.842537 533.116054 87.842537 
C 532.309722 87.842537 531.536308 88.162896 530.966145 88.733058 
C 530.395983 89.30322 530.075624 90.076635 530.075624 90.882967 
C 530.075624 91.689298 530.395983 92.462713 530.966145 93.032875 
C 531.536308 93.603038 532.309722 93.923397 533.116054 93.923397 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 250.681374 93.84465 
C 251.466822 93.84465 252.220205 93.532589 252.775601 92.977193 
C 253.330996 92.421798 253.643058 91.668414 253.643058 90.882967 
C 253.643058 90.097519 253.330996 89.344135 252.775601 88.78874 
C 252.220205 88.233345 251.466822 87.921283 250.681374 87.921283 
C 249.895927 87.921283 249.142543 88.233345 248.587148 88.78874 
C 248.031752 89.344135 247.719691 90.097519 247.719691 90.882967 
C 247.719691 91.668414 248.031752 92.421798 248.587148 92.977193 
C 249.142543 93.532589 249.895927 93.84465 250.681374 93.84465 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 217.007596 94.040118 
C 217.844883 94.040118 218.647988 93.70746 219.240039 93.115409 
C 219.83209 92.523359 220.164747 91.720253 220.164747 90.882967 
C 220.164747 90.04568 219.83209 89.242575 219.240039 88.650524 
C 218.647988 88.058473 217.844883 87.725816 217.007596 87.725816 
C 216.17031 87.725816 215.367204 88.058473 214.775154 88.650524 
C 214.183103 89.242575 213.850445 90.04568 213.850445 90.882967 
C 213.850445 91.720253 214.183103 92.523359 214.775154 93.115409 
C 215.367204 93.70746 216.17031 94.040118 217.007596 94.040118 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 514.800919 461.123387 
C 515.984549 461.123387 517.119861 460.653126 517.956814 459.816173 
C 518.793767 458.97922 519.264028 457.843909 519.264028 456.660278 
C 519.264028 455.476648 518.793767 454.341337 517.956814 453.504384 
C 517.119861 452.667431 515.984549 452.197169 514.800919 452.197169 
C 513.617289 452.197169 512.481978 452.667431 511.645025 453.504384 
C 510.808072 454.341337 510.33781 455.476648 510.33781 456.660278 
C 510.33781 457.843909 510.808072 458.97922 511.645025 459.816173 
C 512.481978 460.653126 513.617289 461.123387 514.800919 461.123387 
z
" clip-path="url(#p8a32aafd77)" style="fill: #46085c; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 939.742271 125.527728 
C 940.846396 125.527728 941.905448 125.089055 942.686182 124.30832 
C 943.466916 123.527586 943.90559 122.468534 943.90559 121.364409 
C 943.90559 120.260284 943.466916 119.201233 942.686182 118.420498 
C 941.905448 117.639764 940.846396 117.20109 939.742271 117.20109 
C 938.638146 117.20109 937.579094 117.639764 936.79836 118.420498 
C 936.017625 119.201233 935.578952 120.260284 935.578952 121.364409 
C 935.578952 122.468534 936.017625 123.527586 936.79836 124.30832 
C 937.579094 125.089055 938.638146 125.527728 939.742271 125.527728 
z
" clip-path="url(#p8a32aafd77)" style="fill: #450559; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 422.101212 202.726306 
C 423.469206 202.726306 424.781355 202.182796 425.748674 201.215478 
C 426.715992 200.248159 427.259502 198.93601 427.259502 197.568016 
C 427.259502 196.200021 426.715992 194.887872 425.748674 193.920554 
C 424.781355 192.953236 423.469206 192.409726 422.101212 192.409726 
C 420.733217 192.409726 419.421068 192.953236 418.45375 193.920554 
C 417.486432 194.887872 416.942922 196.200021 416.942922 197.568016 
C 416.942922 198.93601 417.486432 200.248159 418.45375 201.215478 
C 419.421068 202.182796 420.733217 202.726306 422.101212 202.726306 
z
" clip-path="url(#p8a32aafd77)" style="fill: #470d60; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 657.874331 139.751268 
C 658.708697 139.751268 659.509001 139.419772 660.098986 138.829786 
C 660.688972 138.2398 661.020469 137.439496 661.020469 136.605131 
C 661.020469 135.770765 660.688972 134.970461 660.098986 134.380475 
C 659.509001 133.79049 658.708697 133.458993 657.874331 133.458993 
C 657.039965 133.458993 656.239661 133.79049 655.649676 134.380475 
C 655.05969 134.970461 654.728193 135.770765 654.728193 136.605131 
C 654.728193 137.439496 655.05969 138.2398 655.649676 138.829786 
C 656.239661 139.419772 657.039965 139.751268 657.874331 139.751268 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 332.320214 124.682913 
C 333.200291 124.682913 334.044442 124.333255 334.66675 123.710946 
C 335.289059 123.088637 335.638718 122.244487 335.638718 121.364409 
C 335.638718 120.484332 335.289059 119.640181 334.66675 119.017872 
C 334.044442 118.395564 333.200291 118.045905 332.320214 118.045905 
C 331.440136 118.045905 330.595986 118.395564 329.973677 119.017872 
C 329.351368 119.640181 329.001709 120.484332 329.001709 121.364409 
C 329.001709 122.244487 329.351368 123.088637 329.973677 123.710946 
C 330.595986 124.333255 331.440136 124.682913 332.320214 124.682913 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 296.370032 291.658682 
C 297.071849 291.658682 297.745016 291.379847 298.241275 290.883587 
C 298.737535 290.387328 299.016369 289.714161 299.016369 289.012344 
C 299.016369 288.310527 298.737535 287.63736 298.241275 287.1411 
C 297.745016 286.644841 297.071849 286.366006 296.370032 286.366006 
C 295.668215 286.366006 294.995048 286.644841 294.498788 287.1411 
C 294.002529 287.63736 293.723694 288.310527 293.723694 289.012344 
C 293.723694 289.714161 294.002529 290.387328 294.498788 290.883587 
C 294.995048 291.379847 295.668215 291.658682 296.370032 291.658682 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 857.442235 444.95115 
C 858.378825 444.95115 859.27718 444.579039 859.939449 443.91677 
C 860.601717 443.254501 860.973828 442.356146 860.973828 441.419557 
C 860.973828 440.482968 860.601717 439.584612 859.939449 438.922344 
C 859.27718 438.260075 858.378825 437.887964 857.442235 437.887964 
C 856.505646 437.887964 855.607291 438.260075 854.945022 438.922344 
C 854.282753 439.584612 853.910642 440.482968 853.910642 441.419557 
C 853.910642 442.356146 854.282753 443.254501 854.945022 443.91677 
C 855.607291 444.579039 856.505646 444.95115 857.442235 444.95115 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440256; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
    <path d="M 317.688886 184.948996 
C 318.38417 184.948996 319.05107 184.672757 319.542709 184.181118 
C 320.034349 183.689478 320.310588 183.022578 320.310588 182.327295 
C 320.310588 181.632011 320.034349 180.965111 319.542709 180.473472 
C 319.05107 179.981832 318.38417 179.705593 317.688886 179.705593 
C 316.993603 179.705593 316.326703 179.981832 315.835063 180.473472 
C 315.343424 180.965111 315.067185 181.632011 315.067185 182.327295 
C 315.067185 183.022578 315.343424 183.689478 315.835063 184.181118 
C 316.326703 184.672757 316.993603 184.948996 317.688886 184.948996 
z
" clip-path="url(#p8a32aafd77)" style="fill: #440154; fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
   </g>
   <g id="LineCollection_1">
    <path d="M 445.875938 511.526875 
L 445.875938 66.497812 
" clip-path="url(#p8a32aafd77)" style="fill: none; stroke-dasharray: 3.27904,1.417963; stroke-dashoffset: 0; stroke: #990000; stroke-width: 0.886227"/>
   </g>
   <g id="text_38">
    <g id="patch_3">
     <path d="M 366.532394 510.455411 
L 434.990207 510.455411 
Q 437.740207 510.455411 437.740207 507.705411 
L 437.740207 497.059473 
Q 437.740207 494.309473 434.990207 494.309473 
L 366.532394 494.309473 
Q 363.782394 494.309473 363.782394 497.059473 
L 363.782394 507.705411 
Q 363.782394 510.455411 366.532394 510.455411 
z
" clip-path="url(#p8a32aafd77)" style="fill: #ffffff; stroke: #990000; stroke-width: 0.7; stroke-linejoin: miter"/>
    </g>
    <g clip-path="url(#p8a32aafd77)">
     <!-- 29 Feb 2024 -->
     <g style="fill: #990000" transform="translate(366.532394 505.417755) scale(0.11 -0.11)">
      <defs>
       <path id="DejaVuSans-20" transform="scale(0.015625)"/>
       <path id="DejaVuSans-34" d="M 2419 4116 
L 825 1625 
L 2419 1625 
L 2419 4116 
z
M 2253 4666 
L 3047 4666 
L 3047 1625 
L 3713 1625 
L 3713 1100 
L 3047 1100 
L 3047 0 
L 2419 0 
L 2419 1100 
L 313 1100 
L 313 1709 
L 2253 4666 
z
" transform="scale(0.015625)"/>
      </defs>
      <use xlink:href="#DejaVuSans-32"/>
      <use xlink:href="#DejaVuSans-39" x="63.623047"/>
      <use xlink:href="#DejaVuSans-20" x="127.246094"/>
      <use xlink:href="#DejaVuSans-46" x="159.033203"/>
      <use xlink:href="#DejaVuSans-65" x="211.052734"/>
      <use xlink:href="#DejaVuSans-62" x="272.576172"/>
      <use xlink:href="#DejaVuSans-20" x="336.052734"/>
      <use xlink:href="#DejaVuSans-32" x="367.839844"/>
      <use xlink:href="#DejaVuSans-30" x="431.462891"/>
      <use xlink:href="#DejaVuSans-32" x="495.085938"/>
      <use xlink:href="#DejaVuSans-34" x="558.708984"/>
     </g>
    </g>
   </g>
   <g id="text_39">
    <g id="patch_4">
     <path d="M 462.878126 510.455411 
L 525.617657 510.455411 
Q 528.367657 510.455411 528.367657 507.705411 
L 528.367657 497.059473 
Q 528.367657 494.309473 525.617657 494.309473 
L 462.878126 494.309473 
Q 460.128126 494.309473 460.128126 497.059473 
L 460.128126 507.705411 
Q 460.128126 510.455411 462.878126 510.455411 
z
" clip-path="url(#p8a32aafd77)" style="fill: #ffffff; stroke: #990000; stroke-width: 0.7; stroke-linejoin: miter"/>
    </g>
    <g clip-path="url(#p8a32aafd77)">
     <!-- 1 Mar 2024 -->
     <g style="fill: #990000" transform="translate(462.878126 505.417755) scale(0.11 -0.11)">
      <use xlink:href="#DejaVuSans-31"/>
      <use xlink:href="#DejaVuSans-20" x="63.623047"/>
      <use xlink:href="#DejaVuSans-4d" x="95.410156"/>
      <use xlink:href="#DejaVuSans-61" x="181.689453"/>
      <use xlink:href="#DejaVuSans-72" x="242.96875"/>
      <use xlink:href="#DejaVuSans-20" x="284.082031"/>
      <use xlink:href="#DejaVuSans-32" x="315.869141"/>
      <use xlink:href="#DejaVuSans-30" x="379.492188"/>
      <use xlink:href="#DejaVuSans-32" x="443.115234"/>
      <use xlink:href="#DejaVuSans-34" x="506.738281"/>
     </g>
    </g>
   </g>
  </g>
  <g id="text_40">
   <!-- When were the top posts created? -->
   <g transform="translate(155.711875 28.236562) scale(0.22 -0.22)">
    <defs>
     <path id="DejaVuSans-57" d="M 213 4666 
L 850 4666 
L 1831 722 
L 2809 4666 
L 3519 4666 
L 4500 722 
L 5478 4666 
L 6119 4666 
L 4947 0 
L 4153 0 
L 3169 4050 
L 2175 0 
L 1381 0 
L 213 4666 
z
" transform="scale(0.015625)"/>
     <path id="DejaVuSans-3f" d="M 1222 794 
L 1856 794 
L 1856 0 
L 1222 0 
L 1222 794 
z
M 1838 1253 
L 1241 1253 
L 1241 1734 
Q 1241 2050 1328 2253 
Q 1416 2456 1697 2725 
L 1978 3003 
Q 2156 3169 2236 3316 
Q 2316 3463 2316 3616 
Q 2316 3894 2111 4066 
Q 1906 4238 1569 4238 
Q 1322 4238 1042 4128 
Q 763 4019 459 3809 
L 459 4397 
Q 753 4575 1054 4662 
Q 1356 4750 1678 4750 
Q 2253 4750 2601 4447 
Q 2950 4144 2950 3647 
Q 2950 3409 2837 3195 
Q 2725 2981 2444 2713 
L 2169 2444 
Q 2022 2297 1961 2214 
Q 1900 2131 1875 2053 
Q 1856 1988 1847 1894 
Q 1838 1800 1838 1638 
L 1838 1253 
z
" transform="scale(0.015625)"/>
    </defs>
    <use xlink:href="#DejaVuSans-57"/>
    <use xlink:href="#DejaVuSans-68" x="98.876953"/>
    <use xlink:href="#DejaVuSans-65" x="162.255859"/>
    <use xlink:href="#DejaVuSans-6e" x="223.779297"/>
    <use xlink:href="#DejaVuSans-20" x="287.158203"/>
    <use xlink:href="#DejaVuSans-77" x="318.945312"/>
    <use xlink:href="#DejaVuSans-65" x="400.732422"/>
    <use xlink:href="#DejaVuSans-72" x="462.255859"/>
    <use xlink:href="#DejaVuSans-65" x="501.119141"/>
    <use xlink:href="#DejaVuSans-20" x="562.642578"/>
    <use xlink:href="#DejaVuSans-74" x="594.429688"/>
    <use xlink:href="#DejaVuSans-68" x="633.638672"/>
    <use xlink:href="#DejaVuSans-65" x="697.017578"/>
    <use xlink:href="#DejaVuSans-20" x="758.541016"/>
    <use xlink:href="#DejaVuSans-74" x="790.328125"/>
    <use xlink:href="#DejaVuSans-6f" x="829.537109"/>
    <use xlink:href="#DejaVuSans-70" x="890.71875"/>
    <use xlink:href="#DejaVuSans-20" x="954.195312"/>
    <use xlink:href="#DejaVuSans-70" x="985.982422"/>
    <use xlink:href="#DejaVuSans-6f" x="1049.458984"/>
    <use xlink:href="#DejaVuSans-73" x="1110.640625"/>
    <use xlink:href="#DejaVuSans-74" x="1162.740234"/>
    <use xlink:href="#DejaVuSans-73" x="1201.949219"/>
    <use xlink:href="#DejaVuSans-20" x="1254.048828"/>
    <use xlink:href="#DejaVuSans-63" x="1285.835938"/>
    <use xlink:href="#DejaVuSans-72" x="1340.816406"/>
    <use xlink:href="#DejaVuSans-65" x="1379.679688"/>
    <use xlink:href="#DejaVuSans-61" x="1441.203125"/>
    <use xlink:href="#DejaVuSans-74" x="1502.482422"/>
    <use xlink:href="#DejaVuSans-65" x="1541.691406"/>
    <use xlink:href="#DejaVuSans-64" x="1603.214844"/>
    <use xlink:href="#DejaVuSans-3f" x="1666.691406"/>
   </g>
  </g>
  <g id="text_41">
   <!-- For context: this data was collected at 1 March 2024, around 4pm -->
   <g transform="translate(155.711875 52.690156) scale(0.11 -0.11)">
    <defs>
     <path id="DejaVuSans-78" d="M 3513 3500 
L 2247 1797 
L 3578 0 
L 2900 0 
L 1881 1375 
L 863 0 
L 184 0 
L 1544 1831 
L 300 3500 
L 978 3500 
L 1906 2253 
L 2834 3500 
L 3513 3500 
z
" transform="scale(0.015625)"/>
     <path id="DejaVuSans-2c" d="M 750 794 
L 1409 794 
L 1409 256 
L 897 -744 
L 494 -744 
L 750 256 
L 750 794 
z
" transform="scale(0.015625)"/>
    </defs>
    <use xlink:href="#DejaVuSans-46"/>
    <use xlink:href="#DejaVuSans-6f" x="53.894531"/>
    <use xlink:href="#DejaVuSans-72" x="115.076172"/>
    <use xlink:href="#DejaVuSans-20" x="156.189453"/>
    <use xlink:href="#DejaVuSans-63" x="187.976562"/>
    <use xlink:href="#DejaVuSans-6f" x="242.957031"/>
    <use xlink:href="#DejaVuSans-6e" x="304.138672"/>
    <use xlink:href="#DejaVuSans-74" x="367.517578"/>
    <use xlink:href="#DejaVuSans-65" x="406.726562"/>
    <use xlink:href="#DejaVuSans-78" x="466.5"/>
    <use xlink:href="#DejaVuSans-74" x="525.679688"/>
    <use xlink:href="#DejaVuSans-3a" x="564.888672"/>
    <use xlink:href="#DejaVuSans-20" x="598.580078"/>
    <use xlink:href="#DejaVuSans-74" x="630.367188"/>
    <use xlink:href="#DejaVuSans-68" x="669.576172"/>
    <use xlink:href="#DejaVuSans-69" x="732.955078"/>
    <use xlink:href="#DejaVuSans-73" x="760.738281"/>
    <use xlink:href="#DejaVuSans-20" x="812.837891"/>
    <use xlink:href="#DejaVuSans-64" x="844.625"/>
    <use xlink:href="#DejaVuSans-61" x="908.101562"/>
    <use xlink:href="#DejaVuSans-74" x="969.380859"/>
    <use xlink:href="#DejaVuSans-61" x="1008.589844"/>
    <use xlink:href="#DejaVuSans-20" x="1069.869141"/>
    <use xlink:href="#DejaVuSans-77" x="1101.65625"/>
    <use xlink:href="#DejaVuSans-61" x="1183.443359"/>
    <use xlink:href="#DejaVuSans-73" x="1244.722656"/>
    <use xlink:href="#DejaVuSans-20" x="1296.822266"/>
    <use xlink:href="#DejaVuSans-63" x="1328.609375"/>
    <use xlink:href="#DejaVuSans-6f" x="1383.589844"/>
    <use xlink:href="#DejaVuSans-6c" x="1444.771484"/>
    <use xlink:href="#DejaVuSans-6c" x="1472.554688"/>
    <use xlink:href="#DejaVuSans-65" x="1500.337891"/>
    <use xlink:href="#DejaVuSans-63" x="1561.861328"/>
    <use xlink:href="#DejaVuSans-74" x="1616.841797"/>
    <use xlink:href="#DejaVuSans-65" x="1656.050781"/>
    <use xlink:href="#DejaVuSans-64" x="1717.574219"/>
    <use xlink:href="#DejaVuSans-20" x="1781.050781"/>
    <use xlink:href="#DejaVuSans-61" x="1812.837891"/>
    <use xlink:href="#DejaVuSans-74" x="1874.117188"/>
    <use xlink:href="#DejaVuSans-20" x="1913.326172"/>
    <use xlink:href="#DejaVuSans-31" x="1945.113281"/>
    <use xlink:href="#DejaVuSans-20" x="2008.736328"/>
    <use xlink:href="#DejaVuSans-4d" x="2040.523438"/>
    <use xlink:href="#DejaVuSans-61" x="2126.802734"/>
    <use xlink:href="#DejaVuSans-72" x="2188.082031"/>
    <use xlink:href="#DejaVuSans-63" x="2226.945312"/>
    <use xlink:href="#DejaVuSans-68" x="2281.925781"/>
    <use xlink:href="#DejaVuSans-20" x="2345.304688"/>
    <use xlink:href="#DejaVuSans-32" x="2377.091797"/>
    <use xlink:href="#DejaVuSans-30" x="2440.714844"/>
    <use xlink:href="#DejaVuSans-32" x="2504.337891"/>
    <use xlink:href="#DejaVuSans-34" x="2567.960938"/>
    <use xlink:href="#DejaVuSans-2c" x="2631.583984"/>
    <use xlink:href="#DejaVuSans-20" x="2663.371094"/>
    <use xlink:href="#DejaVuSans-61" x="2695.158203"/>
    <use xlink:href="#DejaVuSans-72" x="2756.4375"/>
    <use xlink:href="#DejaVuSans-6f" x="2795.300781"/>
    <use xlink:href="#DejaVuSans-75" x="2856.482422"/>
    <use xlink:href="#DejaVuSans-6e" x="2919.861328"/>
    <use xlink:href="#DejaVuSans-64" x="2983.240234"/>
    <use xlink:href="#DejaVuSans-20" x="3046.716797"/>
    <use xlink:href="#DejaVuSans-34" x="3078.503906"/>
    <use xlink:href="#DejaVuSans-70" x="3142.126953"/>
    <use xlink:href="#DejaVuSans-6d" x="3205.603516"/>
   </g>
  </g>
  <g id="text_42">
   <!-- Day and time of day (Timezone: GMT) -->
   <g transform="translate(437.562422 550.048437) scale(0.14 -0.14)">
    <defs>
     <path id="DejaVuSans-28" d="M 1984 4856 
Q 1566 4138 1362 3434 
Q 1159 2731 1159 2009 
Q 1159 1288 1364 580 
Q 1569 -128 1984 -844 
L 1484 -844 
Q 1016 -109 783 600 
Q 550 1309 550 2009 
Q 550 2706 781 3412 
Q 1013 4119 1484 4856 
L 1984 4856 
z
" transform="scale(0.015625)"/>
     <path id="DejaVuSans-7a" d="M 353 3500 
L 3084 3500 
L 3084 2975 
L 922 459 
L 3084 459 
L 3084 0 
L 275 0 
L 275 525 
L 2438 3041 
L 353 3041 
L 353 3500 
z
" transform="scale(0.015625)"/>
     <path id="DejaVuSans-47" d="M 3809 666 
L 3809 1919 
L 2778 1919 
L 2778 2438 
L 4434 2438 
L 4434 434 
Q 4069 175 3628 42 
Q 3188 -91 2688 -91 
Q 1594 -91 976 548 
Q 359 1188 359 2328 
Q 359 3472 976 4111 
Q 1594 4750 2688 4750 
Q 3144 4750 3555 4637 
Q 3966 4525 4313 4306 
L 4313 3634 
Q 3963 3931 3569 4081 
Q 3175 4231 2741 4231 
Q 1884 4231 1454 3753 
Q 1025 3275 1025 2328 
Q 1025 1384 1454 906 
Q 1884 428 2741 428 
Q 3075 428 3337 486 
Q 3600 544 3809 666 
z
" transform="scale(0.015625)"/>
     <path id="DejaVuSans-29" d="M 513 4856 
L 1013 4856 
Q 1481 4119 1714 3412 
Q 1947 2706 1947 2009 
Q 1947 1309 1714 600 
Q 1481 -109 1013 -844 
L 513 -844 
Q 928 -128 1133 580 
Q 1338 1288 1338 2009 
Q 1338 2731 1133 3434 
Q 928 4138 513 4856 
z
" transform="scale(0.015625)"/>
    </defs>
    <use xlink:href="#DejaVuSans-44"/>
    <use xlink:href="#DejaVuSans-61" x="77.001953"/>
    <use xlink:href="#DejaVuSans-79" x="138.28125"/>
    <use xlink:href="#DejaVuSans-20" x="197.460938"/>
    <use xlink:href="#DejaVuSans-61" x="229.248047"/>
    <use xlink:href="#DejaVuSans-6e" x="290.527344"/>
    <use xlink:href="#DejaVuSans-64" x="353.90625"/>
    <use xlink:href="#DejaVuSans-20" x="417.382812"/>
    <use xlink:href="#DejaVuSans-74" x="449.169922"/>
    <use xlink:href="#DejaVuSans-69" x="488.378906"/>
    <use xlink:href="#DejaVuSans-6d" x="516.162109"/>
    <use xlink:href="#DejaVuSans-65" x="613.574219"/>
    <use xlink:href="#DejaVuSans-20" x="675.097656"/>
    <use xlink:href="#DejaVuSans-6f" x="706.884766"/>
    <use xlink:href="#DejaVuSans-66" x="768.066406"/>
    <use xlink:href="#DejaVuSans-20" x="803.271484"/>
    <use xlink:href="#DejaVuSans-64" x="835.058594"/>
    <use xlink:href="#DejaVuSans-61" x="898.535156"/>
    <use xlink:href="#DejaVuSans-79" x="959.814453"/>
    <use xlink:href="#DejaVuSans-20" x="1018.994141"/>
    <use xlink:href="#DejaVuSans-28" x="1050.78125"/>
    <use xlink:href="#DejaVuSans-54" x="1089.794922"/>
    <use xlink:href="#DejaVuSans-69" x="1147.753906"/>
    <use xlink:href="#DejaVuSans-6d" x="1175.537109"/>
    <use xlink:href="#DejaVuSans-65" x="1272.949219"/>
    <use xlink:href="#DejaVuSans-7a" x="1334.472656"/>
    <use xlink:href="#DejaVuSans-6f" x="1386.962891"/>
    <use xlink:href="#DejaVuSans-6e" x="1448.144531"/>
    <use xlink:href="#DejaVuSans-65" x="1511.523438"/>
    <use xlink:href="#DejaVuSans-3a" x="1573.046875"/>
    <use xlink:href="#DejaVuSans-20" x="1606.738281"/>
    <use xlink:href="#DejaVuSans-47" x="1638.525391"/>
    <use xlink:href="#DejaVuSans-4d" x="1716.015625"/>
    <use xlink:href="#DejaVuSans-54" x="1802.294922"/>
    <use xlink:href="#DejaVuSans-29" x="1863.378906"/>
   </g>
  </g>
  <g id="text_43">
   <!-- Subreddit Names -->
   <g transform="translate(22.157812 349.463906) rotate(-90) scale(0.14 -0.14)">
    <use xlink:href="#DejaVuSans-53"/>
    <use xlink:href="#DejaVuSans-75" x="63.476562"/>
    <use xlink:href="#DejaVuSans-62" x="126.855469"/>
    <use xlink:href="#DejaVuSans-72" x="190.332031"/>
    <use xlink:href="#DejaVuSans-65" x="229.195312"/>
    <use xlink:href="#DejaVuSans-64" x="290.71875"/>
    <use xlink:href="#DejaVuSans-64" x="354.195312"/>
    <use xlink:href="#DejaVuSans-69" x="417.671875"/>
    <use xlink:href="#DejaVuSans-74" x="445.455078"/>
    <use xlink:href="#DejaVuSans-20" x="484.664062"/>
    <use xlink:href="#DejaVuSans-4e" x="516.451172"/>
    <use xlink:href="#DejaVuSans-61" x="591.255859"/>
    <use xlink:href="#DejaVuSans-6d" x="652.535156"/>
    <use xlink:href="#DejaVuSans-65" x="749.947266"/>
    <use xlink:href="#DejaVuSans-73" x="811.470703"/>
   </g>
  </g>
  <g id="patch_5">
   <path d="M 1020.305469 451.582669 
L 1140.48 451.582669 
L 1140.48 126.442019 
L 1020.305469 126.442019 
L 1020.305469 451.582669 
z
" style="fill: none"/>
  </g>
  <g id="text_44">
   <!-- Number of comments -->
   <g transform="translate(1020.505469 138.035612) scale(0.11 -0.11)">
    <use xlink:href="#DejaVuSans-4e"/>
    <use xlink:href="#DejaVuSans-75" x="74.804688"/>
    <use xlink:href="#DejaVuSans-6d" x="138.183594"/>
    <use xlink:href="#DejaVuSans-62" x="235.595703"/>
    <use xlink:href="#DejaVuSans-65" x="299.072266"/>
    <use xlink:href="#DejaVuSans-72" x="360.595703"/>
    <use xlink:href="#DejaVuSans-20" x="401.708984"/>
    <use xlink:href="#DejaVuSans-6f" x="433.496094"/>
    <use xlink:href="#DejaVuSans-66" x="494.677734"/>
    <use xlink:href="#DejaVuSans-20" x="529.882812"/>
    <use xlink:href="#DejaVuSans-63" x="561.669922"/>
    <use xlink:href="#DejaVuSans-6f" x="616.650391"/>
    <use xlink:href="#DejaVuSans-6d" x="677.832031"/>
    <use xlink:href="#DejaVuSans-6d" x="775.244141"/>
    <use xlink:href="#DejaVuSans-65" x="872.65625"/>
    <use xlink:href="#DejaVuSans-6e" x="934.179688"/>
    <use xlink:href="#DejaVuSans-74" x="997.558594"/>
    <use xlink:href="#DejaVuSans-73" x="1036.767578"/>
   </g>
  </g>
  <g id="QuadMesh_1">
   <g>
    <filter id="colorAdd">
     <feComposite in="SourceGraphic" in2="BackgroundImage" operator="arithmetic" k2="1" k3="1"/>
    </filter>
    <filter id="colorMat">
     <feColorMatrix type="matrix" values="1 0 0 0 0 
0 1 0 0 0 
0 0 1 0 0 
1 1 1 1 0 
0 0 0 0 1 "/>
    </filter>
    <defs>
     <linearGradient id="GR0_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="263.647956" x2="1021.993034" y2="257.99521">
      <stop offset="1" style="stop-color: #450457; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #440154; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR0_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="263.647956" x2="1041.985904" y2="257.99521">
      <stop offset="1" style="stop-color: #450457; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #440154; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR0_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="260.625851" x2="1031.989469" y2="263.647956">
      <stop offset="1" style="stop-color: #450457; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #460a5e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,260.625851 L 1020.505469,263.647956 1043.473469,263.647956 Z" fill="#450457" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,260.625851 L 1020.505469,263.647956 1043.473469,263.647956 Z" fill="url(#GR0_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,260.625851 L 1020.505469,263.647956 1043.473469,263.647956 Z" fill="url(#GR0_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,260.625851 L 1020.505469,263.647956 1043.473469,263.647956 Z" fill="url(#GR0_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR1_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="263.647956" x2="1041.985904" y2="257.99521">
      <stop offset="1" style="stop-color: #460a5e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #440154; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR1_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="257.603746" x2="1041.985904" y2="263.256492">
      <stop offset="1" style="stop-color: #460a5e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #481467; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR1_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="260.625851" x2="1043.473469" y2="260.625851">
      <stop offset="1" style="stop-color: #460a5e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #460a5e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,260.625851 L 1043.473469,263.647956 1043.473469,257.603746 Z" fill="#460a5e" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,260.625851 L 1043.473469,263.647956 1043.473469,257.603746 Z" fill="url(#GR1_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,260.625851 L 1043.473469,263.647956 1043.473469,257.603746 Z" fill="url(#GR1_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,260.625851 L 1043.473469,263.647956 1043.473469,257.603746 Z" fill="url(#GR1_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR2_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="257.603746" x2="1041.985904" y2="263.256492">
      <stop offset="1" style="stop-color: #471164; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #481467; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR2_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="257.603746" x2="1021.993034" y2="263.256492">
      <stop offset="1" style="stop-color: #471164; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #481467; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR2_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="260.625851" x2="1031.989469" y2="257.603746">
      <stop offset="1" style="stop-color: #471164; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #460a5e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,260.625851 L 1043.473469,257.603746 1020.505469,257.603746 Z" fill="#471164" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,260.625851 L 1043.473469,257.603746 1020.505469,257.603746 Z" fill="url(#GR2_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,260.625851 L 1043.473469,257.603746 1020.505469,257.603746 Z" fill="url(#GR2_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,260.625851 L 1043.473469,257.603746 1020.505469,257.603746 Z" fill="url(#GR2_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR3_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="257.603746" x2="1021.993034" y2="263.256492">
      <stop offset="1" style="stop-color: #460a5e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #481467; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR3_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="263.647956" x2="1021.993034" y2="257.99521">
      <stop offset="1" style="stop-color: #460a5e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #440154; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR3_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="260.625851" x2="1020.505469" y2="260.625851">
      <stop offset="1" style="stop-color: #460a5e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #460a5e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,260.625851 L 1020.505469,257.603746 1020.505469,263.647956 Z" fill="#460a5e" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,260.625851 L 1020.505469,257.603746 1020.505469,263.647956 Z" fill="url(#GR3_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,260.625851 L 1020.505469,257.603746 1020.505469,263.647956 Z" fill="url(#GR3_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,260.625851 L 1020.505469,257.603746 1020.505469,263.647956 Z" fill="url(#GR3_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR4_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="257.603746" x2="1021.993034" y2="251.950999">
      <stop offset="1" style="stop-color: #48176a; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #481467; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR4_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="257.603746" x2="1041.985904" y2="251.950999">
      <stop offset="1" style="stop-color: #48176a; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #481467; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR4_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="254.58164" x2="1031.989469" y2="257.603746">
      <stop offset="1" style="stop-color: #48176a; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #481d6e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,254.58164 L 1020.505469,257.603746 1043.473469,257.603746 Z" fill="#48176a" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,254.58164 L 1020.505469,257.603746 1043.473469,257.603746 Z" fill="url(#GR4_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,254.58164 L 1020.505469,257.603746 1043.473469,257.603746 Z" fill="url(#GR4_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,254.58164 L 1020.505469,257.603746 1043.473469,257.603746 Z" fill="url(#GR4_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR5_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="257.603746" x2="1041.985904" y2="251.950999">
      <stop offset="1" style="stop-color: #481c6e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #481467; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR5_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="251.559535" x2="1041.985904" y2="257.212281">
      <stop offset="1" style="stop-color: #481c6e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #482576; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR5_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="254.58164" x2="1043.473469" y2="254.58164">
      <stop offset="1" style="stop-color: #481c6e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #481d6e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,254.58164 L 1043.473469,257.603746 1043.473469,251.559535 Z" fill="#481c6e" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,254.58164 L 1043.473469,257.603746 1043.473469,251.559535 Z" fill="url(#GR5_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,254.58164 L 1043.473469,257.603746 1043.473469,251.559535 Z" fill="url(#GR5_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,254.58164 L 1043.473469,257.603746 1043.473469,251.559535 Z" fill="url(#GR5_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR6_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="251.559535" x2="1041.985904" y2="257.212281">
      <stop offset="1" style="stop-color: #482274; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #482576; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR6_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="251.559535" x2="1021.993034" y2="257.212281">
      <stop offset="1" style="stop-color: #482274; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #482576; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR6_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="254.58164" x2="1031.989469" y2="251.559535">
      <stop offset="1" style="stop-color: #482274; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #481d6e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,254.58164 L 1043.473469,251.559535 1020.505469,251.559535 Z" fill="#482274" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,254.58164 L 1043.473469,251.559535 1020.505469,251.559535 Z" fill="url(#GR6_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,254.58164 L 1043.473469,251.559535 1020.505469,251.559535 Z" fill="url(#GR6_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,254.58164 L 1043.473469,251.559535 1020.505469,251.559535 Z" fill="url(#GR6_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR7_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="251.559535" x2="1021.993034" y2="257.212281">
      <stop offset="1" style="stop-color: #481c6e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #482576; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR7_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="257.603746" x2="1021.993034" y2="251.950999">
      <stop offset="1" style="stop-color: #481c6e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #481467; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR7_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="254.58164" x2="1020.505469" y2="254.58164">
      <stop offset="1" style="stop-color: #481c6e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #481d6e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,254.58164 L 1020.505469,251.559535 1020.505469,257.603746 Z" fill="#481c6e" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,254.58164 L 1020.505469,251.559535 1020.505469,257.603746 Z" fill="url(#GR7_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,254.58164 L 1020.505469,251.559535 1020.505469,257.603746 Z" fill="url(#GR7_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,254.58164 L 1020.505469,251.559535 1020.505469,257.603746 Z" fill="url(#GR7_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR8_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="251.559535" x2="1021.993034" y2="245.906789">
      <stop offset="1" style="stop-color: #472878; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #482576; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR8_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="251.559535" x2="1041.985904" y2="245.906789">
      <stop offset="1" style="stop-color: #472878; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #482576; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR8_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="248.53743" x2="1031.989469" y2="251.559535">
      <stop offset="1" style="stop-color: #472878; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #462e7c; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,248.53743 L 1020.505469,251.559535 1043.473469,251.559535 Z" fill="#472878" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,248.53743 L 1020.505469,251.559535 1043.473469,251.559535 Z" fill="url(#GR8_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,248.53743 L 1020.505469,251.559535 1043.473469,251.559535 Z" fill="url(#GR8_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,248.53743 L 1020.505469,251.559535 1043.473469,251.559535 Z" fill="url(#GR8_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR9_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="251.559535" x2="1041.985904" y2="245.906789">
      <stop offset="1" style="stop-color: #462e7c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #482576; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR9_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="245.515325" x2="1041.985904" y2="251.168071">
      <stop offset="1" style="stop-color: #462e7c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #453781; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR9_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="248.53743" x2="1043.473469" y2="248.53743">
      <stop offset="1" style="stop-color: #462e7c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #462e7c; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,248.53743 L 1043.473469,251.559535 1043.473469,245.515325 Z" fill="#462e7c" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,248.53743 L 1043.473469,251.559535 1043.473469,245.515325 Z" fill="url(#GR9_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,248.53743 L 1043.473469,251.559535 1043.473469,245.515325 Z" fill="url(#GR9_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,248.53743 L 1043.473469,251.559535 1043.473469,245.515325 Z" fill="url(#GR9_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GRa_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="245.515325" x2="1041.985904" y2="251.168071">
      <stop offset="1" style="stop-color: #46347f; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #453781; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GRa_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="245.515325" x2="1021.993034" y2="251.168071">
      <stop offset="1" style="stop-color: #46347f; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #453781; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GRa_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="248.53743" x2="1031.989469" y2="245.515325">
      <stop offset="1" style="stop-color: #46347f; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #462e7c; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,248.53743 L 1043.473469,245.515325 1020.505469,245.515325 Z" fill="#46347f" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,248.53743 L 1043.473469,245.515325 1020.505469,245.515325 Z" fill="url(#GRa_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,248.53743 L 1043.473469,245.515325 1020.505469,245.515325 Z" fill="url(#GRa_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,248.53743 L 1043.473469,245.515325 1020.505469,245.515325 Z" fill="url(#GRa_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GRb_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="245.515325" x2="1021.993034" y2="251.168071">
      <stop offset="1" style="stop-color: #462e7c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #453781; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GRb_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="251.559535" x2="1021.993034" y2="245.906789">
      <stop offset="1" style="stop-color: #462e7c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #482576; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GRb_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="248.53743" x2="1020.505469" y2="248.53743">
      <stop offset="1" style="stop-color: #462e7c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #462e7c; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,248.53743 L 1020.505469,245.515325 1020.505469,251.559535 Z" fill="#462e7c" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,248.53743 L 1020.505469,245.515325 1020.505469,251.559535 Z" fill="url(#GRb_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,248.53743 L 1020.505469,245.515325 1020.505469,251.559535 Z" fill="url(#GRb_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,248.53743 L 1020.505469,245.515325 1020.505469,251.559535 Z" fill="url(#GRb_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GRc_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="245.515325" x2="1021.993034" y2="239.862578">
      <stop offset="1" style="stop-color: #443a82; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #453781; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GRc_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="245.515325" x2="1041.985904" y2="239.862578">
      <stop offset="1" style="stop-color: #443a82; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #453781; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GRc_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="242.493219" x2="1031.989469" y2="245.515325">
      <stop offset="1" style="stop-color: #443a82; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #423f84; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,242.493219 L 1020.505469,245.515325 1043.473469,245.515325 Z" fill="#443a82" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,242.493219 L 1020.505469,245.515325 1043.473469,245.515325 Z" fill="url(#GRc_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,242.493219 L 1020.505469,245.515325 1043.473469,245.515325 Z" fill="url(#GRc_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,242.493219 L 1020.505469,245.515325 1043.473469,245.515325 Z" fill="url(#GRc_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GRd_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="245.515325" x2="1041.985904" y2="239.862578">
      <stop offset="1" style="stop-color: #423f84; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #453781; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GRd_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="239.471114" x2="1041.985904" y2="245.12386">
      <stop offset="1" style="stop-color: #423f84; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #404688; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GRd_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="242.493219" x2="1043.473469" y2="242.493219">
      <stop offset="1" style="stop-color: #423f84; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #423f84; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,242.493219 L 1043.473469,245.515325 1043.473469,239.471114 Z" fill="#423f84" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,242.493219 L 1043.473469,245.515325 1043.473469,239.471114 Z" fill="url(#GRd_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,242.493219 L 1043.473469,245.515325 1043.473469,239.471114 Z" fill="url(#GRd_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,242.493219 L 1043.473469,245.515325 1043.473469,239.471114 Z" fill="url(#GRd_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GRe_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="239.471114" x2="1041.985904" y2="245.12386">
      <stop offset="1" style="stop-color: #414487; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #404688; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GRe_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="239.471114" x2="1021.993034" y2="245.12386">
      <stop offset="1" style="stop-color: #414487; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #404688; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GRe_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="242.493219" x2="1031.989469" y2="239.471114">
      <stop offset="1" style="stop-color: #414487; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #423f84; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,242.493219 L 1043.473469,239.471114 1020.505469,239.471114 Z" fill="#414487" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,242.493219 L 1043.473469,239.471114 1020.505469,239.471114 Z" fill="url(#GRe_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,242.493219 L 1043.473469,239.471114 1020.505469,239.471114 Z" fill="url(#GRe_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,242.493219 L 1043.473469,239.471114 1020.505469,239.471114 Z" fill="url(#GRe_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GRf_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="239.471114" x2="1021.993034" y2="245.12386">
      <stop offset="1" style="stop-color: #423f84; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #404688; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GRf_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="245.515325" x2="1021.993034" y2="239.862578">
      <stop offset="1" style="stop-color: #423f84; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #453781; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GRf_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="242.493219" x2="1020.505469" y2="242.493219">
      <stop offset="1" style="stop-color: #423f84; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #423f84; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,242.493219 L 1020.505469,239.471114 1020.505469,245.515325 Z" fill="#423f84" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,242.493219 L 1020.505469,239.471114 1020.505469,245.515325 Z" fill="url(#GRf_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,242.493219 L 1020.505469,239.471114 1020.505469,245.515325 Z" fill="url(#GRf_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,242.493219 L 1020.505469,239.471114 1020.505469,245.515325 Z" fill="url(#GRf_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR10_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="239.471114" x2="1021.993034" y2="233.818368">
      <stop offset="1" style="stop-color: #3f4989; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #404688; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR10_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="239.471114" x2="1041.985904" y2="233.818368">
      <stop offset="1" style="stop-color: #3f4989; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #404688; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR10_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="236.449009" x2="1031.989469" y2="239.471114">
      <stop offset="1" style="stop-color: #3f4989; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #3c4e8a; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,236.449009 L 1020.505469,239.471114 1043.473469,239.471114 Z" fill="#3f4989" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,236.449009 L 1020.505469,239.471114 1043.473469,239.471114 Z" fill="url(#GR10_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,236.449009 L 1020.505469,239.471114 1043.473469,239.471114 Z" fill="url(#GR10_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,236.449009 L 1020.505469,239.471114 1043.473469,239.471114 Z" fill="url(#GR10_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR11_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="239.471114" x2="1041.985904" y2="233.818368">
      <stop offset="1" style="stop-color: #3c4e8a; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #404688; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR11_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="233.426903" x2="1041.985904" y2="239.07965">
      <stop offset="1" style="stop-color: #3c4e8a; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #39558c; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR11_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="236.449009" x2="1043.473469" y2="236.449009">
      <stop offset="1" style="stop-color: #3c4e8a; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #3c4e8a; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,236.449009 L 1043.473469,239.471114 1043.473469,233.426903 Z" fill="#3c4e8a" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,236.449009 L 1043.473469,239.471114 1043.473469,233.426903 Z" fill="url(#GR11_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,236.449009 L 1043.473469,239.471114 1043.473469,233.426903 Z" fill="url(#GR11_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,236.449009 L 1043.473469,239.471114 1043.473469,233.426903 Z" fill="url(#GR11_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR12_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="233.426903" x2="1041.985904" y2="239.07965">
      <stop offset="1" style="stop-color: #3a528b; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #39558c; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR12_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="233.426903" x2="1021.993034" y2="239.07965">
      <stop offset="1" style="stop-color: #3a528b; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #39558c; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR12_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="236.449009" x2="1031.989469" y2="233.426903">
      <stop offset="1" style="stop-color: #3a528b; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #3c4e8a; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,236.449009 L 1043.473469,233.426903 1020.505469,233.426903 Z" fill="#3a528b" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,236.449009 L 1043.473469,233.426903 1020.505469,233.426903 Z" fill="url(#GR12_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,236.449009 L 1043.473469,233.426903 1020.505469,233.426903 Z" fill="url(#GR12_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,236.449009 L 1043.473469,233.426903 1020.505469,233.426903 Z" fill="url(#GR12_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR13_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="233.426903" x2="1021.993034" y2="239.07965">
      <stop offset="1" style="stop-color: #3c4e8a; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #39558c; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR13_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="239.471114" x2="1021.993034" y2="233.818368">
      <stop offset="1" style="stop-color: #3c4e8a; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #404688; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR13_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="236.449009" x2="1020.505469" y2="236.449009">
      <stop offset="1" style="stop-color: #3c4e8a; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #3c4e8a; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,236.449009 L 1020.505469,233.426903 1020.505469,239.471114 Z" fill="#3c4e8a" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,236.449009 L 1020.505469,233.426903 1020.505469,239.471114 Z" fill="url(#GR13_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,236.449009 L 1020.505469,233.426903 1020.505469,239.471114 Z" fill="url(#GR13_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,236.449009 L 1020.505469,233.426903 1020.505469,239.471114 Z" fill="url(#GR13_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR14_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="233.426903" x2="1021.993034" y2="227.774157">
      <stop offset="1" style="stop-color: #38578c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #39558c; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR14_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="233.426903" x2="1041.985904" y2="227.774157">
      <stop offset="1" style="stop-color: #38578c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #39558c; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR14_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="230.404798" x2="1031.989469" y2="233.426903">
      <stop offset="1" style="stop-color: #38578c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #365c8c; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,230.404798 L 1020.505469,233.426903 1043.473469,233.426903 Z" fill="#38578c" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,230.404798 L 1020.505469,233.426903 1043.473469,233.426903 Z" fill="url(#GR14_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,230.404798 L 1020.505469,233.426903 1043.473469,233.426903 Z" fill="url(#GR14_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,230.404798 L 1020.505469,233.426903 1043.473469,233.426903 Z" fill="url(#GR14_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR15_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="233.426903" x2="1041.985904" y2="227.774157">
      <stop offset="1" style="stop-color: #365c8c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #39558c; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR15_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="227.382693" x2="1041.985904" y2="233.035439">
      <stop offset="1" style="stop-color: #365c8c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #33638d; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR15_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="230.404798" x2="1043.473469" y2="230.404798">
      <stop offset="1" style="stop-color: #365c8c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #365c8c; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,230.404798 L 1043.473469,233.426903 1043.473469,227.382693 Z" fill="#365c8c" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,230.404798 L 1043.473469,233.426903 1043.473469,227.382693 Z" fill="url(#GR15_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,230.404798 L 1043.473469,233.426903 1043.473469,227.382693 Z" fill="url(#GR15_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,230.404798 L 1043.473469,233.426903 1043.473469,227.382693 Z" fill="url(#GR15_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR16_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="227.382693" x2="1041.985904" y2="233.035439">
      <stop offset="1" style="stop-color: #34618d; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #33638d; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR16_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="227.382693" x2="1021.993034" y2="233.035439">
      <stop offset="1" style="stop-color: #34618d; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #33638d; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR16_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="230.404798" x2="1031.989469" y2="227.382693">
      <stop offset="1" style="stop-color: #34618d; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #365c8c; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,230.404798 L 1043.473469,227.382693 1020.505469,227.382693 Z" fill="#34618d" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,230.404798 L 1043.473469,227.382693 1020.505469,227.382693 Z" fill="url(#GR16_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,230.404798 L 1043.473469,227.382693 1020.505469,227.382693 Z" fill="url(#GR16_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,230.404798 L 1043.473469,227.382693 1020.505469,227.382693 Z" fill="url(#GR16_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR17_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="227.382693" x2="1021.993034" y2="233.035439">
      <stop offset="1" style="stop-color: #365c8c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #33638d; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR17_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="233.426903" x2="1021.993034" y2="227.774157">
      <stop offset="1" style="stop-color: #365c8c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #39558c; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR17_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="230.404798" x2="1020.505469" y2="230.404798">
      <stop offset="1" style="stop-color: #365c8c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #365c8c; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,230.404798 L 1020.505469,227.382693 1020.505469,233.426903 Z" fill="#365c8c" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,230.404798 L 1020.505469,227.382693 1020.505469,233.426903 Z" fill="url(#GR17_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,230.404798 L 1020.505469,227.382693 1020.505469,233.426903 Z" fill="url(#GR17_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,230.404798 L 1020.505469,227.382693 1020.505469,233.426903 Z" fill="url(#GR17_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR18_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="227.382693" x2="1021.993034" y2="221.729947">
      <stop offset="1" style="stop-color: #32658d; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #33638d; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR18_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="227.382693" x2="1041.985904" y2="221.729947">
      <stop offset="1" style="stop-color: #32658d; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #33638d; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR18_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="224.360588" x2="1031.989469" y2="227.382693">
      <stop offset="1" style="stop-color: #32658d; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #306a8e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,224.360588 L 1020.505469,227.382693 1043.473469,227.382693 Z" fill="#32658d" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,224.360588 L 1020.505469,227.382693 1043.473469,227.382693 Z" fill="url(#GR18_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,224.360588 L 1020.505469,227.382693 1043.473469,227.382693 Z" fill="url(#GR18_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,224.360588 L 1020.505469,227.382693 1043.473469,227.382693 Z" fill="url(#GR18_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR19_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="227.382693" x2="1041.985904" y2="221.729947">
      <stop offset="1" style="stop-color: #306a8e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #33638d; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR19_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="221.338482" x2="1041.985904" y2="226.991229">
      <stop offset="1" style="stop-color: #306a8e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #2d718e; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR19_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="224.360588" x2="1043.473469" y2="224.360588">
      <stop offset="1" style="stop-color: #306a8e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #306a8e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,224.360588 L 1043.473469,227.382693 1043.473469,221.338482 Z" fill="#306a8e" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,224.360588 L 1043.473469,227.382693 1043.473469,221.338482 Z" fill="url(#GR19_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,224.360588 L 1043.473469,227.382693 1043.473469,221.338482 Z" fill="url(#GR19_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,224.360588 L 1043.473469,227.382693 1043.473469,221.338482 Z" fill="url(#GR19_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR1a_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="221.338482" x2="1041.985904" y2="226.991229">
      <stop offset="1" style="stop-color: #2e6f8e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #2d718e; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR1a_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="221.338482" x2="1021.993034" y2="226.991229">
      <stop offset="1" style="stop-color: #2e6f8e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #2d718e; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR1a_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="224.360588" x2="1031.989469" y2="221.338482">
      <stop offset="1" style="stop-color: #2e6f8e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #306a8e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,224.360588 L 1043.473469,221.338482 1020.505469,221.338482 Z" fill="#2e6f8e" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,224.360588 L 1043.473469,221.338482 1020.505469,221.338482 Z" fill="url(#GR1a_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,224.360588 L 1043.473469,221.338482 1020.505469,221.338482 Z" fill="url(#GR1a_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,224.360588 L 1043.473469,221.338482 1020.505469,221.338482 Z" fill="url(#GR1a_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR1b_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="221.338482" x2="1021.993034" y2="226.991229">
      <stop offset="1" style="stop-color: #306a8e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #2d718e; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR1b_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="227.382693" x2="1021.993034" y2="221.729947">
      <stop offset="1" style="stop-color: #306a8e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #33638d; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR1b_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="224.360588" x2="1020.505469" y2="224.360588">
      <stop offset="1" style="stop-color: #306a8e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #306a8e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,224.360588 L 1020.505469,221.338482 1020.505469,227.382693 Z" fill="#306a8e" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,224.360588 L 1020.505469,221.338482 1020.505469,227.382693 Z" fill="url(#GR1b_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,224.360588 L 1020.505469,221.338482 1020.505469,227.382693 Z" fill="url(#GR1b_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,224.360588 L 1020.505469,221.338482 1020.505469,227.382693 Z" fill="url(#GR1b_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR1c_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="221.338482" x2="1021.993034" y2="215.685736">
      <stop offset="1" style="stop-color: #2c738e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #2d718e; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR1c_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="221.338482" x2="1041.985904" y2="215.685736">
      <stop offset="1" style="stop-color: #2c738e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #2d718e; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR1c_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="218.316377" x2="1031.989469" y2="221.338482">
      <stop offset="1" style="stop-color: #2c738e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #2a778e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,218.316377 L 1020.505469,221.338482 1043.473469,221.338482 Z" fill="#2c738e" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,218.316377 L 1020.505469,221.338482 1043.473469,221.338482 Z" fill="url(#GR1c_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,218.316377 L 1020.505469,221.338482 1043.473469,221.338482 Z" fill="url(#GR1c_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,218.316377 L 1020.505469,221.338482 1043.473469,221.338482 Z" fill="url(#GR1c_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR1d_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="221.338482" x2="1041.985904" y2="215.685736">
      <stop offset="1" style="stop-color: #2a778e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #2d718e; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR1d_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="215.294272" x2="1041.985904" y2="220.947018">
      <stop offset="1" style="stop-color: #2a778e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #287d8e; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR1d_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="218.316377" x2="1043.473469" y2="218.316377">
      <stop offset="1" style="stop-color: #2a778e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #2a778e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,218.316377 L 1043.473469,221.338482 1043.473469,215.294272 Z" fill="#2a778e" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,218.316377 L 1043.473469,221.338482 1043.473469,215.294272 Z" fill="url(#GR1d_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,218.316377 L 1043.473469,221.338482 1043.473469,215.294272 Z" fill="url(#GR1d_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,218.316377 L 1043.473469,221.338482 1043.473469,215.294272 Z" fill="url(#GR1d_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR1e_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="215.294272" x2="1041.985904" y2="220.947018">
      <stop offset="1" style="stop-color: #297b8e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #287d8e; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR1e_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="215.294272" x2="1021.993034" y2="220.947018">
      <stop offset="1" style="stop-color: #297b8e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #287d8e; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR1e_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="218.316377" x2="1031.989469" y2="215.294272">
      <stop offset="1" style="stop-color: #297b8e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #2a778e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,218.316377 L 1043.473469,215.294272 1020.505469,215.294272 Z" fill="#297b8e" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,218.316377 L 1043.473469,215.294272 1020.505469,215.294272 Z" fill="url(#GR1e_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,218.316377 L 1043.473469,215.294272 1020.505469,215.294272 Z" fill="url(#GR1e_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,218.316377 L 1043.473469,215.294272 1020.505469,215.294272 Z" fill="url(#GR1e_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR1f_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="215.294272" x2="1021.993034" y2="220.947018">
      <stop offset="1" style="stop-color: #2a778e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #287d8e; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR1f_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="221.338482" x2="1021.993034" y2="215.685736">
      <stop offset="1" style="stop-color: #2a778e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #2d718e; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR1f_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="218.316377" x2="1020.505469" y2="218.316377">
      <stop offset="1" style="stop-color: #2a778e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #2a778e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,218.316377 L 1020.505469,215.294272 1020.505469,221.338482 Z" fill="#2a778e" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,218.316377 L 1020.505469,215.294272 1020.505469,221.338482 Z" fill="url(#GR1f_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,218.316377 L 1020.505469,215.294272 1020.505469,221.338482 Z" fill="url(#GR1f_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,218.316377 L 1020.505469,215.294272 1020.505469,221.338482 Z" fill="url(#GR1f_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR20_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="215.294272" x2="1021.993034" y2="209.641526">
      <stop offset="1" style="stop-color: #277f8e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #287d8e; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR20_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="215.294272" x2="1041.985904" y2="209.641526">
      <stop offset="1" style="stop-color: #277f8e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #287d8e; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR20_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="212.272167" x2="1031.989469" y2="215.294272">
      <stop offset="1" style="stop-color: #277f8e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #26848e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,212.272167 L 1020.505469,215.294272 1043.473469,215.294272 Z" fill="#277f8e" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,212.272167 L 1020.505469,215.294272 1043.473469,215.294272 Z" fill="url(#GR20_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,212.272167 L 1020.505469,215.294272 1043.473469,215.294272 Z" fill="url(#GR20_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,212.272167 L 1020.505469,215.294272 1043.473469,215.294272 Z" fill="url(#GR20_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR21_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="215.294272" x2="1041.985904" y2="209.641526">
      <stop offset="1" style="stop-color: #26848e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #287d8e; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR21_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="209.250061" x2="1041.985904" y2="214.902807">
      <stop offset="1" style="stop-color: #26848e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #238a8d; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR21_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="212.272167" x2="1043.473469" y2="212.272167">
      <stop offset="1" style="stop-color: #26848e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #26848e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,212.272167 L 1043.473469,215.294272 1043.473469,209.250061 Z" fill="#26848e" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,212.272167 L 1043.473469,215.294272 1043.473469,209.250061 Z" fill="url(#GR21_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,212.272167 L 1043.473469,215.294272 1043.473469,209.250061 Z" fill="url(#GR21_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,212.272167 L 1043.473469,215.294272 1043.473469,209.250061 Z" fill="url(#GR21_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR22_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="209.250061" x2="1041.985904" y2="214.902807">
      <stop offset="1" style="stop-color: #24888d; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #238a8d; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR22_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="209.250061" x2="1021.993034" y2="214.902807">
      <stop offset="1" style="stop-color: #24888d; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #238a8d; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR22_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="212.272167" x2="1031.989469" y2="209.250061">
      <stop offset="1" style="stop-color: #24888d; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #26848e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,212.272167 L 1043.473469,209.250061 1020.505469,209.250061 Z" fill="#24888d" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,212.272167 L 1043.473469,209.250061 1020.505469,209.250061 Z" fill="url(#GR22_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,212.272167 L 1043.473469,209.250061 1020.505469,209.250061 Z" fill="url(#GR22_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,212.272167 L 1043.473469,209.250061 1020.505469,209.250061 Z" fill="url(#GR22_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR23_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="209.250061" x2="1021.993034" y2="214.902807">
      <stop offset="1" style="stop-color: #26848e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #238a8d; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR23_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="215.294272" x2="1021.993034" y2="209.641526">
      <stop offset="1" style="stop-color: #26848e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #287d8e; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR23_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="212.272167" x2="1020.505469" y2="212.272167">
      <stop offset="1" style="stop-color: #26848e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #26848e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,212.272167 L 1020.505469,209.250061 1020.505469,215.294272 Z" fill="#26848e" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,212.272167 L 1020.505469,209.250061 1020.505469,215.294272 Z" fill="url(#GR23_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,212.272167 L 1020.505469,209.250061 1020.505469,215.294272 Z" fill="url(#GR23_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,212.272167 L 1020.505469,209.250061 1020.505469,215.294272 Z" fill="url(#GR23_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR24_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="209.250061" x2="1021.993034" y2="203.597315">
      <stop offset="1" style="stop-color: #228c8d; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #238a8d; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR24_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="209.250061" x2="1041.985904" y2="203.597315">
      <stop offset="1" style="stop-color: #228c8d; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #238a8d; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR24_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="206.227956" x2="1031.989469" y2="209.250061">
      <stop offset="1" style="stop-color: #228c8d; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #21908c; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,206.227956 L 1020.505469,209.250061 1043.473469,209.250061 Z" fill="#228c8d" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,206.227956 L 1020.505469,209.250061 1043.473469,209.250061 Z" fill="url(#GR24_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,206.227956 L 1020.505469,209.250061 1043.473469,209.250061 Z" fill="url(#GR24_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,206.227956 L 1020.505469,209.250061 1043.473469,209.250061 Z" fill="url(#GR24_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR25_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="209.250061" x2="1041.985904" y2="203.597315">
      <stop offset="1" style="stop-color: #21908c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #238a8d; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR25_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="203.205851" x2="1041.985904" y2="208.858597">
      <stop offset="1" style="stop-color: #21908c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #1f968b; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR25_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="206.227956" x2="1043.473469" y2="206.227956">
      <stop offset="1" style="stop-color: #21908c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #21908c; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,206.227956 L 1043.473469,209.250061 1043.473469,203.205851 Z" fill="#21908c" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,206.227956 L 1043.473469,209.250061 1043.473469,203.205851 Z" fill="url(#GR25_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,206.227956 L 1043.473469,209.250061 1043.473469,203.205851 Z" fill="url(#GR25_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,206.227956 L 1043.473469,209.250061 1043.473469,203.205851 Z" fill="url(#GR25_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR26_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="203.205851" x2="1041.985904" y2="208.858597">
      <stop offset="1" style="stop-color: #20948b; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #1f968b; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR26_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="203.205851" x2="1021.993034" y2="208.858597">
      <stop offset="1" style="stop-color: #20948b; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #1f968b; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR26_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="206.227956" x2="1031.989469" y2="203.205851">
      <stop offset="1" style="stop-color: #20948b; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #21908c; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,206.227956 L 1043.473469,203.205851 1020.505469,203.205851 Z" fill="#20948b" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,206.227956 L 1043.473469,203.205851 1020.505469,203.205851 Z" fill="url(#GR26_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,206.227956 L 1043.473469,203.205851 1020.505469,203.205851 Z" fill="url(#GR26_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,206.227956 L 1043.473469,203.205851 1020.505469,203.205851 Z" fill="url(#GR26_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR27_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="203.205851" x2="1021.993034" y2="208.858597">
      <stop offset="1" style="stop-color: #21908c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #1f968b; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR27_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="209.250061" x2="1021.993034" y2="203.597315">
      <stop offset="1" style="stop-color: #21908c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #238a8d; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR27_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="206.227956" x2="1020.505469" y2="206.227956">
      <stop offset="1" style="stop-color: #21908c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #21908c; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,206.227956 L 1020.505469,203.205851 1020.505469,209.250061 Z" fill="#21908c" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,206.227956 L 1020.505469,203.205851 1020.505469,209.250061 Z" fill="url(#GR27_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,206.227956 L 1020.505469,203.205851 1020.505469,209.250061 Z" fill="url(#GR27_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,206.227956 L 1020.505469,203.205851 1020.505469,209.250061 Z" fill="url(#GR27_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR28_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="203.205851" x2="1021.993034" y2="197.553105">
      <stop offset="1" style="stop-color: #1f988a; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #1f968b; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR28_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="203.205851" x2="1041.985904" y2="197.553105">
      <stop offset="1" style="stop-color: #1f988a; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #1f968b; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR28_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="200.183746" x2="1031.989469" y2="203.205851">
      <stop offset="1" style="stop-color: #1f988a; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #209c88; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,200.183746 L 1020.505469,203.205851 1043.473469,203.205851 Z" fill="#1f988a" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,200.183746 L 1020.505469,203.205851 1043.473469,203.205851 Z" fill="url(#GR28_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,200.183746 L 1020.505469,203.205851 1043.473469,203.205851 Z" fill="url(#GR28_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,200.183746 L 1020.505469,203.205851 1043.473469,203.205851 Z" fill="url(#GR28_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR29_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="203.205851" x2="1041.985904" y2="197.553105">
      <stop offset="1" style="stop-color: #209c88; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #1f968b; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR29_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="197.16164" x2="1041.985904" y2="202.814386">
      <stop offset="1" style="stop-color: #209c88; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #20a386; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR29_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="200.183746" x2="1043.473469" y2="200.183746">
      <stop offset="1" style="stop-color: #209c88; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #209c88; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,200.183746 L 1043.473469,203.205851 1043.473469,197.16164 Z" fill="#209c88" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,200.183746 L 1043.473469,203.205851 1043.473469,197.16164 Z" fill="url(#GR29_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,200.183746 L 1043.473469,203.205851 1043.473469,197.16164 Z" fill="url(#GR29_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,200.183746 L 1043.473469,203.205851 1043.473469,197.16164 Z" fill="url(#GR29_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR2a_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="197.16164" x2="1041.985904" y2="202.814386">
      <stop offset="1" style="stop-color: #20a187; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #20a386; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR2a_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="197.16164" x2="1021.993034" y2="202.814386">
      <stop offset="1" style="stop-color: #20a187; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #20a386; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR2a_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="200.183746" x2="1031.989469" y2="197.16164">
      <stop offset="1" style="stop-color: #20a187; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #209c88; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,200.183746 L 1043.473469,197.16164 1020.505469,197.16164 Z" fill="#20a187" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,200.183746 L 1043.473469,197.16164 1020.505469,197.16164 Z" fill="url(#GR2a_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,200.183746 L 1043.473469,197.16164 1020.505469,197.16164 Z" fill="url(#GR2a_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,200.183746 L 1043.473469,197.16164 1020.505469,197.16164 Z" fill="url(#GR2a_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR2b_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="197.16164" x2="1021.993034" y2="202.814386">
      <stop offset="1" style="stop-color: #209c88; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #20a386; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR2b_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="203.205851" x2="1021.993034" y2="197.553105">
      <stop offset="1" style="stop-color: #209c88; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #1f968b; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR2b_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="200.183746" x2="1020.505469" y2="200.183746">
      <stop offset="1" style="stop-color: #209c88; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #209c88; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,200.183746 L 1020.505469,197.16164 1020.505469,203.205851 Z" fill="#209c88" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,200.183746 L 1020.505469,197.16164 1020.505469,203.205851 Z" fill="url(#GR2b_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,200.183746 L 1020.505469,197.16164 1020.505469,203.205851 Z" fill="url(#GR2b_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,200.183746 L 1020.505469,197.16164 1020.505469,203.205851 Z" fill="url(#GR2b_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR2c_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="197.16164" x2="1021.993034" y2="191.508894">
      <stop offset="1" style="stop-color: #22a585; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #20a386; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR2c_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="197.16164" x2="1041.985904" y2="191.508894">
      <stop offset="1" style="stop-color: #22a585; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #20a386; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR2c_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="194.139535" x2="1031.989469" y2="197.16164">
      <stop offset="1" style="stop-color: #22a585; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #24a982; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,194.139535 L 1020.505469,197.16164 1043.473469,197.16164 Z" fill="#22a585" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,194.139535 L 1020.505469,197.16164 1043.473469,197.16164 Z" fill="url(#GR2c_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,194.139535 L 1020.505469,197.16164 1043.473469,197.16164 Z" fill="url(#GR2c_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,194.139535 L 1020.505469,197.16164 1043.473469,197.16164 Z" fill="url(#GR2c_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR2d_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="197.16164" x2="1041.985904" y2="191.508894">
      <stop offset="1" style="stop-color: #24a982; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #20a386; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR2d_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="191.11743" x2="1041.985904" y2="196.770176">
      <stop offset="1" style="stop-color: #24a982; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #29af7f; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR2d_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="194.139535" x2="1043.473469" y2="194.139535">
      <stop offset="1" style="stop-color: #24a982; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #24a982; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,194.139535 L 1043.473469,197.16164 1043.473469,191.11743 Z" fill="#24a982" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,194.139535 L 1043.473469,197.16164 1043.473469,191.11743 Z" fill="url(#GR2d_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,194.139535 L 1043.473469,197.16164 1043.473469,191.11743 Z" fill="url(#GR2d_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,194.139535 L 1043.473469,197.16164 1043.473469,191.11743 Z" fill="url(#GR2d_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR2e_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="191.11743" x2="1041.985904" y2="196.770176">
      <stop offset="1" style="stop-color: #28ad80; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #29af7f; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR2e_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="191.11743" x2="1021.993034" y2="196.770176">
      <stop offset="1" style="stop-color: #28ad80; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #29af7f; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR2e_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="194.139535" x2="1031.989469" y2="191.11743">
      <stop offset="1" style="stop-color: #28ad80; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #24a982; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,194.139535 L 1043.473469,191.11743 1020.505469,191.11743 Z" fill="#28ad80" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,194.139535 L 1043.473469,191.11743 1020.505469,191.11743 Z" fill="url(#GR2e_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,194.139535 L 1043.473469,191.11743 1020.505469,191.11743 Z" fill="url(#GR2e_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,194.139535 L 1043.473469,191.11743 1020.505469,191.11743 Z" fill="url(#GR2e_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR2f_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="191.11743" x2="1021.993034" y2="196.770176">
      <stop offset="1" style="stop-color: #24a982; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #29af7f; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR2f_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="197.16164" x2="1021.993034" y2="191.508894">
      <stop offset="1" style="stop-color: #24a982; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #20a386; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR2f_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="194.139535" x2="1020.505469" y2="194.139535">
      <stop offset="1" style="stop-color: #24a982; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #24a982; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,194.139535 L 1020.505469,191.11743 1020.505469,197.16164 Z" fill="#24a982" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,194.139535 L 1020.505469,191.11743 1020.505469,197.16164 Z" fill="url(#GR2f_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,194.139535 L 1020.505469,191.11743 1020.505469,197.16164 Z" fill="url(#GR2f_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,194.139535 L 1020.505469,191.11743 1020.505469,197.16164 Z" fill="url(#GR2f_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR30_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="191.11743" x2="1021.993034" y2="185.464684">
      <stop offset="1" style="stop-color: #2cb17d; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #29af7f; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR30_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="191.11743" x2="1041.985904" y2="185.464684">
      <stop offset="1" style="stop-color: #2cb17d; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #29af7f; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR30_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="188.095325" x2="1031.989469" y2="191.11743">
      <stop offset="1" style="stop-color: #2cb17d; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #33b67a; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,188.095325 L 1020.505469,191.11743 1043.473469,191.11743 Z" fill="#2cb17d" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,188.095325 L 1020.505469,191.11743 1043.473469,191.11743 Z" fill="url(#GR30_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,188.095325 L 1020.505469,191.11743 1043.473469,191.11743 Z" fill="url(#GR30_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,188.095325 L 1020.505469,191.11743 1043.473469,191.11743 Z" fill="url(#GR30_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR31_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="191.11743" x2="1041.985904" y2="185.464684">
      <stop offset="1" style="stop-color: #33b679; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #29af7f; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR31_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="185.073219" x2="1041.985904" y2="190.725965">
      <stop offset="1" style="stop-color: #33b679; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #3dbc74; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR31_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="188.095325" x2="1043.473469" y2="188.095325">
      <stop offset="1" style="stop-color: #33b679; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #33b67a; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,188.095325 L 1043.473469,191.11743 1043.473469,185.073219 Z" fill="#33b679" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,188.095325 L 1043.473469,191.11743 1043.473469,185.073219 Z" fill="url(#GR31_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,188.095325 L 1043.473469,191.11743 1043.473469,185.073219 Z" fill="url(#GR31_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,188.095325 L 1043.473469,191.11743 1043.473469,185.073219 Z" fill="url(#GR31_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR32_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="185.073219" x2="1041.985904" y2="190.725965">
      <stop offset="1" style="stop-color: #3aba76; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #3dbc74; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR32_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="185.073219" x2="1021.993034" y2="190.725965">
      <stop offset="1" style="stop-color: #3aba76; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #3dbc74; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR32_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="188.095325" x2="1031.989469" y2="185.073219">
      <stop offset="1" style="stop-color: #3aba76; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #33b67a; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,188.095325 L 1043.473469,185.073219 1020.505469,185.073219 Z" fill="#3aba76" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,188.095325 L 1043.473469,185.073219 1020.505469,185.073219 Z" fill="url(#GR32_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,188.095325 L 1043.473469,185.073219 1020.505469,185.073219 Z" fill="url(#GR32_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,188.095325 L 1043.473469,185.073219 1020.505469,185.073219 Z" fill="url(#GR32_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR33_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="185.073219" x2="1021.993034" y2="190.725965">
      <stop offset="1" style="stop-color: #33b679; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #3dbc74; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR33_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="191.11743" x2="1021.993034" y2="185.464684">
      <stop offset="1" style="stop-color: #33b679; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #29af7f; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR33_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="188.095325" x2="1020.505469" y2="188.095325">
      <stop offset="1" style="stop-color: #33b679; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #33b67a; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,188.095325 L 1020.505469,185.073219 1020.505469,191.11743 Z" fill="#33b679" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,188.095325 L 1020.505469,185.073219 1020.505469,191.11743 Z" fill="url(#GR33_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,188.095325 L 1020.505469,185.073219 1020.505469,191.11743 Z" fill="url(#GR33_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,188.095325 L 1020.505469,185.073219 1020.505469,191.11743 Z" fill="url(#GR33_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR34_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="185.073219" x2="1021.993034" y2="179.420473">
      <stop offset="1" style="stop-color: #41be72; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #3dbc74; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR34_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="185.073219" x2="1041.985904" y2="179.420473">
      <stop offset="1" style="stop-color: #41be72; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #3dbc74; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR34_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="182.051114" x2="1031.989469" y2="185.073219">
      <stop offset="1" style="stop-color: #41be72; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #4ac16e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,182.051114 L 1020.505469,185.073219 1043.473469,185.073219 Z" fill="#41be72" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,182.051114 L 1020.505469,185.073219 1043.473469,185.073219 Z" fill="url(#GR34_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,182.051114 L 1020.505469,185.073219 1043.473469,185.073219 Z" fill="url(#GR34_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,182.051114 L 1020.505469,185.073219 1043.473469,185.073219 Z" fill="url(#GR34_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR35_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="185.073219" x2="1041.985904" y2="179.420473">
      <stop offset="1" style="stop-color: #4ac16e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #3dbc74; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR35_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="179.029009" x2="1041.985904" y2="184.681755">
      <stop offset="1" style="stop-color: #4ac16e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #56c667; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR35_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="182.051114" x2="1043.473469" y2="182.051114">
      <stop offset="1" style="stop-color: #4ac16e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #4ac16e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,182.051114 L 1043.473469,185.073219 1043.473469,179.029009 Z" fill="#4ac16e" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,182.051114 L 1043.473469,185.073219 1043.473469,179.029009 Z" fill="url(#GR35_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,182.051114 L 1043.473469,185.073219 1043.473469,179.029009 Z" fill="url(#GR35_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,182.051114 L 1043.473469,185.073219 1043.473469,179.029009 Z" fill="url(#GR35_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR36_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="179.029009" x2="1041.985904" y2="184.681755">
      <stop offset="1" style="stop-color: #52c469; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #56c667; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR36_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="179.029009" x2="1021.993034" y2="184.681755">
      <stop offset="1" style="stop-color: #52c469; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #56c667; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR36_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="182.051114" x2="1031.989469" y2="179.029009">
      <stop offset="1" style="stop-color: #52c469; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #4ac16e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,182.051114 L 1043.473469,179.029009 1020.505469,179.029009 Z" fill="#52c469" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,182.051114 L 1043.473469,179.029009 1020.505469,179.029009 Z" fill="url(#GR36_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,182.051114 L 1043.473469,179.029009 1020.505469,179.029009 Z" fill="url(#GR36_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,182.051114 L 1043.473469,179.029009 1020.505469,179.029009 Z" fill="url(#GR36_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR37_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="179.029009" x2="1021.993034" y2="184.681755">
      <stop offset="1" style="stop-color: #4ac16e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #56c667; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR37_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="185.073219" x2="1021.993034" y2="179.420473">
      <stop offset="1" style="stop-color: #4ac16e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #3dbc74; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR37_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="182.051114" x2="1020.505469" y2="182.051114">
      <stop offset="1" style="stop-color: #4ac16e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #4ac16e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,182.051114 L 1020.505469,179.029009 1020.505469,185.073219 Z" fill="#4ac16e" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,182.051114 L 1020.505469,179.029009 1020.505469,185.073219 Z" fill="url(#GR37_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,182.051114 L 1020.505469,179.029009 1020.505469,185.073219 Z" fill="url(#GR37_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,182.051114 L 1020.505469,179.029009 1020.505469,185.073219 Z" fill="url(#GR37_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR38_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="179.029009" x2="1021.993034" y2="173.376263">
      <stop offset="1" style="stop-color: #5bc864; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #56c667; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR38_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="179.029009" x2="1041.985904" y2="173.376263">
      <stop offset="1" style="stop-color: #5bc864; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #56c667; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR38_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="176.006903" x2="1031.989469" y2="179.029009">
      <stop offset="1" style="stop-color: #5bc864; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #66cb5e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,176.006903 L 1020.505469,179.029009 1043.473469,179.029009 Z" fill="#5bc864" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,176.006903 L 1020.505469,179.029009 1043.473469,179.029009 Z" fill="url(#GR38_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,176.006903 L 1020.505469,179.029009 1043.473469,179.029009 Z" fill="url(#GR38_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,176.006903 L 1020.505469,179.029009 1043.473469,179.029009 Z" fill="url(#GR38_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR39_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="179.029009" x2="1041.985904" y2="173.376263">
      <stop offset="1" style="stop-color: #66cb5e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #56c667; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR39_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="172.984798" x2="1041.985904" y2="178.637544">
      <stop offset="1" style="stop-color: #66cb5e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #75d054; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR39_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="176.006903" x2="1043.473469" y2="176.006903">
      <stop offset="1" style="stop-color: #66cb5e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #66cb5e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,176.006903 L 1043.473469,179.029009 1043.473469,172.984798 Z" fill="#66cb5e" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,176.006903 L 1043.473469,179.029009 1043.473469,172.984798 Z" fill="url(#GR39_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,176.006903 L 1043.473469,179.029009 1043.473469,172.984798 Z" fill="url(#GR39_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,176.006903 L 1043.473469,179.029009 1043.473469,172.984798 Z" fill="url(#GR39_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR3a_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="172.984798" x2="1041.985904" y2="178.637544">
      <stop offset="1" style="stop-color: #70ce57; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #75d054; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR3a_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="172.984798" x2="1021.993034" y2="178.637544">
      <stop offset="1" style="stop-color: #70ce57; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #75d054; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR3a_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="176.006903" x2="1031.989469" y2="172.984798">
      <stop offset="1" style="stop-color: #70ce57; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #66cb5e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,176.006903 L 1043.473469,172.984798 1020.505469,172.984798 Z" fill="#70ce57" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,176.006903 L 1043.473469,172.984798 1020.505469,172.984798 Z" fill="url(#GR3a_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,176.006903 L 1043.473469,172.984798 1020.505469,172.984798 Z" fill="url(#GR3a_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,176.006903 L 1043.473469,172.984798 1020.505469,172.984798 Z" fill="url(#GR3a_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR3b_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="172.984798" x2="1021.993034" y2="178.637544">
      <stop offset="1" style="stop-color: #66cb5e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #75d054; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR3b_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="179.029009" x2="1021.993034" y2="173.376263">
      <stop offset="1" style="stop-color: #66cb5e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #56c667; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR3b_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="176.006903" x2="1020.505469" y2="176.006903">
      <stop offset="1" style="stop-color: #66cb5e; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #66cb5e; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,176.006903 L 1020.505469,172.984798 1020.505469,179.029009 Z" fill="#66cb5e" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,176.006903 L 1020.505469,172.984798 1020.505469,179.029009 Z" fill="url(#GR3b_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,176.006903 L 1020.505469,172.984798 1020.505469,179.029009 Z" fill="url(#GR3b_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,176.006903 L 1020.505469,172.984798 1020.505469,179.029009 Z" fill="url(#GR3b_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR3c_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="172.984798" x2="1021.993034" y2="167.332052">
      <stop offset="1" style="stop-color: #7ad151; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #75d054; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR3c_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="172.984798" x2="1041.985904" y2="167.332052">
      <stop offset="1" style="stop-color: #7ad151; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #75d054; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR3c_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="169.962693" x2="1031.989469" y2="172.984798">
      <stop offset="1" style="stop-color: #7ad151; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #85d44a; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,169.962693 L 1020.505469,172.984798 1043.473469,172.984798 Z" fill="#7ad151" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,169.962693 L 1020.505469,172.984798 1043.473469,172.984798 Z" fill="url(#GR3c_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,169.962693 L 1020.505469,172.984798 1043.473469,172.984798 Z" fill="url(#GR3c_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,169.962693 L 1020.505469,172.984798 1043.473469,172.984798 Z" fill="url(#GR3c_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR3d_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="172.984798" x2="1041.985904" y2="167.332052">
      <stop offset="1" style="stop-color: #85d44a; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #75d054; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR3d_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="166.940588" x2="1041.985904" y2="172.593334">
      <stop offset="1" style="stop-color: #85d44a; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #95d840; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR3d_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="169.962693" x2="1043.473469" y2="169.962693">
      <stop offset="1" style="stop-color: #85d44a; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #85d44a; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,169.962693 L 1043.473469,172.984798 1043.473469,166.940588 Z" fill="#85d44a" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,169.962693 L 1043.473469,172.984798 1043.473469,166.940588 Z" fill="url(#GR3d_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,169.962693 L 1043.473469,172.984798 1043.473469,166.940588 Z" fill="url(#GR3d_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,169.962693 L 1043.473469,172.984798 1043.473469,166.940588 Z" fill="url(#GR3d_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR3e_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="166.940588" x2="1041.985904" y2="172.593334">
      <stop offset="1" style="stop-color: #90d743; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #95d840; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR3e_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="166.940588" x2="1021.993034" y2="172.593334">
      <stop offset="1" style="stop-color: #90d743; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #95d840; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR3e_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="169.962693" x2="1031.989469" y2="166.940588">
      <stop offset="1" style="stop-color: #90d743; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #85d44a; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,169.962693 L 1043.473469,166.940588 1020.505469,166.940588 Z" fill="#90d743" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,169.962693 L 1043.473469,166.940588 1020.505469,166.940588 Z" fill="url(#GR3e_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,169.962693 L 1043.473469,166.940588 1020.505469,166.940588 Z" fill="url(#GR3e_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,169.962693 L 1043.473469,166.940588 1020.505469,166.940588 Z" fill="url(#GR3e_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR3f_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="166.940588" x2="1021.993034" y2="172.593334">
      <stop offset="1" style="stop-color: #85d44a; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #95d840; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR3f_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="172.984798" x2="1021.993034" y2="167.332052">
      <stop offset="1" style="stop-color: #85d44a; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #75d054; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR3f_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="169.962693" x2="1020.505469" y2="169.962693">
      <stop offset="1" style="stop-color: #85d44a; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #85d44a; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,169.962693 L 1020.505469,166.940588 1020.505469,172.984798 Z" fill="#85d44a" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,169.962693 L 1020.505469,166.940588 1020.505469,172.984798 Z" fill="url(#GR3f_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,169.962693 L 1020.505469,166.940588 1020.505469,172.984798 Z" fill="url(#GR3f_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,169.962693 L 1020.505469,166.940588 1020.505469,172.984798 Z" fill="url(#GR3f_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR40_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="166.940588" x2="1021.993034" y2="161.287842">
      <stop offset="1" style="stop-color: #9bd93c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #95d840; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR40_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="166.940588" x2="1041.985904" y2="161.287842">
      <stop offset="1" style="stop-color: #9bd93c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #95d840; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR40_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="163.918482" x2="1031.989469" y2="166.940588">
      <stop offset="1" style="stop-color: #9bd93c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #a8db34; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,163.918482 L 1020.505469,166.940588 1043.473469,166.940588 Z" fill="#9bd93c" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,163.918482 L 1020.505469,166.940588 1043.473469,166.940588 Z" fill="url(#GR40_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,163.918482 L 1020.505469,166.940588 1043.473469,166.940588 Z" fill="url(#GR40_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,163.918482 L 1020.505469,166.940588 1043.473469,166.940588 Z" fill="url(#GR40_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR41_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="166.940588" x2="1041.985904" y2="161.287842">
      <stop offset="1" style="stop-color: #a8db34; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #95d840; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR41_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="160.896377" x2="1041.985904" y2="166.549123">
      <stop offset="1" style="stop-color: #a8db34; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #bade28; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR41_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="163.918482" x2="1043.473469" y2="163.918482">
      <stop offset="1" style="stop-color: #a8db34; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #a8db34; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,163.918482 L 1043.473469,166.940588 1043.473469,160.896377 Z" fill="#a8db34" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,163.918482 L 1043.473469,166.940588 1043.473469,160.896377 Z" fill="url(#GR41_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,163.918482 L 1043.473469,166.940588 1043.473469,160.896377 Z" fill="url(#GR41_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,163.918482 L 1043.473469,166.940588 1043.473469,160.896377 Z" fill="url(#GR41_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR42_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="160.896377" x2="1041.985904" y2="166.549123">
      <stop offset="1" style="stop-color: #b4dd2c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #bade28; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR42_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="160.896377" x2="1021.993034" y2="166.549123">
      <stop offset="1" style="stop-color: #b4dd2c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #bade28; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR42_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="163.918482" x2="1031.989469" y2="160.896377">
      <stop offset="1" style="stop-color: #b4dd2c; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #a8db34; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,163.918482 L 1043.473469,160.896377 1020.505469,160.896377 Z" fill="#b4dd2c" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,163.918482 L 1043.473469,160.896377 1020.505469,160.896377 Z" fill="url(#GR42_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,163.918482 L 1043.473469,160.896377 1020.505469,160.896377 Z" fill="url(#GR42_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,163.918482 L 1043.473469,160.896377 1020.505469,160.896377 Z" fill="url(#GR42_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR43_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="160.896377" x2="1021.993034" y2="166.549123">
      <stop offset="1" style="stop-color: #a8db34; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #bade28; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR43_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="166.940588" x2="1021.993034" y2="161.287842">
      <stop offset="1" style="stop-color: #a8db34; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #95d840; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR43_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="163.918482" x2="1020.505469" y2="163.918482">
      <stop offset="1" style="stop-color: #a8db34; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #a8db34; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,163.918482 L 1020.505469,160.896377 1020.505469,166.940588 Z" fill="#a8db34" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,163.918482 L 1020.505469,160.896377 1020.505469,166.940588 Z" fill="url(#GR43_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,163.918482 L 1020.505469,160.896377 1020.505469,166.940588 Z" fill="url(#GR43_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,163.918482 L 1020.505469,160.896377 1020.505469,166.940588 Z" fill="url(#GR43_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR44_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="160.896377" x2="1021.993034" y2="155.243631">
      <stop offset="1" style="stop-color: #c0df25; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #bade28; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR44_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="160.896377" x2="1041.985904" y2="155.243631">
      <stop offset="1" style="stop-color: #c0df25; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #bade28; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR44_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="157.874272" x2="1031.989469" y2="160.896377">
      <stop offset="1" style="stop-color: #c0df25; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #cbe020; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,157.874272 L 1020.505469,160.896377 1043.473469,160.896377 Z" fill="#c0df25" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,157.874272 L 1020.505469,160.896377 1043.473469,160.896377 Z" fill="url(#GR44_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,157.874272 L 1020.505469,160.896377 1043.473469,160.896377 Z" fill="url(#GR44_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,157.874272 L 1020.505469,160.896377 1043.473469,160.896377 Z" fill="url(#GR44_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR45_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="160.896377" x2="1041.985904" y2="155.243631">
      <stop offset="1" style="stop-color: #cbe020; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #bade28; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR45_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="154.852167" x2="1041.985904" y2="160.504913">
      <stop offset="1" style="stop-color: #cbe020; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #dde318; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR45_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="157.874272" x2="1043.473469" y2="157.874272">
      <stop offset="1" style="stop-color: #cbe020; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #cbe020; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,157.874272 L 1043.473469,160.896377 1043.473469,154.852167 Z" fill="#cbe020" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,157.874272 L 1043.473469,160.896377 1043.473469,154.852167 Z" fill="url(#GR45_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,157.874272 L 1043.473469,160.896377 1043.473469,154.852167 Z" fill="url(#GR45_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,157.874272 L 1043.473469,160.896377 1043.473469,154.852167 Z" fill="url(#GR45_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR46_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="154.852167" x2="1041.985904" y2="160.504913">
      <stop offset="1" style="stop-color: #d7e21b; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #dde318; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR46_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="154.852167" x2="1021.993034" y2="160.504913">
      <stop offset="1" style="stop-color: #d7e21b; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #dde318; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR46_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="157.874272" x2="1031.989469" y2="154.852167">
      <stop offset="1" style="stop-color: #d7e21b; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #cbe020; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,157.874272 L 1043.473469,154.852167 1020.505469,154.852167 Z" fill="#d7e21b" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,157.874272 L 1043.473469,154.852167 1020.505469,154.852167 Z" fill="url(#GR46_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,157.874272 L 1043.473469,154.852167 1020.505469,154.852167 Z" fill="url(#GR46_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,157.874272 L 1043.473469,154.852167 1020.505469,154.852167 Z" fill="url(#GR46_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR47_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="154.852167" x2="1021.993034" y2="160.504913">
      <stop offset="1" style="stop-color: #cbe020; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #dde318; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR47_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="160.896377" x2="1021.993034" y2="155.243631">
      <stop offset="1" style="stop-color: #cbe020; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #bade28; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR47_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="157.874272" x2="1020.505469" y2="157.874272">
      <stop offset="1" style="stop-color: #cbe020; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #cbe020; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,157.874272 L 1020.505469,154.852167 1020.505469,160.896377 Z" fill="#cbe020" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,157.874272 L 1020.505469,154.852167 1020.505469,160.896377 Z" fill="url(#GR47_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,157.874272 L 1020.505469,154.852167 1020.505469,160.896377 Z" fill="url(#GR47_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,157.874272 L 1020.505469,154.852167 1020.505469,160.896377 Z" fill="url(#GR47_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR48_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="154.852167" x2="1021.993034" y2="149.199421">
      <stop offset="1" style="stop-color: #e2e41a; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #dde318; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR48_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="154.852167" x2="1041.985904" y2="149.199421">
      <stop offset="1" style="stop-color: #e2e41a; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #dde318; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR48_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="151.830061" x2="1031.989469" y2="154.852167">
      <stop offset="1" style="stop-color: #e2e41a; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #ede51f; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,151.830061 L 1020.505469,154.852167 1043.473469,154.852167 Z" fill="#e2e41a" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,151.830061 L 1020.505469,154.852167 1043.473469,154.852167 Z" fill="url(#GR48_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,151.830061 L 1020.505469,154.852167 1043.473469,154.852167 Z" fill="url(#GR48_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,151.830061 L 1020.505469,154.852167 1043.473469,154.852167 Z" fill="url(#GR48_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR49_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="154.852167" x2="1041.985904" y2="149.199421">
      <stop offset="1" style="stop-color: #ede51f; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #dde318; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR49_1" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="148.807956" x2="1041.985904" y2="154.460702">
      <stop offset="1" style="stop-color: #ede51f; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #fde725; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR49_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="151.830061" x2="1043.473469" y2="151.830061">
      <stop offset="1" style="stop-color: #ede51f; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #ede51f; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,151.830061 L 1043.473469,154.852167 1043.473469,148.807956 Z" fill="#ede51f" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,151.830061 L 1043.473469,154.852167 1043.473469,148.807956 Z" fill="url(#GR49_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,151.830061 L 1043.473469,154.852167 1043.473469,148.807956 Z" fill="url(#GR49_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,151.830061 L 1043.473469,154.852167 1043.473469,148.807956 Z" fill="url(#GR49_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR4a_0" gradientUnits="userSpaceOnUse" x1="1043.473469" y1="148.807956" x2="1041.985904" y2="154.460702">
      <stop offset="1" style="stop-color: #f8e623; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #fde725; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR4a_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="148.807956" x2="1021.993034" y2="154.460702">
      <stop offset="1" style="stop-color: #f8e623; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #fde725; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR4a_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="151.830061" x2="1031.989469" y2="148.807956">
      <stop offset="1" style="stop-color: #f8e623; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #ede51f; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,151.830061 L 1043.473469,148.807956 1020.505469,148.807956 Z" fill="#f8e623" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,151.830061 L 1043.473469,148.807956 1020.505469,148.807956 Z" fill="url(#GR4a_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,151.830061 L 1043.473469,148.807956 1020.505469,148.807956 Z" fill="url(#GR4a_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,151.830061 L 1043.473469,148.807956 1020.505469,148.807956 Z" fill="url(#GR4a_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
    <defs>
     <linearGradient id="GR4b_0" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="148.807956" x2="1021.993034" y2="154.460702">
      <stop offset="1" style="stop-color: #ede51f; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #fde725; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR4b_1" gradientUnits="userSpaceOnUse" x1="1020.505469" y1="154.852167" x2="1021.993034" y2="149.199421">
      <stop offset="1" style="stop-color: #ede51f; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #dde318; stop-opacity: 0"/>
     </linearGradient>
     <linearGradient id="GR4b_2" gradientUnits="userSpaceOnUse" x1="1031.989469" y1="151.830061" x2="1020.505469" y2="151.830061">
      <stop offset="1" style="stop-color: #ede51f; stop-opacity: 1"/>
      <stop offset="0" style="stop-color: #ede51f; stop-opacity: 0"/>
     </linearGradient>
    </defs>
    <path d="M 1031.989469,151.830061 L 1020.505469,148.807956 1020.505469,154.852167 Z" fill="#ede51f" fill-opacity="1" shape-rendering="crispEdges"/>
    <g stroke="none" stroke-width="0" shape-rendering="crispEdges" filter="url(#colorMat)">
     <path d="M 1031.989469,151.830061 L 1020.505469,148.807956 1020.505469,154.852167 Z" fill="url(#GR4b_0)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,151.830061 L 1020.505469,148.807956 1020.505469,154.852167 Z" fill="url(#GR4b_1)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
     <path d="M 1031.989469,151.830061 L 1020.505469,148.807956 1020.505469,154.852167 Z" fill="url(#GR4b_2)" filter="url(#colorAdd)" shape-rendering="crispEdges"/>
    </g>
   </g>
  </g>
  <g id="LineCollection_2">
   <path d="M 1020.505469 234.328956 
L 1025.099069 234.328956 
" style="fill: none; stroke: #cccccc"/>
   <path d="M 1038.879869 234.328956 
L 1043.473469 234.328956 
" style="fill: none; stroke: #cccccc"/>
   <path d="M 1020.505469 207.81024 
L 1025.099069 207.81024 
" style="fill: none; stroke: #cccccc"/>
   <path d="M 1038.879869 207.81024 
L 1043.473469 207.81024 
" style="fill: none; stroke: #cccccc"/>
   <path d="M 1020.505469 181.291523 
L 1025.099069 181.291523 
" style="fill: none; stroke: #cccccc"/>
   <path d="M 1038.879869 181.291523 
L 1043.473469 181.291523 
" style="fill: none; stroke: #cccccc"/>
   <path d="M 1020.505469 154.772806 
L 1025.099069 154.772806 
" style="fill: none; stroke: #cccccc"/>
   <path d="M 1038.879869 154.772806 
L 1043.473469 154.772806 
" style="fill: none; stroke: #cccccc"/>
  </g>
  <g id="text_45">
   <!-- 3000 -->
   <g transform="translate(1046.473469 236.757206) scale(0.088 -0.088)">
    <use xlink:href="#DejaVuSans-33"/>
    <use xlink:href="#DejaVuSans-30" x="63.623047"/>
    <use xlink:href="#DejaVuSans-30" x="127.246094"/>
    <use xlink:href="#DejaVuSans-30" x="190.869141"/>
   </g>
  </g>
  <g id="text_46">
   <!-- 6000 -->
   <g transform="translate(1046.473469 210.23849) scale(0.088 -0.088)">
    <use xlink:href="#DejaVuSans-36"/>
    <use xlink:href="#DejaVuSans-30" x="63.623047"/>
    <use xlink:href="#DejaVuSans-30" x="127.246094"/>
    <use xlink:href="#DejaVuSans-30" x="190.869141"/>
   </g>
  </g>
  <g id="text_47">
   <!-- 9000 -->
   <g transform="translate(1046.473469 183.719773) scale(0.088 -0.088)">
    <use xlink:href="#DejaVuSans-39"/>
    <use xlink:href="#DejaVuSans-30" x="63.623047"/>
    <use xlink:href="#DejaVuSans-30" x="127.246094"/>
    <use xlink:href="#DejaVuSans-30" x="190.869141"/>
   </g>
  </g>
  <g id="text_48">
   <!-- 12000 -->
   <g transform="translate(1046.473469 157.201056) scale(0.088 -0.088)">
    <use xlink:href="#DejaVuSans-31"/>
    <use xlink:href="#DejaVuSans-32" x="63.623047"/>
    <use xlink:href="#DejaVuSans-30" x="127.246094"/>
    <use xlink:href="#DejaVuSans-30" x="190.869141"/>
    <use xlink:href="#DejaVuSans-30" x="254.492188"/>
   </g>
  </g>
  <g id="text_49">
   <!-- Number of comments -->
   <g transform="translate(1020.505469 285.04155) scale(0.11 -0.11)">
    <use xlink:href="#DejaVuSans-4e"/>
    <use xlink:href="#DejaVuSans-75" x="74.804688"/>
    <use xlink:href="#DejaVuSans-6d" x="138.183594"/>
    <use xlink:href="#DejaVuSans-62" x="235.595703"/>
    <use xlink:href="#DejaVuSans-65" x="299.072266"/>
    <use xlink:href="#DejaVuSans-72" x="360.595703"/>
    <use xlink:href="#DejaVuSans-20" x="401.708984"/>
    <use xlink:href="#DejaVuSans-6f" x="433.496094"/>
    <use xlink:href="#DejaVuSans-66" x="494.677734"/>
    <use xlink:href="#DejaVuSans-20" x="529.882812"/>
    <use xlink:href="#DejaVuSans-63" x="561.669922"/>
    <use xlink:href="#DejaVuSans-6f" x="616.650391"/>
    <use xlink:href="#DejaVuSans-6d" x="677.832031"/>
    <use xlink:href="#DejaVuSans-6d" x="775.244141"/>
    <use xlink:href="#DejaVuSans-65" x="872.65625"/>
    <use xlink:href="#DejaVuSans-6e" x="934.179688"/>
    <use xlink:href="#DejaVuSans-74" x="997.558594"/>
    <use xlink:href="#DejaVuSans-73" x="1036.767578"/>
   </g>
  </g>
  <g id="patch_6">
   <path d="M 1020.505469 324.759782 
L 1065.19137 324.759782 
L 1065.19137 295.813894 
L 1020.505469 295.813894 
L 1020.505469 324.759782 
z
" clip-path="url(#p3197a8cc03)" style="fill: none"/>
  </g>
  <g id="line2d_46">
   <path d="M 1042.848419 310.286838 
" clip-path="url(#p3197a8cc03)" style="fill: none; stroke: #1f77b4; stroke-width: 1.5; stroke-linecap: square"/>
   <defs>
    <path id="mc08ebe1784" d="M 0 10.069831 
C 2.67055 10.069831 5.232081 9.00881 7.120446 7.120446 
C 9.00881 5.232081 10.069831 2.67055 10.069831 0 
C 10.069831 -2.67055 9.00881 -5.232081 7.120446 -7.120446 
C 5.232081 -9.00881 2.67055 -10.069831 0 -10.069831 
C -2.67055 -10.069831 -5.232081 -9.00881 -7.120446 -7.120446 
C -9.00881 -5.232081 -10.069831 -2.67055 -10.069831 0 
C -10.069831 2.67055 -9.00881 5.232081 -7.120446 7.120446 
C -5.232081 9.00881 -2.67055 10.069831 0 10.069831 
z
" style="stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
   </defs>
   <g clip-path="url(#p3197a8cc03)">
    <use xlink:href="#mc08ebe1784" x="1042.848419" y="310.286838" style="fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
   </g>
  </g>
  <g id="text_50">
   <!-- 3000 -->
   <g transform="translate(1068.19137 312.715088) scale(0.088 -0.088)">
    <use xlink:href="#DejaVuSans-33"/>
    <use xlink:href="#DejaVuSans-30" x="63.623047"/>
    <use xlink:href="#DejaVuSans-30" x="127.246094"/>
    <use xlink:href="#DejaVuSans-30" x="190.869141"/>
   </g>
  </g>
  <g id="patch_7">
   <path d="M 1020.505469 362.227201 
L 1065.19137 362.227201 
L 1065.19137 326.759782 
L 1020.505469 326.759782 
L 1020.505469 362.227201 
z
" clip-path="url(#p6aae680b56)" style="fill: none"/>
  </g>
  <g id="line2d_47">
   <path d="M 1042.848419 344.493491 
" clip-path="url(#p6aae680b56)" style="fill: none; stroke: #1f77b4; stroke-width: 1.5; stroke-linecap: square"/>
   <defs>
    <path id="m5a976f353f" d="M 0 13.330596 
C 3.535315 13.330596 6.926309 11.926 9.426155 9.426155 
C 11.926 6.926309 13.330596 3.535315 13.330596 0 
C 13.330596 -3.535315 11.926 -6.926309 9.426155 -9.426155 
C 6.926309 -11.926 3.535315 -13.330596 0 -13.330596 
C -3.535315 -13.330596 -6.926309 -11.926 -9.426155 -9.426155 
C -11.926 -6.926309 -13.330596 -3.535315 -13.330596 0 
C -13.330596 3.535315 -11.926 6.926309 -9.426155 9.426155 
C -6.926309 11.926 -3.535315 13.330596 0 13.330596 
z
" style="stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
   </defs>
   <g clip-path="url(#p6aae680b56)">
    <use xlink:href="#m5a976f353f" x="1042.848419" y="344.493491" style="fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
   </g>
  </g>
  <g id="text_51">
   <!-- 6000 -->
   <g transform="translate(1068.19137 346.921741) scale(0.088 -0.088)">
    <use xlink:href="#DejaVuSans-36"/>
    <use xlink:href="#DejaVuSans-30" x="63.623047"/>
    <use xlink:href="#DejaVuSans-30" x="127.246094"/>
    <use xlink:href="#DejaVuSans-30" x="190.869141"/>
   </g>
  </g>
  <g id="patch_8">
   <path d="M 1020.505469 404.696768 
L 1065.19137 404.696768 
L 1065.19137 364.227201 
L 1020.505469 364.227201 
L 1020.505469 404.696768 
z
" clip-path="url(#pd2dcf45466)" style="fill: none"/>
  </g>
  <g id="line2d_48">
   <path d="M 1042.848419 384.461984 
" clip-path="url(#pd2dcf45466)" style="fill: none; stroke: #1f77b4; stroke-width: 1.5; stroke-linecap: square"/>
   <defs>
    <path id="m3942f10d9f" d="M 0 15.83167 
C 4.198608 15.83167 8.225817 14.163546 11.194681 11.194681 
C 14.163546 8.225817 15.83167 4.198608 15.83167 0 
C 15.83167 -4.198608 14.163546 -8.225817 11.194681 -11.194681 
C 8.225817 -14.163546 4.198608 -15.83167 0 -15.83167 
C -4.198608 -15.83167 -8.225817 -14.163546 -11.194681 -11.194681 
C -14.163546 -8.225817 -15.83167 -4.198608 -15.83167 0 
C -15.83167 4.198608 -14.163546 8.225817 -11.194681 11.194681 
C -8.225817 14.163546 -4.198608 15.83167 0 15.83167 
z
" style="stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
   </defs>
   <g clip-path="url(#pd2dcf45466)">
    <use xlink:href="#m3942f10d9f" x="1042.848419" y="384.461984" style="fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
   </g>
  </g>
  <g id="text_52">
   <!-- 9000 -->
   <g transform="translate(1068.19137 386.890234) scale(0.088 -0.088)">
    <use xlink:href="#DejaVuSans-39"/>
    <use xlink:href="#DejaVuSans-30" x="63.623047"/>
    <use xlink:href="#DejaVuSans-30" x="127.246094"/>
    <use xlink:href="#DejaVuSans-30" x="190.869141"/>
   </g>
  </g>
  <g id="patch_9">
   <path d="M 1020.505469 451.382669 
L 1065.19137 451.382669 
L 1065.19137 406.696768 
L 1020.505469 406.696768 
L 1020.505469 451.382669 
z
" clip-path="url(#p418fb97726)" style="fill: none"/>
  </g>
  <g id="line2d_49">
   <path d="M 1042.848419 429.039718 
" clip-path="url(#p418fb97726)" style="fill: none; stroke: #1f77b4; stroke-width: 1.5; stroke-linecap: square"/>
   <defs>
    <path id="m506a417537" d="M 0 17.939837 
C 4.7577 17.939837 9.321178 16.049583 12.68538 12.68538 
C 16.049583 9.321178 17.939837 4.7577 17.939837 0 
C 17.939837 -4.7577 16.049583 -9.321178 12.68538 -12.68538 
C 9.321178 -16.049583 4.7577 -17.939837 0 -17.939837 
C -4.7577 -17.939837 -9.321178 -16.049583 -12.68538 -12.68538 
C -16.049583 -9.321178 -17.939837 -4.7577 -17.939837 0 
C -17.939837 4.7577 -16.049583 9.321178 -12.68538 12.68538 
C -9.321178 16.049583 -4.7577 17.939837 0 17.939837 
z
" style="stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
   </defs>
   <g clip-path="url(#p418fb97726)">
    <use xlink:href="#m506a417537" x="1042.848419" y="429.039718" style="fill-opacity: 0.698039; stroke: #000000; stroke-opacity: 0.698039; stroke-width: 0.886227"/>
   </g>
  </g>
  <g id="text_53">
   <!-- 12000 -->
   <g transform="translate(1068.19137 431.467968) scale(0.088 -0.088)">
    <use xlink:href="#DejaVuSans-31"/>
    <use xlink:href="#DejaVuSans-32" x="63.623047"/>
    <use xlink:href="#DejaVuSans-30" x="127.246094"/>
    <use xlink:href="#DejaVuSans-30" x="190.869141"/>
    <use xlink:href="#DejaVuSans-30" x="254.492188"/>
   </g>
  </g>
 </g>
 <defs>
  <clipPath id="p8a32aafd77">
   <rect x="155.711875" y="66.497813" width="830.033594" height="445.029062"/>
  </clipPath>
  <clipPath id="p3197a8cc03">
   <path d="M 1020.505469 324.759782 
L 1020.505469 295.813894 
L 1065.19137 295.813894 
L 1065.19137 324.759782 
"/>
  </clipPath>
  <clipPath id="p6aae680b56">
   <path d="M 1020.505469 362.227201 
L 1020.505469 326.759782 
L 1065.19137 326.759782 
L 1065.19137 362.227201 
"/>
  </clipPath>
  <clipPath id="pd2dcf45466">
   <path d="M 1020.505469 404.696768 
L 1020.505469 364.227201 
L 1065.19137 364.227201 
L 1065.19137 404.696768 
"/>
  </clipPath>
  <clipPath id="p418fb97726">
   <path d="M 1020.505469 451.382669 
L 1020.505469 406.696768 
L 1065.19137 406.696768 
L 1065.19137 451.382669 
"/>
  </clipPath>
 </defs>
</svg>
